<a href="https://colab.research.google.com/github/hmghaly/word_align/blob/main/walign2022_NEW.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#Start

In [1]:
from google.colab import drive
import os
drive.mount('/content/drive')
cwd='/content/drive/MyDrive/tr_ar' #directory where we keep the data
if not os.path.exists(cwd): os.makedirs(cwd)  #if the directory doesn't exist, create it
os.chdir(cwd) #change current work directory to the directory where we keep the data
!pwd

Mounted at /content/drive
/content/drive/MyDrive/tr_ar


In [ ]:
!rm -r code_utils #first delete the code_utils folder, then clone from the codebase (very crude till we figure out using github from colab)
!git clone https://github.com/hmghaly/word_align.git code_utils
#!pip install sqlitedict

Cloning into 'code_utils'...
remote: Enumerating objects: 2091, done.
remote: Counting objects: 100% (251/251), done.
remote: Compressing objects: 100% (129/129), done.
remote: Total 2091 (delta 155), reused 199 (delta 122), pack-reused 1840
Receiving objects: 100% (2091/2091), 27.31 MiB | 7.65 MiB/s, done.
Resolving deltas: 100% (997/997), done.


In [2]:
!pip install sqlitedict

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Preparing metadata (setup.py) ... done
  Created wheel for sqlitedict: filename=sqlitedict-2.1.0-py3-none-any.whl size=16863 sha256=a35b8a325034467170a89344cb89d68c50ea76ad9f5a723681f97aabf1db34ca
  Stored in directory: /root/.cache/pip/wheels/f6/48/c4/942f7a1d556fddd2348cb9ac262f251873dfd8a39afec5678e
Successfully built sqlitedict


In [ ]:
#pipeline for indexing 
# both un-corpus, split into parts, and new eluna bitexts
# in the meantime, count Arabic words, update arabic tokenization 
# with proper indexing, we will be able to identify exact/fuzzy matches

In [ ]:
from code_utils.general import *
sent='This is especially illustrated by the references to the Commission’s work on the Nuremberg Principles.'
tokens0=tok(sent)
print(tokens0)

['This', 'is', 'especially', 'illustrated', 'by', 'the', 'references', 'to', 'the', 'Commission', "_'s", 'work', 'on', 'the', 'Nuremberg', 'Principles', '_.']


#Getting updated terminology and bitexts - 15 Feb, 2023
make sure our data is updated

##Get terminology links from eLuna - 27 Jan 23
Do this every time we have a new document, from eLuna HTML, to have a fresh terminology list

In [3]:
import re, json
import time
from code_utils.general import *
from code_utils.web_lib import *

collected_terms_fpath="term/collected-unterm-eluna-terms.txt"
used_ids=[]
if os.path.exists(collected_terms_fpath):
  fopen=open(collected_terms_fpath)
  for line0 in fopen:
    line_dict=json.loads(line0)
    cur_id=line_dict.get("id")
    if cur_id!=None: used_ids.append(cur_id)
  fopen.close()


langs=["en","fr","es","ru","zh","ar"]
def read_term_page(term_page_url0):
  term_dict={}
  term_page_html=get_page_content(term_page_url0)
  term_page_dom_obj=DOM(term_page_html) 
  els=term_page_dom_obj.get_el_by_class('displayElement') 
  print("els",len(els))
  for el0 in els:
    class_name=el0.attrs.get("class","")
    class_list=class_name.split()
    term_text=el0.inner_html.strip()
    #print(term_text,class_list)
    for lang0 in langs:
      if not lang0 in class_list: continue
      exclude0=[lang0,'displayElement','selectable']
      final_class_list=[v for v in class_list if not v in exclude0]
      term_item={"term":term_text,"class":" ".join(final_class_list)}
      term_dict[lang0]=term_dict.get(lang0,[])+[term_item]  
  return term_dict

#eluna_html_fpath="tmp/2301140-eluna.html"
eluna_html_fpath="tmp/eluna-page.html"
fopen=open(eluna_html_fpath)
content=fopen.read()
fopen.close()
root_term_url='https://conferences.unite.un.org/unterm/Display/UNTERM/'
items=re.findall('data-recordid="(.+?)"',content)
items=list(set(items))
print("items",len(items),items[:10])
for term_id0 in items:
  if term_id0 in used_ids: 
    print("already used", term_id0)
    continue
  cur_term_url=root_term_url+term_id0
  # term_page_html=get_page_content(cur_term_url)
  # term_page_dom_obj=DOM(term_page_html)
  print(cur_term_url)
  try:
    term_dict0=read_term_page(cur_term_url)
  except:
    print("problem with:",cur_term_url)
    continue
  term_dict0["id"]=term_id0
  add_term_fopen=open(collected_terms_fpath,"a")
  add_term_fopen.write(json.dumps(term_dict0)+"\n")
  add_term_fopen.close()
  print("term_dict0",term_dict0)
  print("----")
  time.sleep(1)



items 255 ['22d5b3de-ae25-4b00-aaf9-c3e199d62284', 'cfa4729e-37ad-4584-8964-27dbf17143e1', '97e49375-710c-4f1c-bb3f-be865dbaa734', '4bf69580-9c48-442b-9e37-0538d65ccc7d', 'c67e9b33-811b-4d49-b534-e937f863e9a0', 'c73a28a0-bba7-4de3-9674-0f06d0aac7a8', 'c013e75e-f1a8-4300-bb0b-caba1f1e01fd', '066bfd5e-b05d-4ce2-9a65-c5afb924808f', '482a08a1-65d1-4347-b8ba-8e1f0ecc4a2e', '933f08e1-2e32-4290-b69d-9bc399114e65']
https://conferences.unite.un.org/unterm/Display/UNTERM/22d5b3de-ae25-4b00-aaf9-c3e199d62284
els 12
term_dict0 {'en': [{'term': 'the Republic of Honduras', 'class': 'preferred'}, {'term': 'Honduras', 'class': 'preferred'}], 'fr': [{'term': 'la République du Honduras', 'class': 'preferred'}, {'term': 'Honduras (le)', 'class': 'preferred'}], 'es': [{'term': 'la República de Honduras', 'class': 'preferred'}, {'term': 'Honduras', 'class': 'preferred'}], 'ru': [{'term': 'Республика Гондурас', 'class': 'preferred'}, {'term': 'Гондурас', 'class': 'preferred'}], 'zh': [{'term': '洪都拉斯共和国', 'c

Combine all the collected terms into one TSV file for easier lookup - and later consolidation with actual UN items

In [4]:
collected_terms_fpath="term/collected-unterm-eluna-terms.txt"
output_fpath="tmp/out-term.tsv"
output_fopen=open(output_fpath,"w")
used_ids=[]
term_pairs=[]
counter0=0
if os.path.exists(collected_terms_fpath):
  fopen=open(collected_terms_fpath)
  for line0 in fopen:
    line_dict=json.loads(line0)
    cur_id=line_dict.get("id")
    en_items=line_dict.get("en",[])
    ar_items=line_dict.get("ar",[])
    en_terms=[v.get("term","") for v in en_items]
    ar_terms=[v.get("term","") for v in ar_items]
    if en_terms==[] or ar_terms==[]: continue
    en_str,ar_str=" | ".join(en_terms), " | ".join(ar_terms)
    print(" | ".join(en_terms), " | ".join(ar_terms))
    line_out="%s\t%s\n"%(en_str,ar_str)
    output_fopen.write(line_out)
    counter0+=1
    #if cur_id!=None: used_ids.append(cur_id)
  fopen.close()
output_fopen.close()
print("counter0",counter0)

environmental بيئي
Black Lives Matter | BLM أرواح السود غالية | لحياة السود أهميتها
Safe خزانة حديدية
posting إعلان عن وظيفة
Rules القواعد (للمحكمة الإدارية)
United Nations Children's Fund | UNICEF منظمة الأمم المتحدة للطفولة | اليونيسف
United States الولايات المتحدة
Standard نموذجية | موحدة | عادية | معيارية | نمطية | قياسية
secondment انتداب
The Executive Head الرئيس التنفيذي
sanction جزاءات | عقوبات
non-governmental organizations | NGOs منظمات غير حكومية
obligation التزام
conflict of interest تضارب مصالح
Express النقل السريع
Inconsistent غير متساوق | غير منسجم
Food and Agriculture Organization of the United Nations | FAO منظمة الأغذية والزراعة للأمم المتحدة | منظمة الأمم المتحدة للأغذية والزراعة
Subject to مع مراعاة أحكام .., رهنا بـ, بشرط, مع عدم الإخلال بـ
bullying تسلط الأقران | تنمر
procedure إجراء | طريقة | أسلوب
United Nations International Civil Servants Federation | UNISERV اتحاد موظفي الأمم المتحدة المدنيين الدوليين
International Maritime Organization | IMO المنظمة البحرية 

In [ ]:
langs=["en","fr","es","ru","zh","ar"]
term_dict={}
for el0 in els:
  class_name=el0.attrs.get("class","")
  class_list=class_name.split()
  term_text=el0.inner_html.strip()
  for lang0 in langs:
    if not lang0 in class_list: continue
    term_dict[lang0]=term_dict.get(lang0,[])+[term_text]
  print(term_text,class_list)
  #print(el0.inner_html, el0.outer_html, el0.class_list, el0.attrs)
  #print("---")
for a,b in term_dict.items():
  print(a,b)

secondment ['en', 'displayElement', 'preferred', 'selectable']
détachement ['fr', 'displayElement', 'preferred', 'selectable']
adscripción ['es', 'displayElement', 'preferred', 'selectable']
прикомандирование ['ru', 'displayElement', 'preferred', 'selectable']
временное направление ['ru', 'displayElement', 'admitted', 'selectable']
借调 ['zh', 'displayElement', 'preferred', 'selectable']
انتداب ['ar', 'displayElement', 'preferred', 'selectable']
en ['secondment']
fr ['détachement']
es ['adscripción']
ru ['прикомандирование', 'временное направление']
zh ['借调']
ar ['انتداب']


In [ ]:
els=term_page_dom_obj.get_el_by_class('displayElement')
cur_el=els[0]
print("els",len(els),els[:5])


els 7 [<code_utils.web_lib.element object at 0x7f79e65458b0>, <code_utils.web_lib.element object at 0x7f79e62f2c40>, <code_utils.web_lib.element object at 0x7f79e63f2490>, <code_utils.web_lib.element object at 0x7f79e63f2ca0>, <code_utils.web_lib.element object at 0x7f79e63f2e80>]


##Extract Bitexts from eLuna - 31 Jan 2023
We run this with every new job to make sure we have the most updated bitext list

In [ ]:
import re
from code_utils.general import *

#bitext_html_file="bitext_html_table.txt" #pulled from inspect
bitext_html_file="tmp/bitext-table.html" #pulled from inspect
fopen=open(bitext_html_file)
content0=fopen.read()
fopen.close()

bitexts_links_fpath="bitexts/bitexts_links.tsv"
used_ids=[]
if os.path.exists(bitexts_links_fpath):
  fopen=open(bitexts_links_fpath)
  for i0,line0 in enumerate(fopen):
    if i0==0: continue
    line_split=line0.strip().split("\t")
    doc_id,href,is_manual=line_split[:3]
    used_ids.append(doc_id)
  fopen.close()

print("current used ids:",len(used_ids))

prefix_url='https://conferences.unite.un.org'

content0=unescape(content0)
all_trs=get_html_els(content0,"tr")

final_list=[]
for tr0 in all_trs:
  cur_tds=all_trs=get_html_els(tr0,"a")
  #print([tr0])
  hyper_links=re.findall('<a .+?/a>',tr0)
  if len(hyper_links)<1: continue
  href0=re.findall('href="(.+?)"',hyper_links[0])
  anchor_text=re.findall(">(.+)<",hyper_links[0])
  if href0 and len(href0[0])<2: continue
  manual=False
  if '<span class="author user"></span>' in tr0: manual=True
  final_href=prefix_url+href0[0]
  final_list.append((anchor_text[0],final_href,manual))

if not os.path.exists(bitexts_links_fpath):
  out_fopen=open(bitexts_links_fpath,"w")
  headers="%s\t%s\t%s\n"%("Doc","Link","Manual?")
  out_fopen.write(headers)
else:
  out_fopen=open(bitexts_links_fpath,"a")

for doc_id,doc_href,doc_is_manual in final_list:
  if doc_id in used_ids:
    print("already used:",doc_id)
  else:
    print("NEW:",doc_id)

  line="%s\t%s\t%s\n"%(doc_id,doc_href,doc_is_manual)
  out_fopen.write(line)
out_fopen.close()

current used ids: 4794
already used: !0000/ENV/Kyoto Protocol
NEW: (A/76/2) Draft Annual Report of the SC to the GA - Final
NEW: (A/76/412) (A/C.4/76/L.11)
NEW: (A/76/444) (A/C.1/76/L.15)
already used: (DGACM)  Annex II of draft CoC report 2021
NEW: (DGACM/CPCD) CCM website - 2022 wall chart)
already used: (DGACM/CPCD) Revised 2023 calendar
NEW: (DGACM/CPCS)(CCM website - organs/titles/sessions)
NEW: (DGACM/PL) Guidelines on eRegistration for IGOs away fm NY_REV11_25 Novembr 2022_for translation
NEW: (DGACM/PLS) Guidelines on “eRegistration” system/Rev5/Dec2020/5 pages
NEW: (DPPA) CTC meeting in India 29 October 2022
NEW: (DPPA/SCAD) 2140 Yemen - AA letter 4 June 2022
NEW: (DPPA/SCAD/SCSOB) 1533 Listing 46 entries
NEW: (DPPA/SCAD/SCSOB) Committee Guidelines of resolution 1533 (2004) adopted on 20 February 2023
NEW: (DPPA/SCSOB) Yemen to the WGCAAC
NEW: (DPPA/SCSOB/SCAD) S AC.43 2022 Guidelines_Final
already used: (OC/OPPBA/ACABQ/CA/2022/ASG) for Solutions for IDPs
NEW: (OC/OPPFB/ACABQ/

Now crawling into the bitext links, reading the bitext html content, and creating bitext TSV files for each of these

In [ ]:
import sys, shutil
from code_utils.web_lib import *
from code_utils.general import *


bitext_dir="bitexts"
if not os.path.exists(bitext_dir): os.makedirs(bitext_dir)
bitexts_links_fpath="bitexts/bitexts_links.tsv"
out_fopen=open(bitexts_links_fpath)

for i0,line in enumerate(out_fopen):
  if i0==0: continue
  #if i0>5: break
  
  line_split=line.strip().split("\t")
  if len(line_split)<3: continue
  symbol0,link0,manual0=line_split[:3]
  align_type="auto"
  if str(manual0)=="True": align_type="manual"
  print(i0,manual0,align_type)
  align_type_dir=os.path.join(bitext_dir,align_type)
  if not os.path.exists(align_type_dir): 
    print("creating:",align_type_dir)
    os.makedirs(align_type_dir)
  #print("manual0",manual0)
  #file_id0=re.sub("\W+","_",symbol0)
  file_id0=re.sub("\W+","_",symbol0).strip("_") # next time
  tsv_fname0="%s.tsv"%file_id0
  #tsv_fpath=os.path.join(bitext_dir,tsv_fname0)
  tsv_fpath=tsv_align_fpath=os.path.join(align_type_dir,tsv_fname0)
  if os.path.exists(tsv_fpath): 
    #print("exists:", tsv_fpath)
    continue
  print(tsv_fname0,symbol0,link0,manual0)
  try: page_html=get_page_content(link0)
  except: continue
  
  cur_bitext_list=get_bitext(page_html) #get_bitext(page_html)
  cur_bitext_list=[[link0,""]]+cur_bitext_list
  # for a in cur_bitext_list[:5]:
  #   print(a)
  create_tsv(tsv_fpath,cur_bitext_list)
  #if i0>20: break

out_fopen.close()

Streaming output truncated to the last 5000 lines.
1569 False auto
1570 False auto
1571 False auto
1572 True manual
1573 False auto
1574 False auto
1575 False auto
1576 False auto
1577 False auto
1578 False auto
1579 False auto
1580 False auto
1581 False auto
1582 False auto
1583 True manual
1584 False auto
1585 False auto
1586 False auto
1587 False auto
1588 False auto
1589 False auto
1590 True manual
1591 True manual
1592 False auto
1593 False auto
1594 False auto
1595 False auto
1596 False auto
1597 False auto
1598 False auto
1599 False auto
1600 False auto
1601 False auto
1602 False auto
1603 False auto
1604 False auto
1605 False auto
1606 False auto
1607 False auto
1608 False auto
1609 False auto
1610 False auto
1611 False auto
1612 False auto
1613 False auto
1614 False auto
1615 False auto
1616 False auto
1617 False auto
1618 True manual
1619 True manual
1620 False auto
1621 False auto
1622 False auto
1623 False auto
1624 False auto
1625 False auto
1626 False auto
1627 False auto

##combine manually aligned bitexts into a consolidated file - Feb 15, 2023

In [ ]:
#getting manually aligned bitexts
from code_utils.general import *
from code_utils.align_utils import *
tsv_files=get_dir_files("bitexts/manual","tsv")
print("tsv_files",len(tsv_files))
all_ar_sents=[]
fopen_aligned=open("bitexts/aligned-sents.txt","w")

counter=0
for i0,tsv_fpath0 in enumerate(tsv_files):
  if i0%100==0: print(i0 ,"out of", len(tsv_files), "counter:",counter)
  bitext1=get_tsv_bitext(tsv_fpath0)
  for en0,ar0 in bitext1:
    check=[v for v in re.findall("\w+",en0) if not v.isdigit()]
    if check==[]: continue
    if en0==ar0: continue
    #fopen_ar.write(ar0+"\n")
    line0="%s\t%s\n"%(en0,ar0)
    fopen_aligned.write(line0)
    counter+=1
    
  #all_ar_sents.extend([v[1] for v in bitext1 if v[0]!=v[1]])
  #print(tsv_fpath0, len(bitext1), len(all_ar_sents))
fopen_aligned.close()
print("counter",counter)

tsv_files 2214
0 out of 2214 counter: 0
100 out of 2214 counter: 58453
200 out of 2214 counter: 93454
300 out of 2214 counter: 147682
400 out of 2214 counter: 179577
500 out of 2214 counter: 206509
600 out of 2214 counter: 259558
700 out of 2214 counter: 304230
800 out of 2214 counter: 347603
900 out of 2214 counter: 368138
1000 out of 2214 counter: 407580
1100 out of 2214 counter: 444648
1200 out of 2214 counter: 514814
1300 out of 2214 counter: 538895
1400 out of 2214 counter: 661690
1500 out of 2214 counter: 816877
1600 out of 2214 counter: 909735
1700 out of 2214 counter: 1004257
1800 out of 2214 counter: 1082133
1900 out of 2214 counter: 1092890
2000 out of 2214 counter: 1126183
2100 out of 2214 counter: 1160647
2200 out of 2214 counter: 1169585
counter 1170778


## Creating index for eluna manually aligned bitexts - 23 March 2023

In [ ]:
import re, shelve, shutil
from code_utils.general import *
from code_utils.align_utils import *
from code_utils.sqld_utils import *
from code_utils.arabic_lib import *

en_ar_corpus_combined_fname="bitexts/aligned-sents.txt"

excluded_src_tokens=["the","a","an","and","of","its","his","her","their","them","to","is","are","am","been","was","were","be", 
                     "have","has","had", "in", "on", "at", "with", "from","for","that","he","she","it","would",
                     "as","by","they","whose","which"] #we will need to update this
excluded_trg_tokens=["من","على","في","مع", "إلى",
                     "له","تم","إلى","في","عن","إن","أن","به","بها","لها","التي","كان","قد","الذي","الذين",
                     "هو","هي"]

ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})
def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)

fopen=open(en_ar_corpus_combined_fname)
# fopen.seek(start_loc)
# if start_loc!=0: fopen.readline()
#cur_loc=0
cur_line="-"

src_fwd_index0,trg_fwd_index0=[],[]
counter=0
bitext_list=[]
t0=time.time()
while cur_line!="":
  if counter%5000==0: print(counter)
  cur_loc=fopen.tell()
  f0=fopen.readline()
  #print([f0])
  cur_line=f0.strip("\n\r\t")
  line_split=cur_line.split("\t")
  if len(line_split)!=2: continue
  elif f0!="":
    src0,trg0=line_split
    src_toks=tok(src0)
    trg_toks=cur_ar_tok_fn(trg0)
    filtered_src=filter_toks(src_toks,params={"exclude_numbers":True, "excluded_words":excluded_src_tokens}) #src_toks,trg_toks
    filtered_trg=filter_toks(trg_toks,params={"exclude_numbers":True, "excluded_words":excluded_trg_tokens})
    src_sent_fwd_index=index_sent_toks(filtered_src,cur_loc)
    trg_sent_fwd_index=index_sent_toks(filtered_trg,cur_loc)
    src_fwd_index0.extend(src_sent_fwd_index)
    trg_fwd_index0.extend(trg_sent_fwd_index)
    for s_i,s_tok0 in enumerate(src_toks):
      if s_tok0.isupper(): 
        src_fwd_index0.append((s_tok0,cur_loc+0.001*s_i))
        #print((s_tok0,counter+0.001*s_i))
    #bitext_list.append((counter,cur_loc,src0,trg0))
  counter+=1
  #if counter>1000: break
src_inv_index=get_inv_index(src_fwd_index0)
trg_inv_index=get_inv_index(trg_fwd_index0)

src_sqld_fpath="bitexts/src-manual.sqld"
trg_sqld_fpath="bitexts/trg-manual.sqld"
if os.path.exists(src_sqld_fpath): shutil.move(src_sqld_fpath,src_sqld_fpath.replace(".sqld","-OLD.sqld"))
if os.path.exists(trg_sqld_fpath): shutil.move(trg_sqld_fpath,trg_sqld_fpath.replace(".sqld","-OLD.sqld"))

print("now creating indexes")
dict2sqld(src_inv_index,src_sqld_fpath)
dict2sqld(trg_inv_index,trg_sqld_fpath)

# for a,b in src_inv_index.items():
#   print(a,b)
fopen.close()

0
5000
10000
15000
20000
25000
30000
35000
40000
45000
50000
55000
60000
65000
70000
75000
80000
85000
90000
95000
100000
105000
110000
115000
120000
125000
130000
135000
140000
145000
150000
155000
160000
165000
170000
175000
180000
185000
190000
195000
200000
205000
210000
215000
220000
225000
230000
235000
240000
245000
250000
255000
260000
265000
270000
275000
280000
285000
290000
295000
300000
305000
310000
315000
320000
325000
330000
335000
340000
345000
350000
355000
360000
365000
370000
375000
380000
385000
390000
395000
400000
405000
410000
415000
420000
425000
430000
435000
440000
445000
450000
455000
460000
465000
470000
475000
480000
485000
490000
495000
500000
505000
510000
515000
520000
525000
530000
535000
540000
545000
550000
555000
560000
565000
570000
575000
580000
585000
590000
595000
600000
605000
610000
615000
620000
625000
630000
635000
640000
645000
650000
655000
660000
665000
670000
675000
680000
685000
690000
695000
700000
705000
710000
715000
720000
725000
730

#Sentence Alignment Pipeline - Feb 15, 2023

##Count en/ar sent ratio - 4 Jan 2023

In [ ]:
from code_utils.arabic_lib import *
#from code_utils.pandas_utils import *
from code_utils import general
import re,json
from itertools import groupby
from collections import Counter
from random import shuffle, seed

# seed(0)
# batch_size=50000
# excluded_src_tokens=["the","a","an","and","of","its","his","her","their","them","to","is","are","am","been","was","were","be", 
#                      "have","has","had", "in", "on", "at", "with", "from","for","that","he","she","it","would",
#                      "as","by","they","whose","which"] #we will need to update this
# excluded_trg_tokens=["من","على","في","مع", "إلى",
#                      "له","تم","إلى","في","عن","إن","أن","به","بها","لها","التي","كان","قد","الذي","الذين",
#                      "هو","هي"]


# ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})
# def cur_ar_tok_fn(text):
#   cur_toks=tok(text)
#   return tok_ar(cur_toks,ar_counter_dict)

def norm_sent_size(sent_size0,step=10,max_size=400):
  if sent_size0>max_size: return max_size
  norm_val=step*round(sent_size0/step)
  return norm_val

en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"

ratio_dict={}
size_pair_dict={}
counter=0
fopen=open(en_ar_corpus_combined_fname)
cur_line="-"
bitext_list=[]
t0=time.time()
while cur_line!="":
  cur_loc=fopen.tell()
  f0=fopen.readline()
  cur_line=f0.strip("\n\r\t")
  line_split=cur_line.split("\t")
  if len(line_split)!=2: continue
  elif f0!="":
    src0,trg0=line_split
    norm_src_size0,norm_trg_size0=norm_sent_size(len(src0)),norm_sent_size(len(trg0))
    tmp_dict0=size_pair_dict.get(norm_src_size0,{})
    tmp_dict0[-1]=tmp_dict0.get(-1,0)+1
    tmp_dict0[norm_trg_size0]=tmp_dict0.get(norm_trg_size0,0)+1
    size_pair_dict[norm_src_size0]=tmp_dict0
    # size_ratio=round(len(trg0)/len(src0),1)
    # #print(len(src0),len(trg0),size_ratio)
    # ratio_dict[0]=ratio_dict.get(0,0)+1
    # ratio_dict[size_ratio]=ratio_dict.get(size_ratio,0)+1
    #bitext_list.append((counter,cur_loc,src0,trg0))
  counter+=1
  if counter%50000==0: print(counter)
  if counter>1000000: break

  # if len(bitext_list)%batch_size==0 or f0=="":
cur_items=list(size_pair_dict.items())
cur_items.sort()
final_dict={}
for a,b_dict in cur_items:
  
  total=b_dict[-1]
  print(a,total)
  new_tmp_dict={}
  for b0,b_val in b_dict.items():
    b_val_wt=b_val/total
    if b_val<5 or b_val_wt<0.01 or b0<0: continue
    new_tmp_dict[b0]=round(b_val_wt,3)
  final_dict[a]=new_tmp_dict
  print(sorted(list(new_tmp_dict.items())))
  print("---")



# final_size_ratio_dict={}
# for a,b in cur_items:
#   if a==0: continue
#   actual_wt=round(b/ratio_dict[0],2)
#   if actual_wt==0: continue
#   final_size_ratio_dict[a]=actual_wt
#   print(a,b,actual_wt)

out_fpath="en-ar-sent-size-pairs.json"
fopen_out=open(out_fpath,"w")
fopen_out.write(json.dumps(final_dict))
fopen_out.close()

50000
100000
150000
200000
250000
300000
350000
400000
450000
500000
550000
600000
650000
700000
750000
800000
850000
900000
950000
1000000
0 6104
[(0, 0.476), (10, 0.508), (20, 0.013)]
---
10 37139
[(0, 0.06), (10, 0.636), (20, 0.266), (30, 0.019)]
---
20 62776
[(10, 0.2), (20, 0.633), (30, 0.115), (40, 0.032)]
---
30 44423
[(10, 0.059), (20, 0.415), (30, 0.36), (40, 0.117), (50, 0.029), (60, 0.01)]
---
40 44304
[(10, 0.018), (20, 0.168), (30, 0.353), (40, 0.309), (50, 0.088), (60, 0.042), (70, 0.01)]
---
50 34116
[(20, 0.048), (30, 0.165), (40, 0.397), (50, 0.231), (60, 0.102), (70, 0.026), (80, 0.014)]
---
60 37634
[(20, 0.015), (30, 0.054), (40, 0.272), (50, 0.305), (60, 0.216), (70, 0.074), (80, 0.036), (90, 0.011)]
---
70 26626
[(30, 0.016), (40, 0.103), (50, 0.239), (60, 0.325), (70, 0.165), (80, 0.087), (90, 0.031), (100, 0.015)]
---
80 32597
[(40, 0.031), (50, 0.126), (60, 0.296), (70, 0.236), (80, 0.174), (90, 0.068), (100, 0.038), (110, 0.013)]
---
90 28975
[(50, 0.042), (60

#Arabic Spell-checking pipeline - Feb 15, 2023

##Count Arabic tokens - 15 Jan 23
for spell checking and also Arabic tokenization

In [ ]:
from code_utils.general import *
import shelve

#max_n_sents=500000
max_n_sents=None
#en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"
en_ar_corpus_combined_fname="bitexts/ar-un-sents.txt"

def get_word_ch_pair(word0):
  cur_char_pairs0=[]
  word0=" "+word0+" "
  for i0 in range(len(word0)-1):cur_char_pairs0.append(word0[i0]+word0[i0+1])
  return cur_char_pairs0

def get_sent_bigrams(sent_toks0):
  cur_bigrams0=[]
  if not sent_toks0[0]=='<s>': sent_toks0=["<s>"]+sent_toks0+["</s>"]
  for i0 in range(len(sent_toks0)-1):
    word1,word2=sent_toks0[i0],sent_toks0[i0+1]
    cur_bigrams0.append((word1,word2))
  return cur_bigrams0

def normalize_level2(ar_tok_list):
  normalized_toks0=normalize(ar_tok_list)
  new_normalized0=[]
  for tok0 in normalized_toks0:
    if is_arabic(tok0): new_normalized0.append(tok0)
    elif is_punct(tok0) or tok0.isdigit(): new_normalized0.append(tok0) 
    elif tok0[0] in "<_": new_normalized0.append(tok0)
    else: new_normalized0.append("_en_")
  return new_normalized0

ar_bigram_dict={}
ar_word_dict={}
ar_2char_index_dict={}
fopen=open(en_ar_corpus_combined_fname)
cur_line="-"
counter=0
t0=now()
initial_t0=now()
list_sents=[]
final_sents=[]
while cur_line!="":
  cur_loc=fopen.tell()
  f0=fopen.readline()
  cur_line=f0.strip("\n\r\t")
  line_split=cur_line.split("\t")
  #if len(line_split)!=2: continue
  if f0!="":
    if len(line_split)==2: src0,trg0=line_split
    else: trg0=cur_line
    trg0=clean_ar(trg0)
    trg_toks=tok(trg0)
    normalized=normalize_level2(trg_toks)
    list_sents.append(normalized)
    #print("normalized",normalized)
    for a in normalized:
      ar_word_dict[a]=ar_word_dict.get(a,0)+1
    cur_bigrams1=get_sent_bigrams(normalized)
    for a,b in cur_bigrams1:
      valid_arabic=False
      if is_arabic(a) or is_arabic(b): valid_arabic=True
      if valid_arabic: 
        bigram_key="%s %s"%(a,b)
        ar_bigram_dict[bigram_key]=ar_bigram_dict.get(bigram_key,0)+1

  counter+=1
  if counter%10000==0: 
    elapsed=now()-t0
    print(counter, round(elapsed,1))
    final_sents=list(list_sents)
    list_sents=[]
    t0=now()
  if max_n_sents!=None and counter>max_n_sents: break

total_elapsed=now()-initial_t0
word_count_items=list(ar_word_dict.items()) #ar_word_dict, ar_bigram_dict
bigram_count_items=list(ar_bigram_dict.items())
word_count_items.sort(key=lambda x:-x[-1])
bigram_count_items.sort(key=lambda x:-x[-1])
print("word_count_items",len(word_count_items))
for a in word_count_items[:50]:
  print(a)
print("------")
print("bigram_count_items",len(bigram_count_items))
for a in bigram_count_items[:50]:
  print(a)
print("total_elapsed",round(total_elapsed,1))

all_ch_pair_word_list=[]
min_count=5
for ar0,count0 in word_count_items:
  if count0<min_count: continue
  if not is_arabic(ar0): continue
  #print(ar0)
  ch_pairs=list(set(get_word_ch_pair(ar0)))
  for ch0 in ch_pairs: all_ch_pair_word_list.append((ch0,ar0))
  #print(ch_pairs)
all_ch_pair_word_list.sort()
grouped=[(key,[v[1] for v in list(group)]) for key,group in groupby(all_ch_pair_word_list,lambda x:x[0])]
bi_char_index_word_dict=dict(iter(grouped))
print("grouped",len(grouped))
for key0,grp0 in grouped[:100]:
  print(key0,len(grp0),grp0[:10])

10000 4.7
20000 2.9
30000 2.8
40000 3.3
50000 2.3
60000 2.5
70000 2.8
80000 2.4
90000 1.9
100000 2.1
110000 2.7
120000 2.2
130000 2.0
140000 2.0
150000 2.2
160000 2.0
170000 2.1
180000 2.5
190000 2.7
200000 2.7
210000 2.6
220000 2.2
230000 2.7
240000 2.6
250000 2.3
260000 3.3
270000 2.1
280000 2.6
290000 2.6
300000 3.4
310000 3.4
320000 3.8
330000 3.2
340000 2.7
350000 2.9
360000 2.9
370000 2.6
380000 2.6
390000 3.1
400000 2.9
410000 2.5
420000 2.7
430000 2.7
440000 4.6
450000 2.9
460000 2.7
470000 2.8
480000 2.3
490000 2.4
500000 2.4
510000 2.8
520000 1.7
530000 1.4
540000 2.0
550000 2.3
560000 2.5
570000 2.4
580000 2.3
590000 2.2
600000 1.9
610000 2.0
620000 2.3
630000 2.2
640000 2.2
650000 2.0
660000 2.1
670000 2.0
680000 2.5
690000 2.5
700000 2.5
710000 1.5
720000 2.0
730000 2.6
740000 3.4
750000 3.0
760000 3.0
770000 2.8
780000 2.5
790000 2.7
800000 2.4
810000 2.5
820000 2.5
830000 2.6
840000 2.6
850000 2.5
860000 2.2
870000 2.4
880000 2.2
890000 2.2
900000 2.0
910000 2.2
920000 2

save the word counts to tsv file

In [ ]:
word_count_fpath="ar_word_count_recent_docs.tsv"
word_count_fopen=open(word_count_fpath,"w")
for w0,count0 in word_count_items:
  line0="%s\t%s\n"%(w0,count0)
  word_count_fopen.write(line0)
word_count_fopen.close()


##Spell checking functions - Feb 15, 2023
Retrieval and analysis

In [ ]:
#two char word similarity function to retrieve 
def get_sim_word_candidates(word0,bi_char_dict0,top_n=500):
  ch_pairs=list(set(get_word_ch_pair(word0)))
  candidate_dict={}
  for ch0 in ch_pairs:
    ch_words=bi_char_dict0.get(ch0,[])
    for cw0 in ch_words:
      candidate_dict[cw0]=candidate_dict.get(cw0,0)+1
  candidate_dict_items=list(candidate_dict.items())
  candidate_dict_items.sort(key=lambda x:-x[-1])
  top=candidate_dict_items[:top_n]
  cand_sim_list=[]
  for cd0,cd_count0 in top:
    if abs(len(cd0)-len(word0))>1: continue
    avg_len=(len(cd0)+len(word0))/2
    sim_val=similar(cd0,word0)
    #sim_val=sim_val/avg_len
    cand_sim_list.append((cd0,sim_val))
  cand_sim_list.sort(key=lambda x:-x[-1])
  return cand_sim_list

def spell_check(sent_tokens0,bi_char_dict0,word_count_dict0,bigram_dict0):
  if not sent_tokens0[0]=="<s>": sent_tokens0=["<s>"]+sent_tokens0+["</s>"]
  for w_i,word0 in enumerate(sent_tokens0):
    freq_word=False
    freq_prev_bigram,freq_next_bigram=False,False
    sure_correct=False
    sure_incorrect=False
    if w_i==0: continue
    if not is_arabic(word0): continue
    print(word0)
    prev0,next0= sent_tokens0[w_i-1],sent_tokens0[w_i+1]
    prev_count=word_count_dict0.get(prev0,0)
    next_count=word_count_dict0.get(next0,0)
    cur_count=word_count_dict0.get(word0,0)
    prev_cur_bigram="%s %s"%(prev0,word0)
    cur_next_bigram="%s %s"%(word0,next0) 
    prev_cur_bigram_count= bigram_dict0.get(prev_cur_bigram,0)
    cur_next_bigram_count= bigram_dict0.get(cur_next_bigram,0)
    # print("prev_cur_bigram_count",prev_cur_bigram_count)
    # print("cur_next_bigram_count",cur_next_bigram_count)
    if cur_count>100: freq_word=True
    if prev_cur_bigram_count>10: freq_prev_bigram=True
    if cur_next_bigram_count>10: freq_next_bigram=True

    prob_cur_prev,prob_cur_next=0,0
    if prev_count!=0:  prob_cur_prev=prev_cur_bigram_count/prev_count
    if next_count!=0:  prob_cur_next=cur_next_bigram_count/next_count
    total_cur_wt=prob_cur_prev+prob_cur_next
    candidates=get_sim_word_candidates(word0,bi_char_dict0)
    list_candidates_wts=[]
    for cand0,sim_score in candidates[:20]:
      #sim_score=similar(cand0,word0)
      #if cand0==word0: continue
      prev_cand_bigram="%s %s"%(prev0,cand0)
      cand_next_bigram="%s %s"%(cand0,next0) 
      prev_cand_bigram_count= bigram_dict0.get(prev_cand_bigram,0)
      cand_next_bigram_count= bigram_dict0.get(cand_next_bigram,0)
      #if cand_next_bigram_count<5 or prev_cand_bigram_count<5: continue
      prob_cand_prev,prob_cand_next=0,0
      if prev_count!=0:  prob_cand_prev=prev_cand_bigram_count/prev_count
      if next_count!=0:  prob_cand_next=cand_next_bigram_count/next_count
      total_cand_wt=prob_cand_prev+prob_cand_next
      prev_next_cand_count=(prev_cand_bigram_count,cand_next_bigram_count)
      if total_cand_wt==0: continue
      #print("cand0",cand0, total_cand_wt)
      list_candidates_wts.append((cand0,prev_next_cand_count,sim_score, total_cand_wt))
      #print("prev_cand_bigram",prev_cand_bigram, "cand_next_bigram",cand_next_bigram)
    list_candidates_wts.sort(key=lambda x:(-x[-1],-x[-2]))
    if list_candidates_wts: top_candidate,prev_next_cand_count0,sim_score0,top_wt= list_candidates_wts[0]
    else: top_candidate=""
    if top_candidate==word0: 
      print("correct:",word0)
      sure_correct=True
    elif top_candidate=="": print("no candidates:",word0)
    elif freq_prev_bigram or freq_next_bigram: print("correct - freq next/prev bigrams:",word0)
    else: print("more likely:",top_candidate)
    if not sure_correct:
      for c0 in list_candidates_wts[:5]: print(c0)
      print("prev_cur_bigram_count",prev_cur_bigram_count)
      print("cur_next_bigram_count",cur_next_bigram_count)
      print("total_cur_wt",total_cur_wt)
      print("cur_count",cur_count)

      


    # print("prob_cur_next",prob_cur_next,"prob_cur_prev",prob_cur_prev)
    print("----")

#ar_word_dict, ar_bigram_dict      
# sent="2-	وأضاف قائلا إن المملكة العربية السعودية قد شرعت في تنفيذ برنامج وطني للحد من الفقد والهدر في الغذاء. ومن بين أهداف البرنامج نشر الوعي بأهمية التنويع الغذائي، والمساهمة في زيادة مصادر البروتين، واستخدام الموارد الطبيعية بقدر أكبر من الكفاءة. وينشر البرنامج الوعي بالأمراض الناتجة عن الهدر الغذائي وأهمية التعامل مع النفايات. وشدد على أن التعاون المتعدد الأطراف هو السبيل الوحيد للقضاء على انعدام الأمن الغذائي والتحرك نحو نظم غذائية مستدامة وسلاسل إمداد مرنة ولتحقيق الاستخدام الأمثل للموارد. "
sent="ويجب في هذه الحالة ان نفعل شيء"
sent='والاحتياجات المبينن تفاصيلها أدناه متصل بتشغيل مكتب في السلفادور لتصفية البعثة طوال تلك الفترة حتى 55 أيلول / سبتمبر 5555 .'
sent='وبالاضافة إلى ذلك ، يدفع أيضضا للموظفيين في حالة السسفر الرسمي بدل لمكان إقامة المحتفظ به قدره 55 دولارا في اليوم .'
toks=tok(sent)
#toks=final_sents[19]

spell_check(toks,bi_char_index_word_dict,ar_word_dict,ar_bigram_dict)

print(" ".join(toks[1:-1]))
      



# test_word="ان"
# test_outcome=get_sim_word_candidates(test_word,bi_char_index_word_dict)
# for a in test_outcome[:20]:
#   print(a)




# all_ch_pair_word_list=[]
# min_count=5
# for ar0,count0 in word_count_items:
#   if count0<min_count: continue
#   if not is_arabic(ar0): continue
#   #print(ar0)
#   ch_pairs=list(set(get_word_ch_pair(ar0)))
#   for ch0 in ch_pairs: all_ch_pair_word_list.append((ch0,ar0))
#   #print(ch_pairs)
# all_ch_pair_word_list.sort()
# grouped=[(key,[v[1] for v in list(group)]) for key,group in groupby(all_ch_pair_word_list,lambda x:x[0])]
# bi_char_index_word_dict=dict(iter(grouped))
# print("grouped",len(grouped))
# for key0,grp0 in grouped[:100]:
#   print(key0,len(grp0),grp0[:10])

NameError: ignored

#Process manually aligned docs - 22 Jan 2023

In [ ]:
from code_utils.general import *
from code_utils.align_utils import *
tsv_files=get_dir_files("bitexts","tsv")
print("tsv_files",len(tsv_files))
all_ar_sents=[]
fopen_ar=open("bitexts/ar-un-sents.txt","w")
fopen_en=open("bitexts/en-un-sents.txt","w")
counter=0
for i0,tsv_fpath0 in enumerate(tsv_files):
  if i0%100==0: print(i0 ,"out of", len(tsv_files), "counter:",counter)
  bitext1=get_tsv_bitext(tsv_fpath0)
  for en0,ar0 in bitext1:
    check=[v for v in re.findall("\w+",en0) if not v.isdigit()]
    if check==[]: continue
    fopen_en.write(en0+"\n")
    if en0==ar0: continue
    # check_ar=[v for v in check if is_arabic(v)]
    # if check_ar==[]: continue
    fopen_ar.write(ar0+"\n")
    counter+=1
    
  #all_ar_sents.extend([v[1] for v in bitext1 if v[0]!=v[1]])
  #print(tsv_fpath0, len(bitext1), len(all_ar_sents))
fopen_ar.close()
fopen_en.close()
print("counter",counter)

KeyboardInterrupt: ignored

In [ ]:
cur_qa_in_dir="bitexts/manual"
cur_qa_out_dir="qa/manual"
if not os.path.exists(cur_qa_out_dir): os.makedirs(cur_qa_out_dir)
sent_class0="sent0"
tsv_files=[v for v in os.listdir(cur_qa_in_dir) if v.endswith(".tsv")]
for tsv_fname in tsv_files[:200]:
  tsv_fpath0=os.path.join(cur_qa_in_dir,tsv_fname)
  out_fpath=os.path.join(cur_qa_out_dir,html_fname)
  bitext1=get_tsv_bitext(tsv_fpath0)
  if bitext1==[]: continue



In [ ]:
files=get_dir_files("bitexts")
manual_files=get_dir_files("bitexts/manual")
auto_files=get_dir_files("bitexts/auto")

print(len(files),len(manual_files),len(auto_files))
to_remove=[]
for a in files:
  if a in manual_files or a in auto_files: continue
  to_remove.append(a)

to_remove.sort()
print("to_remove",len(to_remove))
for a in to_remove:
  os.remove(a)
  #print(a)

3503 616 2887
to_remove 0


In [ ]:
normalized

['<s>',
 'وينبغي',
 'أن',
 'تكون',
 'الأساس',
 'لإعادة',
 'تنشيط',
 'التعاون',
 'بين',
 'الشمال',
 'والجنوب',
 '،',
 'وأن',
 'يكون',
 'ذلك',
 'إيذانا',
 'ببداية',
 'جديدة',
 'في',
 'التعاون',
 'الانمائي',
 'الدولي',
 'القائم',
 'على',
 'مبدأ',
 'التزامات',
 'كارتاخينا',
 '.',
 '</s>']

In [ ]:
sent="www.jj.cc.edu البند 24 من جدول الاعمال: التنمية and other issues الزراعية والأمن الغذائي والتغذية aaa@gg.vv (تابع) (A/77/70-E/2022/49 و A/77/241)"
toks1=tok(sent)
norm1=normalize_level2(toks1)
print(norm1)

['<s>', '_website_', 'البند', '55', 'من', 'جدول', 'الاعمال', ':', 'التنمية', '_en_', '_en_', '_en_', 'الزراعية', 'والأمن', 'الغذائي', 'والتغذية', '_email_', '(', 'تابع', ')', '(', '_un_', 'و', '_un_', ')', '</s>']


In [ ]:
def word2ch_pair(word0):
  cur_char_pairs0=[]
  word0=" "+word0+" "
  for i0 in range(len(word0)-1):cur_char_pairs0.append(word0[i0]+word0[i0+1])
  return cur_char_pairs0

word1="استأنس"
word2ch_pair(word1)

[' ا', 'اس', 'ست', 'تأ', 'أن', 'نس', 'س ']

In [ ]:
import unicodedata
arabic_letter_dict={}
for i in range(10000):
  char0=chr(i)
  try: name = unicodedata.name(char0).lower()
  except: name=""
  if ('arabic' in name or 'persian' in name): arabic_letter_dict[char0]=True

def is_arabic(word):
  output=False
  if len(word)==0: return False
  if arabic_letter_dict.get(word[0],False) or arabic_letter_dict.get(word[-1],False): output=True
  return output
word1="إذا"
check1=is_arabic(word1)
print(word1,check1)

إذا True


In [ ]:
unicodedata.name("a")

'LATIN SMALL LETTER A'

In [ ]:
def norm_sent_size(sent_size0,step=10,max_size=200):
  if sent_size0>max_size: return max_size
  norm_val=step*round(sent_size0/step)
  return norm_val

test_sent_size=67
norm_sent_size(test_sent_size)

70

#Main word align part- 15 Feb, 2023
working on UN Bitext 

## ★ New walign pipeline - Jan 31, 2022
Including phonetic matching and custom phrase matching, and UN/ACR matching

In [ ]:
#Preparing references
import re, time, shelve
from code_utils.general import *
from code_utils.align_utils import *
from code_utils.arabic_lib import *
#from code_utils.pandas_utils import *
from code_utils import general

from itertools import groupby
from collections import Counter
from random import shuffle, seed

seed(0)
batch_size=50000
excluded_src_tokens=["the","a","an","and","of","its","his","her","their","them","to","is","are","am","been","was","were","be", 
                     "have","has","had", "in", "on", "at", "with", "from","for","that","he","she","it","would",
                     "as","by","they","whose","which"] #we will need to update this
excluded_trg_tokens=["من","على","في","مع", "إلى",
                     "له","تم","إلى","في","عن","إن","أن","به","بها","لها","التي","كان","قد","الذي","الذين",
                     "هو","هي"]

#aligned_fname="aligned.txt"
#en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"

aligned_fname="aligned-eluna.txt"
en_ar_corpus_combined_fname="bitexts/aligned-sents.txt"
index_dir="indexes/un/exp6"


term_shelve_path="terms.shelve"
acr_shelve_path="acronyms.shelve"
phrase_shelve_path="phrases.shelve"
term_shelve_open=shelve.open(term_shelve_path)
acr_shelve_open=shelve.open(acr_shelve_path)
#phrase_shelve_open=shelve.open(phrase_shelve_path)

ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})
def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)



if not os.path.exists(index_dir): os.makedirs(index_dir)
params_fpath=os.path.join(index_dir,"params.json")
retr_params={}
retr_params["lang2_tok_fn"]=cur_ar_tok_fn
retr_params["excluded_words"]=excluded_src_tokens+excluded_trg_tokens
retr_params["term_dict"]=term_shelve_open
retr_params["acr_dict"]=acr_shelve_open
retr_params["max_src_span"]=10




aligned_fpath=os.path.join(index_dir,aligned_fname) #aligned_fname="aligned-eluna.txt"
start_loc=0 #check which line in the bitext file to start with
counter=0
if os.path.exists(aligned_fpath):
  aligned_fopen=open(aligned_fpath)
  for line0 in aligned_fopen:
    line_dict=json.loads(line0.strip())
    cur_loc=line_dict.get("loc")
    cur_i=line_dict.get("i")
    if cur_loc!=None: start_loc=cur_loc
    if cur_i!=None: counter=cur_i
  aligned_fopen.close()

print("start_loc",start_loc,"counter",counter)



fopen=open(en_ar_corpus_combined_fname)
fopen.seek(start_loc)
if start_loc!=0: fopen.readline()
#cur_loc=0
cur_line="-"

#src_fwd_index0,trg_fwd_index0=[],[]
bitext_list=[]
t0=time.time()
while cur_line!="":
  cur_loc=fopen.tell()
  f0=fopen.readline()
  cur_line=f0.strip("\n\r\t")
  line_split=cur_line.split("\t")
  if len(line_split)!=2: continue
  elif f0!="":
    src0,trg0=line_split
    bitext_list.append((counter,cur_loc,src0,trg0))
  counter+=1

  if len(bitext_list)%batch_size==0 or f0=="":
    print("now processing bitext_list:",len(bitext_list))
    last_counter,last_loc=bitext_list[-1][:2]
    if last_loc<start_loc:
      bitext_list=[]
      continue
    bitext_without_counter=[v[1:] for v in bitext_list]
    t0=time.time()
    tmp_src_inv_dict,tmp_trg_inv_dict=index_bitext_list(bitext_without_counter,retr_params)
    elapsed_indexing=time.time()-t0
    print("finished indexing:",round(elapsed_indexing,1))
    retr_params["src_index"]=tmp_src_inv_dict
    retr_params["trg_index"]=tmp_trg_inv_dict
    print("Now aligning bitext sentence pairs")
    #shuffle(bitext_list)
    sum_words=0
    prev_t0=time.time()
    for item0 in bitext_list:
      tmp_counter0,tmp_cur_loc0,tmp_src0,tmp_trg0=item0
      if tmp_cur_loc0<start_loc: continue
      src_toks=tok(tmp_src0)
      trg_toks=tok(tmp_trg0)
      if len(src_toks)>80 or len(trg_toks)>80: continue
      #print(len(src_toks), src_toks)
 
      t0=time.time()
      results=walign(tmp_src0,tmp_trg0,retr_params)
      elapsed=time.time()-t0
      results["loc"]=tmp_cur_loc0
      results["i"]=tmp_counter0
      results["elapsed"]=elapsed
      align_list=results.get("align",[])
      src_tokens_padded=results["src"]
      trg_tokens_padded=results["trg"]
      sum_words+=len(src_tokens_padded)
      #output=present_aligned(src_tokens_padded,trg_tokens_padded,align_list)
      out_fopen=open(aligned_fpath,"a")
      out_fopen.write(json.dumps(results)+"\n")
      out_fopen.close()
      if tmp_counter0%100==0: 
        prev_elapsed=time.time()-prev_t0
        print(tmp_counter0, "elapsed:",round(prev_elapsed,1),"total words processed:",sum_words)
        prev_t0=time.time()
        sum_words=0
      

      #print("elapsed",round(elapsed,4))
    bitext_list=[]
    #break

fopen.close()
term_shelve_open.close()
acr_shelve_open.close()


start_loc 28352128 counter 99998
now processing bitext_list: 50000
finished indexing: 29.8
Now aligning bitext sentence pairs
100000 elapsed: 3.1 total words processed: 75
100100 elapsed: 21.3 total words processed: 2400
100200 elapsed: 18.1 total words processed: 2392
100300 elapsed: 24.1 total words processed: 2501
100400 elapsed: 18.2 total words processed: 1861
100500 elapsed: 22.8 total words processed: 2349
100600 elapsed: 25.1 total words processed: 2680
100700 elapsed: 20.1 total words processed: 2410
100800 elapsed: 20.3 total words processed: 2402
100900 elapsed: 23.4 total words processed: 2479
101000 elapsed: 20.0 total words processed: 2375
101100 elapsed: 19.1 total words processed: 2298
101200 elapsed: 27.6 total words processed: 2372
101300 elapsed: 23.2 total words processed: 2465
101400 elapsed: 24.8 total words processed: 2043
101500 elapsed: 27.0 total words processed: 2765
101600 elapsed: 15.0 total words processed: 2185
101700 elapsed: 12.2 total words processed: 

In [ ]:
aligned_fpath="indexes/un/exp6/aligned-eluna1.txt"
fopen=open(aligned_fpath)
for i0,line0 in enumerate(fopen):
  line_dict0=json.loads(line0)
  aligned_phrases=present_aligned(line_dict0["src"],line_dict0["trg"],line_dict0["align"])
  if line_dict0["terms"]!=[]: print("terms:",line_dict0["terms"])
  if line_dict0["acr"]!=[]: print("acr:",line_dict0["acr"])
  print("--")
  for a in aligned_phrases:
    print(a)
  print("=======")
  #print(line_dict0)
  if i0>150: break
fopen.close()

--
('_-_ a552 _-_ 4a29e3e05f39 _/_ file </s>', '_-_ b58d _-_ df49954858ea _/_ file </s>', [[9, 15], [9, 15]], 1.5)
('_-_ a552 _-_ 4a29e3e05f39 _/_', '_-_ b58d _-_ df49954858ea _/_', [[9, 13], [9, 13]], 0.75)
('_-_ a552 _-_', '_-_ b58d _-_', [[9, 11], [9, 11]], 0.5)
('_-_', '_-_', [[9, 9], [9, 9]], 0.25)
('_-_', '_-_', [[11, 11], [11, 11]], 0.25)
('_/_', '_/_', [[13, 13], [13, 13]], 0.25)
('file </s>', 'file </s>', [[14, 15], [14, 15]], 0.75)
('file', 'file', [[14, 14], [14, 14]], 0.5)
('</s>', '</s>', [[15, 15], [15, 15]], 0.25)
('<s> ._ _._ _/_ cb4d85ff _-_', '<s> ._ _._ _/_ b52b733b _-_', [[0, 5], [0, 5]], 1.25)
('<s> ._ _._', '<s> ._ _._', [[0, 2], [0, 2]], 0.75)
('<s> ._', '<s> ._', [[0, 1], [0, 1]], 0.5)
('<s>', '<s>', [[0, 0], [0, 0]], 0.25)
('._', '._', [[1, 1], [1, 1]], 0.25)
('_._', '_._', [[2, 2], [2, 2]], 0.25)
('_/_ cb4d85ff _-_', '_/_ b52b733b _-_', [[3, 5], [3, 5]], 0.5)
('_/_', '_/_', [[3, 3], [3, 3]], 0.25)
('_-_', '_-_', [[5, 5], [5, 5]], 0.25)
('_-_', '_-_', [[7, 7], 

##Post-Processing of word align output - 5 Jan 2023
aligned sentences to extract phrases

In [ ]:
import os, json, shelve
from itertools import groupby
from code_utils.align_utils import *
matching_dict={}
aligned_fname="aligned.txt"
#aligned_fname="aligned-test1.txt"
#aligned_fname="aligned-test.txt"
#index_dir="indexes/un/exp5"

# index_dir="indexes/un/exp6"
# aligned_fpath=os.path.join(index_dir,aligned_fname)


#phrase_shelve_fname="phrases.shelve"
phrase_shelve_fname="phrases-eluna.shelve"
aligned_fname="aligned-eluna.txt"
aligned_fpath=os.path.join(index_dir,aligned_fname) #aligned_fname="aligned-eluna.txt"
out_fopen=open(aligned_fpath)
for i0,line0 in enumerate(out_fopen):
  #if i0>1000: continue
  if i0%20000==0: print(i0)
  results=json.loads(line0)
  align_list=results.get("align",[])
  src_tokens_padded=results["src"]
  trg_tokens_padded=results["trg"]  
  # if results["acr"]: print("acr:", results["acr"])
  # if results["terms"]: print("terms:", results["terms"])
  # if results["phon"]: print("phon:", results["phon"])
  
  output=present_aligned(src_tokens_padded,trg_tokens_padded,align_list)
  for ot in output: 
    src0,trg0,el0,wt0=ot
    if len(src0.split())>6: continue
    if src0==trg0: continue
    if wt0==0: continue
    src0=src0.lower()
    #print(src0,trg0,wt0)
    tmp_dict=matching_dict.get(src0,{})
    trg_count,trg_cumulative_wt=tmp_dict.get(trg0,(0,0))
    tmp_dict[trg0]=(trg_count+1,trg_cumulative_wt+wt0)
    matching_dict[src0]=tmp_dict
  #print("-----")

out_fopen.close()
final_list=[]
for a,b_dict in matching_dict.items():
  for b,b_vals in b_dict.items():
    b_count,b_wt=b_vals
    if b_count<5: continue
    if b_wt<1: continue
    new_b_wt=b_wt/b_count
    final_list.append((a,b, (b_count, new_b_wt)))
    #final_list.append((a,b, b_count, new_b_wt,b_wt))
    #print(a,b, b_vals)
final_list.sort(key=lambda x:x[0])
grouped=[(key,[v[1:] for v in list(group)]) for key,group in groupby(final_list,lambda x:x[0])]
grouped_dict=dict(iter(grouped))
out_list=list(grouped_dict.items())

#now generating dictionaries with unigram/bigram keys for easy retrieval
phrase_table_dict={}
for src_phrase0,trg_vals in out_list:
  key0=get_ngram_key(src_phrase0)
  tmp_dict=phrase_table_dict.get(key0,{})
  tmp_dict[src_phrase0]=trg_vals
  phrase_table_dict[key0]=tmp_dict



phrase_shelve_path=os.path.join(index_dir,phrase_shelve_fname)

if os.path.exists(phrase_shelve_path): os.remove(phrase_shelve_path)
phrase_shelve_open=shelve.open(phrase_shelve_path)
for a,b in phrase_table_dict.items(): phrase_shelve_open[a]=b
phrase_shelve_open.close()

print("saved to shelve:", phrase_shelve_path)
print("finished processing phrase table, total number of src phrases:",len(out_list))

0
20000
40000
60000
80000
100000
120000
140000
160000
180000
saved to shelve: indexes/un/exp6/phrases-eluna.shelve
finished processing phrase table, total number of src phrases: 27206


In [ ]:
!python run_bitext_walign.py

start_loc 33754892 counter 86833
now processing bitext_list: 50000
finished indexing: 38.8
Now aligning bitext sentence pairs
86900 elapsed: 52.3 total words processed: 2481
87000 elapsed: 72.4 total words processed: 4053
87100 elapsed: 77.8 total words processed: 3838
87200 elapsed: 54.9 total words processed: 3219
87300 elapsed: 62.0 total words processed: 3398
87400 elapsed: 71.9 total words processed: 3490
87500 elapsed: 72.5 total words processed: 3205
87600 elapsed: 46.2 total words processed: 2832
87700 elapsed: 61.0 total words processed: 2985
87800 elapsed: 26.8 total words processed: 2759
87900 elapsed: 35.1 total words processed: 2990
88000 elapsed: 26.0 total words processed: 2089
88100 elapsed: 60.5 total words processed: 3583
88200 elapsed: 33.7 total words processed: 2275
88300 elapsed: 25.6 total words processed: 2684
88400 elapsed: 4.0 total words processed: 1022
88500 elapsed: 36.0 total words processed: 2732
88600 elapsed: 39.4 total words processed: 2716
88700 elaps

In [ ]:
import os, json, shelve
from itertools import groupby
from code_utils.align_utils import *
matching_dict={}
index_dir="indexes/un/exp5"
aligned_fpath=os.path.join(index_dir,"aligned-test.txt")
out_fopen=open(aligned_fpath)
for i0,line0 in enumerate(out_fopen):
  if i0<266900: continue
  results=json.loads(line0)
  align_list=results.get("align",[])
  src_tokens_padded=results["src"]
  trg_tokens_padded=results["trg"]  
  #print("results",results.keys())
  print("terms",results.get("terms",[]))
  print("acr",results.get("acr",[]))
  print("phon",results.get("phon",[]))

out_fopen.close()

Streaming output truncated to the last 5000 lines.
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon [['Mindanao', 'مينداناو']]
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon [['November', 'نوفمبر']]
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon [['Vienna', 'فيينا']]
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon [['Vienna', 'فيينا']]
terms []
acr []
phon [['Vienna', 'فيينا']]
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []
phon []
terms []
acr []

In [ ]:
from code_utils.web_lib import *
url0="http://itrade360.net/app/index"
content0=get_page_content(url0)
dom_obj=DOM(content0)
#print(content0[:1000])
text_items_tags=dom_obj.simple_tag_text_items
for tag0,txt0 in text_items_tags:
  if tag0.startswith("<option"): continue
  if "data_item" in tag0: continue
  has_content_item_class=False
  has_id=False
  
  if not "content_item" in tag0 or "data_item" in tag0: continue
  print(tag0)
  print(txt0.strip())
  print("---")

<span id="company-name-top-label" class="text-blue-600 company-name content_item">
iTrade360
---
<a class="nav-link block pr-2 lg:px-2 py-2 text-gray-600 hover:text-gray-700 focus:text-gray-700 transition duration-150 ease-in-out content_item" href="#!" data-mdb-ripple="true" data-mdb-ripple-color="light" id="dashboard-label">
Dashboard
---
<a class="nav-link block pr-2 lg:px-2 py-2 text-gray-600 hover:text-gray-700 focus:text-gray-700 transition duration-150 ease-in-out content_item" href="#!" data-mdb-ripple="true" data-mdb-ripple-color="light" id="team-label">
Team
---
<a class="nav-link block pr-2 lg:px-2 py-2 text-gray-600 hover:text-gray-700 focus:text-gray-700 transition duration-150 ease-in-out content_item" href="#!" data-mdb-ripple="true" data-mdb-ripple-color="light" id="projects-label">
Projects
---
<button type="button" class="inline-block px-6 py-2.5 mr-2 bg-transparent text-blue-600 font-medium text-xs leading-tight uppercase rounded hover:text-blue-700 hover:bg-gray-100

In [ ]:
#test=re.findall('\<\!\-\-.+?\-\-\>',content0)
test=re.findall('<[^<>]*?>|\<\!\-\-.+?\-\-\>',content0)
for a in test:
  print(a)
  print("----")

<!DOCTYPE html>
----
<html lang="en">
----
<head>
----
<meta charset="UTF-8" />
----
<meta name="viewport" content="width=device-width, initial-scale=1, shrink-to-fit=no" />
----
<meta http-equiv="x-ua-compatible" content="ie=edge" />
----
<script src="https://d3js.org/d3.v4.min.js">
----
</script>
----
<script src="https://d3js.org/topojson.v2.min.js">
----
</script>
----
<script src="d3.tip.js">
----
</script>
----
<link href="https://fonts.googleapis.com/css?family=Raleway" rel='stylesheet' type='text/css'>
----
<title>
----
</title>
----
<!-- Favicon -->
----
<link rel="icon" href="assets/img/mdb-favicon.ico" type="image/x-icon" />
----
<!-- Inter font -->
----
<link
      href="https://fonts.googleapis.com/css2?family=Inter:wght@300;400;500;600;700&display=swap"
      rel="stylesheet"
    />
----
<!-- Tailwind -->
----
<script src="https://cdn.tailwindcss.com">
----
</script>
----
<!-- Tailwind Elements CSS -->
----
<link rel="stylesheet" href="assets/css/index.min.css" />
----
<!

In [ ]:
!chmod 777 ./pypy3.9-v7.3.9-linux64/bin/pypy
!./pypy3.9-v7.3.9-linux64/bin/pypy run_bitext_walign.py

start_loc 1548455 counter 5811
Traceback (most recent call last):
  File "run_bitext_walign.py", line 106, in <module>
    if len(bitext_list)%batch_size==0 or f0=="":
KeyboardInterrupt
^C


In [ ]:
len(tok(tmp_src0))

178

In [ ]:
len(tmp_src0.split())

63

In [ ]:
import time
el0=((0,1),(1,1))
el1=((2,2),(4,4))
t0=time.time()
for i in range(100000):
  el01=combine_els(el0,el1)
  el10=combine_els(el1,el0)
elapsed=time.time()-t0
print("elapsed",elapsed)

print("el01",el01)
print("el10",el10)

elapsed 0.5875754356384277
el01 ((0, 2), (1, 4))
el10 ((0, 2), (1, 4))


#Process UNTerm - 6 Jan 2023

In [5]:
import re, shelve
from code_utils.general import *
from code_utils.align_utils import *
from code_utils.arabic_lib import *

from itertools import groupby
from collections import Counter
ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})

def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)


cur_default_wt=1 #assigned for term/acr items

en_ar_term_dict={} #english term > arabic term
en_acr_dict={} #english acronyms > english terms
en_ar_acr_dict={} #english acronyms > arabic terms
term_fpath="term/all_unterm.tsv"
fopen=open(term_fpath)
first_row_as_headers=True
headers=[]
for i0,line0 in enumerate(fopen):
  #if i0>10: break
  if i0%10000==0: print(i0)
  line_items=line0.strip().split("\t")
  if len(line_items)<2: continue
  line_dict={}
  if i0==0 and first_row_as_headers: headers=line_items
  else: 
    for item_i,item0 in enumerate(line_items): 
      if item_i>len(headers)-1: continue
      split_item=[v.strip() for v in re.split("[;؛]",item0)] # item0.split(";")
      split_item=[v for v in split_item if not v.startswith('[superseded]') and not v.startswith("[deprecated]")]
      test_split_item=[v for v in split_item if v and v[0]=='[']
      if test_split_item: print(test_split_item)
      #split_tok_item=[cur_ar_tok_fn(v) for v in split_item]
      line_dict[headers[item_i]]= split_item #split_tok_item #split_item
  #print(line_dict)
  en_acronyms=line_dict.get("English Acronyms",[""])
  en_acronyms=[v for v in en_acronyms if v]
  #if en_acronyms==[""]: continue
  all_arabic=line_dict.get("Arabic",[])+line_dict.get("Arabic alternate",[])
  all_english=line_dict.get("English preferred",[])+line_dict.get("English alternate",[])
  all_arabic=[v for v in all_arabic if v!=""]
  all_arabic=[" ".join(cur_ar_tok_fn(v)) for v in all_arabic if v!=""]
  all_english_new_lower=[" ".join(tok(v.lower())) for v in all_english if v!=""]
  #all_english_new_lower=[v.lower() for v in all_english_new if v!=""]
  # for a in all_english_new_lower: print(a)
  for en0 in all_english_new_lower: en_ar_term_dict[en0]=en_ar_term_dict.get(en0,[])+all_arabic
  for acr0 in en_acronyms: en_ar_acr_dict[acr0]=en_ar_acr_dict.get(acr0,[])+all_arabic
  #print("en_acronyms",en_acronyms)


  # all_english=[v for v in all_english if v!=""]
  # en_acronyms=[v for v in en_acronyms if v!=""]
  # for en0 in all_english: en_ar_term_dict[en0]=en_ar_term_dict.get(en0,[])+all_arabic
  # for acr0 in en_acronyms: en_acr_dict[acr0]=en_acr_dict.get(acr0,[])+all_english
  # for acr0 in en_acronyms: en_ar_acr_dict[acr0]=en_ar_acr_dict.get(acr0,[])+all_arabic
term_dict=create_bigram_keyed_dict(en_ar_term_dict,default_wt=cur_default_wt)
acr_dict=create_bigram_keyed_dict(en_ar_acr_dict,default_wt=cur_default_wt)

fopen.close()
print("finished creating term_keyed_dict:",len(term_dict.keys()))
print("finished creating acr_keyed_dict:",len(acr_dict.keys()))

# term_shelve_path="terms.shelve"
# acr_shelve_path="acronyms.shelve"
# if os.path.exists(term_shelve_path): os.remove(term_shelve_path)
# if os.path.exists(acr_shelve_path): os.remove(acr_shelve_path)
# term_shelve_open=shelve.open(term_shelve_path)
# for a,b in term_dict.items(): term_shelve_open[a]=b
# term_shelve_open.close()
# acr_shelve_open=shelve.open(acr_shelve_path)
# for a,b in acr_dict.items(): acr_shelve_open[a]=b
# acr_shelve_open.close()



0
['[فريق الخبراء العامل الخاص المنشأ بموجب القرار 6 (د 25) الصادر عن لجنة حقوق الإنسان]']
10000
20000
30000
['[drug name] containing regimen']
40000
50000
60000
70000
['[please fill in]']
80000
['[please fill in]']
90000
finished creating term_keyed_dict: 55774
finished creating acr_keyed_dict: 21055


##Combine UNTerm with eLuna new terminology

In [6]:
#combine with eLuna fresh terminology
import json
collected_terms_fpath="term/collected-unterm-eluna-terms.txt"
fopen=open(collected_terms_fpath)
tmp_term_dict={}
tmp_acr_dict={}
for i0,line0 in enumerate(fopen):
  cur_line_dict=json.loads(line0)
  
  en_terms_raw=cur_line_dict.get("en",[])
  ar_terms_raw=cur_line_dict.get("ar",[])
  if en_terms_raw==[] or ar_terms_raw==[]: continue
  # en_terms=[(v["term"],v["class"]) for v in en_terms_raw]
  # ar_terms=[(v["term"],v["class"]) for v in ar_terms_raw]
  en_terms=[v["term"] for v in en_terms_raw]
  ar_terms=[v["term"] for v in ar_terms_raw]
  ar_terms_tok=[]
  for ar0 in ar_terms: 
    ar_tok0=cur_ar_tok_fn(ar0)
    ar_terms_tok.append(" ".join(ar_tok0))
  #print(en_terms,ar_terms_tok)
  for en0 in en_terms:
    if en0.isupper(): 
      found_acr=en_ar_acr_dict.get(en0,[])+ar_terms_tok
      tmp_acr_dict[en0]=en_ar_acr_dict[en0]=sorted(list(set(found_acr)))
    else: 
      found_term=en_ar_acr_dict.get(en0,[])+ar_terms_tok
      tmp_term_dict[en0]=en_ar_term_dict[en0]=sorted(list(set(found_term)))
    # found_term=en_ar_term_dict.get(en0,[])
    # found_acr=[]
    # if en0.isupper(): 
    #   found_acr=en_ar_acr_dict.get(en0,[])
    # print("found:", en0, "term:", found_term,"acr:", found_acr)
  #print("---")


  #print(cur_line_dict)

  #if i0>500: break

fopen.close()

# for a,b in tmp_term_dict.items():
#   print(a,b)
term_dict=create_bigram_keyed_dict(en_ar_term_dict,default_wt=cur_default_wt)
acr_dict=create_bigram_keyed_dict(en_ar_acr_dict,default_wt=cur_default_wt)

fopen.close()
print("finished creating term_keyed_dict:",len(term_dict.keys()))
print("finished creating acr_keyed_dict:",len(acr_dict.keys()))

term_shelve_path="terms.shelve"
acr_shelve_path="acronyms.shelve"

if os.path.exists(term_shelve_path): os.remove(term_shelve_path)
if os.path.exists(acr_shelve_path): os.remove(acr_shelve_path)

term_shelve_path="terms.shelve"
acr_shelve_path="acronyms.shelve"
term_shelve_open=shelve.open(term_shelve_path)
for a,b in term_dict.items(): term_shelve_open[a]=b
term_shelve_open.close()
acr_shelve_open=shelve.open(acr_shelve_path)
for a,b in acr_dict.items(): acr_shelve_open[a]=b
acr_shelve_open.close()

finished creating term_keyed_dict: 56791
finished creating acr_keyed_dict: 21087


##Match terminology to bitext - 13 Mar 2023

In [ ]:
from code_utils.sqld_utils import *
src_sqld_fpath="bitexts/src-manual.sqld"
#val_dict=get_sqld_val_multiple(src_sqld_fpath,['FICSA','P'])
val_dict=get_sqld_val_multiple(src_sqld_fpath,['apparently'])
for a,b in val_dict.items():
  print(a, len(b),b)

apparently 64 [2625183.007, 5881249.002, 38292696.006, 54086742.01, 54090344.052, 66474208.006, 73967222.013, 75055829.022, 76347357.018, 76436386.027, 76459435.019, 104746602.006, 105793199.034, 109671878.015, 127910315.001, 128935977.009, 133270972.009, 135322158.039, 136010136.027, 136011283.035, 136797805.032, 145059335.0, 153121152.04, 155630265.003, 155922699.033, 157106205.006, 160724457.006, 160980856.003, 167954353.035, 167954353.041, 167980788.017, 171322380.06, 175307128.037, 175841856.008, 175946761.002, 180208197.039, 187695439.012, 202198710.029, 203336616.004, 204483483.035, 210300375.008, 216415708.012, 225202168.013, 229911582.01, 235185070.06, 235476223.013, 253486987.016, 254929720.048, 262655306.0, 265000754.026, 265831270.006, 285217971.023, 290818537.006, 292518097.01, 292521699.052, 293615016.023, 302277610.0, 309589484.033, 312332472.013, 312398168.038, 312962189.039, 318642380.031, 318644204.003, 318763667.0]


## Get mtaching statsitics for src/trg phrases

In [ ]:
from code_utils.sqld_utils import *
from code_utils.align_utils import *
en_ar_corpus_combined_fname="bitexts/aligned-sents.txt"
src_sqld_fpath="bitexts/src-manual.sqld"
trg_sqld_fpath="bitexts/trg-manual.sqld"
fopen=open(en_ar_corpus_combined_fname)

def get_phrase_indexes_sqld(phrase0,sqld_fpath):
  phrase_tokens=phrase0.split()
  inv_dict0=get_sqld_val_multiple(sqld_fpath,list(set(phrase_tokens)))
  indexes0=retr(phrase_tokens,inv_dict0)
  return indexes0
def get_lines_simple(file_obj,index_list):
  line_list=[]
  for a in index_list:
    line_loc=int(a)
    file_obj.seek(line_loc)
    line0=file_obj.readline()
    line_list.append(line0.strip())
  return line_list



src_phrase="subsidiary means"
trg_phrase="وسائل احتياطية"
all_trg_phrases=["وسائل احتياطية","مصادر احتياطية","مصدر احتياطي","وسيلة احتياطية"]

src_indexes=get_phrase_indexes_sqld(src_phrase,src_sqld_fpath)
src_lines=get_lines_simple(fopen,src_indexes)
print(src_phrase,len(src_indexes))
for trg_phrase in all_trg_phrases:
  trg_indexes=get_phrase_indexes_sqld(trg_phrase,trg_sqld_fpath)
  common_indexes=list(set([int(v) for v in src_indexes]).intersection(set([int(v) for v in trg_indexes])))
  print(trg_phrase,len(common_indexes))
# for a in src_lines[:10]:
#   print(a)
# print(len(src_indexes))
# for a in src_indexes[:10]:
#   print(a)
#   line_loc=int(a)
#   fopen.seek(line_loc)
#   line0=fopen.readline()
#   print([line0])
fopen.close()

subsidiary means 127
وسائل احتياطية 73
مصادر احتياطية 8
مصدر احتياطي 8
وسيلة احتياطية 13


##Finally apply UN-term items to bitext

In [ ]:
from code_utils.sqld_utils import *
from code_utils.align_utils import *
src_sqld_fpath="bitexts/src-manual.sqld"
trg_sqld_fpath="bitexts/trg-manual.sqld"

en_ar_corpus_combined_fname="bitexts/aligned-sents.txt"
fopen=open(en_ar_corpus_combined_fname)

def get_lines_simple(file_obj,index_list):
  line_list=[]
  for a in index_list:
    line_loc=int(a)
    file_obj.seek(line_loc)
    line0=file_obj.readline()
    line_list.append(line0.strip())
  return line_list


excluded_src_tokens=["the","a","an","and","of","its","his","her","their","them","to","is","are","am","been","was","were","be", 
                     "have","has","had", "in", "on", "at", "with", "from","for","that","he","she","it","would",
                     "as","by","they","whose","which"] #we will need to update this
excluded_trg_tokens=["من","على","في","مع", "إلى",
                     "له","تم","إلى","في","عن","إن","أن","به","بها","لها","التي","كان","قد","الذي","الذين",
                     "هو","هي"]
used_en_terms={}
un_qa_list_fpath="un_qa_list_new.txt"
if os.path.exists(un_qa_list_fpath):
  un_qa_list_fopen=open(un_qa_list_fpath)
  for line0 in un_qa_list_fopen:
    line_dict0=json.loads(line0)
    en_term0=line_dict0.get("en")
    if en_term0==None: continue
    used_en_terms[en_term0]=True
  un_qa_list_fopen.close()

# for a,b in used_en_terms.items():
#   print(a,b)

all_src_words,all_trg_words=[],[]
items0=list(en_ar_term_dict.items())
for it_i,item0 in enumerate(items0):
  en_phrase,ar_phrase_list=item0
  en_phrase_tokens=en_phrase.lower().split() #tok(en_phrase)
  all_src_words.extend(en_phrase_tokens)
  for ar_phrase in ar_phrase_list:
    ar_phrase_tokens=ar_phrase.lower().split()
    all_trg_words.extend(ar_phrase_tokens)

all_src_words=list(set(all_src_words))
all_trg_words=list(set(all_trg_words))
src_inv_dict0=get_sqld_val_multiple(src_sqld_fpath,all_src_words)
print("identified src inv index dict")
trg_inv_dict0=get_sqld_val_multiple(trg_sqld_fpath,all_trg_words)
print("identified trg inv index dict")

for it_i,item0 in enumerate(items0):
  if it_i%50==0: print(it_i)
  en_phrase,ar_phrase_list=item0
  if used_en_terms.get(en_phrase,False): continue 
  cur_term_dict={}
  cur_term_dict["en"]=en_phrase
  
  #print(en_phrase,ar_phrase_list)
  en_phrase_tokens=en_phrase.split() #tok(en_phrase)
  en_phrase_filtered=filter_toks(en_phrase_tokens,params={"exclude_numbers":True, "excluded_words":excluded_src_tokens})
  cur_term_dict["en_filtered"]=en_phrase_filtered
  
  #src_inv_dict0=get_sqld_val_multiple(src_sqld_fpath,list(set(en_phrase_filtered)))
  src_indexes0=retr(en_phrase_filtered,src_inv_dict0)
  cur_term_dict["count"]=len(src_indexes0)
  #if len(src_indexes0)==0: continue
  #print(en_phrase_filtered, len(src_indexes0))
  ar_phrase_list=list(set(ar_phrase_list))
  remaining_indexes=[int(v) for v in src_indexes0]
  corr_list=[]
  for ar_phrase in ar_phrase_list:
    ar_temp_dict={}
    ar_temp_dict["ar"]=ar_phrase
    ar_phrase_tokens=ar_phrase.split() #tok(en_phrase)
    ar_phrase_filtered=filter_toks(ar_phrase_tokens,params={"exclude_numbers":True, "excluded_words":excluded_trg_tokens})
    ar_temp_dict["ar_filtered"]=ar_phrase_filtered
    #trg_inv_dict0=get_sqld_val_multiple(trg_sqld_fpath,list(set(ar_phrase_filtered)))
    if len(src_indexes0)==0:
      ar_temp_dict["count"]=0
      ar_temp_dict["common"]=0
    else:
      trg_indexes0=retr(ar_phrase_filtered,trg_inv_dict0)
      common_indexes=list(set([int(v) for v in src_indexes0]).intersection(set([int(v) for v in trg_indexes0])))
      ar_temp_dict["count"]=len(trg_indexes0)
      ar_temp_dict["common"]=len(common_indexes)
    corr_list.append(ar_temp_dict)
    #print(ar_phrase, len(common_indexes))
    remaining_indexes=list(set(remaining_indexes).difference(common_indexes))
  cur_term_dict["corr"]=corr_list
  cur_term_dict["remaining"]=remaining_indexes
  un_qa_list_fopen=open(un_qa_list_fpath,"a")
  un_qa_list_fopen.write(json.dumps(cur_term_dict)+"\n")
  un_qa_list_fopen.close()
  # print("remaining_indexes",len(remaining_indexes))
  # lines=get_lines_simple(fopen,remaining_indexes)
  # for a in lines:
  #   split0=a.split("\t")
  #   if len(split0)!=2: continue
  #   en0,ar0=split0
  #   print(en0)
  #   print(ar0)
  #   print("---")
  # print("===========")


fopen.close()

identified src inv index dict
identified trg inv index dict
0
50
100
150
200
250
300
350
400
450
500
550
600
650
700
750
800
850
900
950
1000
1050
1100
1150
1200
1250
1300
1350
1400
1450
1500
1550
1600
1650
1700
1750
1800
1850
1900
1950
2000
2050
2100
2150
2200
2250
2300
2350
2400
2450
2500
2550
2600
2650
2700
2750
2800
2850
2900
2950
3000
3050
3100
3150
3200
3250
3300
3350
3400
3450
3500
3550
3600
3650
3700
3750
3800
3850
3900
3950
4000
4050
4100
4150
4200
4250
4300
4350
4400
4450
4500
4550
4600
4650
4700
4750
4800
4850
4900
4950
5000
5050
5100
5150
5200
5250
5300
5350
5400
5450
5500
5550
5600
5650
5700
5750
5800
5850
5900
5950
6000
6050
6100
6150
6200
6250
6300
6350
6400
6450
6500
6550
6600
6650
6700
6750
6800
6850
6900
6950
7000
7050
7100
7150
7200
7250
7300
7350
7400
7450
7500
7550
7600
7650
7700
7750
7800
7850
7900
7950
8000
8050
8100
8150
8200
8250
8300
8350
8400
8450
8500
8550
8600
8650
8700
8750
8800
8850
8900
8950
9000
9050
9100
9150
9200
9250
9300
9350
9400
9450
9500
9550
960

## Export validated UN Term entries to use in QA

In [ ]:
import json
from itertools import groupby
valid_term_list=[]
first_word_fwd_list=[]
un_qa_list_fpath="un_qa_list.txt"
if os.path.exists(un_qa_list_fpath):
  un_qa_list_fopen=open(un_qa_list_fpath)
  for i0,line0 in enumerate(un_qa_list_fopen):
    line_dict0=json.loads(line0)
    en0=line_dict0.get("en")
    count0=line_dict0.get("count")
    corr=line_dict0.get("corr",[])
    #print(line_dict0)
    
    valid_corr=[]
    for c0 in corr:
      ar0=c0["ar"]
      common0=c0["common"]
      if common0==0: continue
      wt=common0/count0
      valid_corr.append((ar0,common0, round(wt,2)))
      #print(ar0,common0, round(wt,2))
    if valid_corr:
      new_dict={}
      new_dict["en"]=en0
      new_dict["count"]=count0
      new_dict["corr"]=valid_corr
      valid_term_list.append(new_dict)
      first_word=en0.split()[0]
      first_word_fwd_list.append((first_word,new_dict))
      # print(en0,count0)
      # for vc in valid_corr: print(vc)
      # print("---")

    #if i0>500: break
  un_qa_list_fopen.close()

valid_term_list.sort(key=lambda x:-x["count"])
# for a in valid_term_list[:100]:
#   print(a)

valid_term_list_fpath="valid_term_list.json"
valid_term_list_fopen=open(valid_term_list_fpath,"w")
json.dump(valid_term_list,valid_term_list_fopen)
valid_term_list_fopen.close()

first_word_fwd_list.sort(key=lambda x:x[0])
grouped=[(key,[v[1] for v in list(group)]) for key,group in groupby(first_word_fwd_list,lambda x:x[0])]
first_word_term_qa_dict=dict(iter(grouped))
first_word_term_qa_dict_fpath="first_word_term_qa_dict.json"
first_word_term_qa_dict_fopen=open(first_word_term_qa_dict_fpath,"w")
json.dump(first_word_term_qa_dict,first_word_term_qa_dict_fopen)
first_word_term_qa_dict_fopen.close()

# for a,b in grouped:
#   print(a)
#   print(b)


In [ ]:
import json
first_word_term_qa_dict_fpath="first_word_term_qa_dict.json"
first_word_term_qa_dict_fopen=open(first_word_term_qa_dict_fpath)
first_word_term_qa_dict=json.load(first_word_term_qa_dict_fopen)
first_word_term_qa_dict_fopen.close()
word0="community"
res=first_word_term_qa_dict[word0]
for a in res:
  print(a)

{'en': 'community _-_ based organizations', 'count': 37, 'corr': [['منظمات أهلية', 14, 0.38]]}
{'en': 'community of portuguese _-_ speaking countries', 'count': 53, 'corr': [['جماعة ال_بلدان ال_ناطقة بـ ال_برتغالية', 16, 0.3]]}
{'en': 'community of portuguese language _-_ speaking countries', 'count': 2, 'corr': [['جماعة ال_بلدان ال_ناطقة بـ ال_برتغالية', 2, 1.0]]}
{'en': 'community development project', 'count': 3, 'corr': [['مشروع ال_تنمية ال_مجتمعية', 1, 0.33]]}
{'en': 'community policing', 'count': 55, 'corr': [['ال_خفارة ال_مجتمعية', 40, 0.73]]}
{'en': 'community _-_ based policing', 'count': 4, 'corr': [['ال_خفارة ال_مجتمعية', 4, 1.0]]}
{'en': 'community _-_ oriented policing', 'count': 31, 'corr': [['ال_خفارة ال_مجتمعية', 27, 0.87]]}
{'en': 'community development', 'count': 38, 'corr': [['تنمية مجتمعية', 25, 0.66]]}
{'en': 'community service', 'count': 9, 'corr': [['خدمة ال_مجتمع', 5, 0.56]]}
{'en': 'community centre', 'count': 3, 'corr': [['مركز مجتمعي', 3, 1.0]]}
{'en': 'commu

In [ ]:
items0=list(trg_inv_index.items())
for a,b in items0[5000:5600]:
  print(a,b)

trg_sqld_fpath="bitexts/src-manual.sqld"
dict2sqld(trg_inv_index,sqld_fpath)

جسيما [7067.019]
جسيمات [2945.042]
جسيمة [6548.048]
جعل [300.032, 2979.057, 3063.029, 3102.037, 3122.024, 6948.03, 7102.03, 7643.008, 7919.028, 7924.01, 7940.001, 8289.013, 8480.028]
جعلت [1059.017, 7346.002, 7761.013, 8226.045]
جغرافي [204.029, 231.006, 235.017, 246.011, 262.012, 263.033, 264.02, 265.034, 280.022, 289.03, 298.037, 306.055, 325.019, 331.011, 395.025, 413.031, 578.01, 582.031, 584.005, 584.059, 597.022, 666.009, 1081.017, 1300.037, 1561.001, 1605.001, 3185.058, 3347.003, 6847.011, 7899.016]
جغرافيا [3348.021, 6536.032, 6570.022, 6702.007, 6703.009, 6821.103, 7565.011, 7619.066]
جغرافية [454.035, 459.026, 1177.026, 2448.001, 3346.019, 3347.018, 3348.007, 3348.036, 3363.009, 3748.011, 3835.001, 3838.007, 3846.026, 3849.01, 3850.007, 3851.027, 3852.006, 3853.028, 4245.001, 6662.036, 6680.008, 6713.027, 7180.012]
جفاف [2970.026, 2971.014, 2978.03, 2985.024, 7350.01, 9263.046]
جلال [5579.001, 6142.0, 6157.0]
جلب [281.017, 9072.004]
جلسات [2665.081, 2666.005, 3216.066, 3218.0

True

In [ ]:
from code_utils import general
# from code_utils.arabic_lib import *
# from itertools import groupby
# from collections import Counter
# ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})

# def cur_ar_tok_fn(text):
#   cur_toks=tok(text)
#   return tok_ar(cur_toks,ar_counter_dict)

# def walign_NEW(src_sent,trg_sent,params0={}):
#   tok_fn=params0.get("tok_fn",general.tok)
#   lang2_tok_fn=params0.get("lang2_tok_fn")
#   lang1=params0.get("lang1","en")
#   lang2=params0.get("lang2","ar")
#   cur_n_epochs=params0.get("n_epochs",5)
#   cur_max_sent_size=params0.get("max_sent_size",50)
#   cur_max_src_span=params0.get("max_src_span",6)

#   src_index0=params0.get("src_index",{})
#   trg_index0=params0.get("trg_index",{})
#   phrase_dict0=params0.get("phrase_dict",{})
#   term_dict0=params0.get("term_dict",{})
#   acr_dict0=params0.get("acr_dict",{})
#   custom_dict0=params0.get("custom_dict",{})
  
#   src_tokens=tok_fn(src_sent)
#   if lang2_tok_fn!=None: trg_tokens=lang2_tok_fn(trg_sent)
#   else: trg_tokens=tok_fn(trg_sent)
#   if len(src_tokens)>cur_max_sent_size or len(trg_tokens)>cur_max_sent_size: cur_n_epochs=1
#   src_tokens,trg_tokens=add_padding(src_tokens),add_padding(trg_tokens)
#   src_tokens_lower=[v.lower() for v in src_tokens]
#   trg_tokens_lower=[v.lower() for v in trg_tokens]
#   src_tokens_filtered,trg_tokens_filtered=filter_toks(src_tokens,params0),filter_toks(trg_tokens,params0)
#   all_matching=[]
#   phon_match0=get_phon_matching(src_tokens,trg_tokens)
#   exact_match0=get_exact_matching(src_tokens,trg_tokens,default_ratio=0.25)
#   index_match0=get_index_matching(src_tokens_filtered,trg_tokens_filtered,src_index0,trg_index0,max_phrase_length=3,min_intersection_count=3)
#   phrase_match0=match_keyed_dict(src_tokens_lower,trg_tokens_lower,phrase_dict0)
#   term_match0=match_keyed_dict(src_tokens_lower,trg_tokens_lower,term_dict0)
#   acr_match0=match_keyed_dict(src_tokens,trg_tokens,acr_dict0)
#   all_matching=phon_match0+exact_match0+index_match0+phrase_match0+term_match0+acr_match0
#   align_list=get_aligned_path(all_matching,n_epochs=cur_n_epochs,max_src_span=cur_max_src_span,dist_penalty=0)
#   results={}
#   results["src"]=src_tokens
#   results["trg"]=trg_tokens
#   results["align"]=align_list
#   return results

# def match_keyed_dict(src_tokens,trg_tokens,keyed_dict): #match unigram/bigramed keyed dict (phrase table/terms/acronyms/custom)
#   all_matching_list=[]
#   src_unigrams_bigrams=get_unigrams_bigrams(src_tokens)
#   for ub in src_unigrams_bigrams:
#     corr_dict=keyed_dict.get(ub)
#     if corr_dict==None: continue
#     for src_phrase0,corr_trg_vals in corr_dict.items():
#       src_span0=general.is_in(src_phrase0.split(),src_tokens)
#       if not src_span0: continue
#       for trg_phrase0,trg_val0 in corr_trg_vals:
#         trg_span0=general.is_in(trg_phrase0.split(),trg_tokens)
#         if not trg_span0: continue
#         all_matching_list.append((src_phrase0,trg_phrase0,src_span0,trg_span0,trg_val0))
#   return all_matching_list

src_sent='The commissions of inquiry, which have sought to ground the human rights obligations of such actors in the fact that they control territories and populations, have made recommendations to both States and armed groups without obvious distinction, prompting one observer to note that there seemed to be a growing tendency to view the violations thematically, without any particular (special) attention as to whether such violations were committed by a State or a non-State actor.	'
trg_sent='وقدمت لجان التحقيق، التي حرصت على أن تبني التزامات هذه الجهات في مجال حقوق الإنسان على أساس السيطرة التي تمارسها على الأقاليم والسكان، توصيات إلى الدول والجماعات المسلحة على حد سواء من دون أن تميز بينهما تمييزاً واضحاً، مما جعل أحد المراقبين يرى في ذلك نزوعاً متنامياً إلى فحص الانتهاكات من حيث الموضوع، من دون إيلاء أي اعتبار دقيق (خاص) لمسألة ما إذا كانت هذه الانتهاكات قد ارتكبتها دولة أو جهة غير تابعة للدولة.'
#src_sent='According to the United Nations Office for the Coordination of Humanitarian Affairs (OCHA), landmines and unexploded ordnance (UXO) accounted for the largest share of civilian casualties in the period since the signing of the truce in April 2022: As fighting subsided, civilians could move more freely, with many now seeking to access their farmlands and homes.'
#trg_sent='وفقا لمكتب الأمم المتحدة لتنسيق الشؤون الإنسانية، شكلت الألغام الأرضية والذخائر غير المنفجرة أكبر حصة من الضحايا المدنيين في الفترة منذ توقيع الهدنة في نيسان/أبريل 2022: ومع انحسار القتال، يمكن للمدنيين التحرك بحرية أكبر، حيث يسعى الكثيرون الآن إلى الوصول إلى أراضيهم الزراعية ومنازلهم.'

params={}
params["lang2_tok_fn"]=cur_ar_tok_fn
params["phrase_dict"]=phrase_table_dict
params["term_dict"]=term_dict
params["acr_dict"]=acr_dict
# params["lang2_tok_fn"]=cur_ar_tok_fn
# params["lang2_tok_fn"]=cur_ar_tok_fn

out=walign_NEW(src_sent,trg_sent,params)
# for a,b in out.items():
#   print(a,b)
out_items=present_aligned(out["src"],out["trg"],out["align"])
for a in out_items:
  print(a)
# src_tokenized=tok(src_sent)
# src_tokenized_lower=[v.lower() for v in src_tokenized]
# trg_tokenized=cur_ar_tok_fn(trg_sent)

# # src_unigrams_bigrams=get_unigrams_bigrams(src_tokenized)
# # src_unigrams_bigrams_lower=get_unigrams_bigrams(src_tokenized_lower)


# match1=match_keyed_dict(src_tokenized_lower,trg_tokenized,phrase_table_dict)
# for m1 in match1:
#   print("phrase match:", m1)
# match2=match_keyed_dict(src_tokenized_lower,trg_tokenized,term_keyed_dict)
# for m2 in match2:
#   print("term match:", m2)
# match3=match_keyed_dict(src_tokenized,trg_tokenized,acr_keyed_dict)
# for m3 in match3:
#   print("acr match:", m3)


# for a in src_unigrams_bigrams_lower:
#   corr_dict=phrase_table_dict.get(a)
#   if corr_dict==None: continue
#   for src_phrase0,corr_trg_vals in corr_dict.items():
#     src_span0=is_in(src_phrase0.split(),src_unigrams_bigrams_lower)
#     if not src_span0: continue
#     for trg_phrase0,trg_val0 in corr_trg_vals:
#       trg_span0=is_in(trg_phrase0.split(),trg_tokenized)
#       if not trg_span0: continue
#       print(src_phrase0,trg_phrase0,src_span0,trg_span0,trg_val0)

  #print(a,corr_dict)


('violations were committed by a State or', 'ال_انتهاكات قد ارتكبت ـها دولة أو', ((71, 77), (79, 84)), 4.336981128062639)
('violations were committed', 'ال_انتهاكات قد ارتكبت', ((71, 73), (79, 81)), 0.8030226921275782)
('violations', 'ال_انتهاكات', ((71, 71), (79, 79)), 0.6680828289894107)
('committed', 'ارتكبت', ((73, 73), (81, 81)), 0.1349398631381674)
('State or', 'دولة أو', ((76, 77), (83, 84)), 3.5339584359350615)
('State', 'دولة', ((76, 76), (83, 83)), 3)
('or', 'أو', ((77, 77), (84, 84)), 0.5339584359350615)
('human rights', 'حقوق ال_إنسان', ((12, 13), (16, 17)), 3)
('recommendations to both States and armed', 'توصيات إلى ال_دول وـ ال_جماعات ال_مسلحة على حد سواء', ((30, 35), (29, 37)), 2.247002648585721)
('both States and armed', 'ال_دول وـ ال_جماعات ال_مسلحة على حد سواء', ((32, 35), (31, 37)), 1.383493031081254)
('States and armed', 'ال_دول وـ ال_جماعات ال_مسلحة', ((33, 35), (31, 34)), 1.1272656508469105)
('States', 'ال_دول', ((33, 33), (31, 31)), 0.552798023035209)
('armed', '

#QA Pipeline - Feb 15, 2023

## ★ Run QA for current job bitext - 6 Jan 2023
If using Google sheet instead of TSV, add content in:
https://docs.google.com/spreadsheets/d/17KAQke0fUbY6S9-HLdd8slgdJUuKsOxO_wkpz4sM6P0/edit#gid=37808648

In [ ]:
import re,json,shelve
from code_utils import general
from code_utils.general import *
from code_utils.arabic_lib import *
from code_utils.align_utils import *
from code_utils.pandas_utils import *
from code_utils.sqld_utils import *
from code_utils.web_lib import *

from itertools import groupby
from collections import Counter
ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})

co_ref_list=["it","its","they","them","their","that","this", "these","those","latter","former"]

out_fpath="qa/test-output4.html"
max_indexes_per_phrase=30

def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)

term_shelve_path="terms.shelve"
acr_shelve_path="acronyms.shelve"
#phrase_shelve_path="phrases.shelve"

# index_dir="indexes/un/exp6"
# phrase_shelve_path=os.path.join(index_dir,"phrases.shelve")


phrase_shelve_path='indexes/un/exp6/phrases-eluna.shelve' #os.path.join(index_dir,"phrases.shelve")


term_shelve_open=shelve.open(term_shelve_path)
acr_shelve_open=shelve.open(acr_shelve_path)
phrase_shelve_open=shelve.open(phrase_shelve_path)

normative_path="https://docs.google.com/spreadsheets/d/e/2PACX-1vSpf4wpYxSkFFC84xMNFFVM_LKWtQo8wIchL8sksiNSQLZktwPTnLW9jmF2jVpv4gORd9gD9QtcrTGZ/pub?output=xlsx"
normative_obj=get_workbook_obj(normative_path)
normative_cols=["en","ar","type"]
normative_data=get_sheets_cols(normative_obj,["normative"],normative_cols)
normative_tok_list=[]
for src0,trg0,type0 in normative_data:
  src_toks0=tok(src0)
  trg_toks0=cur_ar_tok_fn(trg0)
  normative_tok_list.append((src_toks0,trg_toks0,type0))



src_sent='The commissions of inquiry, which have sought to ground the human rights obligations of such actors in the fact that they control territories and populations, have made recommendations to both States and armed groups without obvious distinction, prompting one observer to note that there seemed to be a growing tendency to view the violations thematically, without any particular (special) attention as to whether such violations were committed by a State or a non-State actor.	'
trg_sent='وقدمت لجان التحقيق، التي حرصت على أن تبني التزامات هذه الجهات في مجال حقوق الإنسان على أساس السيطرة التي تمارسها على الأقاليم والسكان، توصيات إلى الدول والجماعات المسلحة على حد سواء من دون أن تميز بينهما تمييزاً واضحاً، مما جعل أحد المراقبين يرى في ذلك نزوعاً متنامياً إلى فحص الانتهاكات من حيث الموضوع، من دون إيلاء أي اعتبار دقيق (خاص) لمسألة ما إذا كانت هذه الانتهاكات قد ارتكبتها دولة أو جهة غير تابعة للدولة.'
#src_sent='According to the United Nations Office for the Coordination of Humanitarian Affairs (OCHA), landmines and unexploded ordnance (UXO) accounted for the largest share of civilian casualties in the period since the signing of the truce in April 2022: As fighting subsided, civilians could move more freely, with many now seeking to access their farmlands and homes.'
#trg_sent='وفقا لمكتب الأمم المتحدة لتنسيق الشؤون الإنسانية، شكلت الألغام الأرضية والذخائر غير المنفجرة أكبر حصة من الضحايا المدنيين في الفترة منذ توقيع الهدنة في نيسان/أبريل 2022: ومع انحسار القتال، يمكن للمدنيين التحرك بحرية أكبر، حيث يسعى الكثيرون الآن إلى الوصول إلى أراضيهم الزراعية ومنازلهم.'

excluded_src_tokens=["the","a","an","and","of","its","his","her","their","them","to","is","are","am","been","was","were","be", 
                     "have","has","had", "in", "on", "at", "with", "from","for","that","he","she","it","would",
                     "as","by","they","whose","which"] #we will need to update this
excluded_trg_tokens=["من","على","في","مع", "إلى",
                     "له","تم","إلى","في","عن","إن","أن","به","بها","لها","التي","كان","قد","الذي","الذين",
                     "هو","هي"]

params={}
params["lang2_tok_fn"]=cur_ar_tok_fn
params["phrase_dict"]=phrase_shelve_open#phrase_table_dict
params["term_dict"]=term_shelve_open#term_dict
params["acr_dict"]=acr_shelve_open#acr_dict
params["excluded_words"]=excluded_src_tokens+excluded_trg_tokens
params["lang2_tok_fn"]=cur_ar_tok_fn

sent_class0="sent0"
tsv_fpath0="qa/15mar0.tsv"
#tsv_fpath0="qa/14jan1.tsv"
#bitext1=get_tsv_bitext(tsv_fpath0)

#https://docs.google.com/spreadsheets/d/e/2PACX-1vS8-zn0nwjU9U_NMnUkBG6PsdsnN78izRte1BLZjGzJhryDrkDzY7OVds3Szm91r1Vqh8gv4PoAtkkO/pubhtml
job_wb_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vS8-zn0nwjU9U_NMnUkBG6PsdsnN78izRte1BLZjGzJhryDrkDzY7OVds3Szm91r1Vqh8gv4PoAtkkO/pub?output=xlsx'
job_wb_obj=get_workbook_obj(job_wb_path)
cols=["en","ar"]
job_sheets=["doc"]
bitext1=get_sheets_cols(job_wb_obj,job_sheets,cols)

print("retrieved job bitext")


all_src_words,all_trg_words=[],[]
for src0,trg0 in bitext1:
  if src0.strip()==trg0.strip(): continue
  src_toks=tok(src0)
  src_toks_lower=[v.lower() for v in src_toks]
  trg_toks=cur_ar_tok_fn(trg0)
  all_src_words.extend(src_toks_lower)
  all_trg_words.extend(trg_toks)
all_src_words=list(set(all_src_words))
all_trg_words=list(set(all_trg_words))
src_sqld_fpath="bitexts/src-manual.sqld"
trg_sqld_fpath="bitexts/trg-manual.sqld"
src_index_dict=get_sqld_val_multiple(src_sqld_fpath,all_src_words)
trg_index_dict=get_sqld_val_multiple(trg_sqld_fpath,all_trg_words)
print("retrieved indexes for words in current bitext")


src_items=list(src_index_dict.items())
trg_items=list(trg_index_dict.items())
combined=src_items+trg_items
print("combined src+trg words and indexes")

used_indexes_dict={}
for phrase0,indexes0 in combined:
  cur_used_phrase_indexes=[]
  for in0 in indexes0:
    if len(cur_used_phrase_indexes)>=max_indexes_per_phrase: break
    in0_int=int(in0)
    if used_indexes_dict.get(in0_int,False): continue
    used_indexes_dict[in0_int]=True
    cur_used_phrase_indexes.append(in0_int)
keys=list(used_indexes_dict.keys())
print("number of final indexes to retrieve:",len(keys))
en_ar_corpus_combined_fname="bitexts/aligned-sents.txt"
bitext_fopen=open(en_ar_corpus_combined_fname)


lines=get_lines_simple(bitext_fopen,keys)
final_bitext=[]
for a in lines:
  split0=a.split("\t")
  if len(split0)!=2: continue
  final_bitext.append(split0)
bitext_fopen.close()
print("final_bitext:",len(final_bitext))




consistency_check_dict={}

#src_index_dict,trg_index_dict=index_bitext_list(bitext1,params) #final_bitext
src_index_dict,trg_index_dict=index_bitext_list(final_bitext,params)
print("finished indexing refined bitext")
params["src_index"]=src_index_dict
params["trg_index"]=trg_index_dict

final_sent_pair_list_with_classes=[]
strong_mismatch_count,weak_mismatch_count=0,0


for i0,item0 in enumerate(bitext1):
  if i0%10==0: print(i0, "out of", len(bitext1))
  src_sent,trg_sent=item0
  tmp_params=dict(params)
  if len(src_sent.split())>20: 
    tmp_params["n_epochs"]=3
  out=walign(src_sent,trg_sent,tmp_params)
  cur_src0,cur_trg0,cur_align0=out["src"],out["trg"],out.get("align",[])
  ph_list=present_aligned(cur_src0,cur_trg0,cur_align0)
  #phrases=extract_phrases(cur_src0,cur_trg0,cur_align0, max_phrase_size=8, discard_empty_phrases=False)
  for ph0 in ph_list:
    cur_src_phrase,cur_trg_phrase,el0,el_wt0=ph0
    #print(cur_src_phrase,cur_trg_phrase)
    cur_src_phrase=cur_src_phrase.lower()
    tmp_consistency_dict=consistency_check_dict.get(cur_src_phrase,{})
    tmp_consistency_dict[cur_trg_phrase]=tmp_consistency_dict.get(cur_trg_phrase,0)+1
    consistency_check_dict[cur_src_phrase]=tmp_consistency_dict

    # ph_src_toks,ph_trg_toks,ph_wt=ph0
    # #ph_src_str,ph_trg_str=" ".join(ph_src_toks)," ".join(ph_trg_toks)
    # ph_src_str=de_tok2str(ph_src_toks)
    # ph_trg_str=de_tok2str(ph_trg_toks)
    # print(ph_src_str)
    # print(ph_trg_str)

  #print("---")

  src_tok_tags1,trg_tok_tags1=align_words_span_tags(cur_src0,cur_trg0,cur_align0,sent_class="sent0")
  qa_match_list0=qa_match_all(cur_src0,cur_trg0,normative_tok_list)
  src_qa_out,trg_qa_out=qa_add_spans_classes(cur_src0,cur_trg0,qa_match_list0)
  for a in src_qa_out:
    if "strong-mismatch" in a[0]: strong_mismatch_count+=1
    if "weak-mismatch" in a[0]: weak_mismatch_count+=1
    # if not"mismatch" in a[0]: continue
    # print(a)
  de_tok_space_src_items=de_tok_space(cur_src0)
  de_tok_space_trg_items=de_tok_space(cur_trg0)
  src_cell,trg_cell="",""
  for item_i,item0 in enumerate(de_tok_space_src_items):
    src_tok_str,src_tok_space=item0
    if src_tok_str in ['<s>',"</s>"]: continue
    walign_open0,walign_close0=src_tok_tags1[item_i]
    norm_open0,norm_close0=src_qa_out[item_i]
    open0=walign_open0+norm_open0
    close0=norm_close0+walign_close0
    src_cell+=open0+src_tok_str+close0+src_tok_space
  for item_i,item0 in enumerate(de_tok_space_trg_items):
    trg_tok_str,trg_tok_space=item0
    if trg_tok_str in ['<s>',"</s>"]: continue
    walign_open0,walign_close0=trg_tok_tags1[item_i]
    norm_open0,norm_close0=trg_qa_out[item_i]
    open0=walign_open0+norm_open0
    close0=norm_close0+walign_close0
    trg_cell+=open0+trg_tok_str+close0+trg_tok_space
  final_sent_pair_list_with_classes.append((src_cell,trg_cell))    

table_content0=""
for a,b in final_sent_pair_list_with_classes:
  tr0='<tr><td width="50%%">%s</td><td dir="rtl" align="right" width="50%%">%s</td></tr>'%(a,b)
  table_content0+=tr0

c_items=list(consistency_check_dict.items())
c_items.sort(key=lambda x:-sum(x[1].values()))
# for a,b in c_items[:500]:
#   print(a,b)

#Creating the analysis table
analysis_table_content0=""
for key0,corr_dict0 in c_items:
  src_split=key0.split()
  src_split=[v for v in src_split if not v in ["<s>","</s>"]]
  if src_split==[]: continue
  key0=de_tok2str(src_split)
  if len(key0)<2: continue
  corr_cell_items=[]
  for corr_ar_str,corr_count in corr_dict0.items():
    trg_split=corr_ar_str.split()
    trg_split=[v for v in trg_split if not v in ["<s>","</s>"]]
    if trg_split==[]: continue
    corr_ar_str=de_tok2str(trg_split)
    corr_cell_items.append('%s | (%s)'%(corr_ar_str,corr_count))
  corr_cell="<br>".join(corr_cell_items)
  tr0='<tr><td>%s</td><td>%s</td></tr>'%(key0,corr_cell)
  analysis_table_content0+=tr0


qa_template_fpath="qa/qa-template.html"
qa_template_fopen=open(qa_template_fpath)
qa_template_content=qa_template_fopen.read()
qa_template_fopen.close()
qa_template_obj=DOM(qa_template_content)
repl_dict={}
repl_dict["#translation_table"]=(table_content0,{})
repl_dict["#analysis_table"]=(analysis_table_content0,{})
out_html=qa_template_obj.replace(repl_dict)

out_fopen=open(out_fpath,"w")
out_fopen.write(out_html)
out_fopen.close()

print("strong_mismatch_count,weak_mismatch_count",strong_mismatch_count,weak_mismatch_count)
content1=create_align_html_content(final_sent_pair_list_with_classes)
out_fpath=tsv_fpath0.replace(".tsv",".html")
fopen=open(out_fpath,"w")
fopen.write(content1)
fopen.close()

# #create_align_html_content(aligned_html_sent_pairs,phrase_analysis_table="")
# create_align_html_content(final_sent_pair_list_with_classes)

phrase_shelve_open.close()
term_shelve_open.close()
acr_shelve_open.close()


print("finished processing")

retrieved job bitext
retrieved indexes for words in current bitext
combined src+trg words and indexes
number of final indexes to retrieve: 35899
final_bitext: 35899
finished indexing refined bitext
0 out of 134
10 out of 134
20 out of 134
30 out of 134
40 out of 134
50 out of 134
60 out of 134
70 out of 134
80 out of 134
90 out of 134
100 out of 134
110 out of 134
120 out of 134
130 out of 134
strong_mismatch_count,weak_mismatch_count 0 2
finished processing


##New QA

In [ ]:
import shelve
from code_utils.arabic_lib import *
from code_utils.align_utils import *
from code_utils.general import *
from itertools import groupby
from collections import Counter
ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})
def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)

# def qa_keyed_dict(src_tokens,trg_tokens,keyed_dict,filter_params={}): #inspect if for a keyed dict, each phrase found in source have corresponding trg phrase
#   all_qa_list=[]
#   src_tokens=filter_toks(src_tokens,filter_params)
#   trg_tokens=filter_toks(trg_tokens,filter_params)
#   src_unigrams_bigrams=get_unigrams_bigrams(src_tokens)
#   for ub in src_unigrams_bigrams:
#     corr_dict=keyed_dict.get(ub)
#     if corr_dict==None: continue
#     for src_phrase0,corr_trg_vals in corr_dict.items(): #phrase is a token-ready string
#       src_phrase_tokens0=src_phrase0.split()
#       src_phrase_tokens0=filter_toks(src_phrase_tokens0,filter_params)
#       src_span0=general.is_in(src_phrase_tokens0,src_tokens)
#       new_src_span=[]
#       for ss in src_span0:
#         start0,end0=ss
#         if end0-start0==len(src_phrase_tokens0)-1: new_src_span.append(ss)
#       if not new_src_span: continue
#       #the src phrase exists
#       corr_trg_vals.append((src_phrase0,0)) #to account for situations where the corresponding term is also in English
#       trg_corr=[]
#       for trg_phrase0,trg_val0 in corr_trg_vals:
#         trg_phrase_tokens0=trg_phrase0.split()
#         trg_phrase_tokens0=filter_toks(trg_phrase_tokens0,filter_params)
#         trg_span0=general.is_in(trg_phrase_tokens0,trg_tokens)
#         trg_corr.append((trg_phrase0,trg_span0))
#       all_qa_list.append((src_phrase0,src_span0,trg_corr))
#         # if not trg_span0: continue
#         # freq0,wt0=trg_val0
#         # all_matching_list.append((src_phrase0,trg_phrase0,src_span0,trg_span0,freq0,wt0))
#   return all_qa_list


phrase_shelve_path='indexes/un/exp6/phrases-eluna.shelve' #os.path.join(index_dir,"phrases.shelve")
term_shelve_path="terms.shelve"
acr_shelve_path="acronyms.shelve"

#params={}
term_shelve_open=shelve.open(term_shelve_path)
acr_shelve_open=shelve.open(acr_shelve_path)
phrase_shelve_open=shelve.open(phrase_shelve_path)

excluded_src_tokens=["the","a","an","and","of","its","his","her","their","them","to","is","are","am","been","was","were","be", 
                     "have","has","had", "in", "on", "at", "with", "from","for","that","he","she","it","would",
                     "as","by","they","whose","which"] #we will need to update this
excluded_trg_tokens=["من","على","في","مع", "إلى",
                     "له","تم","إلى","في","عن","إن","أن","به","بها","لها","التي","كان","قد","الذي","الذين",
                     "هو","هي"]

params={}
params["lang2_tok_fn"]=cur_ar_tok_fn
params["phrase_dict"]=phrase_shelve_open#phrase_table_dict
params["term_dict"]=term_shelve_open#term_dict
params["acr_dict"]=acr_shelve_open#acr_dict
params["excluded_words"]=excluded_src_tokens+excluded_trg_tokens
params["lang2_tok_fn"]=cur_ar_tok_fn

# params["phrase_dict"]=phrase_shelve_open#phrase_table_dict
# params["term_dict"]=term_shelve_open#term_dict
# params["acr_dict"]=acr_shelve_open#acr_dict
tmp_params=dict(params)
src_sent='	Strongly condemning the increase and continued high level of recruitment and use of children by  armed groups, and strongly urging all parties to immediately release, without preconditions, all children from their ranks, hand them over to relevant civilian child protection actors, and end and prevent further recruitment and use of children, including the re-recruitment of children who have been released, in line with international humanitarian law and, as applicable, the UN Convention on the Rights of the Child and its Optional Protocol on the involvement of children in armed conflict;'
trg_sent='يدين بشدة الزيادة في تجنيد الأطفال واستخدامهم من قبل الجماعات المسلحة واستمرار ارتفاع مستواهم، وإذ يحث بقوة جميع الأطراف على الإفراج فورا ودون شروط مسبقة عن جميع الأطفال من صفوفها، وتسليمهم إلى الجهات المدنية المعنية بحماية الأطفال، وإنهاء ومنع المزيد من تجنيد الأطفال واستخدامهم، بما في ذلك إعادة تجنيد الأطفال الذين أفرج عنهم،  تماشيا مع القانون الدولي الإنساني، وحسب الاقتضاء، اتفاقية الأمم المتحدة لحقوق الطفل وبروتوكولها الاختياري بشأن إشراك الأطفال في النزاعات المسلحة؛'
out=walign(src_sent,trg_sent,tmp_params)
cur_src0,cur_trg0,cur_align0=out["src"],out["trg"],out.get("align",[])
phrases=present_aligned(out["src"],out["trg"],out["align"])
for ph0 in phrases: print(ph0)
print("===========")
cur_src0_lower=[v.lower() for v in cur_src0]
cur_trg0_lower=[v.lower() for v in cur_trg0]
test_term_qa_out=qa_keyed_dict(cur_src0_lower,cur_trg0_lower,term_shelve_open)
for a in test_term_qa_out:
  print(a)

# cur_trg0_filtered=filter_toks(cur_trg0)
# print(cur_trg0)
# print(cur_trg0_filtered)

phrase_shelve_open.close()
term_shelve_open.close()
acr_shelve_open.close()

('international humanitarian law', 'ال_قانون ال_دولي ال_إنساني', ((73, 75), (77, 79)), 3.25)
('UN Convention', 'اتفاقية ال_أمم ال_متحدة', ((82, 83), (85, 87)), 2.1578212225255307)
('UN', 'ال_أمم ال_متحدة', ((82, 82), (86, 87)), 1.4698623761057712)
('Convention', 'اتفاقية', ((83, 83), (85, 85)), 0.6879588464197594)
('Optional Protocol', 'بروتوكول ـها ال_اختياري', ((92, 93), (92, 94)), 1.6307692307692307)
('Protocol', 'بروتوكول', ((93, 93), (92, 92)), 1.0)
('Optional', 'ال_اختياري', ((92, 92), (94, 94)), 0.6307692307692309)
('all parties to immediately release', 'جميع ال_أطراف على ال_إفراج', ((22, 26), (24, 27)), 1.4540076767125316)
('all parties', 'جميع ال_أطراف', ((22, 23), (24, 25)), 1.0227392508538902)
('all', 'جميع', ((22, 22), (24, 24)), 0.6587318952591695)
('parties', 'ال_أطراف', ((23, 23), (25, 25)), 0.3640073555947206)
('release', 'ال_إفراج', ((26, 26), (27, 27)), 0.4678117109728053)
('children in armed conflict', 'ال_أطفال في ال_نزاعات ال_مسلحة', ((98, 101), (97, 100)), 1.30123

##QA Function 
If using Google sheet instead of TSV, add content in:
https://docs.google.com/spreadsheets/d/17KAQke0fUbY6S9-HLdd8slgdJUuKsOxO_wkpz4sM6P0/edit#gid=37808648

Normative: 
https://docs.google.com/spreadsheets/d/1UNzsIzYDmi40Zr2ZkCjv-sJB-gCaIeXKCU5d8-ROVlE/edit#gid=1566558529


In [12]:
import re,json,shelve
from code_utils import general
from code_utils.general import *
from code_utils.arabic_lib import *
from code_utils.align_utils import *
from code_utils.pandas_utils import *
from code_utils.sqld_utils import *
from code_utils.web_lib import *
from itertools import groupby
from collections import Counter
ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})
def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)

co_ref_list=["it","its","they","them","their","that","this", "these","those","latter","former"]
excluded_src_tokens=["the","a","an","and","of","its","his","her","their","them","to","is","are","am","been","was","were","be", 
                     "have","has","had", "in", "on", "at", "with", "from","for","that","he","she","it","would",
                     "as","by","they","whose","which"] #we will need to update this
excluded_trg_tokens=["من","على","في","مع", "إلى",
                     "له","تم","إلى","في","عن","إن","أن","به","بها","لها","التي","كان","قد","الذي","الذين",
                     "هو","هي"]


# normative_obj=get_workbook_obj(normative_path)
# normative_cols=["en","ar","type"]
# normative_data=get_sheets_cols(normative_obj,["normative"],normative_cols)
# normative_tok_list=[]
# for src0,trg0,type0 in normative_data:
#   src_toks0=tok(src0)
#   trg0_split=trg0.split("|")
#   trg_items=[]
#   for ts0 in trg0_split:
#     trg_toks0=cur_ar_tok_fn(ts0.strip())
#     trg_items.append(trg_toks0)
#   normative_tok_list.append((src_toks0,trg_items,type0))

def get_normative(sheet_path,params={}):
  normative_obj=get_workbook_obj(sheet_path)
  normative_cols=["en","ar","type"]
  normative_data=get_sheets_cols(normative_obj,["normative"],normative_cols)
  normative_tok_list=[]
  for src0,trg0,type0 in normative_data:
    src_toks0=general.tok(src0)
    trg0_split=trg0.split("|")
    trg_items=[]
    for ts0 in trg0_split:
      ts0=ts0.strip()
      #trg_toks0=cur_ar_tok_fn(ts0.strip())
      lang2_tok_fn=params.get("lang2_tok_fn")
      if lang2_tok_fn==None: trg_toks0=general.tok(ts0)
      else: trg_toks0=lang2_tok_fn(ts0)      
      trg_items.append(trg_toks0)
    normative_tok_list.append((src_toks0,trg_items,type0)) 
  return normative_tok_list 

def get_unaligned(src0,trg0,aligned0): #use the filtered list
  #excluded_words0=params0.get("excluded_words",[])
  used_xs,used_ys=[],[]
  src_span_dict,trg_span_dict={},{}
  new_align_list=[]
  for el0,el_wt0,el_children0 in aligned0:
    #print(el0,el_wt0,el_children0)
    if el_children0!=[]: continue
    src_span0,trg_span0=el0
    used_xs.extend(list(range(src_span0[0],src_span0[1]+1)))
    used_ys.extend(list(range(trg_span0[0],trg_span0[1]+1)))
  unaligned_x_list,unaligned_y_list=[],[]
  for src_i,src_token0 in enumerate(src0):
    if src_token0=="" or src_token0 in ["<s>","</s>"]: continue
    if src_i in used_xs: continue
    unaligned_x_list.append(src_i)
  for trg_i,trg_token0 in enumerate(trg0):
    if trg_token0=="" or trg_token0 in ["<s>","</s>"]: continue
    if trg_i in used_ys: continue
    unaligned_y_list.append(trg_i)
  return unaligned_x_list,unaligned_y_list

def get_aligned_chunks(aligned0):
  pass


normative_path="https://docs.google.com/spreadsheets/d/e/2PACX-1vSpf4wpYxSkFFC84xMNFFVM_LKWtQo8wIchL8sksiNSQLZktwPTnLW9jmF2jVpv4gORd9gD9QtcrTGZ/pub?output=xlsx"

term_shelve_path="terms.shelve"
acr_shelve_path="acronyms.shelve"
phrase_shelve_path='indexes/un/exp6/phrases-eluna.shelve' #os.path.join(index_dir,"phrases.shelve")
term_shelve_open=shelve.open(term_shelve_path)
acr_shelve_open=shelve.open(acr_shelve_path)
phrase_shelve_open=shelve.open(phrase_shelve_path)

cur_params={}
cur_params["lang2_tok_fn"]=cur_ar_tok_fn
cur_params["normative_list"]=get_normative(normative_path,cur_params)
cur_params["phrase_dict"]=phrase_shelve_open#phrase_table_dict
cur_params["term_dict"]=term_shelve_open#term_dict
cur_params["acr_dict"]=acr_shelve_open#acr_dict
cur_params["excluded_words"]=excluded_src_tokens+excluded_trg_tokens
terms_keys=list(term_shelve_open.keys())
#print(terms_keys[:20])
                     


def qa_exact(src_sent_toks,trg_sent_toks):
  uq_src0=list(set(src_sent_toks))
  uq_trg0=list(set(trg_sent_toks))
  src_digits=[v for v in uq_src0 if v.isdigit()]
  src_symbols=[v for v in uq_src0 if is_symbol(v)] #we can also add websites, twitter handles, hashtags ... etc
  all_qa_matches=[]
  for dig0 in src_digits:
    cur_src_spans=general.is_in([dig0],src_sent_toks)
    cur_trg_spans=general.is_in([dig0],trg_sent_toks)
    all_qa_matches.append((dig0,cur_src_spans,"number", [(dig0,cur_trg_spans)]))
  for dig0 in src_symbols:
    cur_src_spans=general.is_in([dig0],src_sent_toks)
    cur_trg_spans=general.is_in([dig0],trg_sent_toks)
    all_qa_matches.append((dig0,cur_src_spans,"symbol", [(dig0,cur_trg_spans)]))

  return all_qa_matches

def qa_normative(src_sent_toks,trg_sent_toks,normative_list):
  all_norm_matches=[]
  for norm_src0,norm_trg_items0,norm_type0 in normative_list: #tokenized norm src/trg items, and type
    src_spans=general.is_in(norm_src0,src_sent_toks)
    if src_spans==[]: continue
    norm_trg_items0.append(norm_src0)
    trg_corr=[]
    for norm_trg0 in norm_trg_items0:
      trg_spans=general.is_in(norm_trg0,trg_sent_toks) #we'll need to think of cases where there can be multiple trg options
      trg_corr.append((" ".join(norm_trg0),trg_spans))
    #if src_spans==[] and trg_spans==[]: continue
    norm_src0_str=" ".join(norm_src0)
    all_norm_matches.append((norm_src0_str,src_spans,norm_type0,trg_corr))
    #all_norm_matches.append((" ".join(norm_src0)," ".join(norm_trg0),src_spans, trg_spans, cur_type,match_score, criticality)) 
  return all_norm_matches

src_sent0='27 General Assembly During its formal meeting on 28 October 2022, the Working Group on Children and Armed Conflict of the Security Council examined the seventh report of the Secretary-General on children and armed conflict in Sudan (S/2022/627), covering the period between January 2020 to December 2021, which was introduced by the Special Representative of the Secretary-General for Children and Armed Conflict.'
trg_sent0='نظر الفريق العامل المعني بالأطفال والنزاع المسلح التابع لمجلس الأمن، خلال جلسته الرسمية المعقودة في 28 تشرين الأول/أكتوبر 2022، في التقرير السابع للأمين العام عن الأطفال والنزاع المسلح في السودان (S/2022/627)، الذي يغطي الفترة ما بين كانون الثاني/يناير 2020 إلى كانون الأول/ديسمبر 2021، والذي قدمته الممثلة الخاصة للأمين العام المعنية بالأطفال والنزاع المسلح.'
#def qa_term()
#def check_span_in_list()
def span2range(span0):
  start0,end0=span0
  return list(range(start0,end0+1))


def qa(src_sent,trg_sent,params):
  align_counter=0
  used_src_locs,used_trg_locs=[],[]
  #src_tag_spans,trg_tag_spans=[],[]
  src_open_tag_dict,src_close_tag_dict={},{}
  trg_open_tag_dict,trg_close_tag_dict={},{}
  src_toks0=general.tok(src_sent)
  lang2_tok_fn=params.get("lang2_tok_fn")
  if lang2_tok_fn==None: trg_toks0=general.tok(trg_sent)
  else: trg_toks0=lang2_tok_fn(trg_sent)  
  src_toks0=add_padding(src_toks0)
  trg_toks0=add_padding(trg_toks0)
  src_toks_lower0=[v.lower() for v in src_toks0]
  trg_toks_lower0=[v.lower() for v in trg_toks0]
  src_tokens_filtered,trg_tokens_filtered=filter_toks(src_toks0,params),filter_toks(trg_toks0,params)
  term_dict0=params.get("term_dict",{})
  cur_normative_list=params.get("normative_list",[])
  
  norm_matches=qa_normative(src_toks0,trg_toks0,cur_normative_list)
  exact_matches=qa_exact(src_toks0,trg_toks0)
  #term_qa_matches=qa_keyed_dict(src_tokens_filtered,trg_tokens_filtered,term_dict0,"terms",params)
  #term_qa_matches=qa_keyed_dict(src_tokens_filtered,trg_tokens_filtered,term_dict0,"terms",params)
  #term_qa_matches=qa_keyed_dict(src_toks_lower0,trg_toks_lower0,term_dict0,"terms",params)
  term_qa_matches=qa_keyed_dict(src_toks_lower0,trg_toks_lower0,term_dict0,"terms")
  #src_toks_lower0
  all_qa_matches=norm_matches+term_qa_matches+exact_matches
  all_qa_matches.sort(key=lambda x:-len(x[0]))

  for a in all_qa_matches:
    all_src_spans,all_trg_spans=[],[]
    src_phrase0,cur_src_spans0,match_type0,corr_list0=a
    print(src_phrase0,cur_src_spans0,match_type0)
    for src_span0 in cur_src_spans0:
      check_src0=check_span_in_list(src_span0,used_src_locs)
      if check_src0: continue #print("src_span0",src_span0,check_src0)
      all_src_spans.append(src_span0)
    #cur_trg_spans=[]
    for b in corr_list0:
      trg_phrase0,cur_trg_spans=b
      for trg_span0 in cur_trg_spans: 
        check_trg0=check_span_in_list(trg_span0,used_trg_locs)
        if check_trg0: continue
        all_trg_spans.append(trg_span0)
        # pass
        # cur_trg_spans.extend(trg_spans)
    #print("src_spans0",len(src_spans0),"all_trg_spans",len(all_trg_spans))
    if all_src_spans==[]: continue
    matched=False
    match_status=""
    if len(all_trg_spans)==0: 
      if len(src_phrase0.split())==1 and match_type0 in ["terms","acr"]: match_status="minor_mismatch"
      elif len(src_phrase0)==1 and src_phrase0.isdigit(): match_status="minor_mismatch"
      else: match_status="major_mismatch"     
      #matched=False
    elif len(all_trg_spans)<len(all_src_spans): 
      match_status="minor_mismatch"
    else: 
      match_status="matched"
      matched=True
    #if match_status in ["matched","major_mismatch"]:
    for src_span0 in all_src_spans: used_src_locs.extend(span2range(src_span0))
    for trg_span0 in all_trg_spans: used_trg_locs.extend(span2range(trg_span0))
    #print("used_src_locs",sorted(used_src_locs))
    #print("used_trg_locs",sorted(used_trg_locs))
    cur_classes=[match_status,match_type0,"match_check"]
    if match_type0.startswith("normative"): cur_classes.append("normative")
    if matched: 
      aligned_class='walign-%s'%align_counter
      cur_classes.append(aligned_class)
      align_counter+=1
    open_tag='<span class="%s">'%(" ".join(cur_classes))
    close_tag='</span>'

    # print("all_src_spans",all_src_spans,"all_trg_spans",all_trg_spans,"match_status",match_status)
    # print(open_tag)
    for span0 in all_src_spans:
      start0,end0=span0
      src_open_tag_dict[start0]=src_open_tag_dict.get(start0,"")+open_tag
      src_close_tag_dict[end0]=src_close_tag_dict.get(end0,"")+close_tag
    for span0 in all_trg_spans:
      start0,end0=span0
      trg_open_tag_dict[start0]=trg_open_tag_dict.get(start0,"")+open_tag
      trg_close_tag_dict[end0]=trg_close_tag_dict.get(end0,"")+close_tag

      #print(b)
    #print("---")
  walign_out=walign(src_sent,trg_sent,params)
  aligned_list=walign_out["align"]
  aligned_phrases=present_aligned(walign_out["src"],walign_out["trg"],aligned_list)
  
  
  unaligned_x,unaligned_y=get_unaligned(src_tokens_filtered,trg_tokens_filtered,aligned_list)
  #print("unaligned_x,unaligned_y",unaligned_x,unaligned_y)
  unaligned_open_tag='<span class="unaligned">'
  unaligned_close_tag='</span>'
  for a in unaligned_x:
    if a in used_src_locs: continue
    #print("unaligned x:",a,src_toks0[a])
    src_open_tag_dict[a]=src_open_tag_dict.get(a,"")+unaligned_open_tag
    src_close_tag_dict[a]=src_close_tag_dict.get(a,"")+unaligned_close_tag
  for a in unaligned_y:
    if a in used_trg_locs: continue
    #print("unaligned y:",a,trg_toks0[a])
    trg_open_tag_dict[a]=trg_open_tag_dict.get(a,"")+unaligned_open_tag
    trg_close_tag_dict[a]=trg_close_tag_dict.get(a,"")+unaligned_close_tag

  #aligned_open_tag='<span class="aligned">'
  aligned_close_tag='</span>'

  #print("aligned_phrases")
  for a in aligned_phrases: 
    src_phrase0,trg_phrase0,cur_el0,cur_wt0=a
    src_span0,trg_span0=cur_el0
    if check_span_in_list(src_span0,used_src_locs) or check_span_in_list(trg_span0,used_trg_locs): continue
    if check_span_in_list(src_span0,unaligned_x) or check_span_in_list(trg_span0,unaligned_y): continue

    #print(a)
    cur_classes=["aligned"]
    aligned_class='walign-%s'%align_counter
    cur_classes.append(aligned_class)
    aligned_open_tag='<span class="%s">'%(" ".join(cur_classes))
    src_open_tag_dict[src_span0[0]]=src_open_tag_dict.get(src_span0[0],"")+aligned_open_tag
    src_close_tag_dict[src_span0[1]]=src_close_tag_dict.get(src_span0[1],"")+aligned_close_tag
    trg_open_tag_dict[trg_span0[0]]=trg_open_tag_dict.get(trg_span0[0],"")+aligned_open_tag
    trg_close_tag_dict[trg_span0[1]]=trg_close_tag_dict.get(trg_span0[1],"")+aligned_close_tag

    align_counter+=1    

  # for src_i,cur_src_token in enumerate(src_toks0):
  #   print(src_i,src_open_tag_dict.get(src_i,""), cur_src_token,src_close_tag_dict.get(src_i,""))

  de_tok_space_src_items=de_tok_space(src_toks0)
  de_tok_space_trg_items=de_tok_space(trg_toks0)
  src_cell,trg_cell="",""
  for item_i,item0 in enumerate(de_tok_space_src_items):
    src_tok_str,src_tok_space=item0
    if src_tok_str in ['<s>',"</s>"]: continue
    open0=src_open_tag_dict.get(item_i,"")#walign_open0+norm_open0
    close0=src_close_tag_dict.get(item_i,"")#norm_close0+walign_close0
    src_cell+=open0+src_tok_str+close0+src_tok_space
  for item_i,item0 in enumerate(de_tok_space_trg_items):
    trg_tok_str,trg_tok_space=item0
    if trg_tok_str in ['<s>',"</s>"]: continue
    open0=trg_open_tag_dict.get(item_i,"")#walign_open0+norm_open0
    close0=trg_close_tag_dict.get(item_i,"")#norm_close0+walign_close0
    trg_cell+=open0+trg_tok_str+close0+trg_tok_space
  #final_sent_pair_list_with_classes.append((src_cell,trg_cell)) 
  # print(src_cell)
  # print(trg_cell)
  return src_cell,trg_cell


job_wb_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vS8-zn0nwjU9U_NMnUkBG6PsdsnN78izRte1BLZjGzJhryDrkDzY7OVds3Szm91r1Vqh8gv4PoAtkkO/pub?output=xlsx'
job_wb_obj=get_workbook_obj(job_wb_path)
cols=["en","ar"]
job_sheets=["doc"]
bitext1=get_sheets_cols(job_wb_obj,job_sheets,cols)

print("retrieved job bitext")
final_sent_pair_list_with_classes=[]
for i0,bitext_item0 in enumerate(bitext1):
  src_sent0,trg_sent0=bitext_item0
  print(i0)
  print(src_sent0)
  print(trg_sent0)
  print("---")
  src_cell1,trg_cell1=qa(src_sent0,trg_sent0,cur_params)
  final_sent_pair_list_with_classes.append((src_cell1,trg_cell1))
#final_sent_pair_list_with_classes=[(src_cell1,trg_cell1)]
table_content0=""
for a,b in final_sent_pair_list_with_classes:
  tr0='<tr><td width="50%%">%s</td><td dir="rtl" align="right" width="50%%">%s</td></tr>'%(a,b)
  table_content0+=tr0

qa_template_fpath="qa/qa-template.html"
qa_template_fopen=open(qa_template_fpath)
qa_template_content=qa_template_fopen.read()
qa_template_fopen.close()
qa_template_obj=DOM(qa_template_content)
repl_dict={}
repl_dict["#translation_table"]=(table_content0,{})
#repl_dict["#analysis_table"]=(analysis_table_content0,{})
out_html=qa_template_obj.replace(repl_dict)


out_fpath="qa/29mar23.html"
out_fopen=open(out_fpath,"w")
out_fopen.write(out_html)
out_fopen.close()

phrase_shelve_open.close()
term_shelve_open.close()
acr_shelve_open.close()

print("finished QA processing")

Streaming output truncated to the last 5000 lines.
['united', 'nations']
united nations [(47, 48)] terms
development [(7, 7)] terms
global [(38, 38)] terms
forum [(43, 43)] terms
area [(17, 17)] terms
was [(32, 32)] terms
10 [(21, 21)] number
67
5
5-
---
5 [(1, 1)] number
68
The Group therefore urged countries to remain committed to the development of inclusive tax instruments by the United Nations and encouraged OECD to play a supporting role in that regard.
* ولذلك تحث المجموعة البلدان على أن تظل ملتزمة بوضع صكوك ضريبية شاملة من جانب الأمم المتحدة وتشجع منظمة التعاون والتنمية في الميدان الاقتصادي على القيام بدور داعم في هذا الصدد.
---
['تنمية']
['development']
['ال_أمم', 'ال_متحدة']
['united', 'nations']
united nations [(18, 19)] terms
development [(11, 11)] terms
69
It hoped that the draft resolution would help to realize the vision of its ministers.
* وأعرب عن أمل وفده في أن يساعد مشروع القرار على تحقيق رؤية وزرائه.
---
['درجة', 'ال_وضوح']
['درجة', 'ال_نقاء']
['ال_دقة']
['resolutio

In [ ]:
def span2range(span0):
  start0,end0=span0
  return list(range(start0,end0+1))

span1=(5,12)
span2range(span1)

[5, 6, 7, 8, 9, 10, 11, 12]

In [ ]:
cur_trg0_filtered=filter_toks(cur_trg0)
print(cur_trg0)
print(cur_trg0_filtered)

cur_src0_filtered=filter_toks(cur_src0)
print(cur_src0)
print(cur_src0_filtered)

['<s>', 'وـ', 'أقر', 'ال_فريق', 'بـ', 'ال_جهود', 'التي', 'تبذلها', 'فرقة', 'ال_عمل', 'ال_قطرية', 'ال_تابعة', 'لـ', 'ال_أمم', 'ال_متحدة', 'وـ', 'ال_معنية', 'بـ', 'ال_رصد', 'وـ', 'ال_إبلاغ', 'في', 'ال_سودان', '_،', 'فضلا', 'عن', 'ال_تحديات', 'التي', 'تواجه', 'ـها', '_.', '</s>']
['<s>', '', 'أقر', 'فريق', '', 'جهود', 'التي', 'تبذلها', 'فرقة', 'عمل', 'قطرية', 'تابعة', '', 'أمم', 'متحدة', '', 'معنية', '', 'رصد', '', 'إبلاغ', 'في', 'سودان', '', 'فضلا', 'عن', 'تحديات', 'التي', 'تواجه', '', '', '</s>']
['<s>', 'The', 'Group', 'acknowledged', 'the', 'efforts', 'of', 'the', 'United', 'Nations', 'country', 'task', 'force', 'on', 'monitoring', 'and', 'reporting', 'in', 'the', 'Sudan', '_,', 'as', 'well', 'as', 'the', 'challenges', 'that', 'it', 'faced', '_.', '</s>']
['<s>', 'the', 'group', 'acknowledged', 'the', 'efforts', 'of', 'the', 'united', 'nations', 'country', 'task', 'force', 'on', 'monitoring', 'and', 'reporting', 'in', 'the', 'sudan', '', 'as', 'well', 'as', 'the', 'challenges', 'that'

In [ ]:
import shelve
phrase_shelve_path='indexes/un/exp6/phrases-eluna.shelve' #os.path.join(index_dir,"phrases.shelve")

def qa_keyed_dict(src_tokens,trg_tokens,keyed_dict,dict_type="",filter_params={}): #inspect if for a keyed dict, each phrase found in source have corresponding trg phrase
  all_qa_list=[]
  #print("testing")
  #src_tokens=filter_toks(src_tokens,filter_params)
  #trg_tokens=filter_toks(trg_tokens,filter_params)
  src_unigrams_bigrams=get_unigrams_bigrams(src_tokens)
  for ub in src_unigrams_bigrams:
    #print(ub)
    corr_dict=keyed_dict.get(ub)
    #print(corr_dict)
    if corr_dict==None: continue
    for src_phrase0,corr_trg_vals in corr_dict.items(): #phrase is a token-ready string
      #print(src_phrase0)
      src_phrase_tokens0=src_phrase0.split()
      #src_phrase_tokens0=filter_toks(src_phrase_tokens0,filter_params)
      src_span0=general.is_in(src_phrase_tokens0,src_tokens)
      new_src_span=[]
      for ss in src_span0:
        start0,end0=ss
        if end0-start0==len(src_phrase_tokens0)-1: new_src_span.append(ss)
      if not new_src_span: continue
      #the src phrase exists
      #print(src_phrase0)
      corr_trg_vals.append((src_phrase0,0)) #to account for situations where the corresponding term is also in English
      trg_corr=[]
      for trg_phrase0,trg_val0 in corr_trg_vals:
        trg_phrase_tokens0=trg_phrase0.split()
        print(trg_phrase_tokens0)
        #trg_phrase_tokens0=filter_toks(trg_phrase_tokens0,filter_params)
        trg_span0=general.is_in(trg_phrase_tokens0,trg_tokens)
        trg_corr.append((trg_phrase0,trg_span0))
      all_qa_list.append((src_phrase0,src_span0,dict_type,trg_corr))
        # if not trg_span0: continue
        # freq0,wt0=trg_val0
        # all_matching_list.append((src_phrase0,trg_phrase0,src_span0,trg_span0,freq0,wt0))
  return all_qa_list


params={}
term_shelve_open=shelve.open(term_shelve_path)
acr_shelve_open=shelve.open(acr_shelve_path)
phrase_shelve_open=shelve.open(phrase_shelve_path)

src_sent0='calling upon all parties to respect their obligations under international law, to cease the killing and maiming of children, and to end immediately and definitively the indiscriminate use of explosive devices, and calling upon the Government to fully implement its obligations under the Convention on the Prohibition of the Use, Stockpiling, Production and Transfer of Anti-Personnel Mines and on Their Destruction;'
trg_sent0='يهيب بجميع الأطراف أن تحترم التزاماتها بموجب القانون الدولي، وأن تكف عن قتل الأطفال وتشويههم، وأن تضع حدا فوريا ونهائيا للاستخدام العشوائي للأجهزة المتفجرة، ويهيب بالحكومة أن تنفذ بالكامل التزاماتها بموجب اتفاقية حظر استعمال وتخزين وإنتاج ونقل الألغام المضادة للأفراد، وتدمير تلك الألغام؛'
src_toks=tok(src_sent0)
trg_toks=cur_ar_tok_fn(trg_sent0)
src_toks_lower=[v.lower() for v in src_toks]
print(src_toks)
print(trg_toks)
#src_sent='During its formal meeting on 28 October 2022, the Working Group on Children and Armed Conflict of the Security Council examined the seventh report of the Secretary-General on children and armed conflict in Sudan (S/2022/627), covering the period between January 2020 to December 2021, which was introduced by the Special Representative of the Secretary-General for Children and Armed Conflict.'
test=qa_keyed_dict(src_toks_lower,trg_toks,term_shelve_open)
for a in test:
  print(a)

# phrase="convention on"
# out0=term_shelve_open[phrase]
# items0=list(out0.items())
# items0.sort()
# for a,b in items0:
#   print(a,b)

phrase_shelve_open.close()
term_shelve_open.close()
acr_shelve_open.close()

['calling', 'upon', 'all', 'parties', 'to', 'respect', 'their', 'obligations', 'under', 'international', 'law', '_,', 'to', 'cease', 'the', 'killing', 'and', 'maiming', 'of', 'children', '_,', 'and', 'to', 'end', 'immediately', 'and', 'definitively', 'the', 'indiscriminate', 'use', 'of', 'explosive', 'devices', '_,', 'and', 'calling', 'upon', 'the', 'Government', 'to', 'fully', 'implement', 'its', 'obligations', 'under', 'the', 'Convention', 'on', 'the', 'Prohibition', 'of', 'the', 'Use', '_,', 'Stockpiling', '_,', 'Production', 'and', 'Transfer', 'of', 'Anti', '_-_', 'Personnel', 'Mines', 'and', 'on', 'Their', 'Destruction', '_;']
['يهيب', 'بـ', 'جميع', 'ال_أطراف', 'أن', 'تحترم', 'التزامات', 'ـها', 'بموجب', 'ال_قانون', 'ال_دولي', '_،', 'وـ', 'أن', 'تكف', 'عن', 'قتل', 'ال_أطفال', 'وـ', 'تشويه', 'ـهم', '_،', 'وـ', 'أن', 'تضع', 'حدا', 'فوريا', 'وـ', 'نهائيا', 'لـ', 'ال_استخدام', 'ال_عشوائي', 'لـ', 'ال_أجهزة', 'ال_متفجرة', '_،', 'وـ', 'يهيب', 'بـ', 'ال_حكومة', 'أن', 'تنفذ', 'بـ', 'ال_كامل

In [ ]:
c_items=list(consistency_check_dict.items())
c_items.sort(key=lambda x:-sum(x[1].values()))
analysis_table_content=""
for key0,corr_dict0 in c_items[:50]:
  #print(key0)
  corr_cell_items=[]
  for a,b in corr_dict0.items():
    corr_cell_items.append('%s | (%s)'%(a,b))
  corr_cell="<br>".join(corr_cell_items)
  #print(corr_cell)
  tr0='<tr><td>%s</td><td>%s</td></tr>'%(key0,corr_cell)
  analysis_table_content+=tr0
  print(tr0)
    #print(a,b)
  print("------")

<tr><td></s></td><td></s> | (555)</td></tr>
------
<tr><td><s></td><td><s> | (529)</td></tr>
------
<tr><td>_.</td><td>_. | (504)</td></tr>
------
<tr><td>_. </s></td><td>_. </s> | (275)</td></tr>
------
<tr><td>_,</td><td>_, | (265)</td></tr>
------
<tr><td>(_</td><td>(_ | (177)</td></tr>
------
<tr><td>_)_</td><td>_)_ | (111)<br>_)_ _)_ | (2)</td></tr>
------
<tr><td>sources</td><td>مصادر | (25)<br>ال_مصادر | (78)<br>sources | (6)<br>ال_مصدرين | (1)<br>مصدر | (1)<br>مصدرين | (1)</td></tr>
------
<tr><td>international law</td><td>ال_قانون ال_دولي | (84)<br>ال_قانون ال_دولي ال_عام | (1)<br>international law | (6)<br>قانون دولي | (1)<br>دوليا | (1)</td></tr>
------
<tr><td>Article</td><td>ال_مادة | (82)<br>Article | (9)</td></tr>
------
<tr><td>law</td><td>ال_قانون | (65)<br>قانون | (13)<br>law | (10)<br>ال_قواعد | (1)</td></tr>
------
<tr><td>_)</td><td>_) | (80)</td></tr>
------
<tr><td>38</td><td>38 | (72)</td></tr>
------
<tr><td>International</td><td>ال_دولي | (1)<br>International 

## Testing word alignment for QA purposes

In [ ]:
from code_utils.arabic_lib import *
from itertools import groupby
from collections import Counter
ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})

def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)


In [11]:
import re,json,shelve
from code_utils import general
from code_utils.general import *

from code_utils.align_utils import *
from code_utils.pandas_utils import *
from code_utils.sqld_utils import *
from code_utils.web_lib import *

from itertools import groupby

excluded_src_tokens=["the","a","an","and","of","its","his","her","their","them","to","is","are","am","been","was","were","be", 
                     "have","has","had", "in", "on", "at", "with", "from","for","that","he","she","it","would",
                     "as","by","they","whose","which"] #we will need to update this
excluded_trg_tokens=["من","على","في","مع", "إلى",
                     "له","تم","إلى","في","عن","إن","أن","به","بها","لها","التي","كان","قد","الذي","الذين",
                     "هو","هي"]


term_shelve_path="terms.shelve"
acr_shelve_path="acronyms.shelve"
#phrase_shelve_path="phrases.shelve"

# index_dir="indexes/un/exp6"
# phrase_shelve_path=os.path.join(index_dir,"phrases.shelve")


phrase_shelve_path='indexes/un/exp6/phrases-eluna.shelve' #os.path.join(index_dir,"phrases.shelve")

term_shelve_open=shelve.open(term_shelve_path)
acr_shelve_open=shelve.open(acr_shelve_path)
phrase_shelve_open=shelve.open(phrase_shelve_path)


out0=term_shelve_open.get("high -")
for item0 in out0:
  if 'transparency' in item0: print(item0) 
  

params={}
params["lang2_tok_fn"]=cur_ar_tok_fn
params["phrase_dict"]=phrase_shelve_open#phrase_table_dict
params["term_dict"]=term_shelve_open#term_dict
params["acr_dict"]=acr_shelve_open#acr_dict
params["excluded_words"]=excluded_src_tokens+excluded_trg_tokens
params["lang2_tok_fn"]=cur_ar_tok_fn
params["debug"]=True

src_sent='This is especially illustrated by the references to the Commission’s work on the Nuremberg Principles.'
#src_sent="This is especially illustrated by the references to the Commission's work on the Nuremberg Principles."
trg_sent='ويتضح ذلك بصفة خاصة من الإشارات إلى عمل اللجنة بشأن مبادئ نورمبرغ.'

src_sent='A similar example can be found in the commentary to draft conclusion 19, where the Commission noted that “Paragraph 1 of the draft conclusion, which is based on article 41, paragraph 1, of the articles on responsibility of States for internationally wrongful acts, provides that States shall cooperate to bring to an end serious breaches of obligations arising under peremptory norms of general international law (jus cogens)”, para. (2) of the commentary to draft conclusion 19, ibid., pp. 70-71, referring to para. (3) of the commentary to article 41 of the articles on responsibility of States for internationally wrongful acts, Yearbook … 2001, vol. II (Part Two) and corrigendum, p. 114.'
trg_sent='ويمكن العثور على مثال مماثل في شرح مشروع الاستنتاج 19، حيث لاحظت اللجنة أن "الفقرة 1 من مشروع الاستنتاج، التي تستند إلى الفقرة 1 من المادة 41 من المواد المتعلقة بمسؤولية الدول عن الأفعال غير المشروعة دوليا، تنص على أن تتعاون الدول على وضع حد للإخلالات الخطيرة بالالتزامات الناشئة بموجب القواعد الآمرة من القواعد العامة للقانون الدولي (jus cogens)"، الفقرة (2) من شرح مشروع الاستنتاج 19، المرجع نفسه، الصفحات 70-71، التي تشير إلى الفقرة (3) من شرح المادة 41 من المواد المتعلقة بمسؤولية الدول عن الأفعال غير المشروعة دوليا، حولية 2001، المجلد الثاني (الجزء الثاني) والتصويب، الصفحة 114.'

src_sent='The High-level Panel on International Financial Accountability, Transparency and Integrity for Achieving the 2030 Agenda had underscored the need for fully inclusive and effective international tax cooperation at the United Nations, and the President of the seventy-fifth session of the General Assembly had circulated that recommendation to all Member States, for deliberation at the seventy-sixth session.'
trg_sent='* وقد شدد الفريق الرفيع المستوى المعني بتعزيز المساءلة والشفافية والنزاهة في الشؤون المالية الدولية من أجل تحقيق خطة عام 2030 على الحاجة إلى تعاون ضريبي دولي شامل وفعال تماما في الأمم المتحدة، وعمم رئيس الدورة الخامسة والسبعين للجمعية العامة هذه التوصية على جميع الدول الأعضاء، للتداول بشأنها في الدورة السادسة والسبعين.'
out=walign(src_sent,trg_sent,params)
for a,b in out.items():
  print(a)
phrases=present_aligned(out["src"],out["trg"],out["align"])
for ph0 in phrases: print(ph0)
phrase_shelve_open.close()
term_shelve_open.close()
acr_shelve_open.close()

high - level principles on beneficial ownership transparency
high - level principles on fiscal transparency , participation and accountability
src
trg
align
terms
acr
phon
debug
('seventy _-_ fifth session of the General Assembly', 'ال_دورة ال_خامسة وـ ال_سبعين لـ ال_جمعية ال_عامة', ((41, 48), (42, 48)), 4.011457316456126)
('General Assembly', 'ال_جمعية ال_عامة', ((47, 48), (47, 48)), 2.25)
('seventy _-_ fifth session', 'ال_دورة ال_خامسة وـ ال_سبعين', ((41, 44), (42, 45)), 1.784389774979926)
('fifth session', 'ال_دورة ال_خامسة', ((43, 44), (42, 43)), 1.1634810077275886)
('seventy', 'ال_سبعين', ((41, 41), (45, 45)), 0.6209087672523376)
('recommendation to all Member States', 'هذه ال_توصية على جميع ال_دول ال_أعضاء', ((52, 56), (49, 54)), 2.7257451249500457)
('all Member States', 'جميع ال_دول ال_أعضاء', ((54, 56), (52, 54)), 1.901014639967908)
('Member States', 'ال_دول ال_أعضاء', ((55, 56), (53, 54)), 1.2422827447087383)
('all', 'جميع', ((54, 54), (52, 52)), 0.6587318952591695)
('recommen

In [ ]:
def get_aligned_path(matching_list,n_epochs=5,max_dist=4):
  matching_list.sort(key=lambda x:(-round(x[-1],1),x[-2],-len(x[0])-len(x[1]),x[-1])) #sorting criteria - rounded weight, frequency,length, and then just weight
  el_dict={}
  el_child_dict={}
  src_span_el_dict,trg_span_el_dict={},{}
  
  ml_new=[]
  #original_ml=[]
  used_src_phrases,used_trg_phrases=[],[]
  for a in matching_list: #we process the matching list in order to obtain the top matches with their spans
    #TODO: use the counter of used instances spans of src/trg phrases based on the number of spans of a valid pair
    src_phrase0,trg_phrase0,src_locs0,trg_locs0,intersection0,ratio0=a
    valid=True
    for src_span0 in src_locs0:
      for trg_span0 in trg_locs0: 
        el0=(src_span0,trg_span0)
        #original_ml.append((el0,ratio0)) 
        src_span_el_dict[src_span0]=src_span_el_dict.get(src_span0,[])+[(el0,ratio0)] 
        trg_span_el_dict[trg_span0]=trg_span_el_dict.get(trg_span0,[])+[(el0,ratio0)] 
    if src_phrase0 in used_src_phrases or trg_phrase0 in used_trg_phrases: valid=False
    if ratio0<0.01: valid=False

    if not valid: continue
    used_src_phrases.append(src_phrase0)
    used_trg_phrases.append(trg_phrase0)   
    ml_new.append(a) #this is where we store the valid matching phrases with their weights and spans
    #print(">>>>>>>>",a)

  for a in ml_new: #now we create the elements of span pairs
    src_phrase0,trg_phrase0,src_locs0,trg_locs0,intersection0,ratio0=a
    for src_span0 in src_locs0:
      src_start0,src_end0=src_span0
      for trg_span0 in trg_locs0:
        el0=(src_span0,trg_span0)
        found_wt=el_dict.get(el0,0)
        if ratio0>found_wt: 
          el_dict[el0]=ratio0
          #print("added el to dict:", el0,ratio0)
  
  child_dict={}
  used_pair_wt_dict={}
  cur_max_wt0=0
  for epoch0 in range(n_epochs):
    el_items=list(el_dict.items())
    #print("epoch0",epoch0,"items:",len(el_items))
    for i0,item0 in enumerate(el_items):
      el0,wt0=item0
      src_span0,trg_span0=el0
      for item1 in el_items[i0+1:]:
        el1,wt1=item1
        cur_pair_key=(el0,el1)
        combined_wt_check=used_pair_wt_dict.get(cur_pair_key)
        #if pair was used before, and its combined wt is equal to what it was before, skip
        if combined_wt_check==None or combined_wt_check<wt0+wt1: used_pair_wt_dict[cur_pair_key]=wt0+wt1
        else: continue
        src_span1,trg_span1=el1
        cur_src_dist=get_span_dist(src_span0,src_span1)
        cur_trg_dist=get_span_dist(trg_span0,trg_span1) 
        if cur_src_dist>max_dist or cur_trg_dist>max_dist: continue
        if cur_src_dist<0 or cur_trg_dist<0: continue
        if cur_src_dist<1 and src_span0!=src_span1: continue
        if cur_trg_dist<1 and trg_span0!=trg_span1: continue
        if src_span0==src_span1 and cur_trg_dist>2: continue
        if trg_span0==trg_span1 and cur_src_dist>2: continue
        combined_wt01=wt0+wt1
        combined_el01=combine_els(el0,el1) 
        found_wt=el_dict.get(combined_el01,0)
        if combined_wt01>found_wt:
          el_dict[combined_el01]=combined_wt01
          child_dict[combined_el01]=(el0,el1)

    el_items=list(el_dict.items())
    el_items.sort(key=lambda x:-x[-1])
    used_src,used_trg=[],[]
    filled_used_src,filled_used_trg=[],[] #used src/trg for filling purposes - corresponding to src/trg locs already filled by elements without children
    epoch_final_els0=[]
    src_span_dict,trg_span_dict={},{}
    for el0,el_wt0 in el_items: #we refine the el_dict items to get the most highly weighted elements and their children as our solution
      src_span0,trg_span0=el0
      src_range0=list(range(src_span0[0],src_span0[1]+1))
      trg_range0=list(range(trg_span0[0],trg_span0[1]+1))
      if any([v in used_src for v in src_range0]): continue
      if any([v in used_trg for v in trg_range0]): continue
      used_src.extend(src_range0)
      used_trg.extend(trg_range0)
      epoch_final_els0.append((el0,el_wt0))
    final_total_wt=sum([v[1] for v in epoch_final_els0])
    #print("final_total_wt",final_total_wt)
    #for a in epoch_final_els0:
    #   print("final el0:",a)
    # print("==================================")
    if cur_max_wt0>0 and cur_max_wt0==final_total_wt: break
    cur_max_wt0=final_total_wt
  final_els=[]
  for el0,wt0 in epoch_final_els0:  
    children=get_rec_el_children(el0,child_dict,[])
    #final_els.append((el0,wt0,children))
    for ch0 in children:
      sub_children=child_dict.get(ch0,[])
      final_els.append((ch0,el_dict.get(ch0,0),sub_children))
  return final_els



matching_list0=out["debug"]
align_out=get_aligned_path(matching_list0,n_epochs=6,max_dist=4)
phrases0=present_aligned(out["src"],out["trg"],align_out)
for ph0 in phrases0:
  print(ph0)
# for db in out["debug"][:100]:
#   print(db)

('serious breaches of obligations arising under peremptory norms of general international law (_ jus cogens _)_ _”_ _, para _. (_ 2 _) of the commentary to draft conclusion 19 _, ibid _._ _, pp _. 70 _-_ 71', 'ال_خطيرة بـ ال_التزامات ال_ناشئة بموجب ال_قواعد ال_آمرة من ال_قواعد ال_عامة لـ ال_قانون ال_دولي (_ jus cogens _)_ _"_ _، ال_فقرة (_ 2 _) من شرح مشروع ال_استنتاج 19 _، ال_مرجع نفسه _، ال_صفحات 70 _-_ 71', ((60, 98), (54, 89)), 9.405569999683784)
('serious breaches of obligations arising', 'ال_خطيرة بـ ال_التزامات ال_ناشئة', ((60, 64), (54, 57)), 0.8230652411823369)
('serious', 'ال_خطيرة', ((60, 60), (54, 54)), 0.3092806586513874)
('obligations arising', 'ال_التزامات ال_ناشئة', ((63, 64), (56, 57)), 0.5137845825309496)
('obligations', 'ال_التزامات', ((63, 63), (56, 56)), 0.3194002519861602)
('arising', 'ال_ناشئة', ((64, 64), (57, 57)), 0.19438433054478943)
('under peremptory norms of general international law (_ jus cogens _)_ _”_ _, para _. (_ 2 _) of the commentary to draft concl

In [ ]:
from code_utils.web_lib import *
table_content0=""
for a,b in final_sent_pair_list_with_classes:
  tr0='<tr><td>%s</td><td dir="rtl">%s</td></tr>'%(a,b)
  table_content0+=tr0
qa_template_fpath="qa/qa-template.html"
qa_template_fopen=open(qa_template_fpath)
qa_template_content=qa_template_fopen.read()
qa_template_fopen.close()
qa_template_obj=DOM(qa_template_content)
repl_dict={}
repl_dict["#translation_table"]=(table_content0,{})
out_html=qa_template_obj.replace(repl_dict)
out_fpath="tmp/out_template.html"
out_fopen=open(out_fpath,"w")
out_fopen.write(out_html)
out_fopen.close()


In [ ]:
span0=(12,12)
span1=(12,12)
get_span_dist(span0,span1)

0

In [ ]:
final_sent_pair_list_with_classes[10]

('In <span class="aligned sent0 walign-37"><span class="match" style="text-decoration: underline;-webkit-text-decoration-color: lightgreen;text-decoration-color: lightgreen;">1996</span></span>, the <span class="aligned sent0 walign-9"><span class="aligned sent0 walign-10"><span class="aligned sent0 walign-11">Commission</span> <span class="aligned sent0 walign-12">again</span></span> <span class="aligned sent0 walign-13">referred</span></span> to the <span class="aligned sent0 walign-14">statement</span> from the <span class="aligned sent0 walign-24"><span class="aligned sent0 walign-25"><span class="aligned sent0 walign-26">judgment</span></span></span> and the <span class="aligned sent0 walign-22">work</span> of the <span class="aligned sent0 walign-23">Commission</span> in the <span class="aligned sent0 walign-5"><span class="aligned sent0 walign-6">Nuremberg Principles</span> <span class="aligned sent0 walign-7">noting</span></span> “that <span class="aligned sent0 walign-36">indi

In [ ]:
import re,json,shelve
from code_utils import general
from code_utils.general import *
from code_utils.arabic_lib import *
from code_utils.align_utils import *
from code_utils.pandas_utils import *
from code_utils.sqld_utils import *
from itertools import groupby
from collections import Counter
ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})

def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)


job_wb_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vS8-zn0nwjU9U_NMnUkBG6PsdsnN78izRte1BLZjGzJhryDrkDzY7OVds3Szm91r1Vqh8gv4PoAtkkO/pub?output=xlsx'
job_wb_obj=get_workbook_obj(job_wb_path)
cols=["en","ar"]
job_sheets=["doc"]
bitext1=get_sheets_cols(job_wb_obj,job_sheets,cols)
print("retrieved job bitext")

max_indexes_per_phrase=10
all_src_words,all_trg_words=[],[]
for src0,trg0 in bitext1:
  if src0.strip()==trg0.strip(): continue
  src_toks=tok(src0)
  src_toks_lower=[v.lower() for v in src_toks]
  trg_toks=cur_ar_tok_fn(trg0)
  all_src_words.extend(src_toks_lower)
  all_trg_words.extend(trg_toks)
all_src_words=list(set(all_src_words))
all_trg_words=list(set(all_trg_words))
src_sqld_fpath="bitexts/src-manual.sqld"
trg_sqld_fpath="bitexts/trg-manual.sqld"
src_index_dict=get_sqld_val_multiple(src_sqld_fpath,all_src_words)
trg_index_dict=get_sqld_val_multiple(trg_sqld_fpath,all_trg_words)
print("retrieved indexes for words in current bitext")


src_items=list(src_index_dict.items())
trg_items=list(trg_index_dict.items())
combined=src_items+trg_items
print("combined src+trg words and indexes")

used_indexes_dict={}
for phrase0,indexes0 in combined:
  cur_used_phrase_indexes=[]
  for in0 in indexes0:
    if len(cur_used_phrase_indexes)>=max_indexes_per_phrase: break
    in0_int=int(in0)
    if used_indexes_dict.get(in0_int,False): continue
    used_indexes_dict[in0_int]=True
    cur_used_phrase_indexes.append(in0_int)
keys=list(used_indexes_dict.keys())
print("number of final indexes to retrieve:",len(keys))
en_ar_corpus_combined_fname="bitexts/aligned-sents.txt"
bitext_fopen=open(en_ar_corpus_combined_fname)


lines=get_lines_simple(bitext_fopen,keys)
final_bitext=[]
for a in lines:
  split0=a.split("\t")
  if len(split0)!=2: continue
  final_bitext.append(split0)
bitext_fopen.close()

for a,b in final_bitext[:100]:
  print(a)
  print(b)
  print("---")
print("final_bitext",len(final_bitext))


retrieved job bitext
retrieved indexes for words in current bitext
combined src+trg words and indexes
number of final indexes to retrieve: 30277
Those principles ensured that organizations had the required tools to meet their obligations, in accordance with the Charter, to attract and retain staff with the highest level of competence.
وتكفل هذه المبادئ أن يكون لدى المنظمات الأدوات اللازمة للوفاء بالتزاماتها، وفقا للميثاق، لاجتذاب واستبقاء الموظفين ذوي أعلى مستوى من الكفاءة.
---
Recalling paragraph 67 of the Kyoto Declaration, in which Member States recognized the fundamental role of effective international cooperation in preventing and combating crime and to that end underlined the importance of addressing, tackling and effectively responding to international challenges and barriers, in particular measures, that hinder such cooperation and which are not consistent with the Charter of the United Nations and obligations under international law and in that regard urged States, consistent 

In [ ]:
src_items=list(src_index_dict.items())
trg_items=list(trg_index_dict.items())
combined=src_items+trg_items
# for a,b in src_items[:10]:
#   print(a,len(b),b[:10])

max_indexes_per_phrase=10
used_indexes_dict={}
for phrase0,indexes0 in combined:
  cur_used_phrase_indexes=[]
  for in0 in indexes0:
    if len(cur_used_phrase_indexes)>=max_indexes_per_phrase: break
    in0_int=int(in0)
    if used_indexes_dict.get(in0_int,False): continue
    used_indexes_dict[in0_int]=True
    cur_used_phrase_indexes.append(in0_int)
  print(phrase0,len(cur_used_phrase_indexes),cur_used_phrase_indexes[:10])

print(len(used_indexes_dict.keys()))



In [ ]:
en_ar_corpus_combined_fname="bitexts/aligned-sents.txt"
bitext_fopen=open(en_ar_corpus_combined_fname)

keys=list(used_indexes_dict.keys())
lines=get_lines_simple(bitext_fopen,keys)
for a in lines[:50]:
  split0=a.split("\t")
  if len(split0)!=2: continue
  en0,ar0=split0
  print(en0)
  print(ar0)
  print("----")
bitext_fopen.close()

Those principles ensured that organizations had the required tools to meet their obligations, in accordance with the Charter, to attract and retain staff with the highest level of competence.
وتكفل هذه المبادئ أن يكون لدى المنظمات الأدوات اللازمة للوفاء بالتزاماتها، وفقا للميثاق، لاجتذاب واستبقاء الموظفين ذوي أعلى مستوى من الكفاءة.
----
Recalling paragraph 67 of the Kyoto Declaration, in which Member States recognized the fundamental role of effective international cooperation in preventing and combating crime and to that end underlined the importance of addressing, tackling and effectively responding to international challenges and barriers, in particular measures, that hinder such cooperation and which are not consistent with the Charter of the United Nations and obligations under international law and in that regard urged States, consistent with their international obligations, to refrain from applying such measures,
وإذ تشير إلى الفقرة 67 من إعلان كيوتو، التي سلمت فيها الدول الأعضا

In [ ]:
excluded_src_tokens=["the","a","an","and","of","its","his","her","their","them","to","is","are","am","been","was","were","be", 
                     "have","has","had", "in", "on", "at", "with", "from","for","that","he","she","it","would",
                     "as","by","they","whose","which"] #we will need to update this
excluded_trg_tokens=["من","على","في","مع", "إلى",
                     "له","تم","إلى","في","عن","إن","أن","به","بها","لها","التي","كان","قد","الذي","الذين",
                     "هو","هي"]

bitext_i=15
src_used_phrase_dict,trg_used_phrase_dict={},{}
src_phrase_index_list,trg_phrase_index_list=[],[]
for bitext_i in range(len(bitext1)):
  src0,trg0=bitext1[bitext_i]
  src_toks=tok(src0)
  src_toks_lower=[v.lower() for v in src_toks]
  trg_toks=cur_ar_tok_fn(trg0)
  src_toks_filtered=filter_toks(src_toks,params={"exclude_numbers":True, "excluded_words":excluded_src_tokens})
  src_phrase_index_loc_dict=retr_sent_phrase_indexes(src_toks_filtered,src_index_dict,max_phrase_length=4)
  for phrase0,locs_indexes0 in src_phrase_index_loc_dict.items():
    locs0,indexes0=locs_indexes0
    if src_used_phrase_dict.get(phrase0,False): continue
    src_used_phrase_dict[phrase0]=True
    src_phrase_index_list.append((phrase0,indexes0))
    print(phrase0,locs0,len(indexes0))

  print("===")

===
work [(7, 7)] 25033
reliance [(2, 2)] 329
commission’s [(1, 1)] 1301
own [(5, 5)] 3481
prior [(6, 6)] 2768
prior work [(6, 7)] 6
===
===
frequently [(8, 8)] 440
secretariat [(1, 1)] 9070
also [(2, 2)] 38833
referred [(9, 9)] 2909
observed [(3, 3)] 1559
commission [(6, 6)] 17513
secretariat also [(1, 2)] 31
also observed [(2, 3)] 68
===
especially [(2, 2)] 4485
illustrated [(3, 3)] 189
this [(0, 0)] 46310
references [(6, 6)] 599
nuremberg [(13, 13)] 57
principles [(14, 14)] 10141
this  especially [(0, 2)] 48
commission’s work [(9, 10)] 209
===
law [(9, 9)] 37541
criminal [(8, 8)] 6855
consideration [(2, 2)] 5411
topics [(4, 4)] 955
often [(14, 14)] 2509
judgment [(27, 27)] 1412
related [(5, 5)] 19045
international [(7, 7)] 78763
topics related [(4, 5)] 33
related  international [(5, 7)] 48
international criminal [(7, 8)] 1887
international criminal law [(7, 9)] 161
criminal law [(8, 9)] 319
law   commission [(9, 12)] 14
often referred [(14, 15)] 19
===
under [(31, 31), (68, 68)] 314

In [ ]:
max_indexes_per_phrase=15
used_indexes_dict={}
src_phrase_index_list.sort()
print(len(src_phrase_index_list))
for phrase0,indexes0 in src_phrase_index_list:
  #print(phrase0)
  cur_used_phrase_indexes=[]
  for in0 in indexes0:
    if len(cur_used_phrase_indexes)>=max_indexes_per_phrase: break
    in0_int=int(in0)
    if used_indexes_dict.get(in0_int,False): continue
    used_indexes_dict[in0_int]=True
    cur_used_phrase_indexes.append(in0_int)
  # print(len(cur_used_phrase_indexes), cur_used_phrase_indexes)
  # print("----")

print(len(used_indexes_dict.keys()))


3936
49811


In [ ]:
items=list(trg_index_dict.items())
for a,b in items[:10]:
  print(a,b)

يشغل [624302.007, 708092.009, 8563633.015, 10023633.044, 10852167.038, 11036175.068, 11307832.017, 11425976.05, 11666737.014, 11666737.035, 11924937.03, 11999663.011, 12372198.028, 12542684.027, 13353908.015, 14159915.014, 15591668.02, 17866779.014, 23769155.035, 24825217.025, 25591808.014, 26705609.0, 26769145.008, 29395109.094, 29510642.0, 29659552.034, 31707153.001, 34597056.013, 36703079.037, 37754106.0, 37817642.008, 38057635.027, 38165748.018, 39924637.03, 41057884.029, 41559092.019, 42938485.07, 46394187.016, 46490849.029, 46785174.01, 46853977.001, 46959348.006, 50351347.007, 50353895.043, 50452280.027, 53781156.043, 54004988.032, 56279419.01, 56290470.023, 56450662.002, 56840815.006, 59414336.04, 60529964.024, 61158989.006, 64332102.046, 66141866.028, 66233253.011, 66262646.048, 72096724.005, 73041335.024, 74096318.029, 74723153.022, 74745569.012, 76285808.001, 86752607.001, 89340244.029, 103632379.033, 104562789.007, 107914501.009, 108170549.009, 117737224.071, 121828528.005,

In [ ]:
from pandas._libs import missing
first_word_term_qa_dict_fpath="first_word_term_qa_dict.json"
unterm_first_qa_dict=read_json(first_word_term_qa_dict_fpath)

excluded_terms=["international law","can","state","term","step","classified","press","one","section","instead","principal"]
#items=list(unterm_first_qa_dict.items())
# for a,b in items[:10]:
#   print(a,b)
for src0,trg0 in bitext1:
  if src0.strip()==trg0.strip(): continue
  src_toks=tok(src0)
  src_toks_lower=[v.lower() for v in src_toks]
  trg_toks=cur_ar_tok_fn(trg0)
  # print(src0)
  # print(trg0)
  mismatches=[]
  for s0 in list(set(src_toks_lower)):
    term_items=unterm_first_qa_dict.get(s0,[])
    if not term_items: continue
    #print(s0)
    for item0 in term_items:
      item0_en=item0["en"]
      if item0_en in excluded_terms: continue
      if not is_in(item0_en.split(),src_toks_lower): continue
      #print(item0)
      found_corr=[]
      ar_equivs=[]
      for c0 in item0["corr"]:
        ar0=c0[0]
        ar_detok0=de_tok2str(ar0.split()).replace("ـ","")
        ar_equivs.append(ar_detok0)
        #print(ar_detok0)
        ar0=clean_ar(ar0)
        if not is_in(ar0.split(),trg_toks): continue #print("not found >>", ar0)
        found_corr.append(ar0)
        #else: print("FOUND:", ar0)
      if found_corr==[]: 
        ar_equivs_str=" | ".join(ar_equivs)
        mismatches.append((item0_en, ar_equivs_str)) #print("mismatch:",item0_en, ar_equivs)
  if not mismatches: continue
  print(src0)
  print(trg0)
  for a,b in mismatches:
    print("mismatch:", a, b)
  print("----")
      



      #
    
  #print("---")


  

In the draft code of crimes against the peace and security of mankind, the Commission noted in 1951 that article 1, concerning the principle of individual responsibility for crimes under international law was contained in the Charter and the judgment of the Nuremberg Tribunal, referring to the formulation of the Nuremberg principles stating that “any person who commits an act which constitutes a crime under international law is responsible therefore and liable to punishment.”
وفي مشروع مدونة الجرائم المخلة بسلم البشرية وأمنها، لاحظت اللجنة في عام 1951 أن المادة 1 المتعلقة بمبدأ المسؤولية الفردية عن الجرائم بموجب القانون الدولي واردة في الميثاق وفي حكم محكمة نورمبرغ، مشيرة إلى صياغة مبادئ نورمبرغ التي تنص على أن "أي شخص يرتكب فعلا يشكل جريمة بموجب القانون الدولي يكون مسؤولا بالتالي وعرضة للعقاب".
mismatch: code of crimes against the peace and security of mankind مدوّنة الجرائم المخلة بسلم الإنسانية وأمنها
mismatch: individual responsibility مسؤولية فردية
----
Commentary to article 1 of 

In [ ]:
for a,b in consistency_check_dict.items():
  if len(b.keys())==1: continue
  print(a)
  for a0,b0 in b.items():
    print(a0,b0)
  print("---")

luxury goods
ال_سلع ال_كمالية 4
سلع 1
---
luxury
ال_كمالية 5
سلع 1
---
goods
ال_سلع 8
سلع 1
ال_بضائع 1
---
possible
إمكانية 1
ال_محتملة 1
---
transfer
نقل 1
ال_نقل 1
---
foreign
ال_أجنبية 1
أجنبية 1
---
currency
ال_عملات 2
عملات 2
---
annex
ال_مرفق 27
ال_تجارية 1
---
2022
عام 2022 4
عام 4
2022 32
---
beverages
ال_مشروبات 6
مشروبات 1
---
paras
ال_فقرات 7
ال_فقرتان 1
---
initial
ال_أولي 2
أولي 1
---
this
هذا 4
هذه 8
ذلك 1
هذا ال_صدد 1
---
company
ال_شركة 5
شركة 9
ال_معروفة 1
---
previously
سبق 1
سابقا 1
وقت 3
ال_سابق 1
مجال 1
---
Pyongyang
يونغ يانغ 5
Pyongyang 2
يونغ يانغ أونهاسو (_ Pyongyang 1
---
other
ال_أخرى 2
أخرى 1
غير 1
---
<s> Source _: NK News
<s> ال_مصدر _: موقع NK News 1
<s> ال_مصدر _: NK News 1
---
<s> The Panel
<s> وـ حقق ال_فريق 1
<s> وـ واصل ال_فريق 1
<s> كان ال_فريق 3
<s> وـ أجرى ال_فريق 1
<s> وـ يحقق ال_فريق 1
<s> أشار ال_فريق 1
<s> وـ يلاحظ ال_فريق 1
<s> وـ يشدد ال_فريق 1
<s> وـ يقدر ال_فريق 1
---
media
وسائط ال_إعلام 2
وسائط 2
ال_إعلام 2
---
reports
تقارير 4
ال_تقارير

#Check manually aligned docs for QA

In [ ]:
import re,json,shelve
from code_utils import general
from code_utils.general import *
from code_utils.arabic_lib import *
from code_utils.align_utils import *
from code_utils.pandas_utils import *
from itertools import groupby
from collections import Counter
ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})

def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)

term_shelve_path="terms.shelve"
acr_shelve_path="acronyms.shelve"
phrase_shelve_path="phrases.shelve"
term_shelve_open=shelve.open(term_shelve_path)
acr_shelve_open=shelve.open(acr_shelve_path)
phrase_shelve_open=shelve.open(phrase_shelve_path)

normative_path="https://docs.google.com/spreadsheets/d/e/2PACX-1vSpf4wpYxSkFFC84xMNFFVM_LKWtQo8wIchL8sksiNSQLZktwPTnLW9jmF2jVpv4gORd9gD9QtcrTGZ/pub?output=xlsx"
normative_obj=get_workbook_obj(normative_path)
normative_cols=["en","ar","type"]
normative_data=get_sheets_cols(normative_obj,["normative"],normative_cols)
normative_tok_list=[]
for src0,trg0,type0 in normative_data:
  src_toks0=tok(src0)
  trg_toks0=cur_ar_tok_fn(trg0)
  normative_tok_list.append((src_toks0,trg_toks0,type0))

def qa(bitext_input,qa_params={}):
  pass



src_sent='The commissions of inquiry, which have sought to ground the human rights obligations of such actors in the fact that they control territories and populations, have made recommendations to both States and armed groups without obvious distinction, prompting one observer to note that there seemed to be a growing tendency to view the violations thematically, without any particular (special) attention as to whether such violations were committed by a State or a non-State actor.	'
trg_sent='وقدمت لجان التحقيق، التي حرصت على أن تبني التزامات هذه الجهات في مجال حقوق الإنسان على أساس السيطرة التي تمارسها على الأقاليم والسكان، توصيات إلى الدول والجماعات المسلحة على حد سواء من دون أن تميز بينهما تمييزاً واضحاً، مما جعل أحد المراقبين يرى في ذلك نزوعاً متنامياً إلى فحص الانتهاكات من حيث الموضوع، من دون إيلاء أي اعتبار دقيق (خاص) لمسألة ما إذا كانت هذه الانتهاكات قد ارتكبتها دولة أو جهة غير تابعة للدولة.'
#src_sent='According to the United Nations Office for the Coordination of Humanitarian Affairs (OCHA), landmines and unexploded ordnance (UXO) accounted for the largest share of civilian casualties in the period since the signing of the truce in April 2022: As fighting subsided, civilians could move more freely, with many now seeking to access their farmlands and homes.'
#trg_sent='وفقا لمكتب الأمم المتحدة لتنسيق الشؤون الإنسانية، شكلت الألغام الأرضية والذخائر غير المنفجرة أكبر حصة من الضحايا المدنيين في الفترة منذ توقيع الهدنة في نيسان/أبريل 2022: ومع انحسار القتال، يمكن للمدنيين التحرك بحرية أكبر، حيث يسعى الكثيرون الآن إلى الوصول إلى أراضيهم الزراعية ومنازلهم.'

excluded_src_tokens=["the","a","an","and","of","its","his","her","their","them","to","is","are","am","been","was","were","be", 
                     "have","has","had", "in", "on", "at", "with", "from","for","that","he","she","it","would",
                     "as","by","they","whose","which"] #we will need to update this
excluded_trg_tokens=["من","على","في","مع", "إلى",
                     "له","تم","إلى","في","عن","إن","أن","به","بها","لها","التي","كان","قد","الذي","الذين",
                     "هو","هي"]

params={}
params["lang2_tok_fn"]=cur_ar_tok_fn
params["phrase_dict"]=phrase_shelve_open#phrase_table_dict
params["term_dict"]=term_shelve_open#term_dict
params["acr_dict"]=acr_shelve_open#acr_dict
params["excluded_words"]=excluded_src_tokens+excluded_trg_tokens
# params["lang2_tok_fn"]=cur_ar_tok_fn
# params["lang2_tok_fn"]=cur_ar_tok_fn
cur_qa_in_dir="bitexts/manual"
cur_qa_out_dir="qa/manual"
if not os.path.exists(cur_qa_out_dir): os.makedirs(cur_qa_out_dir)
sent_class0="sent0"
tsv_files=[v for v in os.listdir(cur_qa_in_dir) if v.endswith(".tsv")]
for tsv_fname in tsv_files[:200]:
  #if not tsv_fname.endswith(".tsv"): continue
  html_fname=tsv_fname.replace(".tsv",".html")
  tsv_fpath0=os.path.join(cur_qa_in_dir,tsv_fname)
  out_fpath=os.path.join(cur_qa_out_dir,html_fname)
  
  
  # tsv_fpath0="qa/13jan23-0.tsv"
  # tsv_fpath0=os.path.join()
  # out_fpath=tsv_fpath0.replace(".tsv",".html")
  

  #tsv_fpath0="qa/14jan1.tsv"
  bitext1=get_tsv_bitext(tsv_fpath0)
  if bitext1==[]: continue
  # src_index_dict0,trg_index_dict0=index_bitext_list(bitext1,params)
  # params["src_index"]=src_index_dict0
  # params["trg_index"]=trg_index_dict0

  final_sent_pair_list_with_classes=[]
  strong_mismatch_count,weak_mismatch_count=0,0
  for src_sent,trg_sent in bitext1:
    #out=walign(src_sent,trg_sent,params)
    #cur_src0,cur_trg0,cur_align0=out["src"],out["trg"],out.get("align",[])
    cur_src0=tok(src_sent)
    trg_sent=general.from_hindi(trg_sent)
    cur_trg0=cur_ar_tok_fn(trg_sent)
    cur_align0=[]
    src_tok_tags1,trg_tok_tags1=align_words_span_tags(cur_src0,cur_trg0,cur_align0,sent_class="sent0")
    qa_match_list0=qa_match_all(cur_src0,cur_trg0,normative_tok_list)
    src_qa_out,trg_qa_out=qa_add_spans_classes(cur_src0,cur_trg0,qa_match_list0)
    for a in src_qa_out:
      if "strong-mismatch" in a[0]: strong_mismatch_count+=1
      if "weak-mismatch" in a[0]: weak_mismatch_count+=1
      # if not"mismatch" in a[0]: continue
      # print(a)
    de_tok_space_src_items=de_tok_space(cur_src0)
    de_tok_space_trg_items=de_tok_space(cur_trg0)
    src_cell,trg_cell="",""
    for item_i,item0 in enumerate(de_tok_space_src_items):
      src_tok_str,src_tok_space=item0
      if src_tok_str in ['<s>',"</s>"]: continue
      walign_open0,walign_close0=src_tok_tags1[item_i]
      norm_open0,norm_close0=src_qa_out[item_i]
      open0=walign_open0+norm_open0
      close0=norm_close0+walign_close0
      src_cell+=open0+src_tok_str+close0+src_tok_space
    for item_i,item0 in enumerate(de_tok_space_trg_items):
      trg_tok_str,trg_tok_space=item0
      if trg_tok_str in ['<s>',"</s>"]: continue
      walign_open0,walign_close0=trg_tok_tags1[item_i]
      norm_open0,norm_close0=trg_qa_out[item_i]
      open0=walign_open0+norm_open0
      close0=norm_close0+walign_close0
      trg_cell+=open0+trg_tok_str+close0+trg_tok_space
      trg_cell=trg_cell.replace("ـ","")
    final_sent_pair_list_with_classes.append((src_cell,trg_cell))    
  print("out_fpath",out_fpath, len(bitext1))
  print("strong_mismatch_count,weak_mismatch_count",strong_mismatch_count,weak_mismatch_count)
  content1=create_align_html_content(final_sent_pair_list_with_classes)
  print("----")
  
  fopen=open(out_fpath,"w")
  fopen.write(content1)
  fopen.close()

# #create_align_html_content(aligned_html_sent_pairs,phrase_analysis_table="")
# create_align_html_content(final_sent_pair_list_with_classes)

phrase_shelve_open.close()
term_shelve_open.close()
acr_shelve_open.close()

print("finished processing")

out_fpath qa/manual/_0000_ENV_Kyoto_Protocol.html 304
strong_mismatch_count,weak_mismatch_count 4 20
----
out_fpath qa/manual/UNW_2020_L_1.html 129
strong_mismatch_count,weak_mismatch_count 17 22
----
out_fpath qa/manual/UNW_2020_7.html 613
strong_mismatch_count,weak_mismatch_count 19 0
----
out_fpath qa/manual/UNW_2020_4.html 546
strong_mismatch_count,weak_mismatch_count 3 1
----
out_fpath qa/manual/UNW_2020_3.html 500
strong_mismatch_count,weak_mismatch_count 32 1
----
out_fpath qa/manual/UNW_2020_2.html 329
strong_mismatch_count,weak_mismatch_count 7 1
----
out_fpath qa/manual/ST_SG_AC_10_11_Rev_5_Tests_and_Criteria_2009.html 5614
strong_mismatch_count,weak_mismatch_count 183 470
----
out_fpath qa/manual/SPLOS_32_4.html 3518
strong_mismatch_count,weak_mismatch_count 38 16
----
out_fpath qa/manual/SPLOS_32_2.html 986
strong_mismatch_count,weak_mismatch_count 51 27
----
out_fpath qa/manual/SEA_CONV_1982_Law_Sea.html 3263
strong_mismatch_count,weak_mismatch_count 40 131
----
out_fpath 

In [ ]:
bitext1

[]

In [ ]:
from code_utils.arabic_lib import *
from code_utils.general import *
#from code_utils.pandas_utils import *
from code_utils import general
import re,json, time
from itertools import groupby
from collections import Counter
from random import shuffle, seed

import unicodedata
def char_is_punct(char0):
  unicode_check=unicodedata.category(char0)
  if len(unicode_check)>0: return unicode_check[0]=="P"
  return False

def tok_NEW(txt):
  new_str=""
  txt_split=txt.split()
  punc_exits_dict={}
  for char0 in set(txt):
     if char_is_punct(char0):punc_exits_dict[char0]=True 
  #cur_punct_items=[v for v in list(set(txt)) if char_is_punct(v)]
  for item0 in txt_split:
    begin_punc_chars,end_punc_chars="",""
    for char0 in item0: 
      if punc_exits_dict.get(char0,False): begin_punc_chars+=char0
      else: break
    for char0 in reversed(item0): 
      if punc_exits_dict.get(char0,False): end_punc_chars=char0+end_punc_chars
      else: break
    bare_token=item0[len(begin_punc_chars):len(item0)-len(end_punc_chars)]
    splitting_hyphen=True
    if bare_token.lower().startswith("http") or bare_token.lower().startswith("www.") or "@" in bare_token: splitting_hyphen=False
    if splitting_hyphen: bare_token=" _-_ ".join(bare_token.split("-")) 
    if bare_token.endswith("'s"): bare_token=bare_token[:-2]+" _'s"
    #print([item0,begin_punc_chars,end_punc_chars, bare_token])
    for i0,char0 in enumerate(begin_punc_chars):
      if i0==0: new_str+=char0+"_ "
      else: new_str+=" _"+char0+"_ "
    new_str+=bare_token
    for i0,char0 in enumerate(end_punc_chars):
      if i0==len(end_punc_chars)-1: new_str+=" _"+char0
      else: new_str+=" _"+char0+"_ "
    new_str+=" "    
  return [v for v in new_str.split(" ") if v]




ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})
def cur_ar_tok_fn(text):
  cur_toks=tok_NEW(text)
  return tok_ar(cur_toks,ar_counter_dict)

en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"

def de_tok_space(tokens): #outputs list of tokens with the following, whether it is followed by space or not identify which tokens are followed by space and which are not, based on latest tok
  tok_space_list=[]
  for tok_i,tok0 in enumerate(tokens):
    cur_tok=str(tok0)
    prev_tok,next_tok="",""
    if tok_i+1<len(tokens): next_tok=tokens[tok_i+1]
    if tok_i>0: prev_tok=tokens[tok_i-1]
    following=" "
    if next_tok=="": following=""
    if next_tok.startswith("_"): following=""
    if cur_tok.endswith("_"): following=""
    if next_tok.startswith("ـ"): following=""
    if cur_tok.endswith("ـ"): following=""
    if cur_tok.startswith("ال_"):
      if prev_tok.strip("ـ")=="ل":
        cur_tok=cur_tok.replace("ال_","ل")
      else: cur_tok=cur_tok.replace("ال_","ال")
    cur_item= (cur_tok.strip("_"),following)
    tok_space_list.append(cur_item)
  return tok_space_list

def de_tok2str(tokens): #detokenize tokens into string
  detok_str0=""
  tokens_with_space_info0=de_tok_space(tokens)
  for a0 in tokens_with_space_info0: detok_str0+=a0[0]+a0[1]
  return detok_str0
# def de_tok_OLD(tokens): #for folder tokenization output
  # final_list=[]
  # for tok_i,tok0 in enumerate(tokens):
  #   if tok_i+1>=len(tokens)-1: 
  #     final_list.append((tok0,""))
  #     continue
  #   next_tok=tokens[tok_i+1]
  #   following=" "
  #   if general.is_punct(next_tok) and not next_tok in '"([{': following=""
  #   if tok0 in '"([{': following=""
  #   final_list.append((tok0,following))
  # return final_list

src_sent="""The commission's email: "hmghaly@gmail-company.com" and e.g. website 'http://www.aa-site-web.cc' of "(inquiry!, [which] have" sought: to ground the human (rights obligations of such actors in the fact that they control territories and populations, have made recommendations to both States and armed groups without obvious distinction, prompting one observer to note that there seemed to be a growing tendency to view the violations thematically, without any particular (special) attention as to whether such violations were committed by a State or a non-State actor.	 """
trg_sent='وقدمت لجان التحقيق، التي حرصت على أن تبني التزامات هذه الجهات في مجال حقوق الإنسان على أساس السيطرة التي تمارسها على الأقاليم والسكان، توصيات إلى الدول والجماعات المسلحة على حد سواء من دون أن تميز بينهما تمييزاً واضحاً، مما جعل أحد المراقبين يرى في ذلك نزوعاً متنامياً إلى فحص الانتهاكات من حيث الموضوع، من دون إيلاء أي اعتبار دَقيق (خاصّ) لمسألة ما إذا كانَت هذه الانتِهاكات قد ارتكبتها في تشرين الأول/أكتوبر دولة أو جهة غير تابعة للدولة.'

# src_toks=tok(src_sent)
# dtoks=de_tok_space(src_toks)
# detok_str=""
# for tok0,space0 in dtoks: detok_str+=tok0+space0
# print(detok_str)  
str1=trg_sent#+" "+trg_sent
str1=src_sent+" "+src_sent
t0=time.time()
for _ in range(n):
  src_toks=tok(str1)
elapsed=time.time()-t0


n=1000
t0=time.time()
for _ in range(n):
  src_toks_new=cur_ar_tok_fn(str1)
  src_toks_new=tok_NEW(str1)
elapsed_new=time.time()-t0


# for a,b in zip(src_toks_new,src_toks):
#   print("new", a,"old",b)
print(src_toks)
print(src_toks_new)
print("elapsed_new",elapsed_new/n, "elapsed",elapsed/n)

tok_space_list1=de_tok_space(src_toks_new)
print("tok_space_list1",tok_space_list1)
detok_str=de_tok2str(src_toks_new)
# for a in tok_space_list1: detok_str+=a[0]+a[1]

print(src_toks_new)
print(detok_str)


['The', 'commission', "'s", 'email', ':', '"', 'hmghaly', '@', 'gmail', '-', 'company', '.', 'com', '"', 'and', 'e.g.', 'website', "'", "http://www.aa-site-web.cc'", 'of', '"', '(', 'inquiry', '!', ',', '[', 'which', ']', 'have', '"', 'sought', ':', 'to', 'ground', 'the', 'human', '(', 'rights', 'obligations', 'of', 'such', 'actors', 'in', 'the', 'fact', 'that', 'they', 'control', 'territories', 'and', 'populations', ',', 'have', 'made', 'recommendations', 'to', 'both', 'States', 'and', 'armed', 'groups', 'without', 'obvious', 'distinction', ',', 'prompting', 'one', 'observer', 'to', 'note', 'that', 'there', 'seemed', 'to', 'be', 'a', 'growing', 'tendency', 'to', 'view', 'the', 'violations', 'thematically', ',', 'without', 'any', 'particular', '(', 'special', ')', 'attention', 'as', 'to', 'whether', 'such', 'violations', 'were', 'committed', 'by', 'a', 'State', 'or', 'a', 'non', '-', 'State', 'actor', '.', 'The', 'commission', "'s", 'email', ':', '"', 'hmghaly', '@', 'gmail', '-', 'com

In [ ]:
def tok_TEST(txt):
  split0=txt.split()
  for item0 in split0:
    a=item0
  return split0
str1=src_sent+" "+src_sent
n=100000
t0=time.time()
for _ in range(n):
  src_toks_new=tok_TEST(str1)
elapsed_new=time.time()-t0
print("elapsed_new",elapsed_new)

elapsed_new 1.121206283569336


In [ ]:
import unicodedata
def char_is_punct(char0):
  unicode_check=unicodedata.category(char0)
  if len(unicode_check)>0: return unicode_check[0]=="P"
  return False

char1="_"
char_is_punct(char1)

True

In [ ]:
def create_align_html_content(aligned_html_sent_pairs,phrase_analysis_table=""):
    css_content=create_color_classes_css()
    res_html_table=create_align_html_table(aligned_html_sent_pairs)
    

    cur_srcipt="""
    function toggle_bg(){
        $(".aligned").toggleClass("no-bg");
    }
    function toggle_transparent_aligned(){
        $(".aligned").toggleClass("aligned-transparent");
    }
    function init(){
        mismatches=$(".mismatch")
        console.log(mismatches)
    }

    function handle(e){
            if(e.keyCode === 13){
                e.preventDefault(); // Ensure it is only this code that runs
                //alert("Enter was pressed was presses");
                //$(".aligned").toggleClass("aligned-transparent");
                //$(".aligned").toggleClass("no-bg");
            }
        }

    """

    html_main_content="""
    <html>
    <head>
      <title>QA Analysis</title>
      <meta charset="utf-8">
      <meta name="viewport" content="width=device-width, initial-scale=1">
      <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/bootstrap@4.6.2/dist/css/bootstrap.min.css">
      <script src="https://code.jquery.com/jquery-3.6.1.min.js" integrity="sha256-o88AwQnZB+VDvE9tvIXrMQaPlFFSUTR+nldQm1LuPXQ=" crossorigin="anonymous"></script>
      <script src="https://cdn.jsdelivr.net/npm/popper.js@1.16.1/dist/umd/popper.min.js"></script>
      <script src="https://cdn.jsdelivr.net/npm/bootstrap@4.6.2/dist/js/bootstrap.bundle.min.js"></script>
    %s  
    
    <script>%s</script>
    </head>
    <body onload="init()" onkeypress="handle(event)">
    <div class="navbar" id="dashboard">
      <div class="row">
      <div class="column" style="float: left;width: 25%;">Alignment</div>
      <div class="column" style="float: left;width: 25%;">Numbers</div>
      <div class="column" style="float: left;width: 25%;">Terminology</div>
      <div class="column" style="float: left;width: 25%;">Spelling</div>
    </div>

    </div>   
    <div class="main"> 


    %s

    <h2>Phrase Matching Analysis</h2>
    %s
    </div>
    </body>
    </html>
    """%(css_content,cur_srcipt,res_html_table,phrase_analysis_table)
    return html_main_content
test=create_align_html_content("",phrase_analysis_table="")

ValueError: ignored

In [ ]:
from code_utils.pandas_utils import *
normative_path="https://docs.google.com/spreadsheets/d/e/2PACX-1vSpf4wpYxSkFFC84xMNFFVM_LKWtQo8wIchL8sksiNSQLZktwPTnLW9jmF2jVpv4gORd9gD9QtcrTGZ/pub?output=xlsx"
normative_obj=get_workbook_obj(normative_path)
normative_cols=["en","ar","type"]
normative_data=get_sheets_cols(normative_obj,["normative"],normative_cols)
for a in normative_data:
  print(a)

['Afghanistan', 'أفغانستان', 'country']
['Albania', 'ألبانيا', 'country']
['Algeria', 'الجزائر', 'country']
['Andorra', 'أندورا', 'country']
['Angola', 'أنغولا', 'country']
['Antigua and Barbuda', 'أنتيغوا وبربودا', 'country']
['Argentina', 'الأرجنتين', 'country']
['Armenia', 'أرمينيا', 'country']
['Australia', 'أستراليا', 'country']
['Austria', 'النمسا', 'country']
['Azerbaijan', 'أذربيجان', 'country']
['Bahamas', 'جزر البهاما', 'country']
['Bahrain', 'البحرين', 'country']
['Bangladesh', 'بنغلاديش', 'country']
['Barbados', 'بربادوس', 'country']
['Belarus', 'بيلاروس', 'country']
['Belgium', 'بلجيكا', 'country']
['Belize', 'بليز', 'country']
['Benin', 'بنن', 'country']
['Bhutan', 'بوتان', 'country']
['Bolivia (Plurinational State of)', 'بوليفيا (دولة - المتعددة القوميات)', 'country']
['Bolivia', 'بوليفيا (دولة - المتعددة القوميات)', 'country']
['Plurinational State of Bolivia', 'بوليفيا (دولة - المتعددة القوميات)', 'country']
['Bosnia and Herzegovina', 'البوسنة والهرسك', 'country']
['Bo

In [ ]:
# def get_tsv_bitext(tsv_fpath): #extract bitext src/trg sentences even for messy tsvs pasted from eLuna
#   bitext0=[]
#   tsv_fopen=open(tsv_fpath)
#   for i0,line0 in enumerate(tsv_fopen):
#     line_split0=line0.strip().split("\t")
#     cells=[v for v in line_split0 if v]
#     if len(cells)<2: continue
#     src0,trg0=cells[:2]
#     bitext0.append((src0,trg0))
#   tsv_fopen.close()
#   return bitext0


tsv_fpath0="qa/6jan23-1.tsv"
bitext1=get_tsv_bitext(tsv_fpath)
for a in bitext1:
  print(a)
# tsv_fopen=open(tsv_fpath)
# for i0,line0 in enumerate(tsv_fopen):
#   line_split0=line0.strip().split("\t")
#   cells=[v for v in line_split0 if v]
#   if len(cells)<2: continue
#   src0,trg0=cells[:2]
#   print(src0)
#   print(trg0)
#   print("---")
# tsv_fopen.close()


('B.', 'باء-')
('Financial Resources of the Designated Individuals and their Networks', 'الموارد المالية للأفراد المدرجة أسماؤهم في قائمة الجزاءات وشبكاتهم')
('69', '69-')
('Individuals designated under the 2140 sanctions regime, those acting on their behalf or at their direction, and the entities owned or controlled by them, continue to receive, own or control, directly or indirectly, funds, other financial assets, and economic resources, in violation of resolution 2140 (2014) and all subsequent related resolutions.', 'لا يزال الأفراد المحددون بموجب نظام الجزاءات 2140، والذين يتصرفون نيابة عنهم أو بتوجيه منهم، والكيانات التي يمتلكونها أو يسيطرون عليها، يتلقون الأموال والأصول المالية والموارد الاقتصادية الأخرى أو يمتلكونها أو يتحكمون فيها، بصورة مباشرة أو غير مباشرة، في انتهاك للقرار 2140 (2014) وجميع القرارات اللاحقة ذات الصلة.')
('70', '70-')
('Investigations by the Panel revealed the following sources of funding of the Houthis:', 'وكشفت التحقيقات التي أجراها الفريق عن مصادر تمويل ال

In [ ]:
t0=time.time()
for i in range(10):
  src_unigrams_bigrams=get_unigrams_bigrams(src_tokenized)
elapsed=time.time()-t0
print(elapsed)


0.0031681060791015625


In [ ]:
start_i=15600
n=2000
final_dict={}
for src_phrase0,trg_vals in out_list[start_i:start_i+n]:
  #print(src_phrase0)
  src_phrase_split0=src_phrase0.split()
  if len(src_phrase_split0)==1: key0=src_phrase_split0[0]
  else: key0=" ".join(src_phrase_split0[:2])
  tmp_dict=final_dict.get(key0,{})
  tmp_dict[src_phrase0]=trg_vals
  final_dict[key0]=tmp_dict
  # print("key0:",key0)
  # for val0 in trg_vals:print("val0:",val0)
  # print("---")

for a,b in final_dict.items():
  print(a,b) 

registry {'registry': [('قلم ال_محكمة', (11, 0.4639650283553874))]}
regret {'regret': [('ال_أسف', (23, 0.14721382624195917)), ('أسف', (13, 0.14669293554742469))]}
regrets {'regrets': [('تأسف', (31, 0.6913236929922133))]}
regrettable {'regrettable': [('ال_مؤسف', (16, 0.16309523809523804))]}
regrettably {'regrettably': [('ال_أسف', (26, 0.12828110562778902)), ('مما يؤسف', (8, 0.13281831720029785)), ('ال_مؤسف', (15, 0.15625))]}
regretted {'regretted': [('أسفها', (10, 0.24892857142857144)), ('ال_أسف', (11, 0.262861169837914))]}
regular {'regular': [('ال_عادية', (489, 0.4930667015938125)), ('منتظمة', (60, 0.1089823802298)), ('منتظم', (27, 0.07937549805095509)), ('ال_منتظمة', (15, 0.10245253282597684)), ('ال_منتظم', (18, 0.0868773593773367)), ('عادية', (11, 0.4861070940118131))]}
regular basis {'regular basis': [('بصورة منتظمة', (9, 0.12474070080588377)), ('أساس منتظم', (13, 0.4951181840306208))]}
regular budget {'regular budget': [('ال_ميزانية ال_عادية', (266, 0.9788351520605609)), ('ال_عادي

In [ ]:
print("out_list",len(out_list))
start_i=15600
n=200
for a,b in out_list[start_i:start_i+n]:
  print(a,b)

out_list 20197
registry [('قلم ال_محكمة', (11, 0.4639650283553874))]
regret [('ال_أسف', (23, 0.14721382624195917)), ('أسف', (13, 0.14669293554742469))]
regrets [('تأسف', (31, 0.6913236929922133))]
regrettable [('ال_مؤسف', (16, 0.16309523809523804))]
regrettably [('ال_أسف', (26, 0.12828110562778902)), ('مما يؤسف', (8, 0.13281831720029785)), ('ال_مؤسف', (15, 0.15625))]
regretted [('أسفها', (10, 0.24892857142857144)), ('ال_أسف', (11, 0.262861169837914))]
regular [('ال_عادية', (489, 0.4930667015938125)), ('منتظمة', (60, 0.1089823802298)), ('منتظم', (27, 0.07937549805095509)), ('ال_منتظمة', (15, 0.10245253282597684)), ('ال_منتظم', (18, 0.0868773593773367)), ('عادية', (11, 0.4861070940118131))]
regular basis [('بصورة منتظمة', (9, 0.12474070080588377)), ('أساس منتظم', (13, 0.4951181840306208))]
regular budget [('ال_ميزانية ال_عادية', (266, 0.9788351520605609)), ('ال_عادية', (5, 0.6569810214533585))]
regular budget . [('ال_ميزانية ال_عادية .', (14, 1.269254459076474))]
regular budget . </s> [(

In [ ]:
start_i=10600
n=2000
test=list(phrase_table_dict.items())
print(len(test))
for ts in test[start_i:start_i+n]:
  print(ts)

15828
('other resources', {'other resources': [('موارد أخرى', (5, 1.1481838890136165)), ('ال_موارد ال_أخرى', (7, 1.189043083845041))]})
('other sections', {'other sections': [('أبواب أخرى', (5, 0.7869206228868766))]})
('other sectors', {'other sectors': [('ال_قطاعات ال_أخرى', (10, 0.9312891430518666))]})
('other services', {'other services': [('ال_خدمات ال_أخرى', (6, 1.0553129499943996)), ('خدمات أخرى', (5, 1.0140700923260968))]})
('other sources', {'other sources': [('مصادر أخرى', (22, 1.194717853609949)), ('ال_مصادر ال_أخرى', (6, 1.2352515212306123))]})
('other special', {'other special': [('خاصة أخرى', (5, 0.7863325190442261))]})
('other state', {'other state': [('دولة أخرى', (6, 0.9468468924726747)), ('ال_دولة ال_أخرى', (6, 0.941483267513818))]})
('other states', {'other states': [('ال_دول ال_أخرى', (70, 1.0338771044102173)), ('دول أخرى', (47, 1.027070738630719))]})
('other than', {'other than': [('خلاف', (19, 0.12890912597726073))]})
('other tracks', {'other tracks': [('ال_مسارات 

In [ ]:
len(final_list)
final_list.sort()
start_i=26000
n=200
for a in final_list[start_i:start_i+n]:
  print(a)

('international telecommunication union', 'ال_اتحاد ال_دولي', 12, 10.313932769351718)
('international telecommunication union', 'ال_اتحاد ال_دولي لـ ال_اتصالات ال_سلكية وـ ال_لاسلكية', 4, 3.399724304906128)
('international telecommunication union', 'ال_اتحاد ال_دولي لـ ال_مواصلات ال_سلكية وـ ال_لاسلكية', 4, 3.340882564457842)
('international telecommunication union', 'ال_مواصلات ال_سلكية وـ ال_لاسلكية', 6, 3.3103448275862073)
('international telecommunication union .', 'ال_مواصلات ال_سلكية وـ ال_لاسلكية .', 4, 3.206896551724138)
('international terrorism', 'ال_إرهاب ال_دولي', 20, 17.898045914678438)
('international terrorism', 'ال_ارهاب ال_دولي', 24, 16.40935400722496)
('international trade', 'ال_تجارة ال_دولية', 101, 79.13897706599631)
('international trade', 'ال_تجاري ال_دولي', 17, 8.237985424412336)
('international trade </s>', 'ال_تجارة ال_دولية </s>', 3, 3.171632010187512)
('international trade and development', 'ال_تجارة ال_دولية وـ ال_تنمية', 3, 3.8588927715511776)
('internation

In [ ]:
import time
a='international telecommunication union and international verification'
t0=time.time()
for i in range(1000000):
  a1=a.split()
elapsed=time.time()-t0
print(elapsed)


0.8316524028778076


In [ ]:
from code_utils.web_lib import *
fpath1='sent-align/2016452E.html'
fpath2='sent-align/2016452A.html' #test these
with open(fpath2) as fopen:
  content0=fopen.read()

# def html_with_tags2sents(html_content,apply_tika=True):
#   dom_obj=DOM(html_content)
#   text_items_tags=dom_obj.text_items_tags
#   final_text=""
#   for tag0,txt0 in text_items_tags:
#     cur_tag_str,cur_txt_str=tag0,general.unescape(txt0)
#     if tag0.startswith("</"):cur_tag_str="" 
#     else: cur_tag_str= tag0+"\n"
#     if txt0=="<br>": cur_txt_str="\n"
#     final_text+=cur_tag_str+cur_txt_str
#   items=[v for v in final_text.split("\n") if v]
#   final_items=[]
#   for it_i,it0 in enumerate(items):
#     next_it=""
#     if it_i+1<len(items):next_it=items[it_i+1]
#     if it0.startswith("<") and it0.endswith(">"): 
#       if next_it.endswith(">") and next_it.startswith("<"): continue
#       else: final_items.append(it0)
#     else: 
#       if apply_tika:
#         tika_segs=split_tika_fn(it0)
#         for ts in tika_segs:
#           cur_sents=general.ssplit(ts)
#           final_items.extend(cur_sents)
#       else:
#         final_items.extend(general.ssplit(it0))
#     #print('----')
#   final_sents=[]
#   for a in final_items:
#     if a.strip() in "}]." and len(final_sents)>0:  final_sents[-1]=final_sents[-1]+a
#     else: final_sents.append(a)
#   return final_sents

all_cur_sents=html_with_tags2sents(content0)

for a in all_cur_sents:
  print(a)

<title>
A/HRC/38/44
<p class="header">
A/HRC/38/44
<p class="header">
A/HRC/38/44
<p>
الأمم المتحدة
<p>
A/HRC/38/44
<b>
الجمعية العامة
<p>
Distr.: General
<p>
7 December 2020
<p>
Arabic
<p>
Original: English
<b>
مجلس حقوق الإنسان
<b>
الدورة الثامنة والثلاثون
<p class="__Single_Txt_GA">
18 حزيران/يونيه - 6 تموز/يوليه 2018
<p class="__Single_Txt_GA">
البند 3 من جدول الأعمال
<b>
تعزيز وحماية جميع حقوق الإنسان، المدنية والسياسية والاقتصادية والاجتماعية والثقافية، بما في ذلك الحق في التنمية
<p class="__H__Ch_GA">
تقرير المقررة الخاصة المعنية بحالات الإعدام خارج القضاء أو بإجراءات موجزة أو تعسفاً عن الجهات المسلحة غير التابعة للدول: حماية الحق في الحياة[footnoteRef:1]*
[1: *
قُدِّم هذا التقرير بعد انقضاء الموعد النهائي لتضمينه أحدث المستجدات.]
<p class="__H_1_GA">
مذكرة من الأمانة
<p class="__Single_Txt_GA">
تتشرف الأمانة بأن تحيل إلى مجلس حقوق الإنسان تقرير المقررة الخاصة المعنية بحالات الإعدام خارج القضاء أو بإجراءات موجزة أو تعسفاً، أنييس كالامار، المقدم عملاً بقرار المجلس 35/15.
وتركز ال

#Sentence Alignment - 13 Dec 2022

In [ ]:
import json
from code_utils.tika_utils import *
from code_utils.web_lib import *
from code_utils.general import *
from code_utils.align_utils import *
from code_utils.arabic_lib import *

from itertools import groupby
from collections import Counter
ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})

#en_ar_sent_len_ratio_json_fpath="en-ar-sent-size-ratios.json"
en_ar_sent_len_ratio_json_fpath="en-ar-sent-size-pairs.json"
en_ar_sent_len_ratio_json_fopen=open(en_ar_sent_len_ratio_json_fpath)
en_ar_sent_len_ratio_json_dict=json.load(en_ar_sent_len_ratio_json_fopen)
en_ar_sent_len_ratio_json_fopen.close()

print("en_ar_sent_len_ratio_json_dict",en_ar_sent_len_ratio_json_dict)

def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)

def change_file_ext(fpath,out_ext="html"):
  fpath_split0=fpath.split(".")
  fpath_split0[-1]=out_ext
  out_fpath0=".".join(fpath_split0)
  return out_fpath0

#norm_sent_size()
def s_align(src_sents,trg_sents,params={}):
  tok_fn=params.get("tok_fn",general.tok)
  lang2_tok_fn=params.get("lang2_tok_fn")
  lang1=params.get("lang1","en")
  lang2=params.get("lang2","ar")
  cur_n_epochs=params.get("n_epochs",5)
  cur_max_sent_size=params.get("max_sent_size",50)
  cur_max_src_span=params.get("max_src_span",6)
  cur_max_dist=params.get("max_dist",3)
  src_index0=params.get("src_index",{})
  trg_index0=params.get("trg_index",{})
  phrase_dict0=params.get("phrase_dict",{})
  term_dict0=params.get("term_dict",{})
  acr_dict0=params.get("acr_dict",{})
  custom_dict0=params.get("custom_dict",{})
  max_n_sents0=params.get("max_n_sents",3)
  max_sent_dist=params.get("max_sent_dist",50)

  all_src_toks,all_trg_toks=[],[]
  all_src_toks_lower,all_trg_toks_lower=[],[]
  all_src_sent_sizes,all_trg_sent_sizes=[],[]
  for s_i,sent0 in enumerate(src_sents):
    src_toks=tok(sent0)
    cur_counter=len(all_src_toks)
    for tok_i,tok0 in enumerate(src_toks): 
      all_src_toks.append((tok0,s_i,cur_counter+tok_i))
      all_src_toks_lower.append((tok0.lower(),s_i,cur_counter+tok_i))
    #all_src_sent_sizes.append((len(sent0),s_i))
  for s_i,sent0 in enumerate(trg_sents):
    trg_toks=cur_ar_tok_fn(sent0)
    cur_counter=len(all_trg_toks)
    for tok_i,tok0 in enumerate(trg_toks): 
      all_trg_toks.append((tok0,s_i,cur_counter+tok_i))
      all_trg_toks_lower.append((tok0.lower(),s_i,cur_counter+tok_i))
    #all_trg_sent_sizes.append((len(sent0),s_i))

  all_src_tokens_only=[v[0] for v in all_src_toks]
  all_trg_tokens_only=[v[0] for v in all_trg_toks]
  # all_src_toks.sort(key=lambda x:x[0])
  # grouped_src=[(key,[v[1:] for v in list(group)]) for key,group in groupby(all_src_toks,lambda x:x[0])]
  # grouped_src_dict=dict(iter(grouped_src))

  
  # all_trg_toks.sort(key=lambda x:x[0])
  # grouped_trg=[(key,[v[1:] for v in list(group)]) for key,group in groupby(all_trg_toks,lambda x:x[0])]
  # grouped_trg_dict=dict(iter(grouped_trg))

  all_matching=[]
  phon_match0=get_phon_matching(all_src_tokens_only,all_trg_tokens_only,default_ratio=0.1)
  exact_match0=get_exact_matching(all_src_tokens_only,all_trg_tokens_only,default_ratio=0.25)
  all_matching=phon_match0+exact_match0
  # phrase_match0=match_keyed_dict(src_tokens_lower,trg_tokens_lower,phrase_dict0)
  # term_match0=match_keyed_dict(src_tokens_lower,trg_tokens_lower,term_dict0)
  # acr_match0=match_keyed_dict(src_tokens,trg_tokens,acr_dict0)
  #all_matching=phon_match0+exact_match0+phrase_match0+term_match0+acr_match0
  sent_pair_wt_dict={}
  for a in all_matching:
    src_phrase0,trg_phrase0,src_spans0,trg_span0,intersection0,wt0=a
    if general.is_punct(src_phrase0): continue
    # print("src_phrase0,trg_phrase0",src_phrase0,trg_phrase0)
    # print("src_spans0,trg_span0,intersection0,wt0",src_spans0,trg_span0,intersection0,wt0)
    for s_span0 in src_spans0:
      x0,x1=s_span0
      corr_src_sent_ids=sorted(list(set([all_src_toks[vi][1] for vi in range(x0,x1+1)])))
      #print("corr_src_sent_ids",corr_src_sent_ids)
      for t_span0 in trg_span0:
        y0,y1=t_span0
        corr_trg_sent_ids=sorted(list(set([all_trg_toks[vi][1] for vi in range(y0,y1+1)])))
        for src_sent_id in corr_src_sent_ids:
          for trg_sent_id in corr_trg_sent_ids:
            sent_pair_id=(src_sent_id,trg_sent_id)
            sent_pair_wt_dict[sent_pair_id]=sent_pair_wt_dict.get(sent_pair_id,0)+wt0
  sent_pair_wt_dict_items=list(sent_pair_wt_dict.items())
  print("sent_pair_wt_dict",len(sent_pair_wt_dict_items),sent_pair_wt_dict_items[:10])
  return
  #Now working only with sentence sizes
  src_sent_span_sizes,trg_sent_span_sizes=[],[]
  for si,s_sent0 in enumerate(src_sents):
    s_start,s_end=si,min(si+max_n_sents0,len(src_sents))
    for cur_end_i in range(s_start,s_end):
      cur_sent_span=(si,cur_end_i)
      cur_size=sum([len(src_sents[cur_i]) for cur_i in range(si,cur_end_i+1)])
      normalized_size=norm_sent_size(cur_size)
      src_sent_span_sizes.append((normalized_size,cur_sent_span,cur_size))
  for ti,t_sent0 in enumerate(trg_sents):
    t_start,t_end=ti,min(ti+max_n_sents0,len(trg_sents))
    for cur_end_i in range(t_start,t_end):
      cur_sent_span=(ti,cur_end_i)
      cur_size=sum([len(trg_sents[cur_i]) for cur_i in range(ti,cur_end_i+1)])
      normalized_size=norm_sent_size(cur_size)
      trg_sent_span_sizes.append((normalized_size,cur_sent_span,cur_size))
  

  src_sent_span_sizes.sort()
  trg_sent_span_sizes.sort()
  src_size_list_grouped=[(str(key),[v[1] for v in list(group)]) for key,group in groupby(src_sent_span_sizes,lambda x:x[0])]
  trg_size_list_grouped=[(str(key),[v[1] for v in list(group)]) for key,group in groupby(trg_sent_span_sizes,lambda x:x[0])]
  trg_size_list_grouped_dict=dict(iter(trg_size_list_grouped))
  sent_el_dict={}
  src_el_start_dict={}
  trg_el_start_dict={}

  #trg_size_list_grouped_dict_keys=list(trg_size_list_grouped_dict.keys())
  for src_key,src_sent_spans in src_size_list_grouped:
    corr_trg_dict=en_ar_sent_len_ratio_json_dict.get(src_key,{})
    corr_trg_sent_spans_wts=[]
    #print(a,len(b),b[:5],corr_trg_dict)
    for key0,wt0 in corr_trg_dict.items():
      if wt0<0.05: continue
      check_corr_spans0=trg_size_list_grouped_dict.get(key0)
      if check_corr_spans0==None: continue
      for trg_span0 in check_corr_spans0:
        corr_trg_sent_spans_wts.append((trg_span0,wt0))
      #print(key0,wt0,len(check0),check0[:5])
    # print(src_key,"src_sent_spans",len(src_sent_spans),src_sent_spans[:5])
    # print("corr_trg_sent_spans_wts",len(corr_trg_sent_spans_wts),corr_trg_sent_spans_wts[:5])
    # print("---------")
    for src_span0 in src_sent_spans:
      src_start0=src_span0[0]
      for trg_span0,wt0 in corr_trg_sent_spans_wts:
        trg_start0=trg_span0[0]
        if trg_start0-src_start0>max_sent_dist: continue
        el0=(src_span0,trg_span0)
        sent_el_dict[el0]=wt0
        src_el_start_dict[src_start0]=src_el_start_dict.get(src_start0,[])+[(el0,wt0)]
        trg_el_start_dict[trg_start0]=trg_el_start_dict.get(trg_start0,[])+[(el0,wt0)]

  sent_el_dict_items=list(sent_el_dict.items())
  sent_el_dict_items.sort(key=lambda x:-x[-1])
  print("sent_el_dict_items",len(sent_el_dict_items))
  start_el=((-1,-1),(-1,-1))
  end_el=((len(src_sents),len(src_sents)),(len(trg_sents),len(trg_sents)))
  sent_el_dict[start_el]=0
  sent_el_dict[end_el]=0
  src_el_start_dict[len(src_sents)]=[(end_el,0)]
  all_els=list(sent_el_dict.items())
  
  
  transition_dict={}
  transition_list=[]
  for el0,wt0 in all_els:
    #print(el0,wt0)
    src_span0,trg_span0=el0
    x0,x1=src_span0
    y0,y1=trg_span0
    all_next=[]
    tmp_next_el_dict={}
    for x2 in range(x1+1,x1+3):
      corr_els=src_el_start_dict.get(x2,[])
      for next_el0,next_wt0 in corr_els:
        if next_el0[1][0]<=y1 and next_el0[1][0]-y1>max_sent_dist: continue
        if tmp_next_el_dict.get(next_el0)!=None: continue
        tmp_next_el_dict[next_el0]=next_wt0
        #transition_list.append((el0,(next_el0,next_wt0)))
        
      # corr_els=[v for v in corr_els if v[1][0]>y1 and v[1][0]-y1<max_sent_dist]
      # all_next.extend(corr_els)
    for y2 in range(y1+1,y1+3):
      corr_els=trg_el_start_dict.get(y2,[])
      for next_el0,next_wt0 in corr_els:
        if next_el0[0][0]<=x1 and next_el0[0][0]-x1>max_sent_dist: continue
        if tmp_next_el_dict.get(next_el0)!=None: continue
        tmp_next_el_dict[next_el0]=next_wt0
    transition_dict[el0]=tmp_next_el_dict

        # if tmp_used_el_dict.get(next_el0,False)==True: continue
        # tmp_used_el_dict[next_el0]=True        
        # transition_list.append((el0,(next_el0,next_wt0)))

    #   corr_els=[v for v in corr_els if v[0][0]>x1 and v[0][0]-x1<max_sent_dist]
    #   all_next.extend(corr_els)
    # all_next=sorted(list(set(all_next)))
    # all_next_wts=[(v,sent_el_dict.get(v,0)) for v in all_next]
    # transition_dict[el0]=dict(iter(all_next_wts))
    #print("all_next",len(all_next),all_next[:20])

      #print(x2, "corr_els",len(corr_els),corr_els[:5])
    #print("-----")
  td_items=list(transition_dict.items())
  #transition_list.sort()
  for a,b in td_items[:50]:
    print(a,b)
  print("transition_list",len(td_items))
#for a,b in   transition_dict={}
    





# fpath1='sent-align/2222721_en.docx'
# fpath2='sent-align/2222721_ar.docx'
fpath1='sent-align/2016452E.docx'
fpath2='sent-align/2016452A.docx' #test these

fpath1='sent-align/2229490A_en.docx'
fpath2='sent-align/2229490A_ar.docx'
fpath_out1=change_file_ext(fpath1)
fpath_out2=change_file_ext(fpath2)
if not os.path.exists(fpath_out1):tika(fpath1,fpath_out1)
if not os.path.exists(fpath_out2):tika(fpath2,fpath_out2)
sents1=html_file2sents(fpath_out1)
sents2=html_file2sents(fpath_out2)

print("sents1",len(sents1))
print("sents2",len(sents2))

cur_params={}
cur_params["lang2_tok_fn"]=cur_ar_tok_fn

# for a in sents2:
#   #print([a])
#   items0=split_tika_fn(a)
#   for it0 in items0:
#     print(it0)
#   print("---")
s_align(sents1,sents2,cur_params)
# for a in sents1[:20]: print("SRC:", a)
# for a in sents2[:20]: print("TRG:", a)


# src_trg_matching_list=[]
# for src_phrase0,trg_corr_dict in out_list:
#   #print()
#   src_phrase_split0=src_phrase0.split()
#   check_src=grouped_src_dict.get(src_phrase_split0[0])
#   if check_src==None: continue
#   #print(src_phrase0,trg_corr_dict, check_src)
#   #print("---")
#   src_spans= is_in(src_phrase_split0,src_tokens_only)
#   if not src_spans: continue
  
#   for trg_phrase0,trg_wt_freq in trg_corr_dict:
#     trg_phrase_split0=trg_phrase0.split()
#     trg_spans= is_in(trg_phrase_split0,trg_tokens_only)
#     if not trg_spans: continue
#     #print(src_phrase0,trg_phrase0, src_spans,trg_spans)
#     src_trg_matching_list.append((src_phrase0,trg_phrase0, src_spans,trg_spans,trg_wt_freq))


# src_trg_matching_list.sort()
# for a in src_trg_matching_list[:200]:
#   print(a)
  #print("------")

# for a,b in grouped_trg_dict.items():
#   print(a,b)
# for a in all_trg_toks[:50]:
#   print(a)

# for a,b in zip(sents1,sents2):
#   print(a)
#   print(b)
#   print("--")

# in_fpath0="docs/2212878A_P2.docx"
# in_fpath_split0=in_fpath0.split(".")
# in_fpath_split0[-1]="html"
# out_fpath0=".".join(in_fpath_split0)
# tika(in_fpath0,out_fpath0)
# print("out_fpath0",out_fpath0)

en_ar_sent_len_ratio_json_dict {'0': {'10': 0.508, '0': 0.476, '20': 0.013}, '10': {'10': 0.636, '0': 0.06, '20': 0.266, '30': 0.019}, '20': {'20': 0.633, '30': 0.115, '10': 0.2, '40': 0.032}, '30': {'20': 0.415, '30': 0.36, '10': 0.059, '40': 0.117, '50': 0.029, '60': 0.01}, '40': {'40': 0.309, '20': 0.168, '30': 0.353, '50': 0.088, '60': 0.042, '70': 0.01, '10': 0.018}, '50': {'40': 0.397, '30': 0.165, '20': 0.048, '60': 0.102, '70': 0.026, '50': 0.231, '80': 0.014}, '60': {'50': 0.305, '30': 0.054, '80': 0.036, '40': 0.272, '60': 0.216, '70': 0.074, '20': 0.015, '90': 0.011}, '70': {'50': 0.239, '60': 0.325, '40': 0.103, '80': 0.087, '70': 0.165, '90': 0.031, '30': 0.016, '100': 0.015}, '80': {'60': 0.296, '50': 0.126, '70': 0.236, '80': 0.174, '40': 0.031, '110': 0.013, '100': 0.038, '90': 0.068}, '90': {'60': 0.192, '70': 0.237, '80': 0.259, '90': 0.128, '100': 0.076, '50': 0.042, '110': 0.027, '120': 0.015}, '100': {'90': 0.186, '110': 0.053, '70': 0.186, '80': 0.283, '120': 0.03

In [ ]:
def html_file2sents(html_fpath):
  fopen=open(html_fpath)
  content0=fopen.read()
  fopen.close()
  return html2sents(content0)

def split_tika_fn(txt): #split tika footnotes for alignment
  txt=re.sub('(\.\[footnoteRef.+?\])',r'\1\n',txt)
  txt=re.sub('(\s+\[\d+\:)',r'\n\1',txt)
  tmp_items=[v.strip("\xa0' ") for v in txt.split("\n") if v]
  return tmp_items

def html2sents(html_content,apply_tika=True):
  all_sents=[]
  dom_obj0=DOM(html_content)
  dom_text_items=dom_obj0.text_items
  #print(len(dom_text_items))
  for a in dom_text_items:
    para0=general.unescape(a)
    print("para0",para0)
    para_items=para0.split("\t")
    all_sents.extend(para_items)
    # for p0 in para_items:
    #   if apply_tika:
    #     tika_segs=split_tika_fn(p0)
    #     for ts in tika_segs:
    #       cur_sents=general.ssplit(ts)
    #       all_sents.extend(cur_sents)
    #   else:
    #     cur_sents=general.ssplit(p0)
    #     all_sents.extend(cur_sents)

  return all_sents
sents1=html_file2sents(fpath_out1)
#sents2=html_file2sents(fpath_out2)
print("sents1",len(sents1))
#print("sents2",len(sents2))

para0 B.	 Financial Resources of the Designated Individuals and their Networks 
sents1 2


In [ ]:
import re
def split_tika_fn(txt): #split tika footnotes for alignment
  txt=re.sub('(\.\[footnoteRef.+?\])',r'\1\n',txt)
  txt=re.sub('(\s+\[\d+\:)',r'\n\1',txt)
  tmp_items=[v.strip("\xa0' ") for v in txt.split("\n") if v]
  return tmp_items

txt0="""['The Panel concluded investigations into three of the four incidents, those on 17, 20 and 21 January 2022.[footnoteRef:21] Based on the available evidence, the Panel concluded that, in these military operations, the Coalition forces likely did not comply with their obligations under IHL: (i) to distinguish between civilians and combatants and between civilian objects and military objectives, and target only military objectives;']"""
txt0="""'OCHA reported 673 incidents in 103 districts in 19 governorates, where access was impacted, affecting 5.8 million people.[footnoteRef:25]\xa0 [25:  https://reliefweb.int/report/yemen/yemen-access-snapshot-july-september-2022-30-september-2022.]'"""
lines=split_tika_fn(txt0)
for li in lines:
  # print(li.strip("[]'"))
  print(li)
  # print([li.strip()])
  #print(li, tok(li))
# txt=re.sub('(\.\[footnoteRef.+?\])',r'\1\n',txt)
# txt=re.sub('(\s+\[\d+\:)',r'\n\1',txt)
# print([txt])
# print(txt)

OCHA reported 673 incidents in 103 districts in 19 governorates, where access was impacted, affecting 5.8 million people.[footnoteRef:25]
[25:  https://reliefweb.int/report/yemen/yemen-access-snapshot-july-september-2022-30-september-2022.]


In [ ]:
src_tokens_only[:100]

['a/hrc/38/44',
 'a/hrc/38/44',
 'a/hrc/38/44',
 'united',
 'nations',
 'a/hrc/38/44',
 'general',
 'assembly',
 'distr',
 '.',
 ':',
 'general',
 '7',
 'december',
 '2020',
 'original',
 ':',
 'english',
 'human',
 'rights',
 'council',
 'thirty',
 '-',
 'eighth',
 'session',
 '18',
 'june',
 '–',
 '6',
 'july',
 '2018',
 'agenda',
 'item',
 '3',
 'promotion',
 'and',
 'protection',
 'of',
 'all',
 'human',
 'rights',
 ',',
 'civil',
 ',',
 'political',
 ',',
 'economic',
 ',',
 'social',
 'and',
 'cultural',
 'rights',
 ',',
 'including',
 'the',
 'right',
 'to',
 'development',
 'report',
 'of',
 'the',
 'special',
 'rapporteur',
 'on',
 'extrajudicial',
 ',',
 'summary',
 'or',
 'arbitrary',
 'executions',
 'on',
 'armed',
 'non',
 '-',
 'state',
 'actors',
 ':',
 'the',
 'protection',
 'of',
 'the',
 'right',
 'to',
 'life',
 '[',
 'footnoteref',
 ':',
 '2',
 ']',
 '*',
 '[',
 '2',
 ':',
 '*',
 'the',
 'present',
 'report',
 'was',
 'submitted',
 'after']

In [ ]:
from code_utils.align_utils import *
def combine_items_rec(item_list,el_dict0={},penalty=0,max_src_span=6,n_epochs0=3,allow_ortho=False):#combine items recursively
  cur_items=list(item_list) #we do an intial iterative run to get a basic alignment
  cur_item_list0=list(cur_items)
  cur_item_list1=list(cur_items)
  final_list0=[]
  for epoch0 in range(n_epochs0): 
    new_items=match_el_lists(cur_item_list0,cur_item_list1,el_dict0,allow_ortho=allow_ortho, penalty=penalty,max_src_span=max_src_span)
    cur_item_list0=[]
    for a in new_items:
      new_el,new_el_wt,new_el_children=a
      found_wt=el_dict0.get(new_el,0)
      if new_el_wt>found_wt:
        cur_item_list0.append((new_el,new_el_wt))
        cur_item_list1.append((new_el,new_el_wt))
        final_list0.append(a)
  return final_list0


el_wt0=((1,1),(2,2)),0.5
el_wt1=((2,4),(3,3)),0.2
el_wt2=((3,4),(4,4)),0.25
el_wt3=((4,4),(3,4)),0.35
el_wt4=((4,5),(5,5)),0.15
el_wt5=((5,5),(5,5)),0.1
el_wt6=((1,1),(1,1)),0.25
el_list=[el_wt0,el_wt1,el_wt2,el_wt3,el_wt4,el_wt5,el_wt6]

all_new_items=combine_items_rec(el_list,allow_ortho=True)
for an in all_new_items:
  print(an)


(((1, 1), (1, 2)), 0.75, (((1, 1), (1, 1)), ((1, 1), (2, 2))))
(((1, 4), (1, 3)), 0.45, (((1, 1), (1, 1)), ((2, 4), (3, 3))))
(((1, 4), (1, 4)), 0.5, (((1, 1), (1, 1)), ((3, 4), (4, 4))))
(((1, 4), (1, 4)), 0.6, (((1, 1), (1, 1)), ((4, 4), (3, 4))))
(((1, 4), (2, 3)), 0.7, (((1, 1), (2, 2)), ((2, 4), (3, 3))))
(((1, 4), (2, 4)), 0.75, (((1, 1), (2, 2)), ((3, 4), (4, 4))))
(((1, 4), (2, 4)), 0.85, (((1, 1), (2, 2)), ((4, 4), (3, 4))))
(((1, 5), (2, 5)), 0.65, (((1, 1), (2, 2)), ((4, 5), (5, 5))))
(((2, 5), (3, 5)), 0.30000000000000004, (((2, 4), (3, 3)), ((5, 5), (5, 5))))
(((3, 5), (4, 5)), 0.35, (((3, 4), (4, 4)), ((5, 5), (5, 5))))
(((4, 5), (3, 5)), 0.44999999999999996, (((4, 4), (3, 4)), ((5, 5), (5, 5))))
(((1, 4), (1, 3)), 0.95, (((1, 1), (1, 2)), ((2, 4), (3, 3))))
(((1, 5), (1, 5)), 1.05, (((1, 1), (1, 2)), ((2, 5), (3, 5))))
(((1, 4), (1, 4)), 1.0, (((1, 1), (1, 2)), ((3, 4), (4, 4))))
(((1, 5), (1, 5)), 1.1, (((1, 1), (1, 2)), ((3, 5), (4, 5))))
(((1, 4), (1, 4)), 1.1, (((1, 

In [ ]:
#Preparing references
import re, time
from code_utils.general import *
from code_utils.align_utils import *
from code_utils.arabic_lib import *
from code_utils.pandas_utils import *
from code_utils import general

def get_span_dist_NEW(span0,span1):
  if span0[0]>span1[0] or span0[1]>span1[1]: span0,span1=span1,span0
  return span1[0]-span0[1]
n=1000000
span1=(6,8)
span2=(2,7)
t0=time.time()
for i in range(n):
  dist0=get_span_dist(span1,span2)
t1=time.time()
print("elapsed - original:",t1-t0,dist0)
t0=time.time()
for i in range(n):
  dist0=get_span_dist_NEW(span1,span2)
t1=time.time()
print("elapsed - new:",t1-t0,dist0)


elapsed - original: 1.314711332321167 -1
elapsed - new: 0.48160672187805176 -1


In [ ]:
src_phrase="united nations"
trg_phrase="أمم متحدة"
src_tokens=src_phrase.split()
trg_tokens=trg_phrase.split()
src_phrase_index_loc_dict=retr_sent_phrase_indexes(src_tokens,tmp_src_inv_dict)
trg_phrase_index_loc_dict=retr_sent_phrase_indexes(trg_tokens,tmp_trg_inv_dict)
for a,b in src_phrase_index_loc_dict.items():
  print(a,b)
print(trg_tokens)
#tmp_trg_inv_dict
for a,b in trg_phrase_index_loc_dict.items():
  print(a,b)
src_locs,src_indexes=src_phrase_index_loc_dict[src_phrase]
trg_locs,trg_indexes=trg_phrase_index_loc_dict[trg_phrase]
print("src_indexes",src_indexes)
print("trg_indexes",trg_indexes)
ratio1,intersection1=get_src_trg_intersection(src_indexes,trg_indexes)
print("ratio1,intersection1",ratio1,intersection1)

NameError: ignored

#Retrieving phrases for MT and QA of a text - 5 Dec 2022

In [ ]:
from code_utils.tika_utils import *
from code_utils.web_lib import *
from code_utils.general import *
from code_utils.align_utils import *

from sqlitedict import SqliteDict

# def get_unigrams_bigrams(token_list):
#   list_unigrams_bigrams0=[]
#   for uni0 in list(set(token_list)):
#     if uni0.isdigit():continue
#     if len(uni0)<2: continue
#     if not uni0 in list_unigrams_bigrams0:list_unigrams_bigrams0.append(uni0)
#   for i0 in range(len(token_list)-1):
#     bi0,bi1=token_list[i0],token_list[i0+1]
#     if bi0.isdigit() or bi1.isdigit(): continue
#     if len(bi0)<2 or len(bi1)<2: continue
#     bigram0="%s %s"%(bi0,bi1)
#     if not bigram0 in list_unigrams_bigrams0: list_unigrams_bigrams0.append(bigram0)
#   return list_unigrams_bigrams0


index_dir="indexes/un/exp4"
first_sql_fpath=os.path.join(index_dir,"first3.sql")
first_sql_db = SqliteDict(first_sql_fpath)


out_fpath0="docs/2212878A_P2.html"
sents0=html2sents(out_fpath0)
list_unigrams_bigrams=[]
tokenized_sentences=[]
for s0 in sents0:
  toks1=tok(s0)
  toks1_lower=[v.lower() for v in toks1]
  cur_unigrams_bigrams=get_unigrams_bigrams(toks1_lower)
  list_unigrams_bigrams.extend(cur_unigrams_bigrams)
  tokenized_sentences.append(toks1_lower)

list_unigrams_bigrams=list(set(list_unigrams_bigrams))
list_unigrams_bigrams.sort()
print("list_unigrams_bigrams",len(list_unigrams_bigrams))
cur_phrase_dict={}
for word1 in list_unigrams_bigrams[:1000]:
  #print(word1)
  test=first_sql_db.get(word1,[])
  if len(test)==0: continue
  cur_phrase_dict[word1]=test

for t_sent in tokenized_sentences[:5]:
  print(t_sent)
  cur_unigrams_bigrams=get_unigrams_bigrams(t_sent)
  for a in cur_unigrams_bigrams[:5]:
    corr=cur_phrase_dict.get(a,[])
    #corr.sort(key=lambda x:-x[-1][0])
    # print(a)
    if corr: 
      print("corr >>>", a, corr)
      # print(a,len(corr))
      # for corr_item in corr[:2]:
      #   print(">>>", len(corr_item), corr_item[0])
    # for src_phrase0,corr_trg_dict in corr[:1]:
    #   print(src_phrase0)
    #   print(c0)
    # print("------")

    #print(a, corr[:10])

first_sql_db.close()

list_unigrams_bigrams 3369
['translation', 'page', '15']
['57', '.']
['mr', '.', 'zlenko', '(', 'ukraine', ')', 'said', 'that', 'his', 'delegation', 'welcomed', 'the', 'inclusion', 'of', 'paragraph', '45', ',', 'on', 'negative', 'security', 'assurances', 'and', 'supported', 'the', 'language', 'as', 'it', 'stood', '.']
['it', 'was', 'important', 'for', 'the', 'review', 'conference', 'to', 'refer', 'to', 'the', 'adherence', 'to', 'the', 'commitments', 'under', 'the', 'budapest', 'memorandum', 'given', 'the', 'developments', 'in', 'the', 'international', 'security', 'architecture', ',', 'which', 'had', 'been', 'undermined', 'in', '2014', 'when', 'russia', ',', 'a', 'nuclear', '-', 'weapon', 'state', ',', 'occupied', 'crimea', 'and', 'launched', 'its', 'aggression', 'in', 'the', 'east', 'of', 'ukraine', '.']
corr >>> budapest [(('budapest', {'بودابست': (2, 0.2778), 'budapest': (2, 1.0)}),)]
corr >>> aggression [(('aggression', {'ال_عدوان': (36, 23.76099999999999), 'عدوان': (7, 4.5407999999

#OLD -Run QA for current job bitext - 7 Dec 2022


In [ ]:
from code_utils.general import *
from code_utils.align_utils import *
from code_utils.arabic_lib import *
from code_utils.pandas_utils import *
from itertools import groupby
from collections import Counter


ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})
index_dir="indexes/un/exp4"
params_fpath=os.path.join(index_dir,"params.json") #
params_dict=read_json(params_fpath)
params_dict["ar_counter_dict"]=ar_counter_dict
def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)

from sqlitedict import SqliteDict
index_dir="indexes/un/exp4"
first_sql_fpath=os.path.join(index_dir,"first5.sql")
first_sql_db = SqliteDict(first_sql_fpath)


job_wb_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vS8-zn0nwjU9U_NMnUkBG6PsdsnN78izRte1BLZjGzJhryDrkDzY7OVds3Szm91r1Vqh8gv4PoAtkkO/pub?output=xlsx'
job_wb_obj=get_workbook_obj(job_wb_path)
cols=["en","ar"]

job_sheets=["doc"]
job_data=get_sheets_cols(job_wb_obj,job_sheets,cols)
#print(len(data))
#normative
# normative_path=https://docs.google.com/spreadsheets/d/e/2PACX-1vSpf4wpYxSkFFC84xMNFFVM_LKWtQo8wIchL8sksiNSQLZktwPTnLW9jmF2jVpv4gORd9gD9QtcrTGZ/pub?output=xlsx
# normative_obj=get_workbook_obj(job_wb_path)
# normative_cols=["en","ar","type"]
# normative_data=get_sheets_cols(normative_obj,"normative",normative_cols)
#https://docs.google.com/spreadsheets/d/e/2PACX-1vSpf4wpYxSkFFC84xMNFFVM_LKWtQo8wIchL8sksiNSQLZktwPTnLW9jmF2jVpv4gORd9gD9QtcrTGZ/pub?output=xlsx

t_list=tok_bitext(job_data,params_dict)
print("finished indexing extra sentences/references - number of sentences:",len(job_data))

#Now processing references
npt_ref_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vTUXpDvvhBcrRBWqrz-CfoANQ9Hu7kKJ_i_cyyGC7hvBhjiyHtWFhDl7V2AZwULZ86dxZiF-lQ7nTUD/pub?output=xlsx'
cedaw_wb_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vRFH-hHy3lm7pIHpYrYwfWP4GA6GbX6l7uHwnczP6NKOcvXvdw0avrCqMJjxXA9R9LlbB85003FgYAF/pub?output=xlsx'
ref_path_list=[npt_ref_path,cedaw_wb_path]
ref_data=[]
# for ref_wb_path in ref_path_list:
#   ref_wb_obj=get_workbook_obj(ref_wb_path)
#   ref_sheets=list(ref_wb_obj.keys())
#   print("ref_sheets",ref_sheets)
#   cur_ref_data=get_sheets_cols(ref_wb_obj,ref_sheets,cols)
#   ref_data.extend(cur_ref_data)

#src_index1,trg_index1=index_bitext_list(ref_data,params_dict)
cur_data=job_data
src_index1,trg_index1=index_bitext_list(cur_data,params_dict)
print("finished processing references:", len(cur_data))


all_unigrams_bigrams=[]
for a in t_list:
  cur_loc0,cur_src0,cur_trg0=a
  cur_src0_lower=[v.lower() for v in cur_src0]
  all_unigrams_bigrams.extend(get_unigrams_bigrams(cur_src0_lower))

all_unigrams_bigrams=sorted(list(set(all_unigrams_bigrams)))
cur_phrase_dict={}
for word1 in all_unigrams_bigrams:
  test=first_sql_db.get(word1,[])
  if len(test)==0: continue
  cur_phrase_dict[word1]=test

print("all_unigrams_bigrams", len(all_unigrams_bigrams), all_unigrams_bigrams[:20])

align_params0={}
align_params0["phrase_start_dict"]=cur_phrase_dict
align_params0["filter_params"]=params_dict
align_params0["lang2_tok_fn"]=cur_ar_tok_fn
align_params0["src_index"]=src_index1
align_params0["trg_index"]=trg_index1
align_params0["n_epochs"]=1

def qa_phrase(phrase_dict,cur_src,cur_trg): #use phrase dict to qa align phrases
  original_src0=["<s>"]+cur_src+["</s>"]
  original_trg0=["<s>"]+cur_trg+["</s>"]

  cur_src0=[v.lower() for v in original_src0]
  cur_trg0=[v.lower() for v in original_trg0]
  used_xs,used_ys=[],[]
  match1=get_matching_phrases_locs(cur_phrase_dict,cur_src0,cur_trg0)
  match1.sort(key=lambda x:-x[-1])
  cur_el_dict={}
  aligned_elements0=[]
  for m1 in match1:
    res_src_phrase0,corr_trg_str0,src_phrase_locs,trg_phrase_locs,trg_freq0,trg_ratio0=m1
    if len(src_phrase_locs)==len(trg_phrase_locs)==1:
      src_range1=list(range(src_phrase_locs[0][0],src_phrase_locs[0][1]+1))
      trg_range1=list(range(trg_phrase_locs[0][0],trg_phrase_locs[0][1]+1))
      #print("src_range1",src_range1,"trg_range1",trg_range1)
      if any([v in used_xs for v in src_range1]) or any([v in used_ys for v in trg_range1]): continue
      used_xs.extend(src_range1)
      used_ys.extend(trg_range1)
      for sl0 in src_phrase_locs:
        for tl0 in trg_phrase_locs:
          el0=(sl0,tl0)
          aligned_elements0.append((el0,trg_ratio0))
  results0={}
  results0["src"]=original_src0
  results0["trg"]=original_trg0
  results0["align"]=aligned_elements0
  return results0

aligned_html_sent_pairs=[]
extracted_phrase_pair_list=[]
for a in t_list:
  print(a)
  cur_loc0,cur_src0,cur_trg0=a
  # cur_src0=["<s>"]+[v.lower() for v in cur_src0]+["</s>"]
  # cur_trg0=["<s>"]+[v.lower() for v in cur_trg0]+["</s>"]
  res0=qa_phrase(cur_phrase_dict,cur_src0,cur_trg0)
  sent_class="sent_%s"%cur_loc0
  chunk_size0=5
  final_src_tokens1, final_trg_tokens1=align_words_phrases_classes(res0["src"],res0["trg"],res0["align"],sent_class,chunk_size0)
  src_html_str=" ".join([v[0] for v in final_src_tokens1])
  trg_html_str=" ".join([v[0] for v in final_trg_tokens1])
  aligned_html_sent_pairs.append((src_html_str,trg_html_str))
  phrases0=present_aligned(res0)
  for ph0 in phrases0:
    tmp_src_phrase0,tmp_trg_phrase0=ph0[:2]
    tmp_src_phrase0,tmp_trg_phrase0=tmp_src_phrase0.lower(),tmp_trg_phrase0.lower()
    #print(tmp_src_phrase0,tmp_trg_phrase0)
    extracted_phrase_pair_list.append((tmp_src_phrase0,tmp_trg_phrase0))
  print("-----")
extracted_phrase_pair_list.sort()
grouped=[(key,[v[1] for v in list(group)]) for key,group in groupby(extracted_phrase_pair_list,lambda x:x[0])]
phrase_analysis_table='<table border="1">'
for k0,grp0 in grouped:
  #print(k0)
  corr_dict=dict(Counter(grp0))
  corr_dict_keys=list(corr_dict.keys())
  corr_dict_values=list(corr_dict.values())
  key_str="<br>".join([str(v) for v in corr_dict_keys])
  val_str="<br>".join([str(v) for v in corr_dict_values])
  tr='<tr><td>%s</td><td>%s</td><td>%s</td></tr>'%(k0,key_str,val_str)
  phrase_analysis_table+=tr
phrase_analysis_table+='</table>'

# aligned_pairs=[]
# for i0,st0 in enumerate(job_data):
#   continue
#   src0,trg0=st0
#   print(src0,trg0)
#   align_results=walign(src0,trg0,align_params0)
#   print("item",i0, "out of", len(job_data))
#   print(src0,trg0)
#   #phrases_els_wt_list=present_aligned(align_results)
#   align_list=align_results.get("align",[])
#   src_tokens_padded=align_results["src"]
#   trg_tokens_padded=align_results["trg"]
#   #chunk_boundaries0=get_aligned_chunks(align_list)
#   #print("align_list",align_list)
#   #print("chunk_boundaries0",chunk_boundaries0)
#   sent_class="sent_%s"%i0
#   final_src_tokens1, final_trg_tokens1=align_words_phrases_classes(src_tokens_padded,trg_tokens_padded,align_list,sent_class,10)
#   src_html_str=" ".join([v[0] for v in final_src_tokens1])
#   trg_html_str=" ".join([v[0] for v in final_trg_tokens1])
#   aligned_pairs.append((src_html_str,trg_html_str))

css_content=create_color_classes_css()
res_html_table=create_align_html_table(aligned_html_sent_pairs)

cur_srcipt="""
function handle(e){
        if(e.keyCode === 13){
            e.preventDefault(); // Ensure it is only this code that runs
            //alert("Enter was pressed was presses");
            $(".aligned").toggleClass("aligned-transparent");
        }
    }
"""

html_main_content="""
<html>
<head>
%s
<script src="https://code.jquery.com/jquery-3.6.1.min.js" integrity="sha256-o88AwQnZB+VDvE9tvIXrMQaPlFFSUTR+nldQm1LuPXQ=" crossorigin="anonymous"></script>
<script>%s</script>
</head>
<body onkeypress="handle(event)">
%s

<h2>Phrase Matching Analysis</h2>
%s
</body>
</html>
"""%(css_content,cur_srcipt,res_html_table,phrase_analysis_table)

html_out_path="align3.html"
html_out_fopen=open(html_out_path,"w")
html_out_fopen.write(html_main_content)
html_out_fopen.close()

# for a in t_list[:20]:
#   cur_loc0,cur_src0,cur_trg0=a
#   print(cur_src0)
#   print(cur_trg0)
#   cur_src0_lower=[v.lower() for v in cur_src0]
#   cur_trg0_lower=[v.lower() for v in cur_trg0]
#   cur_unigrams_bigrams=list(set(get_unigrams_bigrams(cur_src0_lower)))
#   for a in cur_unigrams_bigrams:
#     res_list=cur_phrase_dict.get(a,[])
#     for res0 in res_list:
#       res_src_phrase0,res_corr_dict=res0
#       res_src_phrase_split=res_src_phrase0.split(" ")
#       src_locs=is_in(res_src_phrase_split,cur_src0_lower)
#       if src_locs:
#         for corr_trg_str0,corr_trg_vals in res_corr_dict.items():
#           corr_trg_str_split=corr_trg_str0.split(" ")
#           trg_locs=is_in(corr_trg_str_split,cur_trg0_lower)
#           if trg_locs:
#             print(res_src_phrase0, corr_trg_str0, corr_trg_vals, src_locs, trg_locs)

        #print(a, res0)

  #print("-----")
  #all_unigrams_bigrams.extend(get_unigrams_bigrams(cur_src0_lower))


first_sql_db.close()


finished indexing extra sentences/references - number of sentences: 141
finished processing references: 141
all_unigrams_bigrams 2687 ['about', 'about and', 'acceded', 'acceded to', 'accelerate', 'accelerate and', 'access', 'access to', 'accidents', 'accordance', 'accordance with', 'accordingly', 'account', 'account its', 'accuracy', 'accuracy of', 'accusing', 'accusing ukraine', 'achieve', 'achieve sustainable']
(0, ['39', '.', '0'], ['39', '-'])
-----
(1, ['Mr', '.', 'Zlenko', '(', 'Ukraine', ')', 'said', 'that', 'the', 'Non', '‑', 'Proliferation', 'Treaty', 'guaranteed', 'the', 'right', 'of', 'all', 'States', 'parties', 'to', 'develop', 'research', ',', 'production', 'and', 'use', 'of', 'nuclear', 'energy', 'for', 'peaceful', 'purposes', ',', 'without', 'discrimination', 'and', 'in', 'conformity', 'with', 'their', 'basic', 'non', '‑', 'proliferation', 'obligations', '.'], ['ال_سيد', 'زلينكو', '(', 'أوكرانيا', ')', ':', 'قال', 'إن', 'معاهدة', 'عدم', 'ال_انتشار', 'تضمن', 'حق', 'جميع',

In [ ]:
els0=list(cur_el_dict.keys())
for e0 in els0:
  print(e0)

((9, 13), (9, 11))
((18, 19), (14, 15))
((18, 20), (14, 16))
((18, 21), (14, 16))
((19, 20), (15, 16))
((35, 36), (32, 33))
((17, 19), (14, 15))
((28, 30), (20, 21))
((29, 30), (20, 21))
((29, 31), (20, 21))
((28, 31), (20, 21))
((19, 21), (15, 16))
((32, 33), (29, 30))
((31, 33), (29, 30))
((5, 5), (4, 4))
((1, 1), (1, 1))
((9, 12), (10, 11))
((9, 12), (41, 42))
((36, 36), (33, 33))
((36, 37), (33, 33))
((17, 18), (14, 15))
((18, 18), (14, 15))
((29, 29), (20, 21))
((17, 19), (15, 15))
((28, 29), (20, 21))
((18, 19), (15, 15))
((18, 19), (14, 14))
((32, 32), (30, 30))
((31, 32), (30, 30))
((12, 12), (11, 11))
((12, 12), (42, 42))
((45, 45), (11, 11))
((45, 45), (42, 42))
((18, 18), (13, 14))
((13, 13), (9, 9))
((18, 18), (14, 14))
((17, 18), (14, 14))
((19, 19), (15, 15))
((29, 29), (21, 21))
((28, 29), (21, 21))
((7, 8), (7, 7))
((16, 16), (13, 13))
((15, 16), (13, 13))
((16, 17), (13, 13))
((15, 17), (13, 13))


#Main tokenization functions - Sept 2022

In [ ]:
from code_utils.general import *
from code_utils.align_utils import *
from code_utils.arabic_lib import *

excluded_src_tokens=["the","a","an","and","of","its","his","her","their","them","to","is","are","am","been","was","were","be", 
                     "have","has","had", "in", "on", "at", "with", "from","for","that","he","she","it","would"] #we will need to update this
excluded_trg_tokens=["من","على","في","مع", "إلى","له","تم","إلى","في","عن"]


from itertools import groupby
from collections import Counter
ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})

def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)


sent1="""
She hasn't endorsed: $1,115,666.5 the chair's proposal (A/76/323/rev.3) [made by] the representative of Argentina to underscore the importance of reviewing reservations or unilateral interpretive declarations that had been made with regard to treaties on the establishment of nuclear-weapon-free zones and their protocols, in order for such reservations and declarations to be withdrawn if they were found to contravene the purposes of those treaties.
"""

sent1="في النافذة الأخيرة وقَد استُقبِلَ بِتَرحيبِ شديدٍ"
tokens1=cur_ar_tok_fn(sent1)
filtered=filter_toks(tokens1)
print(tokens1)
print(filtered)
print("loaded necessary functions")

['في', 'ال_نافذة', 'ال_أخيرة', 'وـ', 'قَد', 'استُقبِلَ', 'بـ', 'ِتَرحيبِ', 'شديدٍ']
['في', 'نافذة', 'أخيرة', '', 'قد', 'استقبل', '', 'ترحيب', 'شديد']
loaded necessary functions


#Test accurate retrieval - Nov 22

In [ ]:
import time
from code_utils.general import *
from code_utils.align_utils import *
from code_utils.arabic_lib import *


sent1="المبادئ التوجيهية"
#sent1="المتعددة الأطراف"
tokens1=cur_ar_tok_fn(sent1)
filtered=filter_toks(tokens1)
print(filtered)
index_dir="indexes/un/exp4"
src_shelve_path=os.path.join(index_dir,"test-src-15000.shelve")
trg_shelve_path=os.path.join(index_dir,"test-trg-15000.shelve")

src_shelve_open=shelve.open(src_shelve_path)
trg_shelve_open=shelve.open(trg_shelve_path)

cur_inv_dict={}
cur_inv_dict["main"]={}
for token0 in list(set(filtered)): cur_inv_dict["main"][token0]=trg_shelve_open.get(token0,[])

test_retr=retr(filtered,cur_inv_dict)

en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"

for a,b_dict in test_retr.items():
  print(a)
  for b0,b_indexes in b_dict.items():
    print(b0, len(b_indexes))
    for line_i in b_indexes[:20]:
      print(line_i)
      continue
      cur_line=go2line(en_ar_corpus_combined_fname,int(line_i))
      src_sent0,trg_sent0=cur_line.strip().split("\t")[:2]
      trg_tokens=cur_ar_tok_fn(trg_sent0)
      filtered_trg_tokens=filter_toks(trg_tokens)
      check=is_in(filtered,filtered_trg_tokens)
      print(src_sent0)
      print(trg_sent0)
      print(filtered_trg_tokens)
      print("check",check)
      print("-------")
  
src_shelve_open.close()
trg_shelve_open.close()



# trg_lines=get_result_lines(test_retr,en_ar_corpus_combined_fname,n_results1=20,n_items_per_meta1=50)
# for a in trg_lines:
#   print("trg:", a)


['مبادئ', 'توجيهية']
('مبادئ',)
main 99
44275.024
63885.035
66743.036
68059.016
84823.008
104432.044
114477.022
127344.042
167528.017
340026.019
342412.03
343141.011
485130.003
492072.034
579538.025
581373.039
586202.047
645208.018
698065.011
703849.005
('مبادئ', 'توجيهية')
main 21
342412.03
2391822.057
3695891.006
3700244.01
4314903.013
2385571.074
3730089.019
4657326.007
3699390.005
3695041.006
4661700.009
4621253.015
4621253.028
1564238.039
4157525.03
3692384.023
343141.011
4283374.092
4876790.001
4153337.017


#New Indexing Pipeline - 16 Nov 2022

In [ ]:
#preparing index shelves
import shelve, json, time
en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"
index_dir="indexes/un/exp4"
if not os.path.exists(index_dir): os.makedirs(index_dir)

from itertools import groupby
from collections import Counter
ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})

max_sent_n_tokens=1000
batch_size=1000
min_n_indexes_per_token=3
lang1="en"
lang2="ar"

cur_params={}
cur_params["excluded_words"]=excluded_src_tokens+excluded_trg_tokens
cur_params["max_sent_n_tokens"]=max_sent_n_tokens
cur_params["lang1"]=lang1
cur_params["lang2"]=lang2
cur_params["exclude_single_chars"]=True
cur_params["batch_size"]=batch_size
cur_params["min_n_indexes_per_token"]=min_n_indexes_per_token
cur_params["ar_counter_dict"]=ar_counter_dict



#print("cur_params",cur_params)
params_fpath=os.path.join(index_dir,"params.json") #index_dir="indexes/un/exp3"
params_fopen=open(params_fpath,"w")
json.dump(cur_params,params_fopen)
params_fopen.close()

index_list_fpath=os.path.join(index_dir,"index-list.txt")
last_indexed=None
if os.path.exists(index_list_fpath):
  index_list_fopen=open(index_list_fpath)
  index_list_lines=[v.strip() for v in index_list_fopen.readlines()]
  index_list_fopen.close()
  if len(index_list_lines)>0: last_indexed=int(index_list_lines[-1])

print("last_indexed",last_indexed)

fopen=open(en_ar_corpus_combined_fname)
cur_loc=0
cur_line="-"
counter=0
#src_fwd_index0,trg_fwd_index0=[],[]
t0=time.time()
sent_pairs=[]
while cur_line!="":
  cur_loc=fopen.tell()
  f0=fopen.readline()
  counter+=1
  if (counter%10000==0): print("processing:",counter)
  if (counter%batch_size==0 and counter>0) or f0=="": 
    print(">>> combining and indexing:", counter)
    src_index1,trg_index1=index_bitext_list(sent_pairs,cur_params)
    #sent_pairs=[]
    break


  if last_indexed!=None and counter<last_indexed: continue
  cur_line=f0.strip("\n\r\t")
  line_split=cur_line.split("\t")
  if len(line_split)!=2: continue
  src0,trg0=line_split
  sent_pairs.append((cur_loc,src0,trg0))


fopen.close()
print("saving indexes to shelves")
src_shelve_path=os.path.join(index_dir,"test-src-%s.shelve"%batch_size)
trg_shelve_path=os.path.join(index_dir,"test-trg-%s.shelve"%batch_size)
if os.path.exists(src_shelve_path):os.remove(src_shelve_path)
if os.path.exists(trg_shelve_path):os.remove(trg_shelve_path)
src_shelve_open=shelve.open(src_shelve_path)
trg_shelve_open=shelve.open(trg_shelve_path)

for cur_src_word,cur_src_indexes in src_index1.items(): src_shelve_open[cur_src_word]=cur_src_indexes
print("saved src indexes")
for cur_trg_word,cur_trg_indexes in trg_index1.items(): trg_shelve_open[cur_trg_word]=cur_trg_indexes
print("saved trg indexes")

src_shelve_open.close()
trg_shelve_open.close()


last_indexed None
>>> combining and indexing: 1000
saving indexes to shelves
saved src indexes
saved trg indexes


#Test alignment - 23 Nov 2022

In [ ]:
import time
from code_utils.general import *
from code_utils.align_utils import *
from code_utils.arabic_lib import *
sys.path.append("code_utils")
import general
import arabic_lib

excluded_src_tokens=["the","a","an","and","of","its","his","her","their","them","to","is","are","am","been","was","were","be", 
                     "have","has","had", "in", "on", "at", "with", "from","for","that","he","she","it","would"] #we will need to update this
excluded_trg_tokens=["من","على","في","مع", "إلى","له","تم","إلى","في","عن"]


from itertools import groupby
from collections import Counter
ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})

def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)

en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"
index_dir="indexes/un/exp4"
params_fpath=os.path.join(index_dir,"params.json")

# src_shelve_path=os.path.join(index_dir,"test-src.shelve")
# trg_shelve_path=os.path.join(index_dir,"test-trg.shelve")
src_shelve_path=os.path.join(index_dir,"test-src-100000.shelve")
trg_shelve_path=os.path.join(index_dir,"test-trg-100000.shelve")
# src_shelve_path=os.path.join(index_dir,"test-src-250000.shelve")
# trg_shelve_path=os.path.join(index_dir,"test-trg-250000.shelve")

src_shelve_open=shelve.open(src_shelve_path)
trg_shelve_open=shelve.open(trg_shelve_path)


retr_params={} #retrieval parameters
retr_params["filter_params"]=read_json(params_fpath)
retr_params["index_dir"]=index_dir#"indexes/un/exp3"
retr_params["meta_suffix"]="meta"
retr_params["max_n_index_files"]=2
#retr_params["single_pass"]=True
retr_params["n_epochs"]=5
retr_params["allow_ortho"]=False

#n_epochs=10
retr_params["apply_size_factor"]=False
retr_params["max_sent_len"]=30
retr_params["max_phrase_len"]=4
retr_params["min_intersection_count"]=5
#retr_params["min_n_indexes_per_token"]=10

retr_params["lang1"]="en"
retr_params["lang2"]="ar"
retr_params["exclude_numbers"]=True
retr_params["max_phrase_dist"]=5 #maximum distance when combining two phrases while aligning
retr_params["min_phrase_wt"]=0.00001 #minimum weight for any phrase
retr_params["tok_fn"]=tok
retr_params["lang2_tok_fn"]=cur_ar_tok_fn
punc_pairs={} #punctuation pairs - en/ar - we can add later phrase pairs
punc_pairs[","]="،"
punc_pairs[";"]="؛"
punc_pairs["?"]="؟"
punc_pairs["in"]="في"
punc_pairs["with"]="مع"
punc_pairs["I"]='ال_أول'
retr_params["punc_pairs"]=punc_pairs
retr_params["only_without_children"]=True
retr_params["reward_combined_phrases"]=True
retr_params["src_index"]=src_shelve_open
retr_params["trg_index"]=trg_shelve_open
retr_params["ar_counter_dict"]=ar_counter_dict

test_i=155#488
test_i=488
#test_i=299
cur_tok_bitext=tok_bitext(sent_pairs[:500],retr_params)
test_item=sent_pairs[test_i]
loc0,src0,trg0=test_item
# for test_i in range(len(cur_tok_bitext)):
#   loc1,src1,trg1=cur_tok_bitext[test_i]
#   print("test_i",test_i, len(src1))
#   # print(src1)
#   # print(trg1)
# print("-----------")
# tt

t0=time.time()
results=walign(src0,trg0,retr_params)
elapsed=time.time()-t0
align_list=results.get("align",[])
src_tokens_padded=results["src"]
trg_tokens_padded=results["trg"]
for pair,wt in align_list:
  s_al,t_al=pair
  print("weight:",round(wt,4))
  print(">>>", s_al, src_tokens_padded[s_al[0]:s_al[1]+1])
  print(">>>", t_al, trg_tokens_padded[t_al[0]:t_al[1]+1])
  print("----")
print(src_tokens_padded)
print(trg_tokens_padded)
print("elapsed",round(elapsed,4))
for a,b in results["analysis_dict"].items():
  print(a,round(b,2))


src_shelve_open.close()
trg_shelve_open.close()


weight: 0.7
>>> (0, 0) ['<s>']
>>> (0, 0) ['<s>']
----
weight: 0.5
>>> (1, 1) ['3']
>>> (1, 1) ['3']
----
weight: 0.5
>>> (5, 5) ['-']
>>> (2, 2) ['-']
----
weight: 0.09
>>> (6, 6) ['Haitian']
>>> (10, 10) ['ال_هايتية']
----
weight: 0.446
>>> (7, 7) ['political']
>>> (6, 6) ['ال_سياسي']
----
weight: 1.0468
>>> (8, 8) ['dialogue']
>>> (5, 5) ['ال_حوار']
----
weight: 0.2358
>>> (9, 9) ['convened']
>>> (4, 4) ['عقد']
----
weight: 0.7917
>>> (11, 11) ['United']
>>> (14, 14) ['ال_متحدة']
----
weight: 0.7991
>>> (12, 12) ['Nations']
>>> (13, 13) ['ال_أمم']
----
weight: 0.7965
>>> (13, 13) ['Headquarters']
>>> (12, 12) ['مقر']
----
weight: 0.7
>>> (15, 15) ['14']
>>> (18, 18) ['14']
----
weight: 0.7
>>> (17, 17) ['16']
>>> (20, 20) ['16']
----
weight: 1.0559
>>> (18, 18) ['July']
>>> (21, 21) ['تموز']
----
weight: 0.8478
>>> (18, 18) ['July']
>>> (23, 23) ['يوليه']
----
weight: 0.7
>>> (19, 19) ['1993']
>>> (24, 24) ['1993']
----
weight: 0.2675
>>> (23, 23) ['conclusion']
>>> (28, 28) ['ختام'

#New Alignment pipeline - 9 Nov 2022

In [ ]:
from code_utils.general import *
from code_utils.align_utils import *
from code_utils.arabic_lib import *
sys.path.append("code_utils")
import general
import arabic_lib

excluded_src_tokens=["the","a","an","and","of","its","his","her","their","them","to","is","are","am","been","was","were","be", 
                     "have","has","had", "in", "on", "at", "with", "from","for","that","he","she","it","would"] #we will need to update this
excluded_trg_tokens=["من","على","في","مع", "إلى","له","تم","إلى","في","عن"]


from itertools import groupby
from collections import Counter
ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})

def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)





en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"
index_dir="indexes/un/exp3"
params_fpath=os.path.join(index_dir,"params.json")

retr_params={} #retrieval parameters
retr_params["filter_params"]=read_json(params_fpath)
retr_params["index_dir"]=index_dir#"indexes/un/exp3"
retr_params["meta_suffix"]="meta"
retr_params["max_n_index_files"]=2
retr_params["single_pass"]=False
retr_params["apply_size_factor"]=False
retr_params["max_sent_len"]=40
retr_params["max_phrase_len"]=8
retr_params["lang1"]="en"
retr_params["lang2"]="ar"
retr_params["exclude_numbers"]=True
retr_params["max_phrase_dist"]=5 #maximum distance when combining two phrases while aligning
retr_params["min_phrase_wt"]=0.0001 #minimum weight for any phrase
retr_params["tok_fn"]=tok
retr_params["lang2_tok_fn"]=cur_ar_tok_fn
punc_pairs={} #punctuation pairs - en/ar - we can add later phrase pairs
punc_pairs[","]="،"
punc_pairs[";"]="؛"
punc_pairs["?"]="؟"
punc_pairs["in"]="في"
retr_params["punc_pairs"]=punc_pairs
retr_params["only_without_children"]=True
retr_params["reward_combined_phrases"]=True


print("retr_params",retr_params)



src_sent1='May She would await the report of subsidiary body 3 and hoped that suitable text on the establishment of a such a zone in the Middle East would be reflected in the Committee’s final report.'
trg_sent1=' أيار/مايو وقالت إنها تنتظر تقرير الهيئة الفرعية 3 وتأمل في أن ينعكس النص المناسب بشأن إنشاء منطقة من هذا القبيل في الشرق الأوسط في التقرير النهائي للجنة.'
#src_sent1='2- COMMENTS 225 OF GOVERNMENTS ON THE REPORT OF THE WORKING GROUP'
#trg_sent1='2- تعليقات 225 الحكومات على تقرير الفريق العامل المعني'
t0=time.time()
print(len(tok(src_sent1)))
print(len(tok(trg_sent1)))
results=walign(src_sent1,trg_sent1,retr_params)
elapsed=time.time()-t0
align_list=results.get("align",[])
src_tokens_padded=results["src"]
trg_tokens_padded=results["trg"]
for pair,wt in align_list:
  s_al,t_al=pair
  print("weight:",round(wt,4))
  print(">>>", s_al, src_tokens_padded[s_al[0]:s_al[1]+1])
  print(">>>", t_al, trg_tokens_padded[t_al[0]:t_al[1]+1])
  print("----")
print("elapsed",round(elapsed,4))


retr_params {'filter_params': {'excluded_words': ['the', 'a', 'an', 'and', 'of', 'its', 'his', 'her', 'their', 'them', 'to', 'is', 'are', 'am', 'been', 'was', 'were', 'be', 'have', 'has', 'had', 'in', 'on', 'at', 'with', 'from', 'for', 'that', 'he', 'she', 'it', 'would', 'من', 'على', 'في', 'مع', 'إلى', 'له', 'تم', 'إلى', 'في'], 'max_sent_n_tokens': 1000, 'lang1': 'en', 'lang2': 'ar', 'exclude_single_chars': True, 'batch_size': 250000, 'min_n_indexes_per_token': 3}, 'index_dir': 'indexes/un/exp3', 'meta_suffix': 'meta', 'max_n_index_files': 2, 'single_pass': False, 'apply_size_factor': False, 'max_sent_len': 40, 'max_phrase_len': 8, 'lang1': 'en', 'lang2': 'ar', 'exclude_numbers': True, 'max_phrase_dist': 5, 'min_phrase_wt': 0.0001, 'tok_fn': <function tok at 0x7f232b3584d0>, 'lang2_tok_fn': <function cur_ar_tok_fn at 0x7f231ff260e0>, 'punc_pairs': {',': '،', ';': '؛', '?': '؟', 'in': 'في'}, 'only_without_children': True, 'reward_combined_phrases': True}
37
30
weight: 0.5
>>> (0, 0) ['<

In [ ]:
#!python retrieve-full.py
!chmod 777 ./pypy3.9-v7.3.9-linux64/bin/pypy
!./pypy3.9-v7.3.9-linux64/bin/pypy retrieve-full.py

retr_params {'filter_params': {'excluded_words': ['the', 'a', 'an', 'and', 'of', 'its', 'his', 'her', 'their', 'them', 'to', 'is', 'are', 'am', 'been', 'was', 'were', 'be', 'have', 'has', 'had', 'in', 'on', 'at', 'with', 'from', 'for', 'that', 'he', 'she', 'it', 'would', 'من', 'على', 'في', 'مع', 'إلى', 'له', 'تم', 'إلى', 'في'], 'max_sent_n_tokens': 1000, 'lang1': 'en', 'lang2': 'ar', 'exclude_single_chars': True, 'batch_size': 250000, 'min_n_indexes_per_token': 3}, 'index_dir': 'indexes/un/exp3', 'meta_suffix': 'meta', 'max_n_index_files': 2, 'lang1': 'en', 'lang2': 'ar', 'exclude_numbers': True, 'max_phrase_dist': 5, 'min_phrase_wt': 0.0001, 'tok_fn': <function tok at 0x0000000004c70d40>, 'lang2_tok_fn': <function cur_ar_tok_fn at 0x00000000049d4200>, 'punc_pairs': {',': '،', ';': '؛', '?': '؟', 'in': 'في'}}
Traceback (most recent call last):
  File "retrieve-full.py", line 55, in <module>
    align_list=results["align"]
KeyError: 'align'


In [ ]:
!python retrieve-full.py

retr_params {'filter_params': {'excluded_words': ['the', 'a', 'an', 'and', 'of', 'its', 'his', 'her', 'their', 'them', 'to', 'is', 'are', 'am', 'been', 'was', 'were', 'be', 'have', 'has', 'had', 'in', 'on', 'at', 'with', 'from', 'for', 'that', 'he', 'she', 'it', 'would', 'من', 'على', 'في', 'مع', 'إلى', 'له', 'تم', 'إلى', 'في'], 'max_sent_n_tokens': 1000, 'lang1': 'en', 'lang2': 'ar', 'exclude_single_chars': True, 'batch_size': 250000, 'min_n_indexes_per_token': 3}, 'index_dir': 'indexes/un/exp3', 'meta_suffix': 'meta', 'max_n_index_files': 2, 'lang1': 'en', 'lang2': 'ar', 'exclude_numbers': True, 'max_phrase_dist': 5, 'min_phrase_wt': 0.0001, 'tok_fn': <function tok at 0x7f90b938db00>, 'lang2_tok_fn': <function cur_ar_tok_fn at 0x7f90b319be60>, 'punc_pairs': {',': '،', ';': '؛', '?': '؟', 'in': 'في'}}
>>> (0, 0) ['<s>']
>>> (0, 0) ['<s>']
----
>>> (3, 3) ['await']
>>> (4, 4) ['تنتظر']
----
>>> (5, 5) ['report']
>>> (5, 5) ['تقرير']
----
>>> (7, 7) ['subsidiary']
>>> (7, 7) ['ال_فرعية']

#Alignment of the full bitext - 28 Nov 2022

In [ ]:
import time
from code_utils.general import *
from code_utils.align_utils import *
from code_utils.arabic_lib import *
sys.path.append("code_utils")

excluded_src_tokens=["the","a","an","and","of","its","his","her","their","them","to","is","are","am","been","was","were","be", 
                     "have","has","had", "in", "on", "at", "with", "from","for","that","he","she","it","would"] #we will need to update this
excluded_trg_tokens=["من","على","في","مع", "إلى","له","تم","إلى","في","عن"]


from itertools import groupby
from collections import Counter
ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})

def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)

en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"
index_dir="indexes/un/exp4"
params_fpath=os.path.join(index_dir,"params.json")

batch_size=100000


retr_params={} #retrieval parameters
retr_params["filter_params"]=read_json(params_fpath)
retr_params["index_dir"]=index_dir#"indexes/un/exp3"
retr_params["meta_suffix"]="meta"
retr_params["max_n_index_files"]=2
#retr_params["single_pass"]=True
retr_params["n_epochs"]=5
retr_params["allow_ortho"]=False

#n_epochs=10
retr_params["apply_size_factor"]=False
retr_params["max_sent_len"]=30
retr_params["max_phrase_len"]=4
retr_params["min_intersection_count"]=5
#retr_params["min_n_indexes_per_token"]=10

retr_params["lang1"]="en"
retr_params["lang2"]="ar"
retr_params["exclude_numbers"]=True
retr_params["max_phrase_dist"]=5 #maximum distance when combining two phrases while aligning
retr_params["min_phrase_wt"]=0.00001 #minimum weight for any phrase
retr_params["tok_fn"]=tok
retr_params["lang2_tok_fn"]=cur_ar_tok_fn
punc_pairs={} #punctuation pairs - en/ar - we can add later phrase pairs
punc_pairs[","]="،"
punc_pairs[";"]="؛"
punc_pairs["?"]="؟"
punc_pairs["in"]="في"
punc_pairs["with"]="مع"
punc_pairs["I"]='ال_أول'
retr_params["punc_pairs"]=punc_pairs
retr_params["only_without_children"]=True
retr_params["reward_combined_phrases"]=True
#retr_params["src_index"]=src_shelve_open
#retr_params["trg_index"]=trg_shelve_open
retr_params["ar_counter_dict"]=ar_counter_dict



aligned_fpath=os.path.join(index_dir,"aligned-test2.txt")
start_loc=0 #check which line in the bitext file to start with
counter=0
if os.path.exists(aligned_fpath):
  aligned_fopen=open(aligned_fpath)
  for line0 in aligned_fopen:
    line_dict=json.loads(line0.strip())
    cur_loc=line_dict.get("loc")
    cur_i=line_dict.get("i")
    if cur_loc!=None: start_loc=cur_loc
    if cur_i!=None: counter=cur_i
  aligned_fopen.close()

print("start_loc",start_loc,"counter",counter)



fopen=open(en_ar_corpus_combined_fname)
fopen.seek(start_loc)
#cur_loc=0
cur_line="-"

#src_fwd_index0,trg_fwd_index0=[],[]
bitext_list=[]
t0=time.time()
while cur_line!="":
  cur_loc=fopen.tell()
  f0=fopen.readline()
  cur_line=f0.strip("\n\r\t")
  line_split=cur_line.split("\t")
  if len(line_split)!=2: continue
  elif f0!="":
    src0,trg0=line_split
    bitext_list.append((counter,cur_loc,src0,trg0))
  counter+=1
  if len(bitext_list)%batch_size==0 or f0=="":
    print("now processing bitext_list:",len(bitext_list))
    last_counter,last_loc=bitext_list[-1][:2]
    if last_loc<start_loc:
      bitext_list=[]
      continue
    bitext_without_counter=[v[1:] for v in bitext_list]
    tmp_src_inv_dict,tmp_trg_inv_dict=index_bitext_list(bitext_without_counter)
    retr_params["src_index"]=tmp_src_inv_dict
    retr_params["trg_index"]=tmp_trg_inv_dict
    for item0 in bitext_list:
      tmp_counter0,tmp_cur_loc0,tmp_src0,tmp_trg0=item0
      print("tmp_counter0,tmp_cur_loc0",tmp_counter0,tmp_cur_loc0)
      if tmp_cur_loc0<start_loc: continue
      results=walign(tmp_src0,tmp_trg0,retr_params)
      results["loc"]=tmp_cur_loc0
      results["i"]=tmp_counter0
      elapsed=time.time()-t0
      align_list=results.get("align",[])
      src_tokens_padded=results["src"]
      trg_tokens_padded=results["trg"]
      for pair,wt in align_list:
        s_al,t_al=pair
        print("weight:",round(wt,4))
        print(">>>", s_al, src_tokens_padded[s_al[0]:s_al[1]+1])
        print(">>>", t_al, trg_tokens_padded[t_al[0]:t_al[1]+1])
        print("----")
      if align_list!=[]:
        aligned_fopen=open(aligned_fpath,"a")
        aligned_fopen.write(json.dumps(results)+"\n")
        aligned_fopen.close()
      print("elapsed",round(elapsed,4))
    bitext_list=[]


fopen.close()




Streaming output truncated to the last 5000 lines.
weight: 0.3136
>>> (13, 13) ['April']
>>> (16, 16) ['أبريل']
----
weight: 0.5
>>> (14, 14) ['1992']
>>> (17, 17) ['1992']
----
weight: 0.1054
>>> (16, 16) ['by']
>>> (18, 18) ['الذي']
----
weight: 0.1518
>>> (17, 17) ['which']
>>> (18, 18) ['الذي']
----
weight: 0.435
>>> (19, 19) ['Council']
>>> (20, 20) ['ال_مجلس']
----
weight: 0.0552
>>> (20, 20) ['established']
>>> (21, 21) ['بموجب']
----
weight: 0.0019
>>> (22, 22) ['United']
>>> (25, 25) ['ال_متحدة']
----
weight: 0.0026
>>> (23, 23) ['Nations']
>>> (24, 24) ['ال_أمم']
----
weight: 0.0956
>>> (24, 24) ['Operation']
>>> (23, 23) ['عملية']
----
weight: 0.2
>>> (25, 25) ['in']
>>> (26, 26) ['في']
----
weight: 0.2
>>> (27, 27) [',']
>>> (28, 28) ['،']
----
weight: 0.5
>>> (28, 28) ['</s>']
>>> (29, 29) ['</s>']
----
elapsed 5003.8141
tmp_counter0,tmp_cur_loc0 3979 1090297
weight: 0.5
>>> (0, 0) ['<s>']
>>> (0, 0) ['<s>']
----
weight: 0.298
>>> (1, 3) ['Bearing', 'in', 'mind']
>>> (1, 2

KeyboardInterrupt: ignored

#Run bitext file alignment - 28 Nov 2022
use script and pypy

In [ ]:
#!python retrieve-full.py
!chmod 777 ./pypy3.9-v7.3.9-linux64/bin/pypy
#!./pypy3.9-v7.3.9-linux64/bin/pypy run_bitext_walign.py
!python run_bitext_walign.py

Streaming output truncated to the last 5000 lines.
----
weight: 0.2636
>>> (12, 12) ['materials']
>>> (12, 12) ['مواد']
----
weight: 0.1211
>>> (17, 17) ['quality']
>>> (18, 18) ['جودة']
----
weight: 0.281
>>> (18, 18) ['control']
>>> (17, 17) ['مراقبة']
----
weight: 0.73
>>> (20, 20) ['locally']
>>> (21, 21) ['محليا']
----
weight: 0.008
>>> (21, 21) ['produced']
>>> (20, 20) ['ال_منتجة']
----
weight: 0.2636
>>> (22, 22) ['materials']
>>> (19, 19) ['ال_مواد']
----
weight: 0.5
>>> (23, 23) ['.']
>>> (22, 22) ['.']
----
weight: 0.5
>>> (24, 24) ['</s>']
>>> (23, 23) ['</s>']
----
weight: 0.3288
>>> (10, 10) ['building']
>>> (13, 13) ['ال_بناء']
----
weight: 0.0515
>>> (13, 13) ['laboratory']
>>> (8, 8) ['مختبر']
----
elapsed 0.4746
tmp_counter0,tmp_cur_loc0 90592 35252395
src_toks 24 trg_toks 15
weight: 0.5
>>> (0, 0) ['<s>']
>>> (0, 0) ['<s>']
----
weight: 0.0811
>>> (3, 3) ['also']
>>> (2, 2) ['ما']
----
weight: 0.1065
>>> (4, 4) ['prepared']
>>> (3, 3) ['أعد']
----
weight: 0.0277
>>> 

In [ ]:
from code_utils.general import *
from code_utils.align_utils import *
from code_utils.arabic_lib import *

from itertools import groupby
from collections import Counter
ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})

def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)


#index_dir="indexes/un/exp3"
index_dir="indexes/un/exp4"
en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"
params_fpath=os.path.join(index_dir,"params.json")

aligned_fpath=os.path.join(index_dir,"aligned1.txt")
start_loc=0 #check which line in the bitext file to start with
counter=0
if os.path.exists(aligned_fpath):
  aligned_fopen=open(aligned_fpath)
  for line0 in aligned_fopen:
    line_dict=json.loads(line0.strip())
    cur_loc=line_dict.get("loc")
    cur_i=line_dict.get("i")
    if cur_loc!=None: start_loc=cur_loc
    if cur_i!=None: counter=cur_i
  aligned_fopen.close()

print("start_loc",start_loc,"counter",counter)


retr_params={} #retrieval parameters
retr_params["filter_params"]=read_json(params_fpath)
retr_params["index_dir"]=index_dir#"indexes/un/exp3"
retr_params["meta_suffix"]="meta"
retr_params["max_n_index_files"]=2
retr_params["single_pass"]=False
retr_params["max_sent_len"]=30
retr_params["max_phrase_len"]=10


retr_params["lang1"]="en"
retr_params["lang2"]="ar"
retr_params["exclude_numbers"]=True
retr_params["apply_size_factor"]=False
retr_params["max_phrase_dist"]=5 #maximum distance when combining two phrases while aligning
retr_params["min_phrase_wt"]=0.01 #minimum weight for any phrase
retr_params["tok_fn"]=tok
retr_params["lang2_tok_fn"]=cur_ar_tok_fn
punc_pairs={} #punctuation pairs - en/ar - we can add later phrase pairs
punc_pairs[","]="،"
punc_pairs[";"]="؛"
punc_pairs["?"]="؟"
punc_pairs["in"]="في"
punc_pairs["on"]="بشأن"
punc_pairs["of"]="من"
punc_pairs["to"]="إلى"
retr_params["punc_pairs"]=punc_pairs


fopen=open(en_ar_corpus_combined_fname)
fopen.seek(start_loc)
#cur_loc=0
cur_line="-"

src_fwd_index0,trg_fwd_index0=[],[]
t0=time.time()
while cur_line!="":
  cur_loc=fopen.tell()
  f0=fopen.readline()
  cur_line=f0.strip("\n\r\t")
  line_split=cur_line.split("\t")
  if len(line_split)!=2: continue
  src0,trg0=line_split
  print(counter)
  print(src0)
  print(trg0)

  t0=time.time()
  results=walign(src0,trg0,retr_params)
  results["loc"]=cur_loc
  results["i"]=counter
  elapsed=time.time()-t0
  align_list=results.get("align",[])
  src_tokens_padded=results["src"]
  trg_tokens_padded=results["trg"]
  for pair,wt in align_list:
    s_al,t_al=pair
    print("weight:",round(wt,4))
    print(">>>", s_al, src_tokens_padded[s_al[0]:s_al[1]+1])
    print(">>>", t_al, trg_tokens_padded[t_al[0]:t_al[1]+1])
    print("----")
  if align_list!=[]:
    aligned_fopen=open(aligned_fpath,"a")
    aligned_fopen.write(json.dumps(results)+"\n")
    aligned_fopen.close()
  print("elapsed",round(elapsed,4))
  counter+=1
  if counter>500: break
fopen.close()

# src_fwd_index0.sort()
# trg_fwd_index0.sort()


start_loc 762 counter 14
14
Norway . 23
النرويج . 25
weight: 0.5
>>> (0, 0) ['<s>']
>>> (0, 0) ['<s>']
----
weight: 0.8754
>>> (1, 1) ['Norway']
>>> (1, 1) ['ال_نرويج']
----
weight: 0.5
>>> (2, 2) ['.']
>>> (2, 2) ['.']
----
weight: 0.5
>>> (4, 4) ['</s>']
>>> (4, 4) ['</s>']
----
elapsed 0.0215
15
United States of America . 25
الولايات المتحدة الأمريكية . 27
weight: 0.5
>>> (0, 0) ['<s>']
>>> (0, 0) ['<s>']
----
weight: 0.5888
>>> (1, 1) ['United']
>>> (2, 2) ['ال_متحدة']
----
weight: 0.1548
>>> (2, 2) ['States']
>>> (1, 1) ['ال_ولايات']
----
weight: 0.2663
>>> (4, 4) ['America']
>>> (3, 3) ['ال_أمريكية']
----
weight: 0.5
>>> (5, 5) ['.']
>>> (4, 4) ['.']
----
weight: 0.5
>>> (7, 7) ['</s>']
>>> (6, 6) ['</s>']
----
elapsed 1.1647
16
* The reply sent on behalf of the Nordic countries is reproduced under the heading "Norway".
* الرد المرسل باسم بلدان الشمال الأوروبي مستنسخ بعنوان "النرويج".
weight: 0.5
>>> (0, 0) ['<s>']
>>> (0, 0) ['<s>']
----
weight: 0.5
>>> (1, 1) ['*']
>>> (1, 1) [

KeyboardInterrupt: ignored

#Extract phrase pairs from aligned bitext 29- Nov 2022
Extracting phrases with their weights and frequencies, and building trie shelves

In [ ]:
import json, shelve
from itertools import groupby
from code_utils.pandas_utils import *
from code_utils.align_utils import *
from code_utils.general import *
from code_utils.arabic_lib import *




counter_dict={}
index_dir="indexes/un/exp4"
en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"
params_fpath=os.path.join(index_dir,"params.json")
phrases_fpath=os.path.join(index_dir,"phrases1.txt")
phrases_fopen=open(phrases_fpath,"w")
#aligned_files=["aligned.txt","cedaw_align.txt"]
aligned_files=["aligned.txt"]
#aligned_files=["cedaw_align.txt"]
for aligned_fname in aligned_files:
  print(aligned_fname)
  aligned_fpath=os.path.join(index_dir,aligned_fname)
  fopen=open(aligned_fpath)
  for i0,line0 in enumerate(fopen):
    #if i0>2000: break
    tmp_dict=json.loads(line0)
    src,trg,align=tmp_dict["src"],tmp_dict["trg"], tmp_dict.get("align",[])
    if i0%100==0: print(i0)
    results=extract_phrases(src,trg,align)
    for rs in results:
      src_tokens1,trg_tokens1,wt1=rs
      src_phrase1=" ".join([v.lower() for v in src_tokens1])
      trg_phrase1=" ".join([v.lower() for v in trg_tokens1])
      cur_obj={}
      cur_obj["src"]=[v.lower() for v in src_tokens1]
      cur_obj["trg"]=[v.lower() for v in trg_tokens1]
      cur_obj["wt"]=round(wt1,4)
      line="%s\t%s\t%s\n"%(src_phrase1,trg_phrase1,round(wt1,4))
      #line=json.dumps(cur_obj)+"\n"
      phrases_fopen.write(line)
      #phrases_fopen.write(json.dumps(cur_obj)+"\n")

    #print("-------")
  fopen.close()
phrases_fopen.close()


aligned.txt
0
100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900
2000
2100
2200
2300
2400
2500
2600
2700
2800
2900
3000
3100
3200
3300
3400
3500
3600
3700
3800
3900
4000
4100
4200
4300
4400
4500
4600
4700
4800
4900
5000
5100
5200
5300
5400
5500
5600
5700
5800
5900
6000
6100
6200
6300
6400
6500
6600
6700
6800
6900
7000
7100
7200
7300
7400
7500
7600
7700
7800
7900
8000
8100
8200
8300
8400
8500
8600
8700
8800
8900
9000
9100
9200
9300
9400
9500
9600
9700
9800
9900
10000
10100
10200
10300
10400
10500
10600
10700
10800
10900
11000
11100
11200
11300
11400
11500
11600
11700
11800
11900
12000
12100
12200
12300
12400
12500
12600
12700
12800
12900
13000
13100
13200
13300
13400
13500
13600
13700
13800
13900
14000
14100
14200
14300
14400
14500
14600
14700
14800
14900
15000
15100
15200
15300
15400
15500
15600
15700
15800
15900
16000
16100
16200
16300
16400
16500
16600
16700
16800
16900
17000
17100
17200
17300
17400
17500
17600
17700
17800
17900
18000
18100
18200
18

#Processing phrase table - 1 Dec 2022

In [ ]:
import os, json, shelve
from itertools import groupby
from sqlitedict import SqliteDict

index_dir="indexes/un/exp4"
#phrases_fpath=os.path.join(index_dir,"phrases.txt")
phrases_fpath=os.path.join(index_dir,"phrases1.txt")
phrases_fopen=open(phrases_fpath)
matching_dict={}
for i0,line0 in enumerate(phrases_fopen):
  if i0%100000==0: print(i0)
  line0_split=line0.strip().split("\t")
  src0,trg0,wt0=line0_split[:3] #tuple(line_dict['src']),tuple(line_dict['trg']),line_dict['wt']
  #src0=tuple(src0.split(" "))
  #trg0=tuple(trg0.split(" "))
  wt0=round(float(wt0),4)
  # line_dict=json.loads(line0)
  # src0,trg0,wt0=tuple(line_dict['src']),tuple(line_dict['trg']),line_dict['wt']
  tmp_dict=matching_dict.get(src0,{})
  found=tmp_dict.get(trg0,(0,0))
  freq0,cum_wt0=found
  tmp_dict[trg0]=(freq0+1,cum_wt0+wt0)
  matching_dict[src0]=tmp_dict

  #if i0>50000: break
  #print(line_dict)
phrases_fopen.close()
print("finished processing phrase table, now populating first token table")
#first_dict={}
#first_shelve_fpath=os.path.join(index_dir,"first.shelve")
first_sql_fpath=os.path.join(index_dir,"first5.sql")
first_sql_db = SqliteDict(first_sql_fpath)


#first_shelve=shelve.open(first_shelve_fpath)
cur_items=list(matching_dict.items())
print(len(cur_items))
item_counter=0
cur_items.sort()
first_list=[]
for a,b_dict in cur_items:
  if item_counter%10000==0: print(item_counter, "out of", len(cur_items))
  src_phrase0=a.split(" ")
  if len(src_phrase0)==1: src_first=src_phrase0[0]#(a[0],"")
  else: src_first=" ".join(src_phrase0[:2]) #tuple(a[:2])
  new_b_dict={}
  for b_key,b_val in b_dict.items():
    if b_val[0]<2: continue
    #print(a,b_key,b_val[0])
    new_wt=b_val[1]/b_val[0]
    new_val=(b_val[0],new_wt)
    #print("b_val",b_val, "new_val",new_val)
    new_b_dict[b_key]=new_val
  first_list.append((src_first,(a,new_b_dict)))
  item_counter+=1
first_list.sort(key=lambda x:x[0])
grouped=[(key,[v[1] for v in list(group)]) for key,group in groupby(first_list,lambda x:x[0])]
for k0,grp0 in grouped:
  #print(k0,grp0)
  first_sql_db[k0] = grp0#{"name": "yet another item"}
print("populated first token shelve")

first_sql_db.commit()
first_sql_db.close()

# for a,b in first_dict.items():
#   print(a)
#   print(len(b))
#   for b0 in b:
#     print(b0)
#   print("----")

0
100000
200000
300000
400000
500000
600000
700000
800000
900000
1000000
1100000
1200000
1300000
1400000
1500000
1600000
1700000
1800000
1900000
2000000
2100000
2200000
2300000
2400000
2500000
2600000
2700000
2800000
2900000
3000000
3100000
3200000
3300000
3400000
3500000
3600000
3700000
3800000
3900000
4000000
4100000
4200000
4300000
4400000
4500000
4600000
4700000
4800000
4900000
5000000
5100000
5200000
5300000
5400000
5500000
5600000
5700000
5800000
5900000
6000000
6100000
6200000
6300000
6400000
6500000
6600000
6700000
6800000
6900000
7000000
7100000
7200000
7300000
7400000
7500000
7600000
7700000
7800000
7900000
8000000
8100000
8200000
8300000
8400000
8500000
8600000
8700000
8800000
8900000
9000000
9100000
9200000
9300000
9400000
9500000
9600000
9700000
9800000
9900000
10000000
10100000
10200000
10300000
10400000
10500000
10600000
10700000
10800000
10900000
11000000
11100000
11200000
11300000
11400000
11500000
11600000
11700000
11800000
11900000
12000000
12100000
12200000
12300000

In [ ]:
from sqlitedict import SqliteDict

index_dir="indexes/un/exp4"
first_sql_fpath=os.path.join(index_dir,"first4.sql")
first_sql_db = SqliteDict(first_sql_fpath)

# first_shelve_fpath=os.path.join(index_dir,"first.shelve")
# first_shelve=shelve.open(first_shelve_fpath)
word1="other countries"
test=first_sql_db.get(word1,[])
print(word1, len(test))
for t_str,t_dict in test[:10]:

  print(t_str)
  print(t_dict)
  print("-----")
  # for t_str,t_dict in t_items: 
  #   for a,b in t_dict.items(): 
  #     if b[0]<5: continue
  #     print(t_str,a,b)
first_sql_db.close()

other countries 349
other countries
{'بلدان أخرى': (48, 51.68410000000002), 'وـ بلدان أخرى إلى': (1, 1.0634), 'غير ـها من بلدان': (1, 0.7079), 'ال_بلدان ال_أخرى': (24, 25.728799999999982), 'بلدان أخري': (1, 0.5804), 'طمأنة ال_بلدان ال_أخرى بشأن': (1, 1.0649), 'غير ـها من ال_بلدان': (1, 0.7075), 'وـ ال_بلدان ال_أخرى التي': (2, 2.1611), 'بـ ال_بلدان ال_أخرى بـ': (1, 1.0675), 'بـ ال_بلدان ال_أخرى بـ أن': (1, 1.0675), 'ـها بـ ال_بلدان ال_أخرى بـ': (1, 1.0675), 'ـها بـ ال_بلدان ال_أخرى بـ أن': (1, 1.0675), 'بلدان': (1, 0.6376), 'إلى بلدان اخرى': (1, 0.6376), 'إلى بلدان أخرى وـ': (1, 1.0675), 'أخرى': (1, 0.543), 'بالنسبة لـ ال_بلدان ال_أخرى': (1, 1.0961), 'من بلدان أخرى وـ': (1, 1.0675), 'من بلدان أخرى وـ ال_عائدين': (1, 1.0675), 'من بلدان أخرى وـ ال_عائدين إلى': (1, 1.0675), 'من بلدان أخرى وـ ال_عائدين إلى ال_وطن': (1, 1.0675), 'من بلدان أخرى وـ ال_عائدين إلى ال_وطن من': (1, 1.0675), 'من بلدان أخرى وـ ال_عائدين إلى ال_وطن من ال_نيكاراغويين': (1, 1.0675), 'ال_بلدان': (1, 0.6376), 'لـ ال_بلدا

In [ ]:
first_dict={}
cur_items=list(matching_dict.items())
cur_items.sort()
for a,b in cur_items:
  src_first=a[0]
  print(src_first, a,b)
  for a1,b1 in b.items():
    freq1,wt1=b1
    if freq1<5: continue
    print(a,a1,b1)

Streaming output truncated to the last 5000 lines.
( ('(', 'from', '1989') {('1989', '('): (1, 1.0)}
( ('(', 'from', '1989', ')') {(')', 'منذ', '1989', '('): (1, 1.5)}
( ('(', 'from', '1989', ')', '.') {(')', 'منذ', '1989', '('): (1, 1.5)}
( ('(', 'from', '1989', ')', '.', '</s>') {(')', 'منذ', '1989', '(', '</s>'): (2, 4.0)}
( ('(', 'from', 'french') {('(', 'from', 'french'): (1, 1.5)}
( ('(', 'from', 'french', 'to') {('(', 'from', 'french', 'to'): (1, 2.0)}
( ('(', 'from', 'french', 'to', 'chinese') {('(', 'from', 'french', 'to', 'chinese'): (1, 2.5)}
( ('(', 'from', 'french', 'to', 'chinese', ')') {('(', 'from', 'french', 'to', 'chinese', ')'): (1, 3.0)}
( ('(', 'from', 'french', 'to', 'chinese', ')', '.') {('(', 'from', 'french', 'to', 'chinese', ')', '.'): (1, 3.5)}
( ('(', 'from', 'french', 'to', 'chinese', ')', '.', '</s>') {('(', 'from', 'french', 'to', 'chinese', ')', '.', '</s>'): (2, 8.0)}
( ('(', 'from', 'german') {('(', 'from', 'german'): (2, 3.0)}
( ('(', 'from', 'german'

KeyboardInterrupt: ignored

In [ ]:
trie_fname="cedaw_trie.shelve"
start_i=700
trie_fpath=os.path.join(index_dir,trie_fname)
trie_shelve_open=shelve.open(trie_fpath)
keys=list(trie_shelve_open.keys())
for key0 in cur_keys[start_i:start_i+20]:
  print(key0)
  for a,b in trie_shelve_open[key0].items():
    print(a,b)  
  #trie_shelve_open[key0]=our_trie
trie_shelve_open.close()

# keys=list(our_trie.keys())
# cur_keys=keys[2000:2110]
# #print()
# for key0 in cur_keys:
#   print(key0)
#   for a,b in our_trie[key0].items():
#     print(a,b)
#   print('--------')

and
 {'': [[('and',), 0.5, 23]]}
andorra
 {'': [[('أندورا',), 0.7509, 4]]}
angola
 {'': [[('أنغولا',), 0.6721, 12]]}
verification {'': {'': [[('ال_تحقق', 'في', 'أنغولا'), 0.81, 4]]}}
animals
 {'': [[('ال_حيوانات',), 0.2901, 4]]}
ankara
 {'': [[('Ankara',), 0.5, 4]]}
annex
 {'': [[('ال_أول',), 0.0397, 18], [('ال_خامس',), 0.0319, 17], [('ال_رابع',), 0.0501, 3], [('ال_رابع', 'عشر'), 0.0865, 3], [('ال_عاشر',), 0.0146, 6], [('ال_مرفق',), 0.7339, 348], [('ال_مرفق', 'ال_أول'), 0.7736, 18], [('ال_مرفق', 'ال_خامس'), 0.7658, 15], [('ال_مرفق', 'ال_رابع', 'عشر'), 0.9069, 3], [('ال_مرفق', 'ال_عاشر'), 0.7484, 6], [('عشر',), 0.0364, 6], [('مرفق',), 0.7339, 101], [('يتضمن',), 0.015, 4], [('يتضمن', 'ال_مرفق'), 0.7489, 4], [('يتضمن', 'ال_مرفق'), 1.4978, 3]]}
ii {'': {'': [[('ال_مرفق', 'ال_ثاني'), 0.8591, 3]]}}
ix {'.': {'': {'': [[('ال_مرفق', 'ال_تاسع', '.'), 1.5326, 3]]}}}
annexes
 {'': [[('ال_مرفقات',), 0.5515, 11], [('ال_مرفقين',), 0.1259, 4]]}
anniversary
 {'': [[('ال_ذكرى',), 0.7098, 10], [('ال_ذكر

In [ ]:
from math import log

def get_size_factor(size0): #account for larger phrases - such as month names - by giving a small factor to increase their weight
  factor0=log(10+size0)/2
  return factor0
# def log_size(cur_n):
#   log(n1+40)

wt1=0.7
wt2=0.65
n1=1
n2=5
# print(wt*log(n1))
# print(wt*log(n2))

print(log(n1+40))
print(log(n2+40))

for i in range(1,20):
  
  f0=get_size_factor(i)
  print(i, log(i),f0)


3.713572066704308
3.8066624897703196
1 0.0 1.1989476363991853
2 0.6931471805599453 1.2424533248940002
3 1.0986122886681098 1.2824746787307684
4 1.3862943611198906 1.3195286648076292
5 1.6094379124341003 1.354025100551105
6 1.791759469228055 1.3862943611198906
7 1.9459101490553132 1.416606672028108
8 2.0794415416798357 1.4451858789480823
9 2.1972245773362196 1.4722194895832201
10 2.302585092994046 1.4978661367769954
11 2.3978952727983707 1.5222612188617115
12 2.4849066497880004 1.545521226679158
13 2.5649493574615367 1.5677471079645748
14 2.6390573296152584 1.5890269151739729
15 2.70805020110221 1.6094379124341003
16 2.772588722239781 1.629048269010741
17 2.833213344056216 1.6479184330021646
18 2.8903717578961645 1.666102255087602
19 2.9444389791664403 1.683647914993237


In [ ]:
for i in range(1,20):
  print(i, log(i))

1 0.0
2 0.6931471805599453
3 1.0986122886681098
4 1.3862943611198906
5 1.6094379124341003
6 1.791759469228055
7 1.9459101490553132
8 2.0794415416798357
9 2.1972245773362196
10 2.302585092994046
11 2.3978952727983707
12 2.4849066497880004
13 2.5649493574615367
14 2.6390573296152584
15 2.70805020110221
16 2.772588722239781
17 2.833213344056216
18 2.8903717578961645
19 2.9444389791664403


In [ ]:

def get_ngram_key(phrase0,ngram=2): #a unigram/bigram or more ngram words as a key for a src phrase, for easy retrieval
  phrase_split=phrase0.split()
  if len(phrase_split)==1: return phrase0
  return " ".join(phrase_split[:ngram])

def create_bigram_keyed_dict(input_dict0,default_wt=0.5,default_freq=100): #or unigram- if src phrase is one word
  bigram_keyed_dict0={}
  for src_phrase0,corr_trg_list in input_dict0.items():
    src_phrase_key0=get_ngram_key(src_phrase0)
    tmp_dict=bigram_keyed_dict0.get(src_phrase_key0,{})
    corr_with_vals=[]
    for trg_phrase0 in corr_trg_list:
      corr_with_vals.append((trg_phrase0,(default_freq,default_wt)))
    tmp_dict[src_phrase0]=corr_with_vals
    bigram_keyed_dict0[src_phrase_key0]=tmp_dict
  return bigram_keyed_dict0

#term_keyed_dict0=create_bigram_keyed_dict(en_ar_term_dict)
acr_keyed_dict0=create_bigram_keyed_dict(en_ar_acr_dict)
#term_items=list(en_ar_term_dict.items())
term_items=list(acr_keyed_dict0.items())
for a,b_dict in term_items[:20]:
  print(">>> SRC:", a)
  for b,vals in b_dict.items():
    print(b,vals)
  print("---")

>>> SRC: VITA
VITA [('منظمة ال_متطوعين لـ ال_مساعدة ال_تقنية', (100, 0.5))]
---
>>> SRC: JRC
JRC [('مركز ال_بحوث ال_مشتركة', (100, 0.5)), ('ال_مركز ال_مشترك لـ ال_بحوث ال_نووية', (100, 0.5)), ('لجنة ال_إصلاح ال_قضائي', (100, 0.5))]
---
>>> SRC: IUSUHM
IUSUHM [('ال_اتحاد ال_دولي لـ ال_صحة وـ ال_خدمات ال_طبية في ال_مدارس وـ ال_جامعات', (100, 0.5))]
---
>>> SRC: CICAD
CICAD [('لجنة ال_بلدان ال_أمريكية لـ مكافحة تعاطي ال_مخدرات', (100, 0.5))]
---
>>> SRC: ASOC
ASOC [('تحالف أنتاركتيكا وـ ال_محيط ال_جنوبي', (100, 0.5)), ('مركز عمليات ال_دعم ال_جوي', (100, 0.5))]
---
>>> SRC: ISP
ISP [('ال_دولة ال_طرف موضع ال_تفتيش', (100, 0.5)), ('مقدم خدمات ال_إنترنت', (100, 0.5)), ('مزود خدمات ال_إنترنت', (100, 0.5)), ('ال_جمعية ال_دولية لـ ال_مسح ال_تصويري', (100, 0.5)), ('ال_جمعية ال_دولية لـ مديري ال_بريد', (100, 0.5)), ('مشروع ال_نظم ال_متكاملة', (100, 0.5)), ('مشروع تنمية ال_قدرات ال_مؤسسية', (100, 0.5))]
---
>>> SRC: BSS
BSS [('معايير ال_أمان ال_أساسية لـ ال_وقاية من ال_اشعاعات', (100, 0.5)), ('معاي

In [ ]:
#test=list(acr_keyed_dict0.items())
test=list(acr_keyed_dict0.keys())
print(len(test))
print(test[0])

21056



#Apply UNTerm terms and acronyms to a list of entities - 2 Jan 2023

In [ ]:
from code_utils.pandas_utils import *
from code_utils.align_utils import *
from code_utils.general import *

test_term=list(term_start_dict.items())
test_acr=list(acr_tok_dict.items())
for a in test_term[:5]: print(a)
for a in test_acr[:5]: print(a)
xls_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vTbn4wzRpVffMPrBlDI_58KPDY_G00CF3QFNlfE0KQad-fgfdLqxRiKS_7E3QFjMBXgyhrozj4hJtaI/pub?output=xlsx'
entities_bitext=get_xls_sheet_col_data(xls_path,"Sheet1",["en","ar"])
term_counter_dict,acr_counter_dict={},{}
raw_src_dict={}
for a in entities_bitext:
  src0,trg0=a
  src_tokens0=tok(src0)#,tok(trg0)
  trg_tokens0=cur_ar_tok_fn(trg0)
  src_tokens0_lower=[v.lower() for v in src_tokens0]
  trg_tokens0_lower=[v.lower() for v in trg_tokens0]

  print("src_tokens0",src_tokens0)
  print("trg_tokens0",trg_tokens0)
  print("---")
  unigrams_bigrams_lower=get_unigrams_bigrams(src_tokens0_lower)
  unigrams_bigrams=get_unigrams_bigrams(src_tokens0)
  for ub in unigrams_bigrams_lower: #processing terms
    corr_dict=term_start_dict.get(ub,{})
    for src_phrase0,trg_phrases0 in corr_dict.items():
      if is_in(src_phrase0,src_tokens0_lower):
        src_key0=" ".join(src_phrase0) #tuple([src_phrase0])
        trg_key0=""
        found_dict=term_counter_dict.get(src_key0,{})
        raw_src_dict[src_key0]=found_dict
        found_dict[trg_key0]=found_dict.get(trg_key0,0)+1
        term_counter_dict[src_key0]=found_dict
        for t_phrase0 in trg_phrases0:
          if is_in(t_phrase0,trg_tokens0_lower):
            trg_key0=" ".join(t_phrase0)
            found_dict=term_counter_dict.get(src_key0,{})
            found_dict[trg_key0]=found_dict.get(trg_key0,0)+1
            term_counter_dict[src_key0]=found_dict
  for ub in unigrams_bigrams: #processing acronyms - need to keep the original case
    corr_dict=acr_tok_dict.get(ub,{})
    for src_phrase0,trg_phrases0 in corr_dict.items():
      if is_in(src_phrase0,src_tokens0):
        src_key0=" ".join(src_phrase0) #tuple([src_phrase0])
        trg_key0=""
        found_dict=acr_counter_dict.get(src_key0,{})
        found_dict[trg_key0]=found_dict.get(trg_key0,0)+1
        acr_counter_dict[src_key0]=found_dict
        for t_phrase0 in trg_phrases0:
          if is_in(t_phrase0,trg_tokens0):
            trg_key0=" ".join(t_phrase0)
            found_dict=acr_counter_dict.get(src_key0,{})
            found_dict[trg_key0]=found_dict.get(trg_key0,0)+1
            acr_counter_dict[src_key0]=found_dict

for a,b in term_counter_dict.items():
  keys=[v for v in list(b.keys()) if v]
  print(a,keys)

('united nations', {('united', 'nations', 'decade', 'against', 'drug', 'abuse'): [['عقد', 'ال_أمم', 'ال_متحدة', 'لـ', 'مكافحة', 'إساءة', 'استعمال', 'ال_مخدرات']], ('united', 'nations', 'trade', 'data', 'interchange', 'directory'): [['دليل', 'ال_أمم', 'ال_متحدة', 'لـ', 'تبادل', 'ال_بيانات', 'ال_تجارية']], ('united', 'nations', 'convention', 'on', 'the', 'liability', 'of', 'operators', 'of', 'transport', 'terminals', 'in', 'international', 'trade'): [['اتفاقية', 'ال_أمم', 'ال_متحدة', 'ال_خاصة', 'بـ', 'مسؤولية', 'متعهدي', 'محطات', 'ال_نقل', 'ال_طرفية', 'في', 'ال_تجارة', 'ال_دولية']], ('united', 'nations', 'convention', 'on', 'contracts', 'for', 'the', 'international', 'sale', 'of', 'goods'): [['اتفاقية', 'ال_أمم', 'ال_متحدة', 'بشأن', 'عقود', 'ال_بيع', 'ال_دولي', 'لـ', 'ال_بضائع'], ['اتفاقية', 'ال_بيع']], ('united', 'nations', 'sales', 'convention', '(', '1980', ')'): [['اتفاقية', 'ال_أمم', 'ال_متحدة', 'بشأن', 'عقود', 'ال_بيع', 'ال_دولي', 'لـ', 'ال_بضائع'], ['اتفاقية', 'ال_بيع']], ('united

#Applying UNTerm to UN bitext corpus - 12 Dec 2022

In [ ]:
import os,json, time
en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"

index_dir="indexes/un/exp4"
if not os.path.exists(index_dir): os.makedirs(index_dir)

term_analysis_fpath=os.path.join(index_dir,"term_analysis.txt")

fopen=open(en_ar_corpus_combined_fname)
batch_size=500
lang2="ar"
last_indexed=0
cur_loc=0
cur_line="-"
counter=0
if os.path.exists(term_analysis_fpath):
  analysis_fopen=open(term_analysis_fpath)
  for line0 in analysis_fopen:
    json_dict=json.loads(line0.strip())
    if json_dict.get("loc")!=None: cur_loc=json_dict.get("loc")
    if json_dict.get("counter")!=None: counter=json_dict.get("counter")
  analysis_fopen.close()
if cur_loc!=0: 
  fopen.seek(cur_loc)
  fopen.readline()

print("starting from:",cur_loc, "counter:",counter)
#src_fwd_index0,trg_fwd_index0=[],[]
batch_list=[]
t0=time.time()
#counter_dict,matching_dict={},{}
term_counter_dict={}
acr_counter_dict={}
while cur_line!="":
  cur_loc=fopen.tell()
  f0=fopen.readline()  
  counter+=1
  #if counter>10000: break
  if (counter%10000==0): print("processing:",counter)
  if (counter%batch_size==0 and counter>0) or f0=="": 
    print(">>> combining and indexing:", counter)
    for loc0,counter0,src_tokens0,trg_tokens0 in batch_list:
      src_tokens0_lower=[v.lower() for v in src_tokens0]
      trg_tokens0_lower=[v.lower() for v in trg_tokens0]
      unigrams_bigrams_lower=get_unigrams_bigrams(src_tokens0_lower)
      unigrams_bigrams=get_unigrams_bigrams(src_tokens0)
      for ub in unigrams_bigrams_lower: #processing terms
        corr_dict=term_start_dict.get(ub,{})
        for src_phrase0,trg_phrases0 in corr_dict.items():
          if is_in(src_phrase0,src_tokens0_lower):
            src_key0=" ".join(src_phrase0) #tuple([src_phrase0])
            trg_key0=""
            found_dict=term_counter_dict.get(src_key0,{})
            found_dict[trg_key0]=found_dict.get(trg_key0,0)+1
            term_counter_dict[src_key0]=found_dict
            for t_phrase0 in trg_phrases0:
              if is_in(t_phrase0,trg_tokens0_lower):
                trg_key0=" ".join(t_phrase0)
                found_dict=term_counter_dict.get(src_key0,{})
                found_dict[trg_key0]=found_dict.get(trg_key0,0)+1
                term_counter_dict[src_key0]=found_dict
      for ub in unigrams_bigrams: #processing acronyms - need to keep the original case
        corr_dict=acr_tok_dict.get(ub,{})
        for src_phrase0,trg_phrases0 in corr_dict.items():
          if is_in(src_phrase0,src_tokens0):
            src_key0=" ".join(src_phrase0) #tuple([src_phrase0])
            trg_key0=""
            found_dict=acr_counter_dict.get(src_key0,{})
            found_dict[trg_key0]=found_dict.get(trg_key0,0)+1
            acr_counter_dict[src_key0]=found_dict
            for t_phrase0 in trg_phrases0:
              if is_in(t_phrase0,trg_tokens0):
                trg_key0=" ".join(t_phrase0)
                found_dict=acr_counter_dict.get(src_key0,{})
                found_dict[trg_key0]=found_dict.get(trg_key0,0)+1
                acr_counter_dict[src_key0]=found_dict
                #print("src_key0",src_key0,"trg_key0",trg_key0)


    new_terms_items_dict,new_acr_items_dict={},{}
    for a,b_dict in term_counter_dict.items():
      if list(b_dict.keys())==[""]: continue
      new_terms_items_dict[a]=b_dict
    for a,b_dict in acr_counter_dict.items():
      if list(b_dict.keys())==[""]: continue
      new_acr_items_dict[a]=b_dict

      #print(a,b_dict)
    json_data_dict={}
    json_data_dict["loc"]=loc0
    json_data_dict["counter"]=counter0
    json_data_dict["terms"]=new_terms_items_dict
    json_data_dict["acr"]=new_acr_items_dict
    analysis_fopen=open(term_analysis_fpath,"a")
    analysis_fopen.write(json.dumps(json_data_dict)+"\n")
    analysis_fopen.close()
    #print("added term analsysi obj, reset list")


    batch_list=[]
    term_counter_dict={}
    acr_counter_dict={}    


  if last_indexed!=None and counter<last_indexed: continue
  cur_line=f0.strip("\n\r\t")
  line_split=cur_line.split("\t")
  if len(line_split)!=2: continue
  src0,trg0=line_split
  src_tokens0=tok(src0)#,tok(trg0)
  if lang2=="ar":trg_tokens0=cur_ar_tok_fn(trg0)
  else: trg_tokens0=tok(trg0)
  batch_list.append((cur_loc,counter,src_tokens0,trg_tokens0))


  # for a in unigrams_bigrams:
  #   corr=acr_tok_dict.get(a,{})
  #   if corr!={}: print("ACR:", a,corr)

  #print("------")

  #cur_loc+=len(f0)
fopen.close()

# for a,b_dict in term_counter_dict.items():
#   if list(b_dict.keys())==[""]: continue
#   print(a,b_dict)


starting from: 722444973 counter: 1858999
>>> combining and indexing: 1859000


NameError: ignored

In [ ]:
index_dir="indexes/un/exp4"
if not os.path.exists(index_dir): os.makedirs(index_dir)

term_analysis_fpath=os.path.join(index_dir,"term_analysis.txt")
term_combined_dict={}
acr_combined_dict={}
analysis_fopen=open(term_analysis_fpath)
for line0 in analysis_fopen:
  json_dict=json.loads(line0.strip())
  tmp_term_data_dict=json_dict.get("terms",{})
  for src_term0,corr_dict0 in tmp_term_data_dict.items():
    found_dict=term_combined_dict.get(src_term0,{})
    for a,b in corr_dict0.items():
      found_dict[a]=found_dict.get(a,0)+b
    term_combined_dict[src_term0]=found_dict
  tmp_acr_data_dict=json_dict.get("acr",{})
  for src_term0,corr_dict0 in tmp_acr_data_dict.items():
    found_dict=acr_combined_dict.get(src_term0,{})
    for a,b in corr_dict0.items():
      found_dict[a]=found_dict.get(a,0)+b
    acr_combined_dict[src_term0]=found_dict

analysis_fopen.close()

term_items=list(term_combined_dict.items())
for a,b in term_items[:100]:
  print("term:", a,b)

print("number of term items:",len(term_items))

acr_items=list(acr_combined_dict.items())
for a,b in acr_items:
  print("acr:", a,b)

print("number of acr items:",len(acr_items))

term: international law commission {'': 1268, 'لجنة ال_قانون ال_دولي': 1144}
term: international law {'': 4168, 'ال_قانون ال_دولي ال_عام': 391}
term: jurisdiction {'': 4360, 'اختصاص': 1625, 'ولاية': 734}
term: international criminal jurisdiction {'': 42, 'اختصاص جنائي دولي': 17, 'ولاية قضائية جنائية دولية': 2}
term: denmark {'': 3240, 'ال_دانمرك': 3150, 'مملكة ال_دانمرك': 17}
term: mexico {'': 5216, 'ال_مكسيك': 4794, 'ال_ولايات ال_متحدة ال_مكسيكية': 3}
term: norway {'': 4270, 'ال_نرويج': 4157, 'مملكة ال_نرويج': 20}
term: general assembly {'': 70092, 'ال_جمعية ال_عامة': 68290, 'ال_جمعية ال_عامة لـ ال_أمم ال_متحدة': 1334}
term: establishment {'': 17342, 'إنشاء': 11126, 'منشأة': 44}
term: sixth committee {'': 2005, 'ال_لجنة ال_سادسة': 1952, 'ال_لجنة ال_قانونية': 7}
term: treaty {'': 15067, 'معاهدة': 8744}
term: international court of justice {'': 2298, 'محكمة ال_عدل ال_دولية': 2253}
term: court of justice {'': 2764, 'محكمة ال_عدل': 2637, 'محكمة ال_عدل لـ ال_جماعات ال_أوروبية': 4}
term: st

In [ ]:
acr_items=list(acr_tok_dict.items())
# for a,b in acr_items[:10]:
#   print(a,b)

acr0="UNDP /"
#acr_key0=tuple(tok(acr0))
print(acr_tok_dict[acr0])

{('UNDP', '/', 'CRMI'): [['مبادرة', 'إدارة', 'ال_مخاطر', 'في', 'منطقة', 'ال_بحر', 'ال_كاريبي']]}


In [ ]:
en_ar_acr_dict["ABN"]
for a,b in en_ar_acr_dict.items():
  if len(b)>1: 
    en_corr=en_acr_dict[a]
    print(a,b)

JRC ['مركز البحوث المشتركة', 'المركز المشترك للبحوث النووية', 'لجنة الإصلاح القضائي']
ASOC ['تحالف أنتاركتيكا والمحيط الجنوبي', 'مركز عمليات الدعم الجوي']
ISP ['الدولة الطرف موضع التفتيش', 'مقدم خدمات الإنترنت', 'مزود خدمات الإنترنت', 'الجمعية الدولية للمسح التصويري', 'الجمعية الدولية لمديري البريد', 'مشروع النظم المتكاملة', 'مشروع تنمية القدرات المؤسسية']
BSS ['معايير الأمان الأساسية للوقاية من الاشعاعات', 'معايير الأمان الأساسية', 'خدمة إذاعية ساتلية']
ETS ['ساتل الاختبارات الهندسية', 'قسم الامتحانات والاختبارات', 'سلسلة الأزمنة الاقتصادية', 'مخطط تبادل حقوق إطلاق الانبعاثات']
ATS ['المنشطات الأمفيتامينية', 'الساتل المخصص لتكنولوجيا التطبيقات', 'نظام معاهدة أنتاركتيكا', 'الساتل المخصص للتكنولوجيا التطبيقية', 'قسم مكافحة الاتجار', 'دائرة الترجمة العربية', 'رابطة العمل التقني الاجتماعي']
PLAN ['المشروع الدولي لكفالة الأطفال', 'جيش التحرير الشعبي الناميبي']
IRS ['الساتل الهندي للاستشعار عن بعد', 'دائرة استرجاع المعلومات', 'نظام الاخطار بالحوادث', 'الحلقة الدراسية الأقاليمية المعنية بتنق

In [ ]:
from code_utils.general import *
from code_utils.align_utils import *
from code_utils.arabic_lib import *

from itertools import groupby
from collections import Counter
ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})

def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)

term_start_dict={}
for src_term,trg_terms in en_ar_term_dict.items():
  src_term_tokens=[v.lower() for v in tok(src_term)]
  if len(src_term_tokens)==1: key=src_term_tokens[0]
  else: key=" ".join(src_term_tokens[:2])
  found_dict=term_start_dict.get(key,{})
  src_term_tuple_key=tuple(src_term_tokens)
  trg_terms_tokenized=[cur_ar_tok_fn(v) for v in trg_terms]
  found_dict[src_term_tuple_key]=trg_terms_tokenized
  term_start_dict[key]=found_dict

    #print(key, src_term_tokens, src_term,trg_terms)

In [ ]:
out_dict=term_start_dict["united nations"]
for a,b in out_dict.items():
  print(a)
  print(b)
  print("--")

Streaming output truncated to the last 5000 lines.
[['مبادئ', 'ال_أمم', 'ال_متحدة', 'ال_متعلقة', 'بـ', 'كبار', 'ال_سن', ':', 'من', 'أجل', 'إضفاء', 'ال_حياة', 'على', 'ال_سنين', 'التي', 'أضيفت', 'إلى', 'ال_حياة'], ['مبادئ', 'ال_أمم', 'ال_متحدة', 'لـ', 'كبار', 'ال_سن']]
--
('united', 'nations', 'inter', '-', 'agency', 'humanitarian', 'needs', 'assessment', 'mission', 'to', 'south', 'lebanon', 'and', 'west', 'bekaa')
[['بعثة', 'ال_أمم', 'ال_متحدة', 'ال_مشتركة', 'بين', 'ال_وكالات', 'لـ', 'تقييم', 'ال_احتياجات', 'ال_إنسانية', 'لـ', 'جنوب', 'لبنان', 'وـ', 'ال_بقاع', 'ال_غربي']]
--
('united', 'nations', 'voluntary', 'fund', 'for', 'indigenous', 'populations')
[['صندوق', 'ال_أمم', 'ال_متحدة', 'لـ', 'ال_تبرعات', 'لصالح', 'ال_شعوب', 'ال_أصلية']]
--
('united', 'nations', 'trust', 'fund', 'for', 'the', 'consolidation', 'of', 'peace', 'through', 'practical', 'disarmament', 'measures')
[['ال_صندوق', 'ال_استئماني', 'لـ', 'توطيد', 'ال_سلام', 'من', 'خلال', 'تدابير', 'عملية', 'لـ', 'نزع', 'ال_سلاح']]
--


In [ ]:
from code_utils.pandas_utils import *
unterm_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vRXvge4WqMXc3OSPdwk853TcGnsVNnFkLCoRA2r-b5IbKi5MTIKQVJ_qdfDY52JOw/pub?output=xlsx'
cur_wb_obj=get_workbook_obj(unterm_path)
cur_sheet_obj=get_sheet_obj(cur_wb_obj,"Sheet1")
#get_xls_sheet_col_data(xls_fpath0,sheet_name0,col_names0,default_val0=0.,exclude_nan=False)

#New pipeline - 26-Oct-2022
combined bitext - just skip words - now tokenization 

In [ ]:
#preparing index shelves
import shelve, json, time
en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"
#index_dir="indexes/un/exp2"
index_dir="indexes/un/exp3"
if not os.path.exists(index_dir): os.makedirs(index_dir)

max_sent_n_tokens=1000
batch_size=250000
min_n_indexes_per_token=3
lang1="en"
lang2="ar"

cur_params={}
cur_params["excluded_words"]=excluded_src_tokens+excluded_trg_tokens
cur_params["max_sent_n_tokens"]=max_sent_n_tokens
cur_params["lang1"]=lang1
cur_params["lang2"]=lang2
cur_params["exclude_single_chars"]=True
cur_params["batch_size"]=batch_size
cur_params["min_n_indexes_per_token"]=min_n_indexes_per_token
print("cur_params",cur_params)
params_fpath=os.path.join(index_dir,"params.json") #index_dir="indexes/un/exp3"
params_fopen=open(params_fpath,"w")
json.dump(cur_params,params_fopen)
params_fopen.close()

index_list_fpath=os.path.join(index_dir,"index-list.txt")
last_indexed=None
if os.path.exists(index_list_fpath):
  index_list_fopen=open(index_list_fpath)
  index_list_lines=[v.strip() for v in index_list_fopen.readlines()]
  index_list_fopen.close()
  if len(index_list_lines)>0: last_indexed=int(index_list_lines[-1])

print("last_indexed",last_indexed)

fopen=open(en_ar_corpus_combined_fname)
cur_loc=0
cur_line="-"
counter=0
src_fwd_index0,trg_fwd_index0=[],[]
t0=time.time()
while cur_line!="":
#for i0,f0 in enumerate(fopen):
#for i0 in range(10):  
  #if counter>100: break

  cur_loc=fopen.tell()
  f0=fopen.readline()
  
  counter+=1

  #if counter>1000000: break
  if (counter%10000==0): print("processing:",counter)
  if (counter%batch_size==0 and counter>0) or f0=="": 
    print(">>> combining and indexing:", counter)
    
    #continue
    cur_src_shelve_fpath=os.path.join(index_dir,"src-%s.shelve"%counter) 
    cur_trg_shelve_fpath=os.path.join(index_dir,"trg-%s.shelve"%counter)

    cur_src_txt_fpath=os.path.join(index_dir,"src-%s.txt"%counter) 
    cur_trg_txt_fpath=os.path.join(index_dir,"trg-%s.txt"%counter)

    if os.path.exists(cur_src_shelve_fpath) and os.path.exists(cur_src_shelve_fpath):
      src_fwd_index0,trg_fwd_index0=[],[]
      continue
    if os.path.exists(cur_src_txt_fpath) and os.path.exists(cur_trg_txt_fpath):
      src_fwd_index0,trg_fwd_index0=[],[]
      continue

    src_fwd_index0.sort()
    trg_fwd_index0.sort()
    grouped_src=[(key,[v[1] for v in list(group)]) for key,group in groupby(src_fwd_index0,lambda x:x[0])]
    grouped_trg=[(key,[v[1] for v in list(group)]) for key,group in groupby(trg_fwd_index0,lambda x:x[0])] 
    # cur_src_shelve_open=shelve.open(cur_src_shelve_fpath)
    # cur_trg_shelve_open=shelve.open(cur_trg_shelve_fpath)
    cur_src_txt_open=open(cur_src_txt_fpath,"w")
    cur_trg_txt_open=open(cur_trg_txt_fpath,"w")

    for k0,grp0 in grouped_src: 
      if len(grp0)<min_n_indexes_per_token: continue
      #cur_src_shelve_open[k0]=grp0
      line0="%s\t%s\n"%(k0,json.dumps(grp0))
      cur_src_txt_open.write(line0)
    for k0,grp0 in grouped_trg: 
      if len(grp0)<min_n_indexes_per_token: continue
      #cur_trg_shelve_open[k0]=grp0
      line0="%s\t%s\n"%(k0,json.dumps(grp0))
      cur_trg_txt_open.write(line0)

    # cur_src_shelve_open.close()
    # cur_trg_shelve_open.close()
    cur_src_txt_open.close()
    cur_trg_txt_open.close()

    src_fwd_index0,trg_fwd_index0=[],[]
    print("finished indexing:",cur_src_shelve_fpath,cur_trg_shelve_fpath, "elapsed:", time.time()-t0)
    t0=time.time()
    index_list_fopen=open(index_list_fpath,"a")
    index_list_fopen.write("%s\n"%counter)
    #index_list_fopen.write(json.dumps([cur_src_shelve_fpath,cur_trg_shelve_fpath])+"\n")
    index_list_fopen.close()

  if last_indexed!=None and counter<last_indexed: continue
  cur_line=f0.strip("\n\r\t")
  line_split=cur_line.split("\t")
  if len(line_split)!=2: continue
  src0,trg0=line_split
  src_tokens0=tok(src0)#,tok(trg0)
  if lang2=="ar":trg_tokens0=cur_ar_tok_fn(trg0)
  else: trg_tokens0=tok(trg0)

  #print(fopen.tell())
  filtered_src0=filter_toks(src_tokens0,cur_params)
  filtered_trg0=filter_toks(trg_tokens0,cur_params)
  indexed_src0=[(v,cur_loc+vi/max_sent_n_tokens) for vi,v in enumerate(filtered_src0) if vi<max_sent_n_tokens and v!=""]
  indexed_trg0=[(v,cur_loc+vi/max_sent_n_tokens) for vi,v in enumerate(filtered_trg0) if vi<max_sent_n_tokens and v!=""]
  src_fwd_index0.extend(indexed_src0)
  trg_fwd_index0.extend(indexed_trg0)
  #counter+=1
  #cur_loc+=len(f0)
fopen.close()
src_fwd_index0.sort()
trg_fwd_index0.sort()
# grouped_src=[(key,[v[1] for v in list(group)]) for key,group in groupby(src_fwd_index0,lambda x:x[0])]
# grouped_trg=[(key,[v[1] for v in list(group)]) for key,group in groupby(trg_fwd_index0,lambda x:x[0])]

# src_shelve_fpath="test-src.shelve"
# src_shelve_fopen=shelve.open(src_shelve_fpath)
# for k0,grp0 in grouped_src: src_shelve_fopen[k0]=grp0
# src_shelve_fopen.close()
# trg_shelve_fpath="test-trg.shelve"
# trg_shelve_fopen=shelve.open(trg_shelve_fpath)
# for k0,grp0 in grouped_trg: trg_shelve_fopen[k0]=grp0
# trg_shelve_fopen.close()


# print("src_fwd_index0",len(src_fwd_index0))
# print("trg_fwd_index0",len(trg_fwd_index0))
# print("grouped_src",len(grouped_src))
# print("grouped_trg",len(grouped_trg))


cur_params {'excluded_words': ['the', 'a', 'an', 'and', 'of', 'its', 'his', 'her', 'their', 'them', 'to', 'is', 'are', 'am', 'been', 'was', 'were', 'be', 'have', 'has', 'had', 'in', 'on', 'at', 'with', 'from', 'for', 'that', 'he', 'she', 'it', 'would', 'من', 'على', 'في', 'مع', 'إلى', 'له', 'تم', 'إلى', 'في'], 'max_sent_n_tokens': 1000, 'lang1': 'en', 'lang2': 'ar', 'exclude_single_chars': True, 'batch_size': 250000, 'min_n_indexes_per_token': 3}
last_indexed 15500000
processing: 10000
processing: 20000
processing: 30000
processing: 40000
processing: 50000
processing: 60000
processing: 70000
processing: 80000
processing: 90000
processing: 100000
processing: 110000
processing: 120000
processing: 130000
processing: 140000
processing: 150000
processing: 160000
processing: 170000
processing: 180000
processing: 190000
processing: 200000
processing: 210000
processing: 220000
processing: 230000
processing: 240000
processing: 250000
>>> combining and indexing: 250000
processing: 260000
processi

#Create meta indexes -30-oct-2022

In [ ]:
#create meta indexes
import shelve, json, time
en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"
index_dir="indexes/un/exp3"
index_list_fpath=os.path.join(index_dir,"index-list.txt")
src_meta_shelve_fpath=os.path.join(index_dir,"src-meta.shelve")
trg_meta_shelve_fpath=os.path.join(index_dir,"trg-meta.shelve")
# src_meta_shelve_fpath=os.path.join(index_dir,"src-meta.shelve")
# trg_meta_shelve_fpath=os.path.join(index_dir,"trg-meta.shelve")

src_meta_shelve_open=shelve.open(src_meta_shelve_fpath)
trg_meta_shelve_open=shelve.open(trg_meta_shelve_fpath)

index_list_fopen=open(index_list_fpath)
index_list_lines=[v.strip() for v in index_list_fopen.readlines()]
index_list_lines=sorted(list(set(index_list_lines)),key=lambda x:int(x))
index_list_fopen.close()
print(len(index_list_lines))
print(index_list_lines)
for i0,index_id in enumerate(index_list_lines):
  cur_src_txt_fpath=os.path.join(index_dir,"src-%s.txt"%index_id) 
  cur_trg_txt_fpath=os.path.join(index_dir,"trg-%s.txt"%index_id)
  cur_src_txt_fopen=open(cur_src_txt_fpath)
  cur_trg_txt_fopen=open(cur_trg_txt_fpath)
  print(i0)
  print("cur_src_txt_fpath",cur_src_txt_fpath)
  print("cur_trg_txt_fpath",cur_trg_txt_fpath)
  
  src_line,trg_line="-","-"
  print("processing source indexes")
  while src_line!="":
    loc0=cur_src_txt_fopen.tell()
    src_line=cur_src_txt_fopen.readline()
    loc1=cur_src_txt_fopen.tell()
    src_word=src_line.split("\t")[0]
    src_found_dict=src_meta_shelve_open.get(src_word,{})
    #src_found_dict[index_id]=loc0
    src_found_dict[index_id]=(loc0,loc1-loc0)
    src_meta_shelve_open[src_word]=src_found_dict
  print("processing target indexes")
  while trg_line!="":
    loc0=cur_trg_txt_fopen.tell()
    trg_line=cur_trg_txt_fopen.readline()
    loc1=cur_trg_txt_fopen.tell()
    trg_word=trg_line.split("\t")[0]
    trg_found_dict=trg_meta_shelve_open.get(trg_word,{})
    #trg_found_dict[index_id]=loc0
    trg_found_dict[index_id]=(loc0,loc1-loc0)
    trg_meta_shelve_open[trg_word]=trg_found_dict    
    #print(src_word, loc0)

  cur_src_txt_fopen.close()
  cur_trg_txt_fopen.close()
  print("---")

src_meta_shelve_open.close()
trg_meta_shelve_open.close()

75
['250000', '500000', '750000', '1000000', '1250000', '1500000', '1750000', '2000000', '2250000', '2500000', '2750000', '3000000', '3250000', '3500000', '3750000', '4000000', '4250000', '4500000', '4750000', '5000000', '5250000', '5500000', '5750000', '6000000', '6250000', '6500000', '6750000', '7000000', '7250000', '7500000', '7750000', '8000000', '8250000', '8500000', '8750000', '9000000', '9250000', '9500000', '9750000', '10000000', '10250000', '10500000', '10750000', '11000000', '11250000', '11500000', '11750000', '12000000', '12250000', '12500000', '12750000', '13000000', '13250000', '13500000', '13750000', '14000000', '14250000', '14500000', '14750000', '15000000', '15250000', '15500000', '15750000', '16000000', '16250000', '16500000', '16750000', '17000000', '17250000', '17500000', '17750000', '18000000', '18250000', '18500000', '18539208']
0
cur_src_txt_fpath indexes/un/exp3/src-250000.txt
cur_trg_txt_fpath indexes/un/exp3/trg-250000.txt
processing source indexes
processing t

#Indexing an arbitrary bitext - 14 Nov 2022

In [ ]:
import math
from code_utils.pandas_utils import *
from code_utils.align_utils import *
from code_utils.general import *
from code_utils.arabic_lib import *

from itertools import groupby
from collections import Counter
ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})

index_dir="indexes/un/exp3"
params_fpath=os.path.join(index_dir,"params.json") #
params_dict=read_json(params_fpath)
params_dict["ar_counter_dict"]=ar_counter_dict


wb_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vRFH-hHy3lm7pIHpYrYwfWP4GA6GbX6l7uHwnczP6NKOcvXvdw0avrCqMJjxXA9R9LlbB85003FgYAF/pub?output=xlsx'
wb_obj=get_workbook_obj(wb_path)
sheets=list(wb_obj.keys())
ref_sheets=[v for v in sheets if not v in ["document","normative"]]
cols=["en","ar"]
data=get_sheets_cols(wb_obj,ref_sheets,cols)
#print(len(data))
src_index1,trg_index1=index_bitext_list(data,params_dict)

t_list=tok_bitext(data,params_dict)
print("finished indexing extra sentences/references - number of sentences:",len(data))

# for d in data[:5]:
#   print(d)


finished indexing extra sentences/references - number of sentences: 1524


#Now the QA - 15 Nov 2022

In [ ]:
import time, random
from code_utils.general import *
from code_utils.align_utils import *
from code_utils.arabic_lib import *
from code_utils.pandas_utils import *
sys.path.append("code_utils")

from itertools import groupby
from collections import Counter
ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})

def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)

def random_color():
  rand = lambda: random.randint(100, 255)
  return '#%02X%02X%02X' % (rand(), rand(), rand())

def create_color_classes_css(n_classes=100):
  chars = '0123456789ABCDEF'
  css_str0='<style>\n'
  for class_i in range(n_classes):
    class_name="walign-%s"%(class_i)
    cur_color=random_color() #'#'+''.join(random.sample(chars,6))
    cur_css_line='.%s {background: %s;}\n'%(class_name,cur_color)
    css_str0+=cur_css_line
  css_str0+='</style>\n'
  return css_str0

def create_align_html_table(list_aligned_classed0):
  table_str0='<table border="1">'
  for item0 in list_aligned_classed0:
    src_cell0,trg_cell0=item0[:2]
    tr0='<tr><td>%s</td><td dir="rtl">%s</td></tr>'%(src_cell0,trg_cell0)
    table_str0+=tr0
  table_str0+='</table>'
  return table_str0



en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"
index_dir="indexes/un/exp4"
params_fpath=os.path.join(index_dir,"params.json")

# src_shelve_path=os.path.join(index_dir,"test-src.shelve")
# trg_shelve_path=os.path.join(index_dir,"test-trg.shelve")
# src_shelve_path=os.path.join(index_dir,"test-src-200000.shelve")
# trg_shelve_path=os.path.join(index_dir,"test-trg-200000.shelve")
src_shelve_path=os.path.join(index_dir,"test-src-50000.shelve")
trg_shelve_path=os.path.join(index_dir,"test-trg-50000.shelve")


src_shelve_open=shelve.open(src_shelve_path)
trg_shelve_open=shelve.open(trg_shelve_path)


retr_params={} #retrieval parameters
retr_params["filter_params"]=read_json(params_fpath)
retr_params["index_dir"]=index_dir#"indexes/un/exp3"
retr_params["max_n_index_files"]=2
retr_params["max_sent_len"]=100
retr_params["max_phrase_len"]=4
retr_params["lang1"]="en"
retr_params["lang2"]="ar"
retr_params["exclude_numbers"]=True
retr_params["min_phrase_wt"]=0.0001 #minimum weight for any phrase
retr_params["tok_fn"]=tok
retr_params["lang2_tok_fn"]=cur_ar_tok_fn
punc_pairs={} #punctuation pairs - en/ar - we can add later phrase pairs
punc_pairs[","]="،"
punc_pairs[";"]="؛"
punc_pairs["?"]="؟"
punc_pairs["in"]="في"
punc_pairs["with"]="مع"
retr_params["punc_pairs"]=punc_pairs
retr_params["only_without_children"]=False
retr_params["reward_combined_phrases"]=False


# test_i=505
# test_item=sent_pairs[test_i]
# loc0,src0,trg0=test_item
# print(src0)
# print(trg0)

wb_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vRFH-hHy3lm7pIHpYrYwfWP4GA6GbX6l7uHwnczP6NKOcvXvdw0avrCqMJjxXA9R9LlbB85003FgYAF/pub?output=xlsx'
wb_obj=get_workbook_obj(wb_path)
sheets=list(wb_obj.keys())
ref_sheets=[v for v in sheets if not v in ["normative"]]
doc_sheet=["document"]
cols=["en","ar"]
ref_data=get_sheets_cols(wb_obj,ref_sheets,cols)
doc_data=get_sheets_cols(wb_obj,doc_sheet,cols)
#print(len(data))
src_extra_index1,trg_extra_index1=index_bitext_list(ref_data,retr_params)

t_list=tok_bitext(doc_data,retr_params)
print("finished indexing extra sentences/references - number of sentences:",len(doc_data))

# print("t_list",t_list[test_i])
# print(doc_data[test_i])
all_src_tokens,all_trg_tokens=[],[]
for loc0,src0,trg0 in t_list:
  src0=filter_toks(src0,retr_params)
  trg0=filter_toks(trg0,retr_params)
  for st0 in src0: all_src_tokens.append(st0.lower())
  for tt0 in trg0: all_trg_tokens.append(tt0.lower())

all_src_tokens,all_trg_tokens=list(set(all_src_tokens)),list(set(all_trg_tokens))
new_src_index_dict,new_trg_index_dict={},{}
for a in all_src_tokens: new_src_index_dict[a]=src_shelve_open.get(a,[])
for a in all_trg_tokens: new_trg_index_dict[a]=trg_shelve_open.get(a,[]) 



retr_params["src_index"]=new_src_index_dict
retr_params["trg_index"]=new_trg_index_dict
#retr_params["extra_src_index"]=src_extra_index1
#retr_params["extra_trg_index"]=trg_extra_index1



# print(len(all_src_tokens),all_src_tokens[:20])
# print(len(all_trg_tokens),all_trg_tokens[:20])

aligned_pairs=[]
test_i=12
test_item=doc_data[test_i]
for test_i, test_item in enumerate(doc_data):
  src1,trg1=test_item
  t0=time.time()
  print(test_i)
  print("src1",src1)
  print("trg1",trg1)
  results=walign(src1,trg1,retr_params)
  elapsed=time.time()-t0
  print("elapsed",round(elapsed,4))
  align_list=results.get("align",[])
  src_tokens_padded=results["src"]
  trg_tokens_padded=results["trg"]
  final_src_tokens1, final_trg_tokens1=align_words_phrases_classes(src_tokens_padded,trg_tokens_padded,align_list)
  src_html_str=" ".join([v[0] for v in final_src_tokens1])
  trg_html_str=" ".join([v[0] for v in final_trg_tokens1])
  aligned_pairs.append((src_html_str,trg_html_str))

css_content=create_color_classes_css()
res_html_table=create_align_html_table(aligned_pairs)

html_main_content="""
<html>
<head>
%s
</head>
<body>
%s
</body>
</html>
"""%(css_content,res_html_table)

html_out_path="test-align4.html"
html_out_fopen=open(html_out_path,"w")
html_out_fopen.write(html_main_content)
html_out_fopen.close()

# src_tokens_padded=results["src"]
# trg_tokens_padded=results["trg"]
# for pair,wt in align_list:
#   s_al,t_al=pair
#   print("weight:",round(wt,4))
#   print(">>>", s_al, src_tokens_padded[s_al[0]:s_al[1]+1])
#   print(">>>", t_al, trg_tokens_padded[t_al[0]:t_al[1]+1])
#   print("----")



src_shelve_open.close()
trg_shelve_open.close()



finished indexing extra sentences/references - number of sentences: 438
0
src1 United Nations
trg1 الأمم المتحدة
elapsed 0.0542
1
src1 CEDAW/C/HND/CO/9
trg1 CEDAW/C/HND/CO/9
elapsed 0.0009
2
src1 Convention on the Elimination of All Forms of Discrimination against Women
trg1 اتفاقية القضاء على جميع أشكال التمييز ضد المرأة
elapsed 0.1357
3
src1 Distr.: General
trg1 Distr.: General
elapsed 0.0185
4
src1 2022-11-01 00:00:00
trg1 2022-11-01 00:00:00
elapsed 0.4386
5
src1 Original: English
trg1 Original: English
elapsed 0.0113
6
src1 Committee on the Elimination of Discrimination  against Women
trg1 اللجنة المعنية بالقضاء على التمييز ضد المرأة‏‏
elapsed 0.0497
7
src1 Concluding observations on the ninth periodic report of Honduras*
trg1 الملاحظات الختامية بشأن التقرير الدوري التاسع لهندوراس*
elapsed 0.048
8
src1 Adopted by the Committee at its eighty-third session (10–28 October 2022).
trg1 اعتمدتها اللجنة في دورتها الثالثة والثمانين (10-28 تشرين الأول/أكتوبر 2022).
elapsed 0.3812
9
src1 Th

KeyboardInterrupt: ignored

In [ ]:
!./pypy3.9-v7.3.9-linux64/bin/pypy -m ensurepip
!./pypy3.9-v7.3.9-linux64/bin/pypy -mpip install pandas

Looking in links: /tmp/tmpvzx5jc4d
Processing /tmp/tmpvzx5jc4d/setuptools-58.1.0-py3-none-any.whl
Processing /tmp/tmpvzx5jc4d/pip-22.0.4-py3-none-any.whl
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.2/5.2 MB 18.7 MB/s eta 0:00:00
  Installing build dependencies ... canceledERROR: Operation cancelled by user


In [ ]:
!chmod 777 ./pypy3.9-v7.3.9-linux64/bin/pypy
#!./pypy3.9-v7.3.9-linux64/bin/pypy qa0.py
!python qa0.py

finished indexing extra sentences/references - number of sentences: 438
0
src1 United Nations
trg1 الأمم المتحدة
elapsed 0.092
1
src1 CEDAW/C/HND/CO/9
trg1 CEDAW/C/HND/CO/9
elapsed 0.0011
2
src1 Convention on the Elimination of All Forms of Discrimination against Women
trg1 اتفاقية القضاء على جميع أشكال التمييز ضد المرأة
elapsed 0.2339
3
src1 Distr.: General
trg1 Distr.: General
elapsed 0.0281
4
src1 2022-11-01 00:00:00
trg1 2022-11-01 00:00:00
elapsed 0.4676
5
src1 Original: English
trg1 Original: English
elapsed 0.0056
6
src1 Committee on the Elimination of Discrimination  against Women
trg1 اللجنة المعنية بالقضاء على التمييز ضد المرأة‏‏
elapsed 0.0396
7
src1 Concluding observations on the ninth periodic report of Honduras*
trg1 الملاحظات الختامية بشأن التقرير الدوري التاسع لهندوراس*
elapsed 0.0415
8
src1 Adopted by the Committee at its eighty-third session (10–28 October 2022).
trg1 اعتمدتها اللجنة في دورتها الثالثة والثمانين (10-28 تشرين الأول/أكتوبر 2022).
elapsed 0.3379
9
src1 Th

In [ ]:
import shelve, math, sys
import random

sys.path.append("code_utils")
import general
trie_fname="cedaw_trie.shelve"
index_dir="indexes/un/exp3"
trie_fpath=os.path.join(index_dir,trie_fname)
trie_shelve_open=shelve.open(trie_fpath)



test_i=57
test_item=t_list[test_i]
test_id,test_src,test_trg=test_item
test_src='The lack of independence, impartiality and gender-responsiveness of the justice system which is reinforced by insufficient resource allocation, poor infrastructure and lack of specialized gender-based violence units and personnel, including police officers, prosecutors and judges trained on gender issues, resulting in a dysfunctional and corrupt judiciary and an overall culture of impunity;'
test_trg='الافتقار إلى استقلال نظام العدالة وحياده ومراعاته للمنظور الجنساني، وهو ما يعززه @ عدم كفاية تخصيص الموارد، وضعف الهياكل الأساسية، والافتقار إلى وحدات وموظفين متخصصين في مجال العنف القائم على نوع الجنس، بمن فيهم ضباط الشرطة والمدعون العامون والقضاة المدربون على القضايا الجنسانية، مما يؤدي إلى اختلال وظيفي وفساد الجهاز القضائي وإلى ثقافة عامة للإفلات من العقاب؛'
test_src=[v.lower() for v in test_src]
test_trg=[v.lower() for v in test_trg]
test_src_padded=["<s>"]+test_src+["</s>"]
test_trg_padded=["<s>"]+test_trg+["</s>"]
cur_ml1=apply_trie(test_src_padded,test_trg_padded,trie_shelve_open)
cur_ml2=match_exact_tokens(test_src_padded,test_trg_padded)
cur_ml=cur_ml1+cur_ml2

print(test_src)
print(test_trg)


aligned0=get_aligned_path(test_src_padded,test_trg_padded,cur_ml)
aligned0.sort(key=lambda x:-x[-1])
print("aligned0",aligned0)

final_src_tokens1, final_trg_tokens1=align_words_phrases_classes(test_src_padded,test_trg_padded,aligned0)
for a in final_src_tokens1: print("src:", a)
for a in final_trg_tokens1: print("trg:", a)
src_html_str=" ".join([v[0] for v in final_src_tokens1])
trg_html_str=" ".join([v[0] for v in final_trg_tokens1])

res_html_table="""
<table><tr><td>%s</td><td dir="rtl">%s</td></tr></table>
"""%(src_html_str,trg_html_str)

print("src_html_str",src_html_str)
print("trg_html_str",trg_html_str)

def create_color_classes_css(n_classes=100):
  chars = '0123456789ABCDEF'
  css_str0='<style>\n'
  for class_i in range(n_classes):
    class_name="walign-%s"%(class_i)
    cur_color='#'+''.join(random.sample(chars,6))
    cur_css_line='.%s {background: %s;}\n'%(class_name,cur_color)
    css_str0+=cur_css_line
  css_str0+='</style>\n'
  return css_str0

css_str=create_color_classes_css()
html_main_content="""
<html>
<head>
%s
</head>
<body>
%s
</body>
</html>
"""%(css_str,res_html_table)

html_out_path="test-align.html"
html_out_fopen=open(html_out_path,"w")
html_out_fopen.write(html_main_content)
html_out_fopen.close()
# src_open_dict,src_close_dict={},{}
# trg_open_dict,trg_close_dict={},{}
# for align_i,align_item in enumerate(aligned0):
  
#   span_name="walign-%s"%align_i
#   al0,al_wt=align_item
#   src_span0,trg_span0=al0
#   src_i0,src_i1=src_span0
#   trg_i0,trg_i1=trg_span0
#   src_phrase0=test_src_padded[src_i0:src_i1+1]
#   trg_phrase0=test_trg_padded[trg_i0:trg_i1+1]
#   if len(src_phrase0)>6: continue
#   src_open_dict[src_i0]=src_open_dict.get(src_i0,[])+[span_name]
#   src_close_dict[src_i1]=src_close_dict.get(src_i1,[])+[span_name]
#   trg_open_dict[trg_i0]=trg_open_dict.get(trg_i0,[])+[span_name]
#   trg_close_dict[trg_i1]=trg_close_dict.get(trg_i1,[])+[span_name]
#   print(al0,al_wt)
#   print(src_phrase0)
#   print(trg_phrase0)
#   print("---")

# for tok_i,src_tok0 in enumerate(test_src_padded):
#   if src_tok0 in ["<s>","</s>"]: continue
#   open_classes=src_open_dict.get(tok_i,[])
#   close_classes=src_close_dict.get(tok_i,[])
#   open_classes_str=" ".join(open_classes)
#   close_classes_str=" ".join(close_classes)
#   cur_str=""
#   #if open_classes!=[]:  cur_str+='<span class="%s">'%open_classes_str
#   for class0 in open_classes: cur_str+='<span class="%s">'%class0
#   cur_str+=src_tok0
#   for class0 in close_classes: cur_str+='</span>'
#   print(cur_str)
  

  #print(open_classes_str,src_tok0,close_classes_str)
  # if open_classes!=[]: print(open_classes, src_tok0)
  # print()

trie_shelve_open.close()

['t', 'h', 'e', ' ', 'l', 'a', 'c', 'k', ' ', 'o', 'f', ' ', 'i', 'n', 'd', 'e', 'p', 'e', 'n', 'd', 'e', 'n', 'c', 'e', ',', ' ', 'i', 'm', 'p', 'a', 'r', 't', 'i', 'a', 'l', 'i', 't', 'y', ' ', 'a', 'n', 'd', ' ', 'g', 'e', 'n', 'd', 'e', 'r', '-', 'r', 'e', 's', 'p', 'o', 'n', 's', 'i', 'v', 'e', 'n', 'e', 's', 's', ' ', 'o', 'f', ' ', 't', 'h', 'e', ' ', 'j', 'u', 's', 't', 'i', 'c', 'e', ' ', 's', 'y', 's', 't', 'e', 'm', ' ', 'w', 'h', 'i', 'c', 'h', ' ', 'i', 's', ' ', 'r', 'e', 'i', 'n', 'f', 'o', 'r', 'c', 'e', 'd', ' ', 'b', 'y', ' ', 'i', 'n', 's', 'u', 'f', 'f', 'i', 'c', 'i', 'e', 'n', 't', ' ', 'r', 'e', 's', 'o', 'u', 'r', 'c', 'e', ' ', 'a', 'l', 'l', 'o', 'c', 'a', 't', 'i', 'o', 'n', ',', ' ', 'p', 'o', 'o', 'r', ' ', 'i', 'n', 'f', 'r', 'a', 's', 't', 'r', 'u', 'c', 't', 'u', 'r', 'e', ' ', 'a', 'n', 'd', ' ', 'l', 'a', 'c', 'k', ' ', 'o', 'f', ' ', 's', 'p', 'e', 'c', 'i', 'a', 'l', 'i', 'z', 'e', 'd', ' ', 'g', 'e', 'n', 'd', 'e', 'r', '-', 'b', 'a', 's', 'e', 'd',

KeyboardInterrupt: ignored

In [ ]:
diac=u'\u064e\u064f\u0650\u0651\u0652\u064c\u064b\u064d\u0640\ufc62'
diac=u'\u064e\u064f\u0650\u0651\u0652\u064c\u064b\u064d\ufc62'
for d in diac:
  print([d], d, ord(d))

['َ'] َ 1614
['ُ'] ُ 1615
['ِ'] ِ 1616
['ّ'] ّ 1617
['ْ'] ْ 1618
['ٌ'] ٌ 1612
['ً'] ً 1611
['ٍ'] ٍ 1613
['ﱢ'] ﱢ 64610


#creating an arbitrary aligned list - 14 Nov 2022

In [ ]:
import os, json
cur_align_fname="cedaw_align.txt"

index_dir="indexes/un/exp3"
params_fpath=os.path.join(index_dir,"params.json")
en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"

retr_params={} #retrieval parameters
retr_params["filter_params"]=read_json(params_fpath)

retr_params["index_dir"]=index_dir#"indexes/un/exp3"
retr_params["meta_suffix"]="meta"
retr_params["max_n_index_files"]=2
retr_params["single_pass"]=False
retr_params["apply_size_factor"]=False
retr_params["max_sent_len"]=40
retr_params["max_phrase_len"]=8
retr_params["lang1"]="en"
retr_params["lang2"]="ar"
retr_params["exclude_numbers"]=True
retr_params["max_phrase_dist"]=5 #maximum distance when combining two phrases while aligning
retr_params["min_phrase_wt"]=0.0001 #minimum weight for any phrase
retr_params["tok_fn"]=tok
retr_params["lang2_tok_fn"]=cur_ar_tok_fn
punc_pairs={} #punctuation pairs - en/ar - we can add later phrase pairs
punc_pairs[","]="،"
punc_pairs[";"]="؛"
punc_pairs["?"]="؟"
punc_pairs["in"]="في"
retr_params["punc_pairs"]=punc_pairs
retr_params["only_without_children"]=False
retr_params["reward_combined_phrases"]=True
retr_params["extra_src_index"]=src_index1
retr_params["extra_trg_index"]=trg_index1
#print("retr_params",retr_params)

aligned_fpath=os.path.join(index_dir,cur_align_fname)
start_loc=0 #check which line in the bitext file to start with
counter=0
if os.path.exists(aligned_fpath):
  aligned_fopen=open(aligned_fpath)
  for line0 in aligned_fopen:
    line_dict=json.loads(line0.strip())
    cur_loc=line_dict.get("loc")
    cur_i=line_dict.get("i")
    if cur_loc!=None: start_loc=cur_loc
    if cur_i!=None: counter=cur_i
  aligned_fopen.close()

print("start_loc",start_loc,"counter",counter)




sent_i=519

src_sent1='May She would await the report of subsidiary body 3 and hoped that suitable text on the establishment of a such a zone in the Middle East would be reflected in the Committee’s final report.'
trg_sent1=' أيار/مايو وقالت إنها تنتظر تقرير الهيئة الفرعية 3 وتأمل في أن ينعكس النص المناسب بشأن إنشاء منطقة من هذا القبيل في الشرق الأوسط في التقرير النهائي للجنة.'
#src_sent1='2- COMMENTS 225 OF GOVERNMENTS ON THE REPORT OF THE WORKING GROUP'
#trg_sent1='2- تعليقات 225 الحكومات على تقرير الفريق العامل المعني'
for sent_i,cur_item in enumerate(data):
  if sent_i<counter: continue
  print(sent_i)
  #cur_item=data[sent_i]
  src_sent1,trg_sent1=cur_item
  t0=time.time()
  print(len(tok(src_sent1)))
  print(len(tok(trg_sent1)))
  results=walign(src_sent1,trg_sent1,retr_params)
  elapsed=time.time()-t0
  align_list=results.get("align",[])
  src_tokens_padded=results["src"]
  trg_tokens_padded=results["trg"]
  results["i"]=sent_i
  for pair,wt in align_list:
    s_al,t_al=pair
    print("weight:",round(wt,4))
    print(">>>", s_al, src_tokens_padded[s_al[0]:s_al[1]+1])
    print(">>>", t_al, trg_tokens_padded[t_al[0]:t_al[1]+1])
    print("----")
  if align_list!=[]:
    aligned_fopen=open(aligned_fpath,"a")
    aligned_fopen.write(json.dumps(results)+"\n")
    aligned_fopen.close()

  print("elapsed",round(elapsed,4))

Streaming output truncated to the last 5000 lines.
>>> (8, 9) ['real', 'risk']
>>> (7, 8) ['خطرا', 'حقيقيا']
----
weight: 0.7275
>>> (11, 11) ['torture']
>>> (12, 12) ['ال_تعذيب']
----
weight: 0.1275
>>> (13, 13) ['other']
>>> (14, 14) ['غير']
----
weight: 0.122
>>> (14, 14) ['ill']
>>> (18, 18) ['ال_معاملة']
----
weight: 0.423
>>> (16, 16) ['treatment']
>>> (18, 18) ['ال_معاملة']
----
weight: 0.1195
>>> (17, 17) ['should']
>>> (3, 4) ['ال_رسالة', 'أن']
----
weight: 0.0213
>>> (17, 17) ['should']
>>> (3, 3) ['ال_رسالة']
----
weight: 0.0982
>>> (17, 17) ['should']
>>> (4, 4) ['أن']
----
weight: 0.0029
>>> (19, 19) ['return']
>>> (21, 21) ['عادت']
----
weight: 0.5464
>>> (21, 21) ['Somalia']
>>> (23, 23) ['ال_صومال']
----
weight: 0.8774
>>> (24, 28) ['breach', 'of', 'articles', '2', ',']
>>> (24, 30) ['،', 'ما', 'يشكل', 'انتهاكا', 'لـ', 'ال_مواد', '2']
----
weight: 0.6774
>>> (24, 27) ['breach', 'of', 'articles', '2']
>>> (26, 30) ['يشكل', 'انتهاكا', 'لـ', 'ال_مواد', '2']
----
weight: 0.

In [ ]:
!wget https://dlcdn.apache.org/tika/2.6.0/tika-app-2.6.0.jar
# #!wget https://dlcdn.apache.org/tika/2.6.0/tika-2.6.0-src.zip
# !unzip tika-2.6.0-src.zip

--2022-12-05 12:29:23--  https://dlcdn.apache.org/tika/2.6.0/tika-app-2.6.0.jar
Resolving dlcdn.apache.org (dlcdn.apache.org)... 151.101.2.132, 2a04:4e42::644
Connecting to dlcdn.apache.org (dlcdn.apache.org)|151.101.2.132|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 52526918 (50M) [application/java-archive]
Saving to: ‘tika-app-2.6.0.jar’

tika-app-2.6.0.jar  100%[===================>]  50.09M  63.0MB/s    in 0.8s    

2022-12-05 12:29:26 (63.0 MB/s) - ‘tika-app-2.6.0.jar’ saved [52526918/52526918]



In [ ]:
from openpyxl import Workbook

#Reading a word document with Tika - 5 Dec 2022

In [ ]:
#!java -jar tika-app-2.6.0.jar -h docs/ecosoc2.docx > tika_out.html
from code_utils.tika_utils import *
from code_utils.web_lib import *
from code_utils.general import *


#in_fpath0="docs/ecosoc2.docx"
in_fpath0="docs/2212878A_P2.docx"
#out_fpath0="docs/ecosoc2.html"
in_fpath_split0=in_fpath0.split(".")
in_fpath_split0[-1]="html"
out_fpath0=".".join(in_fpath_split0)
tika(in_fpath0,out_fpath0)
print("out_fpath0",out_fpath0)

# fopen=open(out_fpath0)
# content0=fopen.read()
# fopen.close()

# dom_obj0=DOM(content0)
# dom_text_items=dom_obj0.text_items
# for a in dom_text_items:
#   para0=unescape(a)
#   para_items=para0.split("\t")
#   for p0 in para_items: print(p0)
#   #print([para0])

out_fpath0 docs/2212878A_P2.html


In [ ]:
import time, json, shelve, os, re, sys
from itertools import groupby
from math import log


#from general import * 
sys.path.append("code_utils")
import general
import arabic_lib

from itertools import groupby
from collections import Counter
ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})

index_dir="indexes/un/exp3"
params_fpath=os.path.join(index_dir,"params.json") #
params_dict=read_json(params_fpath)
params_dict["ar_counter_dict"]=ar_counter_dict

def tok_bitext(list0,params0={}):
  cur_ar_counter_dict=params0.get("ar_counter_dict",{})
  tokenized_bitext_list0=[]
  for cur_loc,src_trg in enumerate(list0):
    src0,trg0=src_trg
    try:
      src_toks0=tok(src0)
      trg_toks0=tok(trg0)
      if params0.get("lang2")=="ar": trg_toks0=arabic_lib.tok_ar(trg_toks0,cur_ar_counter_dict)
    except: continue
    tokenized_bitext_list0.append((cur_loc,src_toks0,trg_toks0))
  return tokenized_bitext_list0

t_list=tok_bitext(data,params_dict)
for tl in t_list[:20]:
  print(tl)

(0, ['CEDAW/C/GAB/CO/7', '2202978E', '.', 'docx', '(', 'ENGLISH', ')'], ['CEDAW/C/GAB/CO/7', '2202978A', '.', 'docx', '(', 'ARABIC', ')'])
(1, ['CEDAW/C/GAB/CO/7'], ['CEDAW/C/GAB/CO/7'])
(2, ['United', 'Nations'], ['ال_أمــم', 'ال_متحـدة'])
(3, ['CEDAW/C/GAB/CO/7'], ['CEDAW/C/GAB/CO/7'])
(4, ['Convention', 'on', 'the', 'Elimination'], ['اتفاقية', 'ال_قضاء', 'على', 'جميـع'])
(5, ['of', 'All', 'Forms', 'of', 'Discrimination', 'against', 'Women'], ['أشكال', 'ال_تمييز', 'ضد', 'ال_مرأة'])
(6, ['Distr', '.', ':', 'General'], ['Distr', '.', ':', 'General'])
(8, ['Original', ':', 'English'], ['Arabic', 'Original', ':', 'English'])
(9, ['CEDAW/C/GAB/CO/7'], ['CEDAW/C/GAB/CO/7'])
(10, ['/', '3'], ['22', '-', '02978'])
(11, ['22', '-', '02978'], ['/', '3'])
(12, ['22', '-', '02978', '(', 'E', ')', '140322'], ['180322', '180322', '22', '-', '02978', 'X', '(', 'A', ')'])
(13, ['*', '2202978', '*'], ['*', '2202978', '*'])
(14, ['22', '-', '02978'], ['/', '4'])
(15, ['/', '4'], ['22', '-', '02978'])


#OLD - retrieving items from meta/indexes - 3-Nov-2022

In [ ]:
# import time, json, shelve, os
# def go2line(fpath0,loc0,size0=None):
#   fopen0=open(fpath0)
#   fopen0.seek(loc0)
#   #line0=fopen0.readline()
#   if size0!=None: line0=fopen0.read(size0)
#   else: line0=fopen0.readline()
#   line0=line0.split("\n")[0]
#   fopen0.close()
#   return line0

# def get_unigram_locs(tok_list0):
#   enum_list=[(v,i) for i,v in enumerate(tok_list0)]
#   enum_list.sort()
#   grouped=[(key,[v[1] for v in list(group)]) for key,group in groupby(enum_list,lambda x:x[0])]
#   loc_dict0=dict(iter(grouped))
#   return loc_dict0

# def count_results(result_dict0):
#   count0=0
#   for a,b in result_dict0.items():count0+=len(b)
#   return count0

# def list_results(result_dict0):
#   res_list0=[]
#   for a,b in result_dict0.items():res_list0.extend(b)#count0+=len(b)
#   return res_list0


# def offset_results(result_dict0,offset0,max_sent_size0=1000):
#   new_dict0={}
#   for a,b in result_dict0.items():
#     new_b=[v-(offset0/max_sent_size0) for v in b]
#     new_dict0[a]=new_b
#   return new_dict0

# #we start here, getting from the meta shelve the locations of the indexes of this word in each of the inverted index text files
# def get_word_indexes(word1,index_prefix1,retr_params1): #index_prefix is either src/trg
#   index_dir1=retr_params1.get("index_dir") #main directory where the inverted index text files are stored
#   meta_suffix1=retr_params1.get("meta_suffix","meta") #suffix of the shelve meta file (usually sr-meta.shelve or trg-meta.shelve)
#   max_n_index_files=retr_params1.get("max_n_index_files",50) #maximum number of inverted index files to process
#   cur_meta_shelve_path=os.path.join(index_dir1,"%s-%s.shelve"%(index_prefix1,meta_suffix1))
#   cur_meta_shelve_open=shelve.open(cur_meta_shelve_path)
#   cur_meta_found=cur_meta_shelve_open.get(word1,{})
#   result_dict={}
  
#   n_results=0
#   elapsed_list=[]
#   t0=time.time()
#   meta_index_items=list(cur_meta_found.items())
  
#   if max_n_index_files!=None: meta_index_items=meta_index_items[:max_n_index_files]
#   #print(meta_index_items)
#   #return result_dict
#   for index_id,index_loc in meta_index_items:
#     #print(index_id,index_loc)
#     cur_loc0,cur_size0=index_loc
#     cur_txt_fpath=os.path.join(index_dir1,"%s-%s.txt"%(index_prefix1,index_id)) 
#     #print(cur_txt_fpath,cur_loc0,cur_size0)
#     cur_meta_line=go2line(cur_txt_fpath,cur_loc0,cur_size0)
#     #cur_meta_line=go2line2(cur_txt_fpath,cur_loc0)
#     cur_raw_indexes_str=cur_meta_line.strip().split("\t")[1]
#     cur_raw_indexes=json.loads(cur_raw_indexes_str)
#     result_dict[index_id]=cur_raw_indexes
#     #n_results+=len(cur_raw_indexes)
#   #result_dict["n"]=n_results
#   #print(len(result_dict.keys()))
#   return result_dict

# def get_result_lines(result_dict1,bitext_fpath1,n_results1=20,n_items_per_meta1=50):
#   final_results=[]
#   for index_id,indexes0 in result_dict1.items():
#     if n_items_per_meta1!=None: indexes0=indexes0[:n_items_per_meta1]
#     for ind0 in indexes0:
#       final_results.append((index_id,ind0))

#   final_results.sort(key=lambda x:x[-1]-int(x[-1]))
#   final_src_trg_items=[]
#   for res0 in final_results[:n_results1]:
#     index_id,ind0=res0
#     #cur_line0=go2line2(bitext_fpath1,int(ind0))
#     cur_line0=go2line(bitext_fpath1,int(ind0))
#     cur_split0=cur_line0.strip().split("\t")
#     if len(cur_split0)!=2: continue
#     src0,trg0=cur_split0
#     final_src_trg_items.append((src0,trg0,ind0,index_id))  
#   return final_src_trg_items

# def get_index_intersection(index_dict1,offset_index_dict2): #when we are getting phrase indexes of multiple tokens
#   combined_dict0={}
#   for index_id,cur_indexes in index_dict1.items():
#     offset_indexes=offset_index_dict2.get(index_id,[])
#     intersection0=list(set(cur_indexes).intersection(set(offset_indexes)))
#     combined_dict0[index_id]=intersection0
#   return combined_dict0

# def get_index_match_ratio_count(index_dict1,index_dict2): #match src/trg indexes
#   index1_count,index2_count,intersection_count=0,0,0
#   for index_id,cur_indexes1 in index_dict1.items():
#     cur_indexes2=index_dict2.get(index_id,[])
#     cur_indexes1=[int(v) for v in cur_indexes1]
#     cur_indexes2=[int(v) for v in cur_indexes2]

#     intersection0=list(set(cur_indexes1).intersection(set(cur_indexes2)))
#     index1_count+=len(cur_indexes1)
#     index2_count+=len(cur_indexes2)
#     intersection_count+=len(intersection0)
#   ratio0=0
#   if index1_count+index2_count>0: ratio0=intersection_count/(index1_count+index2_count-intersection_count)
#   return ratio0, intersection_count
#     #combined_dict0[index_id]=intersection0


# def get_phrase_locs(tokens0,max_phrase_len=8): #identify locations of phrases of content words - excluding empty string/filtered tokens
#   content_words_locs=[w_i for w_i,wd0 in enumerate(tokens0) if wd0!=""]
#   all_phrases0=[]
#   for ii0,cur_loc0 in enumerate(content_words_locs):
#     cur_phrase=[cur_loc0]
#     all_phrases0.append(list(cur_phrase))
#     next_locs=content_words_locs[ii0+1:]
#     for nl in next_locs:
#       cur_phrase+=[nl]
#       all_phrases0.append(list(cur_phrase))
#   all_phrase_locs_str=[]
#   for ap0 in all_phrases0:
#     phrase_tokens=tokens0[ap0[0]:ap0[-1]+1]
#     if len(phrase_tokens)>max_phrase_len: continue
#     all_phrase_locs_str.append((tuple(phrase_tokens),ap0))
#   return all_phrase_locs_str

# def combine_phrase_locs(all_phrase_locs_str0):
#   phrase_locs_str_sorted=sorted(all_phrase_locs_str0)
#   combined_phrase_locs=[(key,[v[1] for v in list(group)]) for key,group in groupby(phrase_locs_str_sorted,lambda x:x[0])]
#   phrase_locs_dict0=dict(iter(combined_phrase_locs)) # key: phrase token strings > vals: corresponding locations
#   return phrase_locs_dict0


# def get_phrase_locs_indexes(tokens0,res_dict0,max_phrase_len=8): 
#   all_phrases_locs_str=get_phrase_locs(tokens0,max_phrase_len) #get the geometric listing of all possible phrases made of content words
#   phrase_locs_dict=combine_phrase_locs(all_phrases_locs_str)
#   # for a,b in phrase_locs_dict.items():
#   #   print(a,b, len(b))

#   all_phrases_locs_str.sort(key=lambda x:len(x[1])) #sort them by size
#   phrase_result_dict={} #we put the results in a dictionary, where the keys are the phrase string, and the values are the index/results with proper offset
#   for phrase_tokens,phrase0 in all_phrases_locs_str:
#     found_phrase_indexes=phrase_result_dict.get(phrase_tokens) #check if this phrase was found in previous iterations
#     if found_phrase_indexes!=None: #if it was found, we skip to the next
#       #print("found already", phrase_tokens)
#       continue
#     #print(phrase_tokens,phrase0)
#     prev_tokens=[] #to check if the phrase is just a single token or not
#     last_item,prev_items=phrase0[-1],phrase0[:-1] #we need to get the location of the last token
#     if len(prev_items)>0: prev_tokens=tokens0[prev_items[0]:prev_items[-1]+1] #if the phrase has multiple tokens, identify previous tokens // the ones before the last token
#     first_item=phrase0[0] #the location of the first token
#     last_word=tokens0[last_item] #the string of the last token
#     last_offset=last_item-first_item #the offset of the last token (location of last token minus location of first token)
#     cur_word_indexes=res_dict0.get(last_word,{})  #now retrieve the indexes for each word
#     cur_offset_indexes=offset_results(cur_word_indexes,last_offset) #offset the indexes according to the current offset
#     found_prev_tokens_index_dict=phrase_result_dict.get(tuple(prev_tokens),{}) #check if previous tokens in the phrase have indexes that were found already
#     if len(prev_items)>0 and found_prev_tokens_index_dict=={}: continue #if there are previous tokens, but no indexes found for them - NEED TO CHECK
#     if prev_items!=[]: 
#       cur_offset_indexes=get_index_intersection(found_prev_tokens_index_dict,cur_offset_indexes) #If there are previous tokens and indexes, find the intersection -ALSO CHECK THIS
#     phrase_result_dict[phrase_tokens]=cur_offset_indexes
#   new_dict={}
#   for a,b in phrase_locs_dict.items():
#     new_dict[a]=[b,phrase_result_dict.get(a,{})]
    
#   return new_dict

def get_matching(src_tok0,trg_toks0,src_index_dict0,trg_index_dict0,max_phrase_len=8):
  src_output=get_phrase_locs_indexes(src_tok0,src_index_dict0,max_phrase_len)
  trg_output=get_phrase_locs_indexes(trg_toks0,trg_index_dict0,max_phrase_len)
  matching_list=[]
  phrase_count_src_dict,phrase_count_trg_dict={},{} #how many instances of both src/trg phrases
  for src_phrase_str,src_indexes_locs in src_output.items(): phrase_count_src_dict[src_phrase_str]=len(src_indexes_locs[0])
  for trg_phrase_str,trg_indexes_locs in trg_output.items(): phrase_count_trg_dict[trg_phrase_str]=len(trg_indexes_locs[0])


  for src_phrase_str,src_indexes_locs in src_output.items():
    src_locs0,src_indexes0=src_indexes_locs
    for trg_phrase_str,trg_indexes_locs in trg_output.items():
      trg_locs0,trg_indexes0=trg_indexes_locs
      min_locs_count=min(len(src_locs0),len(trg_locs0)) #we subtract from the number of locs of each phrase the minimum
      ratio1,intersection1=get_index_match_ratio_count(src_indexes0,trg_indexes0)
      if ratio1==0: continue
      matching_list.append((src_phrase_str,trg_phrase_str,min_locs_count,intersection1,ratio1))

  matching_list.sort(key=lambda x:-x[-1])
  for ml in matching_list:
    src_phrase_str,trg_phrase_str,min_locs_count,intersection1,ratio1=ml
    if phrase_count_src_dict[src_phrase_str]>0 or phrase_count_trg_dict[trg_phrase_str]>0:
      print(src_phrase_str,trg_phrase_str, ratio1)
      print(phrase_count_src_dict[src_phrase_str],phrase_count_trg_dict[trg_phrase_str])
      print("----")

    phrase_count_src_dict[src_phrase_str]=phrase_count_src_dict[src_phrase_str]-min_locs_count
    phrase_count_trg_dict[trg_phrase_str]=phrase_count_trg_dict[trg_phrase_str]-min_locs_count

  return matching_list


index_dir="indexes/un/exp3"
params_fpath=os.path.join(index_dir,"params.json")
with open(params_fpath) as params_fopen:
  filter_params=json.load(params_fopen) #token filtering parameteres
print(filter_params)

en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"

retr_params={} #retrieval parameters
retr_params["index_dir"]="indexes/un/exp3"
retr_params["meta_suffix"]="meta"
retr_params["max_n_index_files"]=2

sent='The Regular Process is in its third cycle (2021–2025), with the first and second World Ocean Assessments published in 2016 and 2021, respectively.'
sent='More diverse perspectives, such as those of youth, should be integrated into that domain.'
sent="""	
Her delegation welcomed the inclusion of paragraphs on the central role of IAEA and the importance of safeguards, as well as the inclusion of paragraphs on the importance of gender in non-proliferation and safeguards-related activities.
"""
src_sent='Ireland supported the recommendation made by the representative of Australia on including the text on gender in the operational part of the report.'
trg_sent='وتؤيد أيرلندا التوصية التي قدمها ممثل أستراليا بشأن إدراج النص المتعلق بالجوانب الجنسانية في الجزء التنفيذي من التقرير.'

src_sent='The language on the verification standard, specifically with regard to the additional protocol, should be strengthened, as should the text on the small quantities protocol.'
trg_sent='وينبغي تعزيز الصياغة المتعلقة بمعيار التحقق، ولا سيما فيما يتعلق بالبروتوكول الإضافي، وكذلك النص المتعلق ببروتوكول الكميات الصغيرة.'

src_sent1='She would await the report of subsidiary body 3 and hoped that suitable text on the establishment of a such a zone in the Middle East would be reflected in the Committee’s final report.'
trg_sent1='وقالت إنها تنتظر تقرير الهيئة الفرعية 3 وتأمل في أن ينعكس النص المناسب بشأن إنشاء منطقة من هذا القبيل في الشرق الأوسط في التقرير النهائي للجنة.'

src_sent1="""
Failing to strike such a balance in any final move, without such a balance would be counterproductive and would critically affect the credibility of any final document.
"""
trg_sent1="""
ومن شأن الفشل في تحقيق هذا التوازن أن يؤدي إلى نتائج عكسية وأن يؤثر تأثيرا حاسما على مصداقية أي وثيقة ختامية.
"""

#sent='The Regular Process is in its third cycle'
#sent='Contribution made by Sustainable Development Goal 14 to achieving other Goals'
#sent='Statements were made by the representatives of 25 States and statements were also made by others'
src_tokens=tok(src_sent)
src_tokens1=filter_toks(src_tokens,filter_params) #need to make filter_tokens > OLD
trg_tokens=cur_ar_tok_fn(trg_sent)
trg_tokens1=filter_toks(trg_tokens,filter_params) #need to make filter_tokens > OLD

#print(src_tokens1)
unique_src_tokens=list(set([v for v in src_tokens1 if v!=""]))
unique_trg_tokens=list(set([v for v in trg_tokens1 if v!=""]))
t0=time.time()
src_retr_dict={}
for ut in unique_src_tokens:
  #print("src token indexes for:", ut)
  src_retr_dict[ut]=get_word_indexes(ut,"src",retr_params)
trg_retr_dict={}
for ut in unique_trg_tokens:
  #print("trg token indexes for:",ut)
  trg_retr_dict[ut]=get_word_indexes(ut,"trg",retr_params)
elapsed=time.time()-t0
print("src:",len(unique_src_tokens),"trg:",len(unique_trg_tokens),"elapsed:",round(elapsed,4))


src_tokens1=["<s>"]+src_tokens1+["</s>"]
trg_tokens1=["<s>"]+trg_tokens1+["</s>"]

print("now mtaching src -trg tokens/phrases")
t0=time.time()
matching_list=get_matching(src_tokens1,trg_tokens1,src_retr_dict,trg_retr_dict,4)
elapsed=time.time()-t0
for a in matching_list:
  print(a)
print("elapsed:",round(elapsed,4))


{'excluded_words': ['the', 'a', 'an', 'and', 'of', 'its', 'his', 'her', 'their', 'them', 'to', 'is', 'are', 'am', 'been', 'was', 'were', 'be', 'have', 'has', 'had', 'in', 'on', 'at', 'with', 'from', 'for', 'that', 'he', 'she', 'it', 'would', 'من', 'على', 'في', 'مع', 'إلى', 'له', 'تم', 'إلى', 'في'], 'max_sent_n_tokens': 1000, 'lang1': 'en', 'lang2': 'ar', 'exclude_single_chars': True, 'batch_size': 250000, 'min_n_indexes_per_token': 3}
src: 13 trg: 17 elapsed: 24.9597
now mtaching src -trg tokens/phrases
('protocol',) ('بروتوكول',) 0.7305428384565075
2 2
----
('small',) ('صغيرة',) 0.5574832775919732
1 1
----
('text',) ('نص',) 0.5405181347150259
1 1
----
('verification',) ('التحقق',) 0.4486652977412731
1 1
----
('should',) ('ينبغي',) 0.4287181242512408
2 1
----
('quantities',) ('كميات',) 0.4032697547683924
1 1
----
('small', 'quantities') ('كميات', 'صغيرة') 0.3333333333333333
1 1
----
('additional', 'protocol') ('بروتوكول', 'إضافي') 0.1724137931034483
1 1
----
('should', '', 'strengthene

#OLD - Building the align class - 7 Nov 2022

In [ ]:
# def get_unigram_locs(tok_list0):
#   enum_list=[(v,i) for i,v in enumerate(tok_list0)]
#   enum_list.sort()
#   grouped=[(key,[v[1] for v in list(group)]) for key,group in groupby(enum_list,lambda x:x[0])]
#   loc_dict0=dict(iter(grouped))
#   return loc_dict0
import time, json, shelve, os
def go2line(fpath0,loc0,size0=None):
  fopen0=open(fpath0)
  fopen0.seek(loc0)
  #line0=fopen0.readline()
  if size0!=None: line0=fopen0.read(size0)
  else: line0=fopen0.readline()
  line0=line0.split("\n")[0]
  fopen0.close()
  return line0

def get_unigram_locs(tok_list0):
  enum_list=[(v,i) for i,v in enumerate(tok_list0)]
  enum_list.sort()
  grouped=[(key,[v[1] for v in list(group)]) for key,group in groupby(enum_list,lambda x:x[0])]
  loc_dict0=dict(iter(grouped))
  return loc_dict0

def count_results(result_dict0):
  count0=0
  for a,b in result_dict0.items():count0+=len(b)
  return count0

def list_results(result_dict0):
  res_list0=[]
  for a,b in result_dict0.items():res_list0.extend(b)#count0+=len(b)
  return res_list0


def offset_results(result_dict0,offset0,max_sent_size0=1000):
  new_dict0={}
  for a,b in result_dict0.items():
    new_b=[v-(offset0/max_sent_size0) for v in b]
    new_dict0[a]=new_b
  return new_dict0

#we start here, getting from the meta shelve the locations of the indexes of this word in each of the inverted index text files
def get_word_indexes(word1,index_prefix1,retr_params1): #index_prefix is either src/trg
  index_dir1=retr_params1.get("index_dir") #main directory where the inverted index text files are stored
  meta_suffix1=retr_params1.get("meta_suffix","meta") #suffix of the shelve meta file (usually sr-meta.shelve or trg-meta.shelve)
  max_n_index_files=retr_params1.get("max_n_index_files",50) #maximum number of inverted index files to process
  cur_meta_shelve_path=os.path.join(index_dir1,"%s-%s.shelve"%(index_prefix1,meta_suffix1))
  cur_meta_shelve_open=shelve.open(cur_meta_shelve_path)
  cur_meta_found=cur_meta_shelve_open.get(word1,{})
  result_dict={}
  
  n_results=0
  elapsed_list=[]
  t0=time.time()
  meta_index_items=list(cur_meta_found.items())
  
  if max_n_index_files!=None: meta_index_items=meta_index_items[:max_n_index_files]
  #print(meta_index_items)
  #return result_dict
  for index_id,index_loc in meta_index_items:
    #print(index_id,index_loc)
    cur_loc0,cur_size0=index_loc
    cur_txt_fpath=os.path.join(index_dir1,"%s-%s.txt"%(index_prefix1,index_id)) 
    #print(cur_txt_fpath,cur_loc0,cur_size0)
    cur_meta_line=go2line(cur_txt_fpath,cur_loc0,cur_size0)
    #cur_meta_line=go2line2(cur_txt_fpath,cur_loc0)
    cur_raw_indexes_str=cur_meta_line.strip().split("\t")[1]
    cur_raw_indexes=json.loads(cur_raw_indexes_str)
    result_dict[index_id]=cur_raw_indexes
    #n_results+=len(cur_raw_indexes)
  #result_dict["n"]=n_results
  #print(len(result_dict.keys()))
  return result_dict

def get_result_lines(result_dict1,bitext_fpath1,n_results1=20,n_items_per_meta1=50):
  final_results=[]
  for index_id,indexes0 in result_dict1.items():
    if n_items_per_meta1!=None: indexes0=indexes0[:n_items_per_meta1]
    for ind0 in indexes0:
      final_results.append((index_id,ind0))

  final_results.sort(key=lambda x:x[-1]-int(x[-1]))
  final_src_trg_items=[]
  for res0 in final_results[:n_results1]:
    index_id,ind0=res0
    #cur_line0=go2line2(bitext_fpath1,int(ind0))
    cur_line0=go2line(bitext_fpath1,int(ind0))
    cur_split0=cur_line0.strip().split("\t")
    if len(cur_split0)!=2: continue
    src0,trg0=cur_split0
    final_src_trg_items.append((src0,trg0,ind0,index_id))  
  return final_src_trg_items

def get_index_intersection(index_dict1,offset_index_dict2): #when we are getting phrase indexes of multiple tokens
  combined_dict0={}
  for index_id,cur_indexes in index_dict1.items():
    offset_indexes=offset_index_dict2.get(index_id,[])
    intersection0=list(set(cur_indexes).intersection(set(offset_indexes)))
    combined_dict0[index_id]=intersection0
  return combined_dict0

def get_index_match_ratio_count(index_dict1,index_dict2): #match src/trg indexes
  index1_count,index2_count,intersection_count=0,0,0
  for index_id,cur_indexes1 in index_dict1.items():
    cur_indexes2=index_dict2.get(index_id,[])
    cur_indexes1=[int(v) for v in cur_indexes1]
    cur_indexes2=[int(v) for v in cur_indexes2]

    intersection0=list(set(cur_indexes1).intersection(set(cur_indexes2)))
    index1_count+=len(cur_indexes1)
    index2_count+=len(cur_indexes2)
    intersection_count+=len(intersection0)
  ratio0=0
  if index1_count+index2_count>0: ratio0=intersection_count/(index1_count+index2_count-intersection_count)
  return ratio0, intersection_count
    #combined_dict0[index_id]=intersection0


def get_phrase_locs(tokens0,max_phrase_len=8): #identify locations of phrases of content words - excluding empty string/filtered tokens
  content_words_locs=[w_i for w_i,wd0 in enumerate(tokens0) if wd0!=""]
  all_phrases0=[]
  for ii0,cur_loc0 in enumerate(content_words_locs):
    cur_phrase=[cur_loc0]
    all_phrases0.append(list(cur_phrase))
    next_locs=content_words_locs[ii0+1:]
    for nl in next_locs:
      cur_phrase+=[nl]
      all_phrases0.append(list(cur_phrase))
  all_phrase_locs_str=[]
  for ap0 in all_phrases0:
    phrase_tokens=tokens0[ap0[0]:ap0[-1]+1]
    if len(phrase_tokens)>max_phrase_len: continue
    all_phrase_locs_str.append((tuple(phrase_tokens),ap0))
  return all_phrase_locs_str

def combine_phrase_locs(all_phrase_locs_str0):
  phrase_locs_str_sorted=sorted(all_phrase_locs_str0)
  combined_phrase_locs=[(key,[v[1] for v in list(group)]) for key,group in groupby(phrase_locs_str_sorted,lambda x:x[0])]
  phrase_locs_dict0=dict(iter(combined_phrase_locs)) # key: phrase token strings > vals: corresponding locations
  return phrase_locs_dict0


def get_phrase_locs_indexes(tokens0,res_dict0,max_phrase_len=8): 
  all_phrases_locs_str=get_phrase_locs(tokens0,max_phrase_len) #get the geometric listing of all possible phrases made of content words
  phrase_locs_dict=combine_phrase_locs(all_phrases_locs_str)
  all_phrases_locs_str.sort(key=lambda x:len(x[1])) #sort them by size
  phrase_result_dict={} #we put the results in a dictionary, where the keys are the phrase string, and the values are the index/results with proper offset
  for phrase_tokens,phrase0 in all_phrases_locs_str:
    found_phrase_indexes=phrase_result_dict.get(phrase_tokens) #check if this phrase was found in previous iterations
    if found_phrase_indexes!=None: #if it was found, we skip to the next
      #print("found already", phrase_tokens)
      continue
    #print(phrase_tokens,phrase0)
    prev_tokens=[] #to check if the phrase is just a single token or not
    last_item,prev_items=phrase0[-1],phrase0[:-1] #we need to get the location of the last token
    if len(prev_items)>0: prev_tokens=tokens0[prev_items[0]:prev_items[-1]+1] #if the phrase has multiple tokens, identify previous tokens // the ones before the last token
    first_item=phrase0[0] #the location of the first token
    last_word=tokens0[last_item] #the string of the last token
    last_offset=last_item-first_item #the offset of the last token (location of last token minus location of first token)
    cur_word_indexes=res_dict0.get(last_word,{})  #now retrieve the indexes for each word
    cur_offset_indexes=offset_results(cur_word_indexes,last_offset) #offset the indexes according to the current offset
    found_prev_tokens_index_dict=phrase_result_dict.get(tuple(prev_tokens),{}) #check if previous tokens in the phrase have indexes that were found already
    if len(prev_items)>0 and found_prev_tokens_index_dict=={}: continue #if there are previous tokens, but no indexes found for them - NEED TO CHECK
    if prev_items!=[]: 
      cur_offset_indexes=get_index_intersection(found_prev_tokens_index_dict,cur_offset_indexes) #If there are previous tokens and indexes, find the intersection -ALSO CHECK THIS
    phrase_result_dict[phrase_tokens]=cur_offset_indexes
  new_dict={}
  for a,b in phrase_locs_dict.items():
    new_dict[a]=[b,phrase_result_dict.get(a,{})]
    
  return new_dict

def combine_els(el1,el2):
  src_span1,trg_span1=el1
  src_span2,trg_span2=el2
  x1_0,x1_1=src_span1
  x2_0,x2_1=src_span2
  y1_0,y1_1=trg_span1
  y2_0,y2_1=trg_span2
  min_x=min(x1_0,x1_1,x2_0,x2_1)
  max_x=max(x1_0,x1_1,x2_0,x2_1)
  min_y=min(y1_0,y1_1,y2_0,y2_1)
  max_y=max(y1_0,y1_1,y2_0,y2_1)
  new_src_span=(min_x,max_x)
  new_trg_span=(min_y,max_y)
  return (new_src_span,new_trg_span)

def get_span_dist(span1,span2):
  span1_x1,span1_x2=span1
  span2_x1,span2_x2=span2
  d1=abs(span1_x2-span1_x1)
  d2=abs(span2_x2-span2_x1)
  max_x=max(span1_x1,span1_x2,span2_x1,span2_x2)
  min_x=min(span1_x1,span1_x2,span2_x1,span2_x2)
  d_total=max_x-min_x
  return d_total-d1-d2

def get_rec_el_children(el0,el_child_dict0,el_list0=[]):
  cur_children0=el_child_dict0.get(el0,[])
  if cur_children0==[]: el_list0.append(el0)
  for ch0 in cur_children0:
    el_list0=get_rec_el_children(ch0,el_child_dict0,el_list0)
  return el_list0

# def djk(pt0,pt1,transition_dict0,pt_list0=None):
#   path_wt_dict0={}
#   prev_dict0={}
#   if pt_list0==None: pt_list0=list(transition_dict0.keys())
#   for cur_pt in pt_list0:
#     following_dict0=transition_dict0.get(cur_pt,{})
#     found_cur_path_wt=path_wt_dict0.get(cur_pt,0)
#     for next_pt,next_wt in following_dict0.items():
#       combined_wt=found_cur_path_wt+next_wt
#       found_next_wt=path_wt_dict0.get(next_pt,0)
#       if combined_wt>found_next_wt:
#         path_wt_dict0[next_pt]=combined_wt
#         prev_dict0[next_pt]=cur_pt
#   cur_pt=pt1
#   out_path=[]
#   while cur_pt!=None:
#     out_path.append(cur_pt)
#     if cur_pt==pt0: break
#     cur_pt=prev_dict0.get(cur_pt)
#   out_path=list(reversed(out_path))
#   return out_path, path_wt_dict0.get(pt1)


def get_ne_se_dict(all_elements0): #elements are pairs of src/trg spans
  se_transition_dict0,ne_transition_dict0={},{} #identify the possible transitions from one element to another - southeast or northeast
  for el0,el_wt0 in all_elements0:
    #print(el0,el_wt0)
    src_span0,trg_span0=el0
    se_transition_dict0[el0]={}
    ne_transition_dict0[el0]={}
    ne_list,se_list=[],[]
    for el1,el_wt1 in all_elements0:
      src_span1,trg_span1=el1
      if src_span0==src_span1 or trg_span0==trg_span1: continue
      if src_span1[0]<=src_span0[1]: continue
      src_span_dist=get_span_dist(src_span0,src_span1)
      trg_span_dist=get_span_dist(trg_span0,trg_span1)
      direction=None
      if trg_span1[0]>trg_span0[1]: 
        direction="se"
        se_list.append((el1,el_wt1))
        se_transition_dict0[el0][el1]=el_wt0
      if trg_span1[1]<trg_span0[0]: 
        direction="ne"
        ne_list.append((el1,el_wt1))
        ne_transition_dict0[el0][el1]=el_wt0
      if direction==None: continue
  return se_transition_dict0, ne_transition_dict0

def split_path_chunks(path_list0,skip_last=False): #split a path e.g. cur_list=["a","b","c","d","0"] to chunks e.g. ["a","b"], ["b","c","d"]
  path_chunks0=[]
  if skip_last: last_i0,last_i1=len(path_list0)-2,len(path_list0)-1
  else: last_i0,last_i1=len(path_list0)-1,len(path_list0)
  for path_i0 in range(last_i0):
    for path_i1 in range(path_i0+1,last_i1):
      cur_chunk=path_list0[path_i0:path_i1+1]
      path_chunks0.append(cur_chunk)
  return path_chunks0


def walign(src_sent0,trg_sent0,retr_align_params0={}):
  filter_params0=retr_align_params0.get("filter_params",{})
  lang1=retr_align_params0.get("lang1","en")
  lang2=retr_align_params0.get("lang2","ar")
  exclude_numbers=retr_align_params0.get("exclude_numbers",False)
  max_phrase_len=retr_align_params0.get("max_phrase_len",8) #when we get the phrases from a sentence
  max_phrase_dist=retr_align_params0.get("max_phrase_dist",10) #maximum distance when combining two phrases
  min_phrase_wt=retr_align_params0.get("min_phrase_wt",0.01)
  lang2_tok_fn=retr_align_params0.get("lang2_tok_fn")
  punc_pairs0=retr_align_params0.get("punc_pairs",{}) 
  src_tokens=tok(src_sent0)
  if lang2=="ar" and lang2_tok_fn!=None: trg_tokens=lang2_tok_fn(trg_sent0)
  else: trg_tokens=tok(trg_sent0)
  src_tokens_filtered=filter_toks(src_tokens,filter_params0)
  trg_tokens_filtered=filter_toks(trg_tokens,filter_params0) #need to make filter_tokens > OLD
  unique_src_tokens=list(set([v for v in src_tokens_filtered if v!=""]))
  unique_trg_tokens=list(set([v for v in trg_tokens_filtered if v!=""]))
  src_tokens_padded=["<s>"]+src_tokens+["</s>"] #filter_toks(self.src_tokens,filter_params0)
  trg_tokens_padded=["<s>"]+trg_tokens+["</s>"]
  src_tok_loc_dict=get_unigram_locs(src_tokens_padded)
  trg_tok_loc_dict=get_unigram_locs(trg_tokens_padded)
  src_tokens_filtered_padded=["<s>"]+src_tokens_filtered+["</s>"] #main list to be aligned
  trg_tokens_filtered_padded=["<s>"]+trg_tokens_filtered+["</s>"]

  #Now we load the indexes for our tokens
  t0=time.time()
  src_index_dict,trg_index_dict={},{}
  src_retr_dict={}
  for ut in unique_src_tokens: 
    if ut.isdigit() and exclude_numbers: continue
    src_index_dict[ut]=get_word_indexes(ut,"src",retr_align_params0)
  for ut in unique_trg_tokens: 
    if ut.isdigit() and exclude_numbers: continue
    trg_index_dict[ut]=get_word_indexes(ut,"trg",retr_align_params0)
  elapsed=time.time()-t0
  print("src:",len(unique_src_tokens),"trg:",len(unique_trg_tokens),"elapsed:",round(elapsed,4))
  #print("now mtaching src -trg tokens/phrases")
  #Now we start the matching between src/trg tokens
  t0=time.time()

  src_output=get_phrase_locs_indexes(src_tokens_filtered_padded,src_index_dict,max_phrase_len)
  trg_output=get_phrase_locs_indexes(trg_tokens_filtered_padded,trg_index_dict,max_phrase_len)
  matching_list=[]
  phrase_count_src_dict,phrase_count_trg_dict={},{} #how many instances of each src/trg phrases
  for src_phrase_str,src_indexes_locs in src_output.items(): phrase_count_src_dict[src_phrase_str]=len(src_indexes_locs[0])
  for trg_phrase_str,trg_indexes_locs in trg_output.items(): phrase_count_trg_dict[trg_phrase_str]=len(trg_indexes_locs[0])

  for src_phrase_str,src_indexes_locs in src_output.items():
    src_locs0,src_indexes0=src_indexes_locs
    for trg_phrase_str,trg_indexes_locs in trg_output.items():
      trg_locs0,trg_indexes0=trg_indexes_locs
      if src_phrase_str==trg_phrase_str: ratio1,intersection1=0.5, 1000
      else: ratio1,intersection1=get_index_match_ratio_count(src_indexes0,trg_indexes0)
      min_locs_count=min(len(src_locs0),len(trg_locs0)) #we subtract from the number of locs of each phrase the minimum
      if ratio1==0: continue
      if ratio1<min_phrase_wt: continue
      if intersection1<2: continue
      matching_list.append((src_phrase_str,trg_phrase_str,src_locs0,trg_locs0,min_locs_count,intersection1,ratio1))

  matching_list.sort(key=lambda x:-x[-1])
  new_matching_list=[]
  for ml in matching_list:
    src_phrase_str,trg_phrase_str,src_locs0,trg_locs0,min_locs_count,intersection1,ratio1=ml
    if phrase_count_src_dict[src_phrase_str]>0 or phrase_count_trg_dict[trg_phrase_str]>0:
      new_matching_list.append((src_phrase_str,trg_phrase_str,src_locs0,trg_locs0,intersection1,ratio1))
    phrase_count_src_dict[src_phrase_str]=phrase_count_src_dict[src_phrase_str]-min_locs_count #subtract the minimum count of instances from both src and trg
    phrase_count_trg_dict[trg_phrase_str]=phrase_count_trg_dict[trg_phrase_str]-min_locs_count
  
  for src_punc0,trg_punc0 in punc_pairs0.items(): #now let's match punctuation from the original tokens
    punc_src_locs=src_tok_loc_dict.get(src_punc0,[])
    if punc_src_locs==[]: continue
    punc_trg_locs=trg_tok_loc_dict.get(trg_punc0,[])
    if punc_trg_locs==[]: continue
    ratio1,intersection1=0.2, 100
    src_punc0,trg_punc0=tuple([src_punc0]),tuple([trg_punc0])
    punc_src_locs=[[v] for v in punc_src_locs]
    punc_trg_locs=[[v] for v in punc_trg_locs]
    new_matching_list.append((src_punc0,trg_punc0,punc_src_locs,punc_trg_locs,intersection1,ratio1))

  new_matching_list.sort(key=lambda x:-x[-1])
  elapsed=time.time()-t0
  print("finished matching words and phrases:", elapsed)
  #Now we have the matching list - let's align
  el_dict={} #weight of each element
  el_child_dict={} #children of each element
  for a in new_matching_list:
    #print(a)
    src_phrase_str,trg_phrase_str,src_locs0,trg_locs0,intersection1,ratio1=a
    for sl0 in src_locs0:
      s_min,s_max=sl0[0],sl0[-1]
      for tl0 in trg_locs0:
        t_min,t_max=tl0[0],tl0[-1]
        el0=((s_min,s_max) ,(t_min,t_max))
        el_dict[el0]=ratio1
  first_src_span,first_trg_span=(0,0),(0,0)
  last_src_span=(len(src_tokens_padded)-1,len(src_tokens_padded)-1)
  last_trg_span=(len(trg_tokens_padded)-1,len(trg_tokens_padded)-1)
  ne_el=(last_src_span,first_trg_span) #north eastern element - uppermost rightmost, so we go diagonally up to the right
  se_el=(last_src_span,last_trg_span)
  el_dict[ne_el]=0
  top_wt=0
  full_src_span0=(0,len(src_tokens_padded)-1)
  full_trg_span0=(0,len(trg_tokens_padded)-1)
  full_el=(full_src_span0,full_trg_span0)

  #start iteration here
  n_epochs=10
  for epoch0 in range(n_epochs):
    print("epoch0",epoch0)
    all_elements=list(el_dict.items())
    all_elements.sort()
    se_transition_dict,ne_transition_dict=get_ne_se_dict(all_elements)
    new_el_counter=0
    for cur_el,b in se_transition_dict.items():
      next_els=list(b.keys())
      if len(next_els)<2: continue
      cur_pts=[cur_el]+next_els
      cur_path,cur_path_wt=djk(cur_el,se_el,se_transition_dict,cur_pts)
      path_el_wts=[(v, el_dict.get(v,0)) for v in cur_path]
      path_el_wts_chunks=split_path_chunks(path_el_wts)
      #print("se",cur_el,next_els)
      for chunk in path_el_wts_chunks:
        chunk_wt=sum([v[1] for v in chunk])
        chunk_els=[v[0] for v in chunk]
        combined_el=combine_els(chunk_els[0],chunk_els[-1])
        found_wt=el_dict.get(combined_el,0)
        found_children=el_child_dict.get(combined_el,[])
        if chunk_wt>found_wt:
          #print("combined_el",combined_el,"chunk_wt",chunk_wt,"found_wt",found_wt,"found_children",found_children)
          el_dict[combined_el]=chunk_wt
          el_child_dict[combined_el]=chunk_els
          new_el_counter+=1
    print("finished processing SE, new_el_counter:",new_el_counter)
    for cur_el,b in ne_transition_dict.items():
      next_els=list(b.keys())
      if len(next_els)<2: continue
      cur_pts=[cur_el]+next_els
      cur_path,cur_path_wt=djk(cur_el,ne_el,ne_transition_dict,cur_pts)
      path_el_wts=[(v, el_dict.get(v,0)) for v in cur_path]
      path_el_wts_chunks=split_path_chunks(path_el_wts)
      #print("ne",cur_el,next_els)
      for chunk in path_el_wts_chunks:
        chunk_wt=sum([v[1] for v in chunk])
        chunk_els=[v[0] for v in chunk]
        combined_el=combine_els(chunk_els[0],chunk_els[-1])
        found_wt=el_dict.get(combined_el,0)
        found_children=el_child_dict.get(combined_el,[])
        if chunk_wt>found_wt:
          #print("combined_el",combined_el,"chunk_wt",chunk_wt,"found_wt",found_wt,"found_children",found_children)
          el_dict[combined_el]=chunk_wt
          el_child_dict[combined_el]=chunk_els
          new_el_counter+=1
    print("finished processing NE, new_el_counter:",new_el_counter)
    cur_full_wt=el_dict.get(full_el,0)
    print("full_el",full_el,"cur_full_wt",cur_full_wt)
    if cur_full_wt>0 and cur_full_wt==top_wt: break
    top_wt=cur_full_wt
  align_list=get_rec_el_children(full_el,el_child_dict,el_list0=[])
  # for s_al,t_al in align_list:
  #   print(">>>", s_al, src_tokens_padded[s_al[0]:s_al[1]+1])
  #   print(">>>", t_al, trg_tokens_padded[t_al[0]:t_al[1]+1])
  #   print("----")
  result_dict0={}
  result_dict0["src"]=src_tokens_padded
  result_dict0["trg"]=trg_tokens_padded
  result_dict0["align"]=align_list
  return result_dict0

  # return
  
  # used_el_pairs={}
  # child_dict={}
  # top_wt=0
  # full_src_span0=(0,len(src_tokens_filtered_padded)-1)
  # full_trg_span0=(0,len(trg_tokens_filtered_padded)-1)
  # full_el=(full_src_span0,full_trg_span0)
  # for epoch0 in range(20):
  #   print("epoch0",epoch0)
  #   all_elements=list(el_dict.items())
  #   all_elements.sort()
  #   for el_i,el_item0 in enumerate(all_elements):
  #     el0,el_wt0=el_item0
  #     src_span0,trg_span0=el0
  #     for el_item1 in all_elements[el_i+1:]:
  #       if used_el_pairs.get((el_item0,el_item1),False): continue
  #       el1,el_wt1=el_item1
  #       el_pair_key=(el0,el1)
  #       src_span1,trg_span1=el1
  #       if src_span0==src_span1 or trg_span0==trg_span1: continue
  #       #if src_span1[0]<=src_span0[1]: continue
  #       src_span_dist=get_span_dist(src_span0,src_span1)
  #       trg_span_dist=get_span_dist(trg_span0,trg_span1)
  #       if trg_span_dist<1 or src_span_dist<1: continue
  #       if src_span_dist> max_phrase_dist or trg_span_dist> max_phrase_dist: continue
  #       used_el_pairs[(el_item0,el_item1)]=True
  #       combined_el=combine_els(el0,el1)
  #       combined_wt=el_wt0+el_wt1
  #       found_wt=el_dict.get(combined_el,0)
  #       if combined_wt>found_wt:
  #         el_dict[combined_el]=combined_wt
  #         child_dict[combined_el]=(el0,el1)
  #     #print("----")
  #   cur_full_wt=el_dict.get(full_el,0)
  #   print("full_el",full_el,"cur_full_wt",cur_full_wt)
  #   if cur_full_wt>0 and cur_full_wt==top_wt: break
  #   top_wt=cur_full_wt
  # if cur_full_wt>0:
  #   align_list=get_rec_el_children(full_el,child_dict,el_list0=[])
  # else:
  #   wt_list=list(el_dict.items())
  #   wt_list.sort(key=lambda x:-x[1])
  #   top_el=wt_list[0][0]
  #   print("couldn't find full el:",full_el, "used the top el instead", top_el)
  #   align_list=get_rec_el_children(top_el,child_dict,el_list0=[])
  # for s_al,t_al in align_list:
  #   print(">>>", s_al, src_tokens_padded[s_al[0]:s_al[1]+1])
  #   print(">>>", t_al, trg_tokens_padded[t_al[0]:t_al[1]+1])
  #   print("----")
  # result_dict0={}
  # result_dict0["src"]=src_tokens_padded
  # result_dict0["trg"]=trg_tokens_padded
  # result_dict0["align"]=align_list
  # return result_dict0


index_dir="indexes/un/exp3"
params_fpath=os.path.join(index_dir,"params.json")
with open(params_fpath) as params_fopen:
  filter_params=json.load(params_fopen) #token filtering parameteres
#print(filter_params)

en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"

retr_params={} #retrieval parameters
retr_params["filter_params"]=filter_params

retr_params["index_dir"]="indexes/un/exp3"
retr_params["meta_suffix"]="meta"
retr_params["max_n_index_files"]=2
retr_params["lang1"]="en"
retr_params["lang2"]="ar"
retr_params["exclude_numbers"]=True
retr_params["max_phrase_dist"]=5 #maximum distance when combining two phrases while aligning
retr_params["min_phrase_wt"]=0.0001 #minimum weight for any phrase
retr_params["lang2_tok_fn"]=cur_ar_tok_fn



punc_pairs={} #punctuation pairs - en/ar - we can add later phrase pairs
punc_pairs[","]="،"
punc_pairs[";"]="؛"
punc_pairs["?"]="؟"
#punc_pairs["in"]="في"
retr_params["punc_pairs"]=punc_pairs



src_sent1='She would await the report of subsidiary body 3 and hoped that suitable text on the establishment of a such a zone in the Middle East would be reflected in the Committee’s final report.'
trg_sent1='وقالت إنها تنتظر تقرير الهيئة الفرعية 3 وتأمل في أن ينعكس النص المناسب بشأن إنشاء منطقة من هذا القبيل في الشرق الأوسط في التقرير النهائي للجنة.'

# src_sent1="At any rate, this would work?"
# trg_sent1="؟على أي حال، سوف ينجح هذا الأمر"

src_sent1="In 2015, the General assembly decided that the secretary-general will continue his work."
trg_sent1="في عام 2015، قررت الجمعية العامة أن يواصل الأمين العام عمله."

src_sent1='Having listened carefully to discussions on the issue of export controls throughout the Review Conference, her delegation had not heard of specific instances to support the view that export controls constrained peaceful uses of nuclear energy.'
trg_sent1='وقالت إن وفد بلدها، بعد أن استمع بعناية إلى المناقشات المتعلقة بمسألة ضوابط التصدير طوال المؤتمر الاستعراضي، لم يسمع عن حالات محددة تؤيد الرأي القائل بأن ضوابط التصدير تقيد الاستخدامات السلمية للطاقة النووية.'

src_sent0='Her delegation echoed calls by other delegations on the importance of including suitable wording on a nuclear-weapon-free zone in the Middle East.'
trg_sent0='وقالت إن وفد بلدها يكرر نداءات الوفود الأخرى بشأن أهمية إدراج صيغة مناسبة بشأن إنشاء منطقة خالية من الأسلحة النووية في الشرق الأوسط.'
walign_obj=walign(src_sent1,trg_sent1,retr_params)
print(src_sent1)
print(trg_sent1)

src: 22 trg: 29 elapsed: 2.2115
finished matching words and phrases: 15.283461809158325
epoch0 0
finished processing SE, new_el_counter: 505
finished processing NE, new_el_counter: 672
full_el ((0, 39), (0, 41)) cur_full_wt 5.894223582822251
epoch0 1
finished processing SE, new_el_counter: 716
finished processing NE, new_el_counter: 1075
full_el ((0, 39), (0, 41)) cur_full_wt 6.97697024115995
epoch0 2
finished processing SE, new_el_counter: 546
finished processing NE, new_el_counter: 722
full_el ((0, 39), (0, 41)) cur_full_wt 7.368244665737796
epoch0 3
finished processing SE, new_el_counter: 167
finished processing NE, new_el_counter: 185
full_el ((0, 39), (0, 41)) cur_full_wt 7.527105428247841
epoch0 4
finished processing SE, new_el_counter: 26
finished processing NE, new_el_counter: 29
full_el ((0, 39), (0, 41)) cur_full_wt 7.527105428247841
>>> (0, 0) ['<s>']
>>> (0, 0) ['<s>']
----
>>> (1, 1) ['Having']
>>> (7, 8) ['بعد', 'أن']
----
>>> (2, 2) ['listened']
>>> (9, 9) ['استمع']
----

In [ ]:
def split_path_chunks(path_list0,skip_last=True):
  path_chunks0=[]
  if skip_last: last_i0,last_i1=len(path_list0)-2,len(path_list0)-1
  else: last_i0,last_i1=len(path_list0)-1,len(path_list0)
  for path_i0 in range(last_i0):
    for path_i1 in range(path_i0+1,last_i1):
      cur_chunk=path_list0[path_i0:path_i1+1]
      path_chunks0.append(cur_chunk)
  return path_chunks0

cur_list=["a","b","c","d","0"]
ch_list=split_path_chunks(cur_list,False)
for a in ch_list:
  print(a)

['a', 'b']
['a', 'b', 'c']
['a', 'b', 'c', 'd']
['a', 'b', 'c', 'd', '0']
['b', 'c']
['b', 'c', 'd']
['b', 'c', 'd', '0']
['c', 'd']
['c', 'd', '0']
['d', '0']


In [ ]:
def djk(pt0,pt1,transition_dict0,pt_list0=None):
  path_wt_dict0={}
  prev_dict0={}
  if pt_list0==None: pt_list0=list(transition_dict0.keys())
  for cur_pt in pt_list0:
    following_dict0=transition_dict0.get(cur_pt,{})
    found_cur_path_wt=path_wt_dict0.get(cur_pt,0)
    for next_pt,next_wt in following_dict0.items():
      combined_wt=found_cur_path_wt+next_wt
      found_next_wt=path_wt_dict0.get(next_pt,0)
      if combined_wt>found_next_wt:
        path_wt_dict0[next_pt]=combined_wt
        prev_dict0[next_pt]=cur_pt
  cur_pt=pt1
  out_path=[]
  while cur_pt!=None:
    out_path.append(cur_pt)
    if cur_pt==pt0: break
    cur_pt=prev_dict0.get(cur_pt)
  out_path=list(reversed(out_path))
  return out_path, path_wt_dict0.get(pt1)

transition_dict1={}
transition_dict1["0"]={"a":0.1,"b":0.1}
transition_dict1["a"]={"b":0.1,"c":0.1,"d":0.2,"e":0.9}
transition_dict1["b"]={"c":0.1,"d":0.1,"e":0.1}
transition_dict1["c"]={"d":0.5,"e":0.9}
transition_dict1["d"]={"e":0.4}

#path,wt=djk("a","e",transition_dict1,pt_list0=["a","c","e"])
path,wt=djk("0","d",transition_dict1)
print("path",path,wt)

path ['0', 'a', 'b', 'c', 'd'] 0.8


In [ ]:
#actual class - OLD


# class walign_cls:
#   def __init__(self,src_sent0,trg_sent0,retr_align_params0={},filter_params0={}) -> None:
#     #first - load parameters and adjust tokenization and location info
#     #self.retr_align_params=retr_align_params0
#     lang1=retr_align_params0.get("lang1","en")
#     lang2=retr_align_params0.get("lang2","ar")
#     exclude_numbers=retr_align_params0.get("exclude_numbers",False)
#     max_phrase_len=retr_align_params0.get("max_phrase_len",8) #when we get the phrases from a sentence
#     max_phrase_dist=retr_align_params0.get("max_phrase_dist",10) #maximum distance when combining two phrases
#     lang2_tok_fn=retr_align_params0.get("lang2_tok_fn")
#     punc_pairs0=retr_align_params0.get("punc_pairs",{}) 
#     self.src_tokens=tok(src_sent0)
#     if lang2=="ar" and lang2_tok_fn!=None: self.trg_tokens=lang2_tok_fn(trg_sent0)
#     else: self.trg_tokens=tok(trg_sent0)
#     self.src_tokens_filtered=filter_toks(self.src_tokens,filter_params0)
#     self.trg_tokens_filtered=filter_toks(self.trg_tokens,filter_params0) #need to make filter_tokens > OLD
#     self.unique_src_tokens=list(set([v for v in self.src_tokens_filtered if v!=""]))
#     self.unique_trg_tokens=list(set([v for v in self.trg_tokens_filtered if v!=""]))
#     self.src_tokens_padded=["<s>"]+self.src_tokens+["</s>"] #filter_toks(self.src_tokens,filter_params0)
#     self.trg_tokens_padded=["<s>"]+self.trg_tokens+["</s>"]
#     self.src_tok_loc_dict=get_unigram_locs(self.src_tokens_padded)
#     self.trg_tok_loc_dict=get_unigram_locs(self.trg_tokens_padded)
#     self.src_tokens_filtered_padded=["<s>"]+self.src_tokens_filtered+["</s>"] #main list to be aligned
#     self.trg_tokens_filtered_padded=["<s>"]+self.trg_tokens_filtered+["</s>"]

#     #Now we load the indexes for our tokens
#     t0=time.time()
#     self.src_index_dict,self.trg_index_dict={},{}
#     src_retr_dict={}
#     for ut in self.unique_src_tokens: 
#       if ut.isdigit() and exclude_numbers: continue
#       self.src_index_dict[ut]=get_word_indexes(ut,"src",retr_align_params0)
#     for ut in self.unique_trg_tokens: 
#       if ut.isdigit() and exclude_numbers: continue
#       self.trg_index_dict[ut]=get_word_indexes(ut,"trg",retr_align_params0)
#     elapsed=time.time()-t0
#     print("src:",len(self.unique_src_tokens),"trg:",len(self.unique_trg_tokens),"elapsed:",round(elapsed,4))
#     #print("now mtaching src -trg tokens/phrases")
#     #Now we start the matching between src/trg tokens
#     t0=time.time()

#     src_output=get_phrase_locs_indexes(self.src_tokens_filtered_padded,self.src_index_dict,max_phrase_len)
#     trg_output=get_phrase_locs_indexes(self.trg_tokens_filtered_padded,self.trg_index_dict,max_phrase_len)
#     matching_list=[]
#     phrase_count_src_dict,phrase_count_trg_dict={},{} #how many instances of each src/trg phrases
#     for src_phrase_str,src_indexes_locs in src_output.items(): phrase_count_src_dict[src_phrase_str]=len(src_indexes_locs[0])
#     for trg_phrase_str,trg_indexes_locs in trg_output.items(): phrase_count_trg_dict[trg_phrase_str]=len(trg_indexes_locs[0])

#     for src_phrase_str,src_indexes_locs in src_output.items():
#       src_locs0,src_indexes0=src_indexes_locs
#       for trg_phrase_str,trg_indexes_locs in trg_output.items():
#         trg_locs0,trg_indexes0=trg_indexes_locs
#         if src_phrase_str==trg_phrase_str: ratio1,intersection1=1., 1000
#         else: ratio1,intersection1=get_index_match_ratio_count(src_indexes0,trg_indexes0)
#         min_locs_count=min(len(src_locs0),len(trg_locs0)) #we subtract from the number of locs of each phrase the minimum
        
#         if ratio1==0: continue
#         matching_list.append((src_phrase_str,trg_phrase_str,src_locs0,trg_locs0,min_locs_count,intersection1,ratio1))

#     matching_list.sort(key=lambda x:-x[-1])
#     new_matching_list=[]
#     for ml in matching_list:
#       src_phrase_str,trg_phrase_str,src_locs0,trg_locs0,min_locs_count,intersection1,ratio1=ml
#       if phrase_count_src_dict[src_phrase_str]>0 or phrase_count_trg_dict[trg_phrase_str]>0:
#         new_matching_list.append((src_phrase_str,trg_phrase_str,src_locs0,trg_locs0,intersection1,ratio1))
#       phrase_count_src_dict[src_phrase_str]=phrase_count_src_dict[src_phrase_str]-min_locs_count #subtract the minimum count of instances from both src and trg
#       phrase_count_trg_dict[trg_phrase_str]=phrase_count_trg_dict[trg_phrase_str]-min_locs_count
    
#     for src_punc0,trg_punc0 in punc_pairs0.items(): #now let's match punctuation from the original tokens
#       punc_src_locs=self.src_tok_loc_dict.get(src_punc0,[])
#       if punc_src_locs==[]: continue
#       punc_trg_locs=self.trg_tok_loc_dict.get(trg_punc0,[])
#       if punc_trg_locs==[]: continue
#       ratio1,intersection1=0.2, 100
#       src_punc0,trg_punc0=tuple([src_punc0]),tuple([trg_punc0])
#       punc_src_locs=[[v] for v in punc_src_locs]
#       punc_trg_locs=[[v] for v in punc_trg_locs]
#       new_matching_list.append((src_punc0,trg_punc0,punc_src_locs,punc_trg_locs,intersection1,ratio1))

#     new_matching_list.sort(key=lambda x:-x[-1])
#     elapsed=time.time()-t0
#     print("finished matching words and phrases:", elapsed)
#     #Now we have the matching list - let's align
#     el_dict={}
#     for a in new_matching_list:
#       src_phrase_str,trg_phrase_str,src_locs0,trg_locs0,intersection1,ratio1=a
#       for sl0 in src_locs0:
#         s_min,s_max=sl0[0],sl0[-1]
#         for tl0 in trg_locs0:
#           t_min,t_max=tl0[0],tl0[-1]
#           el0=((s_min,s_max) ,(t_min,t_max))
#           el_dict[el0]=ratio1
    
#     used_el_pairs={}
#     child_dict={}
#     top_wt=0
#     full_src_span0=(0,len(self.src_tokens_filtered_padded)-1)
#     full_trg_span0=(0,len(self.trg_tokens_filtered_padded)-1)
#     full_el=(full_src_span0,full_trg_span0)
#     for epoch0 in range(20):
#       print("epoch0",epoch0)
#       all_elements=list(el_dict.items())
#       all_elements.sort()
#       for el_i,el_item0 in enumerate(all_elements):
#         el0,el_wt0=el_item0
#         src_span0,trg_span0=el0
#         for el_item1 in all_elements[el_i+1:]:
#           if used_el_pairs.get((el_item0,el_item1),False): continue
#           el1,el_wt1=el_item1
#           el_pair_key=(el0,el1)
#           src_span1,trg_span1=el1
#           if src_span0==src_span1 or trg_span0==trg_span1: continue
#           #if src_span1[0]<=src_span0[1]: continue
#           src_span_dist=get_span_dist(src_span0,src_span1)
#           trg_span_dist=get_span_dist(trg_span0,trg_span1)
#           if trg_span_dist<1 or src_span_dist<1: continue
#           if src_span_dist> max_phrase_dist: continue
#           used_el_pairs[(el_item0,el_item1)]=True
#           combined_el=combine_els(el0,el1)
#           combined_wt=el_wt0+el_wt1
#           found_wt=el_dict.get(combined_el,0)
#           if combined_wt>found_wt:
#             el_dict[combined_el]=combined_wt
#             child_dict[combined_el]=(el0,el1)
#         #print("----")
#       cur_full_wt=el_dict.get(full_el,0)
#       print("full_el",full_el,"cur_full_wt",cur_full_wt)
#       if cur_full_wt>0 and cur_full_wt==top_wt: break
#       top_wt=cur_full_wt
#     if cur_full_wt>0:
#       align_list=get_rec_el_children(full_el,child_dict,el_list0=[])
#     else:
#       wt_list=list(el_dict.items())
#       wt_list.sort(key=lambda x:-x[1])
#       top_el=wt_list[0][0]
#       print("couldn't find full el:",full_el, "used the top el instead", top_el)
#       align_list=get_rec_el_children(top_el,child_dict,el_list0=[])
#     for s_al,t_al in align_list:
#       print(">>>", s_al, self.src_tokens_padded[s_al[0]:s_al[1]+1])
#       print(">>>", t_al, self.trg_tokens_padded[t_al[0]:t_al[1]+1])
#       print("----")


NameError: ignored

In [ ]:
def get_unigram_locs(tok_list0):
  enum_list=[(v,i) for i,v in enumerate(tok_list0)]
  enum_list.sort()
  grouped=[(key,[v[1] for v in list(group)]) for key,group in groupby(enum_list,lambda x:x[0])]
  loc_dict0=dict(iter(grouped))
  return loc_dict0

sent="this is, indeed, what I thought. But this is not, at all, everything I wanted."
toks1=tok(sent)
out=get_unigram_locs(toks1)
print(toks1)
print(out)

['this', 'is', ',', 'indeed', ',', 'what', 'I', 'thought', '.', 'But', 'this', 'is', 'not', ',', 'at', 'all', ',', 'everything', 'I', 'wanted', '.']
{',': [2, 4, 13, 16], '.': [8, 20], 'But': [9], 'I': [6, 18], 'all': [15], 'at': [14], 'everything': [17], 'indeed': [3], 'is': [1, 11], 'not': [12], 'this': [0, 10], 'thought': [7], 'wanted': [19], 'what': [5]}


#OLD - Retrieve sentence - 1-Nov-2022

In [ ]:
import json
index_dir="indexes/un/exp2"
params_fpath=os.path.join(index_dir,"params.json")
with open(params_fpath) as params_fopen:
  filter_params=json.load(params_fopen) #token filtering parameteres
print(filter_params)

en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"




# for a in tokens1:
#   print(a)
#print(tokens1)
def get_phrase_locs(tokens0): #identify locations of phrases of content words - excluding empty string/filtered tokens
  content_words_locs=[w_i for w_i,wd0 in enumerate(tokens0) if wd0!=""]
  all_phrases0=[]
  for ii0,cur_loc0 in enumerate(content_words_locs):
    cur_phrase=[cur_loc0]
    all_phrases0.append(list(cur_phrase))
    next_locs=content_words_locs[ii0+1:]
    for nl in next_locs:
      cur_phrase+=[nl]
      all_phrases0.append(list(cur_phrase))
  all_phrase_locs_str=[]
  for ap0 in all_phrases0:
    phrase_tokens=tokens0[ap0[0]:ap0[-1]+1]
    all_phrase_locs_str.append((tuple(phrase_tokens),ap0))
  return all_phrase_locs_str

def combine_phrase_locs(all_phrase_locs_str0):
  phrase_locs_str_sorted=sorted(all_phrase_locs_str0)
  combined_phrase_locs=[(key,[v[1] for v in list(group)]) for key,group in groupby(phrase_locs_str_sorted,lambda x:x[0])]
  phrase_locs_dict0=dict(iter(combined_phrase_locs)) # key: phrase token strings > vals: corresponding locations
  return phrase_locs_dict0


def get_phrase_locs_indexes(tokens0,res_dict0): 
  all_phrases_locs_str=get_phrase_locs(tokens0) #get the geometric listing of all possible phrases made of content words
  phrase_locs_dict=combine_phrase_locs(all_phrases_locs_str)

  all_phrases_locs_str.sort(key=lambda x:len(x[1])) #sort them by size
  phrase_result_dict={} #we put the results in a dictionary, where the keys are the phrase string, and the values are the index/results with proper offset
  for phrase_tokens,phrase0 in all_phrases_locs_str:
    found_phrase_indexes=phrase_result_dict.get(phrase_tokens) #check if this phrase was found in previous iterations
    if found_phrase_indexes!=None: #if it was found, we skip to the next
      #print("found already", phrase_tokens)
      continue
    #print(phrase_tokens,phrase0)
    prev_tokens=[] #to check if the phrase is just a single token or not
    last_item,prev_items=phrase0[-1],phrase0[:-1] #we need to get the location of the last token
    if len(prev_items)>0: prev_tokens=tokens0[prev_items[0]:prev_items[-1]+1] #if the phrase has multiple tokens, identify previous tokens // the ones before the last token
    first_item=phrase0[0] #the location of the first token
    last_word=tokens0[last_item] #the string of the last token
    last_offset=last_item-first_item #the offset of the last token (location of last token minus location of first token)
    cur_word_indexes=res_dict0.get(last_word,{})  #now retrieve the indexes for each word
    cur_offset_indexes=offset_results(cur_word_indexes,last_offset) #offset the indexes according to the current offset
    found_prev_tokens_index_dict=phrase_result_dict.get(tuple(prev_tokens),{}) #check if previous tokens in the phrase have indexes that were found already
    if len(prev_items)>0 and found_prev_tokens_index_dict=={}: continue #if there are previous tokens, but no indexes found for them - NEED TO CHECK
    if prev_items!=[]: 
      cur_offset_indexes=get_index_intersection(found_prev_tokens_index_dict,cur_offset_indexes) #If there are previous tokens and indexes, find the intersection -ALSO CHECK THIS
    phrase_result_dict[phrase_tokens]=cur_offset_indexes
  new_dict={}
  for a,b in phrase_locs_dict.items():
    new_dict[a]=[b,phrase_result_dict.get(a,{})]
    
  return new_dict

  # for a,phrase_results0 in phrase_result_dict.items():
  #   #print(a,b.keys())
  #   combined_results=count_results(phrase_results0)
  #   phrase_str=" ".join(a)
  #   print(phrase_str, n_results)
  #   print("---")
  #   t1=time.time()
  #   lines=get_result_lines(phrase_results0,en_ar_corpus_combined_fname,n_results1=5)
  #   elapsed2=time.time()-t1
  #   print("elapsed2",round(elapsed2,4))
  #   for a in lines:
  #     print(">>>",phrase_str)
  #     src,trg=a[:2]
  #     print(src)
  #     print(trg)
  #     print("----")  
  #   print("==========")


retr_params={} #retrieval parameters
retr_params["index_dir"]="indexes/un/exp2"
retr_params["meta_suffix"]="meta2"
retr_params["max_n_index_files"]=10

sent='The Regular Process is in its third cycle (2021–2025), with the first and second World Ocean Assessments published in 2016 and 2021, respectively.'
#sent='The Regular Process is in its third cycle'
sent='Contribution made by Sustainable Development Goal 14 to achieving other Goals'
sent='Statements were made by the representatives of 25 States and statements were also made by others'
tokens=tok(sent)
print("tokens",tokens)
tokens1=filter_toks(tokens,filter_params) #need to make filter_tokens > OLD
print(tokens1)
unique_tokens=list(set([v for v in tokens1 if v!=""]))
src_retr_dict={}
for ut in unique_tokens:
  print(ut)
  src_retr_dict[ut]=get_word_indexes(ut,"src",retr_params)

tokens1=["<s>"]+tokens1+["</s>"]

# phrase_locs_str=get_phrase_locs(tokens1)
# phrase_locs_str_sorted=sorted(phrase_locs_str)
# combined_phrase_locs=[(key,[v[1] for v in list(group)]) for key,group in groupby(phrase_locs_str_sorted,lambda x:x[0])]
# for phrase_str,indexes_locs in combined_phrase_locs:
#   indexes0,locs0=b
#   listed_results=list_results(indexes0)
#   print(phrase_str)
#   print(locs0)
#   print(len(listed_results),listed_results[:5])
#   print("------")


output=get_phrase_locs_indexes(tokens1,src_retr_dict)
for phrase_str,indexes_locs in output.items():
  locs0,indexes0=indexes_locs
  #print("indexes0",indexes0)
  listed_results=list_results(indexes0)
  if len(listed_results)==0: continue
  print(phrase_str)
  print(locs0)
  print(len(listed_results),listed_results[:5])
  print("------")
  lines=get_result_lines(indexes0,en_ar_corpus_combined_fname,n_results1=3)
  # elapsed2=time.time()-t1
  # print("elapsed2",round(elapsed2,4))
  for a in lines:
    #print(">>>",phrase_str)
    src,trg=a[:2]
    print(src)
    print(trg)
    print("----")  
  print("==========")


# all_phrases=get_phrase_locs(tokens1)
# all_phrases.sort(key=lambda x:len(x))
# phrase_result_dict={}
# for phrase0 in all_phrases:
#   phrase_tokens=tokens1[phrase0[0]:phrase0[-1]+1]
#   prev_tokens=[]
#   last_item,prev_items=phrase0[-1],phrase0[:-1]
#   if len(prev_items)>0: prev_tokens=tokens1[prev_items[0]:prev_items[-1]+1]
#   last_word=tokens1[last_item]
#   cur_word_indexes=src_retr_dict.get(last_word,{}) 
#   cur_offset_indexes=offset_results(cur_word_indexes,last_item)
#   found_prev_tokens_index_dict=phrase_result_dict.get(tuple(prev_tokens),{})
#   if len(prev_items)>0 and found_prev_tokens_index_dict=={}: continue
#   if prev_items!=[]: 
#     cur_offset_indexes=get_index_intersection(found_prev_tokens_index_dict,cur_offset_indexes)
#   cur_count0=count_results(cur_offset_indexes)
#   if cur_count0>0: phrase_result_dict[tuple(phrase_tokens)]=cur_offset_indexes

# for a,phrase_results0 in phrase_result_dict.items():
#   #print(a,b.keys())
#   combined_results=count_results(phrase_results0)
#   phrase_str=" ".join(a)
#   print(phrase_str, n_results)
#   print("---")
#   t1=time.time()
#   lines=get_result_lines(phrase_results0,en_ar_corpus_combined_fname,n_results1=5)
#   elapsed2=time.time()-t1
#   print("elapsed2",round(elapsed2,4))
#   for a in lines:
#     print(">>>",phrase_str)
#     src,trg=a[:2]
#     print(src)
#     print(trg)
#     print("----")  
#   print("==========")



# for ii0,cur_loc0 in enumerate(content_words_locs):
#   next_locs=content_words_locs[ii0+1:]
#   print(cur_loc0, next_locs)
#   for ii1,next_loc0 in enumerate(next_locs):
#     print(content_words_locs[ii0:ii0+ii1+1], next_loc0)
  





{'excluded_words': ['the', 'a', 'an', 'and', 'of', 'its', 'his', 'her', 'their', 'them', 'to', 'is', 'are', 'am', 'been', 'have', 'has', 'had', 'in', 'on', 'at', 'with', 'from', 'for', 'that', 'he', 'she', 'it', 'would', 'من', 'على', 'في', 'مع', 'إلى', 'له', 'تم', 'إلى', 'في'], 'max_sent_n_tokens': 1000, 'lang1': 'en', 'lang2': 'ar', 'exclude_single_chars': True, 'batch_size': 250000, 'min_n_indexes_per_token': 3}
tokens ['Statements', 'were', 'made', 'by', 'the', 'representatives', 'of', '25', 'States', 'and', 'statements', 'were', 'also', 'made', 'by', 'others']
['statements', 'were', 'made', 'by', '', 'representatives', '', '25', 'states', '', 'statements', 'were', 'also', 'made', 'by', 'others']
statements
25
states
made
also
were
others
by
representatives
('25',)
[[8]]
14711 [794.006, 1115.016, 154074.011, 220431.009, 252545.006]
------
25/ KPMG, "Cross-border M & A recovers", op. cit.
)25( KPMG, "Cross-border M & A recovers", op.
----
25/ UNCTC, Foreign Direct Investment and Indu

In [ ]:
#!python retrieve-full.py
!chmod 777 ./pypy3.9-v7.3.9-linux64/bin/pypy
!./pypy3.9-v7.3.9-linux64/bin/pypy retrieve-full.py

{'excluded_words': ['the', 'a', 'an', 'and', 'of', 'its', 'his', 'her', 'their', 'them', 'to', 'is', 'are', 'am', 'been', 'was', 'were', 'be', 'have', 'has', 'had', 'in', 'on', 'at', 'with', 'from', 'for', 'that', 'he', 'she', 'it', 'would', 'من', 'على', 'في', 'مع', 'إلى', 'له', 'تم', 'إلى', 'في'], 'max_sent_n_tokens': 1000, 'lang1': 'en', 'lang2': 'ar', 'exclude_single_chars': True, 'batch_size': 250000, 'min_n_indexes_per_token': 3}
src: 15 trg: 20 elapsed: 8.5834
now mtaching src -trg tokens/phrases
(('await', '', 'report'), ('أن',), 6.0339833944776985e-06)
(('reflected', '', '', 'committee'), ('أن',), 1.2068112426535365e-05)
(('committee', '', 'final'), ('لجنة',), 1.7494751574527642e-05)
(('committee', '', 'final', 'report'), ('لجنة',), 1.7494751574527642e-05)
(('reflected', '', '', 'committee'), ('هذا',), 2.183263105036788e-05)
(('such', '', 'zone'), ('أن',), 2.4135351048681e-05)
(('such', '', 'zone'), ('إن',), 2.5555186425084973e-05)
(('reflected', '', '', 'committee'), ('إن',), 

In [ ]:
!python retrieve-full.py

{'excluded_words': ['the', 'a', 'an', 'and', 'of', 'its', 'his', 'her', 'their', 'them', 'to', 'is', 'are', 'am', 'been', 'was', 'were', 'be', 'have', 'has', 'had', 'in', 'on', 'at', 'with', 'from', 'for', 'that', 'he', 'she', 'it', 'would', 'من', 'على', 'في', 'مع', 'إلى', 'له', 'تم', 'إلى', 'في'], 'max_sent_n_tokens': 1000, 'lang1': 'en', 'lang2': 'ar', 'exclude_single_chars': True, 'batch_size': 250000, 'min_n_indexes_per_token': 3}
src: 15 trg: 20 elapsed: 1.1892
now mtaching src -trg tokens/phrases
(('await', '', 'report'), ('أن',), 6.0339833944776985e-06)
(('reflected', '', '', 'committee'), ('أن',), 1.2068112426535365e-05)
(('committee', '', 'final'), ('لجنة',), 1.7494751574527642e-05)
(('committee', '', 'final', 'report'), ('لجنة',), 1.7494751574527642e-05)
(('reflected', '', '', 'committee'), ('هذا',), 2.183263105036788e-05)
(('such', '', 'zone'), ('أن',), 2.4135351048681e-05)
(('such', '', 'zone'), ('إن',), 2.5555186425084973e-05)
(('reflected', '', '', 'committee'), ('إن',), 

In [ ]:
# import time, json
# index_dir="indexes/un/exp2"
# en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"
# def go2line(fpath0,loc0,size0=None):
#   fopen0=open(fpath0)
#   fopen0.seek(loc0)
#   #line0=fopen0.readline()
#   if size0!=None: line0=fopen0.read(size0)
#   else: line0=fopen0.readline()
#   line0=line0.split("\n")[0]
#   fopen0.close()
#   return line0

# def get_word_indexes(word1,index_prefix1,index_dir1,meta_suffix1="meta2",max_n_index_files=50):
#   cur_meta_shelve_path=os.path.join(index_dir1,"%s-%s.shelve"%(prefix,meta_suffix1))
#   cur_meta_shelve_open=shelve.open(cur_meta_shelve_path)
#   cur_meta_found=cur_meta_shelve_open.get(word1,{})
#   result_dict={}
#   n_results=0
#   elapsed_list=[]
#   t0=time.time()
#   meta_index_items=list(cur_meta_found.items())
#   for index_id,index_loc in meta_index_items[:max_n_index_files]:
#     cur_loc0,cur_size0=index_loc
#     cur_txt_fpath=os.path.join(index_dir1,"%s-%s.txt"%(index_prefix1,index_id)) 
#     cur_meta_line=go2line(cur_txt_fpath,cur_loc0,cur_size0)
#     cur_raw_indexes_str=cur_meta_line.strip().split("\t")[1]
#     cur_raw_indexes=json.loads(cur_raw_indexes_str)
#     result_dict[index_id]=cur_raw_indexes
#     n_results+=len(cur_raw_indexes)
#   result_dict["n"]=n_results
#   return result_dict
#     # elapsed2=time.time()-t1
#     # elapsed_list.append((cur_txt_fpath,len(cur_raw_indexes),round(elapsed,4),"elapsed2",round(elapsed2,4)))
#     # t0=time.time()
#     # t1=time.time()


# # word1="يحاول"
# # prefix="trg"

# word1="associated"
# prefix="src"
# # src_meta_shelve_fpath=os.path.join(index_dir,"src-meta1.shelve")
# # trg_meta_shelve_fpath=os.path.join(index_dir,"trg-meta1.shelve")
# # # src_meta_shelve_fpath=os.path.join(index_dir,"src-meta.shelve")
# # # trg_meta_shelve_fpath=os.path.join(index_dir,"trg-meta.shelve")

# # src_meta_shelve_open=shelve.open(src_meta_shelve_fpath)
# # trg_meta_shelve_open=shelve.open(trg_meta_shelve_fpath)

# cur_meta_shelve_path=os.path.join(index_dir,"%s-meta2.shelve"%prefix)
# cur_meta_shelve_open=shelve.open(cur_meta_shelve_path)


# #src_meta_found=src_meta_shelve_open.get(word1,{})
# cur_meta_found=cur_meta_shelve_open.get(word1,{})
# print(cur_meta_found)
# result_dict={}
# n_results=0
# elapsed_list=[]
# t0=time.time()
# #for index_id,index_loc in src_meta_found.items():
# print("retrieving meta indexes")
# meta_index_items=list(cur_meta_found.items())
# for index_id,index_loc in meta_index_items[:50]:
#   cur_loc0,cur_size1=index_loc
#   #print(index_id,index_loc)
#   cur_txt_fpath=os.path.join(index_dir,"%s-%s.txt"%(prefix,index_id)) 
#   cur_meta_line=go2line(cur_txt_fpath,cur_loc0,cur_size1)

#   elapsed=time.time()-t0
#   t0=time.time()
#   t1=time.time()

#   cur_raw_indexes_str=cur_meta_line.strip().split("\t")[1]
#   cur_raw_indexes=json.loads(cur_raw_indexes_str)
#   result_dict[index_id]=cur_raw_indexes
#   n_results+=len(cur_raw_indexes)
#   elapsed2=time.time()-t1
#   elapsed_list.append((cur_txt_fpath,len(cur_raw_indexes),round(elapsed,4),"elapsed2",round(elapsed2,4)))
#   t0=time.time()
#   t1=time.time()

#   #print(cur_line)

# for el in elapsed_list:
#   print(el)
# print("n_results",n_results)
# final_results=[]
# for index_id,indexes0 in result_dict.items():
#   for ind0 in indexes0[:50]:
#     final_results.append((index_id,ind0))

# final_results.sort(key=lambda x:x[-1]-int(x[-1]))
# for res0 in final_results[:20]:
#   #index_id,ind0,src0,trg0=res0
#   index_id,ind0=res0
#   cur_line0=go2line(en_ar_corpus_combined_fname,int(ind0))
#   src0,trg0=cur_line0.strip().split("\t")  
#   print(index_id)
#   print(ind0)
#   print(src0)
#   print(trg0)
#   print("=============")

# # src_meta_shelve_open.close()
# # trg_meta_shelve_open.close()

# cur_meta_shelve_open.close()


In [ ]:
cur_meta_line

'strive\t[193757760.016, 194033638.046, 195467981.035, 195947014.004, 196053535.011, 196124083.004, 196442913.013, 196444654.013, 197038348.011, 197275843.012, 197355076.053, 198460496.019, 198971034.002, 199012841.01, 199249043.002, 199528309.016, 200228593.002, 201012690.027, 201066332.01, 201128574.012, 201418719.023, 201663728.004, 201977086.008, 203032874.004, 203141216.003, 203527800.004, 203616437.036, 203675639.029, 203776199.044, 204181112.012, 204704173.027, 205203725.074, 205429542.002, 205670254.004, 206138414.013, 206166143.014, 207529492.005, 207785332.012, 207813930.002, 208640226.01, 208643630.014, 211082892.002, 211221058.009, 212237911.017, 212346694.006, 214195584.01, 214766192.008, 216413899.01, 216603699.01, 217324793.006, 220697158.004, 221063736.008, 221381790.008, 221605242.019, 222251009.019, 223521502.016, 223666528.011, 224246850.011, 224646277.01, 225120636.004, 225235082.013, 225929521.024, 226679392.021, 227508747.005, 227784334.004, 227907520.007, 2282249

In [ ]:
loc,size=(2000060, 143881)
#indexes/un/exp2/trg-1000000.txt 31374060 143881
t0=time.time()
fopen=open('indexes/un/exp2/trg-8000000.txt',"r")
fopen.seek(loc)
elapsed1=time.time()-t0
#line0=fopen.readline()
t1=time.time()
#line0=fopen.read(1500)
line0=fopen.readline()
#line0=fopen.readable()
elapsed2=time.time()-t1
fopen.close()
elapsed=time.time()-t0
print("elapsed2",round(elapsed2,4))
#print("elapsed1",round(elapsed1,4), "elapsed",round(elapsed,4),"elapsed2",round(elapsed2,4))
print(line0)

elapsed2 0.0058
.0, 3089484747.0, 3089497480.0, 3090260310.0, 3090543473.0, 3090570775.0, 3090602901.0, 3097994799.0, 3099767982.002, 3100424987.0, 3101687175.0, 3102794931.0, 3104508507.02, 3105288064.0, 3105302876.012, 3109732376.001, 3109833320.024, 3113908363.002, 3118960535.0, 3120778671.002, 3122309964.0, 3123153492.015, 3123998217.0, 3124133360.0, 3124270994.0, 3124295833.0, 3124341351.0, 3124363501.0, 3124370295.0, 3124376345.0, 3124470885.0, 3124480897.0, 3124492758.0, 3124521782.0, 3124575691.0, 3124620941.0, 3124699506.0, 3127049711.0, 3127057068.003, 3127590328.0, 3127598557.003, 3127791439.0, 3127804697.003, 3128142220.0, 3130580272.0]



In [ ]:
!tail -50 indexes/un/exp2/src-17000000.txt
fpath='UNv1.0.en-ar-combined.txt'
fopen=open(fpath)
fopen.seek(7335429745)
fopen.seek(6772369758)

line=fopen.readline()
fopen.close()
print(">>> line:", line)

zerrougui's	[6770623081.007, 6770625635.005, 6770626601.028, 6770678966.012, 6770679473.015, 6770694882.01, 6770713382.028, 6770713796.016, 6770715900.017, 6770716405.1, 6770718769.004, 6770721053.005, 6770723215.034]
zeyad	[6773280361.003, 6773283717.016, 6773284763.007, 6773290992.033, 6773312224.057, 6773326591.031]
zeydulla	[6772369758.003, 6772373237.016, 6772374254.007]
zfns	[6756340178.056, 6756341756.006, 6756428599.056, 6756430216.006]
zhang	[6672990318.001, 6675447682.002, 6676228619.002, 6676634522.002, 6676738713.002, 6678563929.002, 6678969186.002, 6684981481.0, 6685022241.012, 6685022769.001, 6685752053.014, 6713586327.001, 6767605704.002, 6767676965.001]
zhangshi	[6762624457.015, 6762645025.015, 6762667308.034]
zhanna	[6769020395.003, 6769023397.016, 6769024405.007]
zhao	[6670350562.002, 6680578568.001, 6680596608.001, 6681579483.002, 6696763730.001, 6696794336.001, 6696798679.001, 6696808951.002]
zheglov	[6675825834.002, 6676131023.002, 6676273071.002, 6676447241.002]
z

In [ ]:
# #preparing index shelves
# import shelve, json, time
# en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"
# index_dir="indexes/un/exp2"
# if not os.path.exists(index_dir): os.makedirs(index_dir)

# max_sent_n_tokens=1000
# lang1="en"
# lang2="ar"

# cur_params={}
# cur_params["excluded_words"]=excluded_src_tokens+excluded_trg_tokens
# cur_params["max_sent_n_tokens"]=max_sent_n_tokens
# cur_params["lang1"]=lang1
# cur_params["lang2"]=lang2
# cur_params["exclude_single_chars"]=True
# params_fpath=os.path.join(index_dir,"params.json")
# params_fopen=open(params_fpath,"w")
# json.dump(cur_params,params_fopen)
# params_fopen.close()

# index_list_fpath=os.path.join(index_dir,"index-list.txt")
# last_indexed=None
# if os.path.exists(index_list_fpath):
#   index_list_fopen=open(index_list_fpath)
#   index_list_lines=[v.strip() for v in index_list_fopen.readlines()]
#   index_list_fopen.close()
#   if len(index_list_lines)>0: last_indexed=int(index_list_lines[-1])

# print("last_indexed",last_indexed)

# fopen=open(en_ar_corpus_combined_fname)
# cur_loc=0
# cur_line="-"
# counter=0
# src_fwd_index0,trg_fwd_index0=[],[]
# t0=time.time()
# while cur_line!="":
# #for i0,f0 in enumerate(fopen):
# #for i0 in range(10):  
#   #if counter>100: break

#   cur_loc=fopen.tell()
#   f0=fopen.readline()
  
#   counter+=1

#   #if counter>1000000: break
#   if (counter%50000==0 and counter>0) or f0=="": 
#     print(counter)
    
#     #continue
#     cur_src_shelve_fpath=os.path.join(index_dir,"src-%s.shelve"%counter) 
#     cur_trg_shelve_fpath=os.path.join(index_dir,"trg-%s.shelve"%counter)
#     if os.path.exists(cur_src_shelve_fpath) and os.path.exists(cur_src_shelve_fpath):
#       src_fwd_index0,trg_fwd_index0=[],[]
#       #counter+=1
#       continue

#     src_fwd_index0.sort()
#     trg_fwd_index0.sort()
#     grouped_src=[(key,[v[1] for v in list(group)]) for key,group in groupby(src_fwd_index0,lambda x:x[0])]
#     grouped_trg=[(key,[v[1] for v in list(group)]) for key,group in groupby(trg_fwd_index0,lambda x:x[0])] 
#     cur_src_shelve_open=shelve.open(cur_src_shelve_fpath)
#     cur_trg_shelve_open=shelve.open(cur_trg_shelve_fpath)
#     for k0,grp0 in grouped_src: cur_src_shelve_open[k0]=grp0
#     for k0,grp0 in grouped_trg: cur_trg_shelve_open[k0]=grp0
#     cur_src_shelve_open.close()
#     cur_trg_shelve_open.close()
#     src_fwd_index0,trg_fwd_index0=[],[]
#     print("finished indexing:",cur_src_shelve_fpath,cur_trg_shelve_fpath, "elapsed:", time.time()-t0)
#     t0=time.time()
#     index_list_fopen=open(index_list_fpath,"a")
#     index_list_fopen.write("%s\n"%counter)
#     #index_list_fopen.write(json.dumps([cur_src_shelve_fpath,cur_trg_shelve_fpath])+"\n")
#     index_list_fopen.close()

#   if last_indexed!=None and counter<last_indexed: continue
#   cur_line=f0.strip("\n\r\t")
#   line_split=cur_line.split("\t")
#   if len(line_split)!=2: continue
#   src0,trg0=line_split
#   src_tokens0=tok(src0)#,tok(trg0)
#   if lang2=="ar":trg_tokens0=cur_ar_tok_fn(trg0)
#   else: trg_tokens0=tok(trg0)

#   #print(fopen.tell())
#   filtered_src0=filter_toks(src_tokens0,cur_params)
#   filtered_trg0=filter_toks(trg_tokens0,cur_params)
#   indexed_src0=[(v,cur_loc+vi/max_sent_n_tokens) for vi,v in enumerate(filtered_src0) if vi<max_sent_n_tokens and v!=""]
#   indexed_trg0=[(v,cur_loc+vi/max_sent_n_tokens) for vi,v in enumerate(filtered_trg0) if vi<max_sent_n_tokens and v!=""]
#   src_fwd_index0.extend(indexed_src0)
#   trg_fwd_index0.extend(indexed_trg0)
#   #counter+=1
#   #cur_loc+=len(f0)
# fopen.close()
# src_fwd_index0.sort()
# trg_fwd_index0.sort()
# # grouped_src=[(key,[v[1] for v in list(group)]) for key,group in groupby(src_fwd_index0,lambda x:x[0])]
# # grouped_trg=[(key,[v[1] for v in list(group)]) for key,group in groupby(trg_fwd_index0,lambda x:x[0])]

# # src_shelve_fpath="test-src.shelve"
# # src_shelve_fopen=shelve.open(src_shelve_fpath)
# # for k0,grp0 in grouped_src: src_shelve_fopen[k0]=grp0
# # src_shelve_fopen.close()
# # trg_shelve_fpath="test-trg.shelve"
# # trg_shelve_fopen=shelve.open(trg_shelve_fpath)
# # for k0,grp0 in grouped_trg: trg_shelve_fopen[k0]=grp0
# # trg_shelve_fopen.close()


# # print("src_fwd_index0",len(src_fwd_index0))
# # print("trg_fwd_index0",len(trg_fwd_index0))
# # print("grouped_src",len(grouped_src))
# # print("grouped_trg",len(grouped_trg))


last_indexed 17300000
50000
finished indexing: indexes/un/exp1/src-50000.shelve indexes/un/exp1/trg-50000.shelve elapsed: 6.691086530685425
100000
finished indexing: indexes/un/exp1/src-100000.shelve indexes/un/exp1/trg-100000.shelve elapsed: 5.057390928268433
150000
finished indexing: indexes/un/exp1/src-150000.shelve indexes/un/exp1/trg-150000.shelve elapsed: 4.746932506561279
200000
finished indexing: indexes/un/exp1/src-200000.shelve indexes/un/exp1/trg-200000.shelve elapsed: 4.8925981521606445
250000
finished indexing: indexes/un/exp1/src-250000.shelve indexes/un/exp1/trg-250000.shelve elapsed: 4.951043605804443
300000
finished indexing: indexes/un/exp1/src-300000.shelve indexes/un/exp1/trg-300000.shelve elapsed: 4.826070547103882
350000
finished indexing: indexes/un/exp1/src-350000.shelve indexes/un/exp1/trg-350000.shelve elapsed: 5.300532579421997
400000
finished indexing: indexes/un/exp1/src-400000.shelve indexes/un/exp1/trg-400000.shelve elapsed: 4.924514293670654
450000
finis

#Retrieving tokens and phrases - 27-Oct-2012
from multiple shelves sr/trg

In [ ]:
import shelve, json, time
en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"
index_dir="indexes/un/exp1"
index_list_fpath=os.path.join(index_dir,"index-list.txt")
index_list_lines=[]
if os.path.exists(index_list_fpath):
  index_list_fopen=open(index_list_fpath)
  index_list_lines=[v.strip() for v in index_list_fopen.readlines()]
  index_list_fopen.close()
index_list_lines=sorted(list(set(index_list_lines)),key=lambda x:int(x))
print("index_list_lines",index_list_lines)
combined_src_shelve_fpath=os.path.join(index_dir,"src-combined.shelve") 
combined_trg_shelve_fpath=os.path.join(index_dir,"trg-combined.shelve")
combined_src_shelve_fopen=shelve.open(combined_src_shelve_fpath)
combined_trg_shelve_fopen=shelve.open(combined_trg_shelve_fpath)

src_tok_counter,trg_tok_counter={},{}
shelve_src_trg_handles_dict={}
for item0 in index_list_lines[:5]:
  cur_src_shelve_fpath=os.path.join(index_dir,"src-%s.shelve"%item0) 
  cur_trg_shelve_fpath=os.path.join(index_dir,"trg-%s.shelve"%item0)
  print(item0)
  print(cur_src_shelve_fpath)
  print(cur_trg_shelve_fpath)
  cur_src_shelve_fopen=shelve.open(cur_src_shelve_fpath)
  cur_trg_shelve_fopen=shelve.open(cur_trg_shelve_fpath)
  for i0,key0 in enumerate(cur_src_shelve_fopen):
    vals=cur_src_shelve_fopen[key0]
    src_tok_counter[key0]=src_tok_counter.get(key0,0)+len(vals)
    #print(key0,len(vals),vals[:5])
    if i0>1000: break

  #shelve_src_trg_handles_dict[item0]=[cur_src_shelve_fopen,cur_trg_shelve_fopen]
  cur_src_shelve_fopen.close()
  cur_trg_shelve_fopen.close()

cur_items=list(src_tok_counter.items())
cur_items.sort(key=lambda x:-x[-1])
for a,b in cur_items[:200]:
  if b<5: continue
  if len(a)<2: continue
  print(a,b)
# print("opened shelve handles")
# for item0,shelve_handles0 in shelve_src_trg_handles_dict.items():
#   for sh_handle0 in shelve_handles0: sh_handle0.close()
# print("closed shelve handles")
combined_src_shelve_fopen.close()
combined_trg_shelve_fopen.close()

index_list_lines ['50000', '100000', '150000', '200000', '250000', '300000', '350000', '400000', '450000', '500000', '550000', '600000', '650000', '700000', '750000', '800000', '850000', '900000', '950000', '1000000', '1050000', '1100000', '1150000', '1200000', '1250000', '1300000', '1350000', '1400000', '1450000', '1500000', '1550000', '1600000', '1650000', '1700000', '1750000', '1800000', '1850000', '1900000', '1950000', '2000000', '2050000', '2100000', '2150000', '2200000', '2250000', '2300000', '2350000', '2400000', '2450000', '2500000', '2550000', '2600000', '2650000', '2700000', '2750000', '2800000', '2850000', '2900000', '2950000', '3000000', '3050000', '3100000', '3150000', '3200000', '3250000', '3300000', '3350000', '3400000', '3450000', '3500000', '3550000', '3600000', '3650000', '3700000', '3750000', '3800000', '3850000', '3900000', '3950000', '4000000', '4050000', '4100000', '4150000', '4200000', '4250000', '4300000', '4350000', '4400000', '4450000', '4500000', '4550000', '

In [ ]:
is_punct("$")

False

In [ ]:
#from itertools import chain
from code_utils.general import *
import re, time
# def tok_new(str0):
#   pass

removelist=""
#re.sub(r'[^\w'+removelist+']', '',mystring)
# multi_dot_words=["e.g.","i.e.","U.S.A.","U.K.","O.K."," v."," vs."," v.s.", " et al."," etc.", " al."]
# dot_words=["Mr","Ms","Dr","Art","art","Chap","chap","No","no","rev","Rev","Add","para","Para","Paras","paras"]
multi_dot_words=["e.g.","i.e.","u.s.a.","u.k.","o.k."," v."," vs."," v.s.", " et al."," etc.", " al."]
dot_words=["Mr","Ms","Dr","Art","art","Chap","chap","No","no","rev","Rev","Add","para","Para","Paras","paras"]

text="""
This is a new, maybe old, Mr. Ghaly, and Dr. Kala text: U.S.A please check? and e.g. also "WHAT IS THIS?" Here is our 1) question b) answer! The secretary-general 1.687% and $1000 to do this at #metoo @secgen re-imagined this A. B. "here is it." said the monk
what else? A/751/Add.12 and A.12/45/55.
I don't know, probably we should try "this other approach"!
"""
#text="$$what is this $1000 bill @me"
# def tok_new(text0):
#   iter0=re.finditer("^(\W+)(\S+)", text0) #items with non-alpha in the beginning of the string
#   iter1=re.finditer("\s(\W+)(\S+)", text0) #items with non-alpha in the beginning
#   iter2=re.finditer("(\S+?)(\W+)\s", text0) #items ending with non-alpha
#   full_list=[]
#   for a in chain(iter0,iter1,iter2):
#     start_i,end_i=a.span()
#     grp0=a.group(0)#.strip()
#     grp1=a.group(1)
#     grp2=a.group(2)
#     full_list.append((start_i,end_i,grp0,grp1,grp2))
#     #print("grp0",grp0,"grp1",grp1,"grp2",grp2)
#   full_list.sort()
#   final_str=""
#   prev_i=0
#   for a in full_list:
#     start_i,end_i,grp0,grp1,grp2=a
#     final_str+=text0[prev_i:start_i]
#     prev_i=end_i

#     add_space_after,add_space_before=True,True
#     if not grp1[0].isalnum():
#       if grp1.strip() in "@#": add_space_after=False
#       if add_space_after: final_str+=" "+grp1+" "+grp2
#       else: final_str+=" "+grp0
#     else:
#       full0,prev0,cur0=grp0,grp1,grp2
#       print(a)
#       if full0.strip().lower() in multi_dot_words: add_space_before=False
#       if prev0 in dot_words: add_space_before=False
#       if prev0.isdigit() and prev0 in ".-": add_space_before=False
#       if prev0.isupper() and prev0 in ".-": add_space_before=False
#       if len(prev0)==1: add_space_before=False
#       final_str+=prev0
#       if add_space_before: 
#         final_str+=" "
#       final_str+=" ".join(list(cur0))+" "
#   final_str+=text0[prev_i:]
#   out_tokens=[v for v in re.split("\s+",final_str) if v]
#   return out_tokens

  # final_str_tokens=final_str.split()

  # print(final_str_tokens)

ar_text=""" 22-
وقد استضافت الصين بنجاح دورة الألعاب الأولمبية الشتوية للأشخاص ذوي الإعاقة في بيجين 2022، مستفيدة من هذه الفرصة للتعجيل بتطوير خدمات إمكانية الوصول وتعزيز إدماج الأشخاص ذوي الإعاقة في التعليم والتوظيف.
"""
text="""
Ms. Kayess (Chair of the Committee on the Rights of Persons with Disabilities), panellist, said that she recognized all the candidates that demonstrated their commitment to the Convention by standing for election to the Committee on the Rights of Persons with Disabilities.
"""
text="""
ورحب مجلس حقوق الإنسان، في دورته الخامسة والأربعين، في قراره 45/5 بشأن حقوق الإنسان والتدابير القسرية الانفرادية، بالوثيقة الختامية والإعلان المعتمدين في مؤتمر القمة الثامن عشر لرؤساء دول وحكومات حركة بلدان عدم الانحياز، الذي عقد في باكو، أذربيجان، يومي 25 و 26 تشرين الأول/ أكتوبر 2019، وأكدت فيهما الحركة من جديد، ضمن أمور أخرى، موقفها المبدئي المتمثل في إدانة اتخاذ وتطبيق تدابير قسرية انفرادية ضد بلدان الحركة، وهي تدابير تنتهك ميثاق الأمم المتحدة والقانون الدولي، وتقوض، في جملة ما تقوضه، مبادئ السيادة والسلامة الإقليمية والاستقلال السياسي وتقرير المصير وعدم التدخل.

"""
#tok_new(text)
#tok_new(ar_text)


#non_space=re.findall("\S+",text)

def tok_new(text0):
  non_space=text0.split() #simple split by space
  all_tokens0=[]
  for a in non_space:
    leading0,trailing0="","" #get the leading and trailing non-alpha characters
    max_val=min(len(a),3) #iterating a number of characters from the beginning and end of token
    for i0 in range(1,max_val+1): 
      if not a[-i0].isalnum():trailing0=a[-i0]+trailing0
      else: break
    for i0 in range(0,max_val): 
      if not a[i0].isalnum():leading0+=a[i0]
      else: break
    main=a[len(leading0):len(a)-len(trailing0)]
    main_trailing=main+trailing0 #combine main part of the token with the 
    add_space_after,add_space_before=True,True #if we need to add space  between lead/main/trailing parts
    if leading0!="" and leading0 in "#@": add_space_after=False #keep hashtags and mentions
    if main in dot_words or main_trailing.lower() in multi_dot_words: add_space_before=False #things like e.g. U.S.A.
    if main.isdigit() and trailing0 in ".-)(": add_space_before=False #For things like 1. 2) 
    if len(main)==1: add_space_before=False #and A. B.
    cur_items_str="" #start building the string
    if leading0!="": cur_items_str+=" ".join(list(leading0)) #split the leading chars, add them to final str
    if add_space_after: cur_items_str+=" " #if there is a space between leading and main
    cur_items_str+=main #add the main part
    if add_space_before: cur_items_str+=" " #if there is space between main and trailing
    if trailing0!="": cur_items_str+=" ".join(list(trailing0)) #split trailing chars and add them
    all_tokens0.extend(cur_items_str.split()) #split the final string and add it to the list of tokens
  return all_tokens0
#print(all_tokens)
t0=time.time()
for _ in range(1000):
  all_tokens=tok_new(text)
t1=time.time()
print("new tokenizer:", t1-t0)
print(all_tokens)

print("---")
t0=time.time()
for _ in range(1000):
  all_tokens=tok(text)
t1=time.time()
print("old tokenizer:", t1-t0)
print(all_tokens)
# for a in all_tokens:
#   print(a)



new tokenizer: 0.3965146541595459
['ورحب', 'مجلس', 'حقوق', 'الإنسان', '،', 'في', 'دورته', 'الخامسة', 'والأربعين', '،', 'في', 'قراره', '45/5', 'بشأن', 'حقوق', 'الإنسان', 'والتدابير', 'القسرية', 'الانفرادية', '،', 'بالوثيقة', 'الختامية', 'والإعلان', 'المعتمدين', 'في', 'مؤتمر', 'القمة', 'الثامن', 'عشر', 'لرؤساء', 'دول', 'وحكومات', 'حركة', 'بلدان', 'عدم', 'الانحياز', '،', 'الذي', 'عقد', 'في', 'باكو', '،', 'أذربيجان', '،', 'يومي', '25', 'و', '26', 'تشرين', 'الأول', '/', 'أكتوبر', '2019', '،', 'وأكدت', 'فيهما', 'الحركة', 'من', 'جديد', '،', 'ضمن', 'أمور', 'أخرى', '،', 'موقفها', 'المبدئي', 'المتمثل', 'في', 'إدانة', 'اتخاذ', 'وتطبيق', 'تدابير', 'قسرية', 'انفرادية', 'ضد', 'بلدان', 'الحركة', '،', 'وهي', 'تدابير', 'تنتهك', 'ميثاق', 'الأمم', 'المتحدة', 'والقانون', 'الدولي', '،', 'وتقوض', '،', 'في', 'جملة', 'ما', 'تقوضه', '،', 'مبادئ', 'السيادة', 'والسلامة', 'الإقليمية', 'والاستقلال', 'السياسي', 'وتقرير', 'المصير', 'وعدم', 'التدخل', '.']
---
old tokenizer: 0.30153751373291016
['ورحب', 'مجلس', 'حقوق'

In [ ]:
"$".isalnum()

False

##RNN definition

In [ ]:
from collections import OrderedDict
#Let's build the network - here is a small cheat sheet for possible RNN classes based on input and output size
#https://github.com/hmghaly/rnn/blob/master/classes.py

#here the size of the output is the same as the size of the input
#the depth of the output depends on the number of possible outcome categories (e.g. different phonemes)
import torch
import torch.nn as nn
#import torch.nn.functional as F
import torch.optim as optim
import random
import dill as pickle
import numpy as np
from code_utils import np_lstm

torch.manual_seed(1)
random.seed(1)

torch.manual_seed(1)
random.seed(1)

device = torch.device('cpu')
#device = torch.device('cuda')

class RNN(nn.Module):
  def __init__(self, input_size, hidden_size, output_size,num_layers, matching_in_out=False, apply_sigmoid=False, apply_softmax=False, batch_size=1):
    super(RNN, self).__init__()
    self.input_size = input_size
    self.hidden_size = hidden_size
    self.output_size = output_size
    self.num_layers = num_layers
    self.batch_size = batch_size
    self.apply_softmax=apply_softmax
    self.apply_sigmoid=apply_sigmoid
    self.matching_in_out = matching_in_out #length of input vector matches the length of output vector 
    self.lstm = nn.LSTM(input_size, hidden_size,num_layers)
    self.hidden2out = nn.Linear(hidden_size, output_size)
    if self.apply_softmax: self.softmax =nn.Softmax(dim=2)
    if self.apply_sigmoid: self.sigmoid =nn.Sigmoid() 
    
    #self.sigmoid = torch.sigmoid(dim=1)
    self.hidden = self.init_hidden()
  def forward(self, feature_list):
    self.hidden = self.init_hidden() ### check
    feature_list=torch.tensor(feature_list)
    feature_list=feature_list.to(device) #### <<<<<<<<<<<<<<<<< 
    if self.matching_in_out:
      lstm_out, _ = self.lstm( feature_list.view(len( feature_list), 1, -1))
      output_scores = self.hidden2out(lstm_out.view(len( feature_list), -1))
      if self.apply_sigmoid: output_scores=self.sigmoid(output_scores).to(device)
      elif self.apply_softmax: output_scores=self.softmax(output_scores).to(device)
      #output_scores = torch.sigmoid(output_space) #we'll need to check if we need this sigmoid
      return output_scores #output_scores
    else:
      outs=[]
      for i in range(len(feature_list)):
        cur_ft_tensor=feature_list[i]#.view([1,1,self.input_size])
        cur_ft_tensor=cur_ft_tensor.view([1,1,self.input_size])
        lstm_out, self.hidden = self.lstm(cur_ft_tensor, self.hidden)
        outs=self.hidden2out(lstm_out)
        if self.apply_sigmoid: outs = self.sigmoid(outs).to(device) #self.sigmoid =nn.Sigmoid()
        elif self.apply_softmax: outs = self.softmax(outs).to(device)
        
      return outs
  def init_hidden(self):
    #return torch.rand(self.num_layers, self.batch_size, self.hidden_size)
    return (torch.rand(self.num_layers, self.batch_size, self.hidden_size).to(device),
            torch.rand(self.num_layers, self.batch_size, self.hidden_size).to(device))
    
def split_train_test(all_data0,train_ratio=0.8):
  train_size=int(len(all_data0)*train_ratio)
  train_set0,tes_set0=all_data0[:train_size],all_data0[train_size:]
  return train_set0,tes_set0    

#Loading and indexing sentences
new approach - just indexing and word alignment for all the data

## Loading functions

In [ ]:
#main indexing functions
import os, time, json
from collections import Counter


def get_words_vector(words,wv_model,excluded_words=[]):
  wd_counter=Counter(words)
  flag=False
  total_count0=0
  wd_vector_dict={}
  for wd0,wd0_n in wd_counter.items():
    if wd0 in excluded_words: continue
    try: cur_vec0=wv_model[wd0]
    except: continue
    wd_vector_dict[wd0]=cur_vec0
    weighted_vec0=cur_vec0*wd0_n
    if flag==False: total_vec0=weighted_vec0
    else: total_vec0+=weighted_vec0
    flag=True
    total_count0+=wd0_n
  if total_count0==0: return [],{}
  avg_vec=total_vec0/total_count0
  return avg_vec,wd_vector_dict

def file_len(fpath0): #get the number of lines in the cache file
  if not os.path.exists(fpath0): return 0
  with open(fpath0) as fopen:
    for i0,f0 in enumerate(fopen): pass
  return i0+1

def idx_match(idx1,idx2,min_common=5): #This function is to give a ratio of matching between the inverted indexes for two words
    if len(idx1)==0 or len(idx2)==0: return 0
    intersection=len(list(set(idx1).intersection(set(idx2))))
    union=len(idx1)+len(idx2)-intersection
    if union==0: return 0
    if intersection<min_common: return 0    
    return float(intersection)/union


def rtrv_idx(tokens,idx_dict, params0={}): #get the indexes of a phrase - we can extend it to as many tokens as we want
    lower=params0.get("lower",True)
    remove_al=params0.get("remove_al",True)
    cur_indexes=idx_dict.get(tokens[0],[])
    for ti,ta in enumerate(tokens[1:]):
        cur_offset=ti+1
        cur_raw_idx=idx_dict.get(ta,[])
        cur_offset_idx=[(v[0],v[1]-cur_offset) for v in cur_raw_idx]
        cur_indexes=list(set(cur_indexes).intersection(set(cur_offset_idx)))
    cur_indexes=[v[0] for v in cur_indexes]
    cur_indexes=sorted(list(set(cur_indexes)))
    return cur_indexes


class sent_cls:
  def __init__(self,raw_sent0="",raw_tokens0=[],tokens0=[],map0=[]) -> None:
      self.raw_sent=raw_sent0
      self.raw_tokens=raw_tokens0
      self.tokens=tokens0 #filtered tokens
      self.map=map0 #mapping of filtered tokens to raw tokens #raw_tokens,map

class indexing: #get a list of sentences, outputs indexes
  def __init__(self,raw_sentences0,tok_function, params0={}):
    lang=params0.get("lang","en")
    stop_words=params0.get("stop_words",[]) #excluded words
    ignore_punc=params0.get("ignore_punc",False) #skip punctuation or not
    ignore_ar_pre_suf=params0.get("ignore_ar_pre_suf",False) #ignore arabic prefixes and suffixes
    remove_al=params0.get("remove_al", False) #remocve alif laam in Arabic
    index_words=params0.get("index_words", True) #keep the index of each word in a sentence, not just the sentence number
    lower=params0.get("lower", False) #make all words lower case or not
    stemming=params0.get("stemming", False) #stem each word or not
    self.fwd_index=[]
    self.all_tok_sentences=[]
    self.all_tok_original_sentences=[]
    self.all_mappings=[]
    self.sent_obj_list=[]
    self.inv_index={}
    for sent_i,sent0 in enumerate(raw_sentences0):
      #if sent_i%5000==0: print(sent_i)
      tokens=tok_function(sent0)
      #tokens,cur_mapping,original_tokens=filter_tokens(tokens, lang,stop_words, ignore_punc,ignore_ar_pre_suf,remove_al,index_words,lower,stemming)
      tokens,cur_mapping,original_tokens=filter_tokens(tokens, params0)
      self.all_tok_original_sentences.append(original_tokens)
      self.all_mappings.append(cur_mapping)
      enumerated_toks=[(v,sent_i,s_i) for s_i,v in enumerate(tokens)]
      cur_sent_obj0=sent_cls(sent0,original_tokens,tokens,cur_mapping)
      self.sent_obj_list.append(cur_sent_obj0)
      #cur_sent_obj0
      self.all_tok_sentences.append(tokens)
      self.fwd_index.extend(enumerated_toks)
    self.fwd_index.sort()
    grouped=[(key,[v[1:] for v in list(group)]) for key,group in groupby(self.fwd_index,lambda x:x[0])]
    self.inv_index=dict(iter(grouped))

def filter_tokens(token_list0, params0={}):
#def filter_tokens(token_list0, lang="en",stop_words=[], ignore_punc=False,ignore_ar_pre_suf=False,remove_al=True,index_words=True,lower=True,stemming=False):
  tokens_original=list(token_list0)
  tokens_copy_enum=[(i,v) for i,v in enumerate(token_list0)]   
  ignore_punc=params0.get("ignore_punc",False)
  ignore_ar_pre_suf=params0.get("ignore_ar_pre_suf",False)
  remove_al=params0.get("remove_al",False)
  lower=params0.get("lower",False)
  stemming=params0.get("stemming",False)
  lang=params0.get("lang","en")
  stop_words=params0.get("stop_words",[])
  #if lang=="ar": tokens=tok_ar(tokens,count_dict) #tok_ar(tokens)
  if ignore_punc: tokens_copy_enum=[(i,v) for i,v in tokens_copy_enum if not is_punct(v)]
  if ignore_ar_pre_suf: tokens_copy_enum=[(i,v) for i,v in tokens_copy_enum if not v.startswith("ـ") and not v.endswith("ـ")]
  if stop_words: tokens_copy_enum=[(i,v) for i,v in tokens_copy_enum if not v.lower() in stop_words]
  if remove_al: tokens_copy_enum=[(i,v.replace("ال_","")) for i,v in tokens_copy_enum if not v.lower() in stop_words]
  tokens_out=[v[1] for v in tokens_copy_enum]
  if lower: tokens_out=[v.lower() for v in tokens_out]
  cur_mapping=[v[0] for v in tokens_copy_enum]
  return tokens_out,cur_mapping, tokens_original

def get_tok_loc(tok_list):
  tok_locs_list=[]
  for i_,cur_tok in enumerate(tok_list):
    tok_locs_list.append(((cur_tok,),(i_,i_))) #to get unigrams and their locations
    if i_<len(tok_list)-1: tok_locs_list.append(((cur_tok,tok_list[i_+1]), (i_,i_+1))) #to get bigrams and their locations
  tok_locs_list.sort(key=lambda x:x[0])
  grouped=[(key,[v[1] for v in list(group)]) for key,group in groupby(tok_locs_list,lambda x:x[0])]
  return grouped

def get_rec_el_children(el0,el_child_dict0,el_list0=[]):
  cur_children0=el_child_dict0.get(el0,[])
  if cur_children0==[]: el_list0.append(el0)
  for ch0 in cur_children0:
    el_list0=get_rec_el_children(ch0,el_child_dict0,el_list0)
  return el_list0

def combine_els(el1,el2):
  src_span1,trg_span1=el1
  src_span2,trg_span2=el2
  x1_0,x1_1=src_span1
  x2_0,x2_1=src_span2
  y1_0,y1_1=trg_span1
  y2_0,y2_1=trg_span2
  min_x=min(x1_0,x1_1,x2_0,x2_1)
  max_x=max(x1_0,x1_1,x2_0,x2_1)
  min_y=min(y1_0,y1_1,y2_0,y2_1)
  max_y=max(y1_0,y1_1,y2_0,y2_1)
  new_src_span=(min_x,max_x)
  new_trg_span=(min_y,max_y)
  return (new_src_span,new_trg_span)

# def check_span_overlap(span1,span2):
#   span1_x1,span1_x2=span1
#   span2_x1,span2_x2=span2
#   d1=abs(span1_x2-span1_x1)
#   d2=abs(span2_x2-span2_x1)
#   max_x=max(span1_x1,span1_x2,span2_x1,span2_x2)
#   min_x=min(span1_x1,span1_x2,span2_x1,span2_x2)
#   d_total=max_x-min_x
#   overlapping=False
#   if d_total<=d1+d2: overlapping=True
#   return overlapping

def get_span_dist(span1,span2):
  span1_x1,span1_x2=span1
  span2_x1,span2_x2=span2
  d1=abs(span1_x2-span1_x1)
  d2=abs(span2_x2-span2_x1)
  max_x=max(span1_x1,span1_x2,span2_x1,span2_x2)
  min_x=min(span1_x1,span1_x2,span2_x1,span2_x2)
  d_total=max_x-min_x
  return d_total-d1-d2



# def overlaps(el1,el2,max_dist=10):
#   src_span1,trg_span1=el1
#   src_span2,trg_span2=el2
#   x1_0,x1_1=src_span1
#   x2_0,x2_1=src_span2
#   y1_0,y1_1=trg_span1
#   y2_0,y2_1=trg_span2
#   #if x2_0<=x1_1: return True
#   output=False
#   if check_span_overlap(src_span1,src_span2): output=True
#   if check_span_overlap(trg_span1,trg_span2): output=True
#   if get_span_dist(trg_span1,trg_span2)>max_dist: output=True

#   # min_x=min(x1_0,x1_1,x2_0,x2_1)
#   # max_x=max(x1_0,x1_1,x2_0,x2_1)
#   # min_y=min(y1_0,y1_1,y2_0,y2_1)
#   # max_y=max(y1_0,y1_1,y2_0,y2_1)
#   # new_src_span=(min_x,max_x)
#   # new_trg_span=(min_y,max_y)
#   return output

# def overlaps_OLD(span1,span2):
#   span1_i0,span1_i1=span1
#   span2_i0,span2_i1=span2
#   if span1_i0>=span2_i0 and span1_i0<=span2_i1: return True
#   if span1_i1>=span2_i0 and span1_i1<=span2_i1: return True
#   if span2_i0>=span1_i0 and span2_i0<=span1_i1: return True
#   if span2_i1>=span1_i0 and span2_i1<=span1_i1: return True
#   return False


def walign(src_obj0,trg_obj0,src_inv_dict0,trg_inv_dict0,walign_params0={}):
  min_retrieved_index_count=walign_params0.get("min_retrieved_index_count",3) #3
  max_dist=walign_params0.get("max_dist",10)
  min_ratio=walign_params0.get("min_ratio",0.05)
  max_sent_size=walign_params0.get("max_sent_size")
  n_epochs=walign_params0.get("n_epochs",20)
  output={}

  span_el_dict={} #which elements corresponds to this span - sorted by weight
  start_span_dict={} #show all the spans corresponding to a src location
  el_child_dict={} #show which elements are children of which
  el_wt_dict={} #show the weight of each element

  
  span_wt_dict={} #wight of each span -> the weight of the highest element it includes
  span_child_dict={} #which subspans this span consists of
  span_top_elms_dict={} #show the top elements for each span
  
  
  
  all_phrase_pairs=[]
  src0,trg0=src_obj0.tokens, trg_obj0.tokens
  original_src0,original_trg0=src_obj0.raw_tokens, trg_obj0.raw_tokens
  map_src0,map_trg0=src_obj0.map, trg_obj0.map
  #trg0=trg_obj0.tokens #raw_tokens,map
  #if len(src0)>35: return


  src0=['<s>']+src0+['</s>'] #first we pad the sentence tokens with start and end sentence markers
  trg0=['<s>']+trg0+['</s>'] #for both src and trg
  original_src0=['<s>']+original_src0+['</s>'] #first we pad the sentence tokens with start and end sentence markers
  original_trg0=['<s>']+original_trg0+['</s>'] #for both src and trg

  output["src"]=original_src0
  output["trg"]=original_trg0
  

  
  if max_sent_size!=None and len(src0)>max_sent_size: return output


  # self.src0=src0
  # self.trg0=trg0
  #print(src0)
  src_grouped=get_tok_loc(src0) #group all the locations for a list of consecutive tokens (src then trg)
  trg_grouped=get_tok_loc(trg0)
  src_side,trg_side=[],[] #mapping unigrams and bigrams to both their locations within the sentence and retrieved indexes from inverted dict
  src_locs_count_dict={} #how many times did the current token/bigram/phrase appeared in the src sent tokens
  trg_locs_count_dict={} #and same for trg
  for s_toks0,s_locs_grp0 in src_grouped: #retrive the indexes for each token sequence, map them to the locations
    src_indexes0= rtrv_idx(s_toks0,src_inv_dict0)
    s_toks_str0=" ".join(s_toks0) 
    src_side.append((s_toks_str0,s_locs_grp0,src_indexes0))
    src_locs_count_dict[s_toks_str0]=len(s_locs_grp0)
  for t_toks0,t_locs_grp0 in trg_grouped:
    trg_indexes0= rtrv_idx(t_toks0,trg_inv_dict0)
    t_toks_str0=" ".join(t_toks0)
    trg_side.append((t_toks_str0,t_locs_grp0,trg_indexes0))
    trg_locs_count_dict[t_toks_str0]=len(t_locs_grp0)

  #now starting the match the indexes of both src and trg token locations and get the corresponding rations/weights
  matching_list=[]
  all_elements=[] #to create elements (pairs of src-trg spans)
  tmp_ratio_dict={}
  for src_item0 in src_side: #examining all src tokens/bigrams with their locs/spans and retrieved indexes
    s_toks_str0,s_locs_grp0,src_indexes0=src_item0
    for trg_item0 in trg_side: #and get also all trg tokens/bigrams with locs/spand and retrieved indexes
      t_toks_str0,t_locs_grp0,trg_indexes0=trg_item0
      cur_ratio=0
      if s_toks_str0==t_toks_str0: cur_ratio=1.0 #if the src equals the target (e.g. numbers), the matching ratio is 1
      else: 
        if len(src_indexes0)<min_retrieved_index_count or len(trg_indexes0)<min_retrieved_index_count: continue #if the number of retrieved indexes is less than certain threshold, we keep the ratio as zero
        cur_ratio=idx_match(src_indexes0,trg_indexes0,5)
      if cur_ratio==0: continue
      matching_list.append(([s_toks_str0,s_locs_grp0],[t_toks_str0,t_locs_grp0], cur_ratio))

  #####
  #Now filtering the matching list
  matching_list.sort(key=lambda x:-x[-1])
  valid_list=[] #the final list of acceptable phrase pairs, their locs, and matching ratio
  for ml in matching_list:
    a,b,r=ml
    src_phrase0,src_locs=a #for the current src phrase and how many locations it occurs in the current sentence
    trg_phrase0,trg_locs=b #and same for trg phrase
    min_count=min(len(src_locs), len(trg_locs)) #and we get the minimum occurance between the src and trg phrase
    found_src_count=src_locs_count_dict[src_phrase0] #and then we check whether the src phrase was used before
    found_trg_count=trg_locs_count_dict[trg_phrase0] #and same for trg phrase
    if found_src_count<1 or found_trg_count<1: continue #if either was used before, their count would be zero or less, so we exclude current pair
    src_locs_count_dict[src_phrase0]=found_src_count-min_count #if not, we proceed, abd subtract the minimum count from the "unused" count of the current src phrase
    trg_locs_count_dict[trg_phrase0]=found_trg_count-min_count #and same for trg
    valid_list.append(ml)
  #Now we star processing the valid pairs, with their actual geometric spans and weights
  #first populate the main dictionaries: span_el_dict,  start_span_dict, el_child_dict, el_wt_dict
  span_el_list=[] #list of spans and elements
  all_src_spans=[]
  for vl in valid_list:
    #print(">>>", vl)
    a,b,cur_ratio=vl
    src_phrase0,src_locs=a #for the current src phrase and how many locations it occurs in the current sentence
    trg_phrase0,trg_locs=b #and same for trg phrase
    for sl0 in src_locs:
      if not sl0 in all_src_spans: all_src_spans.append(sl0)
      for tl0 in trg_locs:
        cur_el=(sl0,tl0) #an element is a tuple containing the span of src indexes and span of trg indexes
        el_wt_dict[cur_el]=cur_ratio #initially populating the element weight dict
        span_el_list.append((sl0,cur_el,cur_ratio))
  span_el_list.sort(key=lambda x:x[0])
  span_el_list_grouped=[(key,[v[1] for v in list(group)]) for key,group in groupby(span_el_list,lambda x:x[0])]
  all_src_spans.sort()
  all_src_spans_grouped=[(key,list(group)) for key,group in groupby(all_src_spans,lambda x:x[0])]
  for sp0,elements0 in span_el_list_grouped: span_el_dict[sp0]=elements0 #initially populating the span-elements dict
  for start_i0,spans0 in all_src_spans_grouped: start_span_dict[start_i0]=spans0 #initially poplating the start/spans dict
  top_score=0
  full_src_span0=(0,len(src0)-1)
  full_trg_span0=(0,len(trg0)-1)
  full_el=(full_src_span0,full_trg_span0)
  #all_top_scores=[]

  for ep0 in range(n_epochs):
    #continue
    cur_start_locs=sorted(list(set(start_span_dict.keys())))
    #print(ep0, "cur_start_locs",cur_start_locs)
    for i_,loc_i in enumerate(cur_start_locs):
      next_locs=cur_start_locs[i_+1:]
      cur_spans=start_span_dict[loc_i]
      next_spans=[]
      for nl in next_locs: next_spans.extend(start_span_dict[nl])
      #print(ep0,"cur_spans",cur_spans,"next_spans",next_spans)

      for cs in cur_spans: 
        cur_els=span_el_dict.get(cs,[])
        #print("$$$$$ cur_els",cur_els)
        for ns in next_spans:
          #if ns[0]<=cs[1]: continue #print("exclude:",cs,ns)
          x_dist=get_span_dist(cs,ns)
          #print("????", cs,ns, "x_dist",x_dist)
          if x_dist<1 or x_dist>max_dist: continue
          #else: print("++++", cs,ns)
          next_els=span_el_dict.get(ns,[])
          #print("#### next_els",next_els)
          for cur_el0 in cur_els:
            cur_wt0=el_wt_dict[cur_el0]
            cur_x_span,cur_y_span=cur_el0
            for next_el0 in next_els:
              if cur_el0==next_el0: continue
              next_x_span,next_y_span=next_el0
              y_dist=get_span_dist(cur_y_span,next_y_span)
              if y_dist<1 or y_dist>max_dist: continue #print("Excluded XXX: cur_el0",cur_el0, "next_el0",next_el0,"y_dist",y_dist)
              next_wt0=el_wt_dict[next_el0] 
              combined_wt0=cur_wt0+next_wt0
              combined_el0=combine_els(cur_el0,next_el0) #get_min_max(cur_el0,next_el0)
              found_combined_wt=el_wt_dict.get(combined_el0,0)
              #print(">>>", cur_el0, next_el0,"combined_wt0",combined_wt0,"found_combined_wt",found_combined_wt)       
              if combined_wt0>found_combined_wt:
                el_wt_dict[combined_el0]=combined_wt0
                el_child_dict[combined_el0]=[cur_el0,next_el0]
                tmp_src_span0=combined_el0[0]
                #print("tmp_src_span0",tmp_src_span0)
                found_span_elements=span_el_dict.get(tmp_src_span0,[])
                if not combined_el0 in found_span_elements: found_span_elements.append(combined_el0)
                found_span_elements.sort(key=lambda x:-el_wt_dict[x])
                span_el_dict[tmp_src_span0]=found_span_elements
                #print("span_el_dict[tmp_src_span0]",span_el_dict[tmp_src_span0])
                found_start_spans=start_span_dict.get(tmp_src_span0[0])
                if not tmp_src_span0 in found_start_spans: found_start_spans.append(tmp_src_span0)
                start_span_dict[tmp_src_span0[0]]=found_start_spans
                #print("start_span_dict[tmp_src_span0[0]]",start_span_dict[tmp_src_span0[0]])
                #print(ep0, "cur_el0",cur_el0, "next_el0",next_el0,"combined_el0",combined_el0, "combined_wt0",round(combined_wt0,4), "y_dist",y_dist)
        

    cur_score=el_wt_dict.get(full_el,0)
    wt_list=list(el_wt_dict.items())
    wt_list.sort(key=lambda x:-x[1])
    #print(ep0, wt_list[0], "cur_score",cur_score, "top",top_score)
    # for wl in wt_list[:5]:
    #   print(ep0, wl)
    # print("----")
    # print(all_top_scores)
    # all_top_scores.append(cur_score)

    if cur_score>top_score: top_score=cur_score
    elif cur_score==top_score and cur_score>0: break

  if el_wt_dict.get(full_el,0)>0:
    align_list=get_rec_el_children(full_el,el_child_dict,el_list0=[])
  else:
    top_el=wt_list[0][0]
    print("couldn't find full el:",full_el, "used the top el instead", top_el)
    align_list=get_rec_el_children(top_el,el_child_dict,el_list0=[])

  
  if align_list!=[]:
    # src0=src_obj0.tokens
    # trg0=trg_obj0.tokens
    output_align_list=[]

    # print("aligned")
    # print(src0)
    # print(trg0)
    # print(map_src0)
    # print(map_trg0)
    adj_src_map=[0]+[v+1 for v in map_src0]+[len(original_src0)-1]
    adj_trg_map=[0]+[v+1 for v in map_trg0]+[len(original_trg0)-1]
    # print(original_src0)
    # print(original_trg0)
    # print("adj_src_map",adj_src_map)
    # print("adj_trg_map",adj_trg_map)
    for a in align_list:
      src_span0,trg_span0=a
      x0,x1=src_span0
      y0,y1=trg_span0
      new_x0,new_x1=adj_src_map[x0],adj_src_map[x1]
      new_y0,new_y1=adj_trg_map[y0],adj_trg_map[y1]
      new_src_pan=new_x0,new_x1
      new_trg_span=new_y0,new_y1
      
      src_phrase0=src0[src_span0[0]:src_span0[1]+1]
      trg_phrase0=trg0[trg_span0[0]:trg_span0[1]+1]

      output_align_list.append((new_src_pan,new_trg_span))

      src_phrase1=original_src0[new_x0:new_x1+1]
      trg_phrase1=original_trg0[new_y0:new_y1+1]
    #   print(a,src_phrase0, trg_phrase0)
    #   print("src_phrase1",src_phrase1)
    #   print("trg_phrase1",trg_phrase1)
    #   print("---")
    # print("==============")
  #out["align"]=output_align_list
  output["align"]=output_align_list
  return output


##Starting Indexing/Alignment

In [ ]:
#Starting the experiment
exp_dir="exp00"
batch_size=100000
#batch_size=5000


ar_corpus_fname="UNv1.0.ar-en-clean2.ar"
en_corpus_fname="UNv1.0.ar-en.en"
cur_walign_dir="un-walign"

full_align_dir_path=os.path.join(cur_walign_dir,exp_dir)
if not os.path.exists(full_align_dir_path): os.makedirs(full_align_dir_path)


params={}
params["lang"]="en"
params["ignore_punc"]=True
params["stop_words"]=[]
params["ignore_ar_pre_suf"]=True
params["remove_al"]=True
params["index_words"]=True
params["lower"]=True
params["stemming"]=False

walign_params={}
walign_params["min_retrieved_index_count"]=3
walign_params["max_dist"]=5
walign_params["max_sent_size"]=60
walign_params["min_ratio"]=0.05
walign_params["n_epochs"]=5

walign_params_fpath=os.path.join(full_align_dir_path,"walign-params.json")
indexing_params_fpath=os.path.join(full_align_dir_path,"indexing-params.json")
with open(walign_params_fpath,"w") as walign_fopen:
  json.dump(walign_params,walign_fopen)


#print("file size:", file_len(en_corpus_fname))

src_params,trg_params=dict(params),dict(params) #we copy the default parameters
src_params["stop_words"]=["the","of","an","a","and","is","are", "to","been","it","as","for","have"]
trg_params["stop_words"]=["إلى"]

indexing_params={}
indexing_params["src"]=src_params
indexing_params["trg"]=trg_params
with open(indexing_params_fpath,"w") as indexing_fopen:
  json.dump(indexing_params,indexing_fopen)



ar_fopen=open(ar_corpus_fname)
en_fopen=open(en_corpus_fname)
src_sents,trg_sents=[],[]
for pair_i,pair in enumerate(zip(en_fopen,ar_fopen)):
  if pair_i>batch_size: break
  #print(pair_i)
  if pair_i>0 and pair_i%batch_size==0: #if the current line number of the bitext matches the btach size, we start processing batch
    #walign_sentences(src_sents,trg_sents,cur_align_fname)
    cur_align_fname=os.path.join(full_align_dir_path,"%s.txt"%pair_i) #the output goes into the filename named after the current line number
    cur_size=file_len(cur_align_fname) #we check how many lines in the current file
    if cur_size==len(src_sents): continue #if the files has an equal number of lines to the batch size, we proceed to next batch
    #uncheck the above line after you finish experiments
    print("indexing src sentences")
    
    src_index_obj=indexing(src_sents, tok,src_params)
    print("indexing trg sentences")
    trg_index_obj=indexing(trg_sents, cur_ar_tok_fn,trg_params)
    print("finished indexing, now aligning words")
    print("number of sentences:",len(src_sents))
    # start_i=1000
    # n_sents=50
    # sent_counter=0
    for sent_i in range(len(src_sents)): #range(start_i,start_i+n_sents):
      if sent_i%1000==0: print("now aligning", sent_i)
      #sent_counter+=1
      #if sent_counter>35: break
      
      if sent_i<cur_size: 
        #print("skipping now")
        continue #also uncheck this after finishing experiments
      print("sent_i",sent_i)
      #cur_obj={}
      #print(src_sents[sent_i])
      #print(trg_sents[sent_i])
      # cur_src0=src_sents[i_] 
      # cur_trg0=trg_sents[i_]
      cur_src_obj0=src_index_obj.sent_obj_list[sent_i]
      cur_trg_obj0=trg_index_obj.sent_obj_list[sent_i]
      output0=walign(cur_src_obj0,cur_trg_obj0,src_index_obj.inv_index,trg_index_obj.inv_index,walign_params0=walign_params)
      #walign(cur_src_obj0,cur_trg_obj0,src_index_obj.inv_index,trg_index_obj.inv_index)
      #cur_obj["src"]=src_sents[sent_i]
      json_str=json.dumps(output0)
      cur_align_fopen=open(cur_align_fname,"a")
      cur_align_fopen.write(json_str+"\n")
      cur_align_fopen.close()


    
    print(pair_i, "number of unique src words", len(src_index_obj.inv_index))
    print(pair_i, "number of unique trg words", len(trg_index_obj.inv_index))
    print("resetting sentence lists")
    print("----------")
    #print("processing sentences")
    src_sents,trg_sents=[],[]
    #break
  if pair_i%10000==0: print(pair_i)
  src_line,trg_line=pair
  src_line,trg_line=src_line.strip("\n\r\t "),trg_line.strip("\n\r\t ")
  src_sents.append(src_line)
  trg_sents.append(trg_line)

ar_fopen.close()
en_fopen.close()

0
10000
20000
30000
40000
50000
60000
70000
80000
90000
indexing src sentences
indexing trg sentences
finished indexing, now aligning words
number of sentences: 100000
now aligning 0
now aligning 1000
now aligning 2000
now aligning 3000
now aligning 4000
now aligning 5000
now aligning 6000
now aligning 7000
now aligning 8000
now aligning 9000
now aligning 10000
now aligning 11000
now aligning 12000
now aligning 13000
now aligning 14000
now aligning 15000
now aligning 16000
now aligning 17000
now aligning 18000
now aligning 19000
now aligning 20000
now aligning 21000
now aligning 22000
now aligning 23000
now aligning 24000
now aligning 25000
now aligning 26000
now aligning 27000
now aligning 28000
now aligning 29000
now aligning 30000
now aligning 31000
sent_i 31520


KeyboardInterrupt: ignored

##Testing Alignment Output

In [ ]:
start_i=3900
n_sents=20
sent_counter=0
for sent_i in range(start_i,start_i+n_sents):
  #if sent_i%1000==0: print("now aligning", sent_i)
  sent_counter+=1
  #if sent_counter>35: break
  print("sent_i",sent_i)
  #if sent_i<cur_size: continue #also uncheck this after finishing experiments
  cur_obj={}
  print(src_sents[sent_i])
  print(trg_sents[sent_i])
  # cur_src0=src_sents[i_] 
  # cur_trg0=trg_sents[i_]
  cur_src_obj0=src_index_obj.sent_obj_list[sent_i]
  #if len(cur_src_obj0.tokens)>20: continue
  cur_trg_obj0=trg_index_obj.sent_obj_list[sent_i]
  output0=walign(cur_src_obj0,cur_trg_obj0,src_index_obj.inv_index,trg_index_obj.inv_index,walign_params0=walign_params)
  cur_aligned_spans=output0.get("align")
  if cur_aligned_spans!=None:
    cur_src_tokens=output0["src"]
    cur_trg_tokens=output0["trg"]
    for src_span0,trg_span0 in cur_aligned_spans:
      print("src_span0,trg_span0",src_span0,trg_span0)
      print(cur_src_tokens[src_span0[0]:src_span0[1]+1])
      print(cur_trg_tokens[trg_span0[0]:trg_span0[1]+1])
    # for a,b in output0.items():
    #   print(a,b)
    print("-------")
  #print(output0)
  # cur_obj["src"]=src_sents[sent_i]
  # json_str=json.dumps(cur_obj)
  # cur_align_fopen=open(cur_align_fname,"a")
  # cur_align_fopen.write(json_str+"\n")
  # cur_align_fopen.close()

sent_i 3900
For the period ending 30 April 1993, voluntary contributions received by UNIKOM for which no budgetary provision was made in the cost estimates, and as valued by the donor Government, are shown below. 93-40057 (E) 160793 /... Estimated value (United States
وفيما يتعلق بالفترة المنتهية في 30 نيسان/أبريل 1993، يرد أدناه بيان التبرعات التي تلقتها بعثة المراقبة والتي لم يرصد بشأنها اعتماد في الميزانية في تقدير التكاليف، ووفقا للقيمة التي حددتها الحكومة المتبرعة.
0 (((0, 23), (0, 32)), 7.862982656080205) cur_score 0 top 0
1 (((0, 26), (0, 32)), 8.597533636525494) cur_score 7.658684337986297 top 0
2 (((0, 35), (0, 34)), 9.134889846843263) cur_score 9.134889846843263 top 7.658684337986297
3 (((0, 35), (0, 34)), 9.501195559987828) cur_score 9.501195559987828 top 9.134889846843263
4 (((0, 35), (0, 34)), 9.521654623591965) cur_score 9.521654623591965 top 9.501195559987828
src_span0,trg_span0 (0, 0) (0, 0)
['<s>']
['<s>']
src_span0,trg_span0 (3, 3) (5, 5)
['period']
['ال_فترة']
src_sp

##Processing aligned materials

In [ ]:
import os,json

def extract_phrases(src_tokens0,trg_tokens0,align_list0,max_size=10): #extracting phrases from aligned pairs of src/trg tokens, filling the gaps of unaligned tokens 
  src_size,trg_size=len(src_tokens0),len(trg_tokens0)
  #expanded_spans=[]
  expanded_spans=list(align_list0)
  used_src_locs,used_trg_locs=[],[]
  for i0, align_span_pair0 in enumerate(align_list0):
    src_span0,trg_span0=align_span_pair0
    used_src_locs.extend(range(src_span0[0],src_span0[1]+1))
    used_trg_locs.extend(range(trg_span0[0],trg_span0[1]+1))
  # print("used_src_locs",used_src_locs)
  # print("used_trg_locs",used_trg_locs)

  for i0, align_span_pair0 in enumerate(align_list0):
    src_span0,trg_span0=align_span_pair0
    for align_span_pair1 in align_list0[i0+1:]:
      src_span1,trg_span1=align_span_pair1
      #print(align_span_pair0, align_span_pair1)
      combined_src_span=(src_span0[0],src_span1[1])
      combined_trg_span=min(trg_span0[0],trg_span1[1]),max(trg_span0[0],trg_span1[1])
      valid=True
      for align_span_pair2 in align_list0:
        if align_span_pair2==align_span_pair0 or align_span_pair2==align_span_pair1: continue
        src_span2,trg_span2=align_span_pair2
        if (src_span2[0]>=combined_src_span[0] and src_span2[0]<=combined_src_span[1]) or (src_span2[1]>=combined_src_span[0] and src_span2[1]<=combined_src_span[1]):
          if trg_span2[1]>combined_trg_span[1] or trg_span2[0]<combined_trg_span[0]:
            valid=False
            #print("outside:",align_span_pair2)
            break
      if not valid: continue
      expanded_spans.append((combined_src_span,combined_trg_span))

      # print("combined_src_span",combined_src_span)
      # print("combined_trg_span",combined_trg_span)
  final_spans=[]
  for combined_src_span, combined_trg_span in expanded_spans:
    x0,x1=combined_src_span
    y0,y1=combined_trg_span
    if x1-x0>max_size: continue
    src_starting_locs=[x0]
    src_ending_locs=[x1]
    trg_starting_locs=[y0]
    trg_ending_locs=[y1]
    go_x_pre,go_x_post,go_y_pre,go_y_post=True,True,True, True
    for offset0 in range(1,10):
      pre_x0=x0-offset0
      if pre_x0>=0 and not pre_x0 in used_src_locs: src_starting_locs.append(pre_x0)
      else: break
    for offset0 in range(1,10):
      post_x1=x1+offset0
      if post_x1<src_size and not post_x1 in used_src_locs: src_ending_locs.append(post_x1) 
      else: break
    for offset0 in range(1,10):
      pre_y0=y0-offset0
      if pre_y0>=0 and not pre_y0 in used_trg_locs: trg_starting_locs.append(pre_y0) 
      else: break
    for offset0 in range(1,10):
      post_y1=y1+offset0
      if post_y1<trg_size and not post_y1 in used_trg_locs: trg_starting_locs.append(post_y1)
      else: break
    # print("src_starting_locs",src_starting_locs)
    # print("src_ending_locs",src_ending_locs)
    # print("trg_starting_locs",trg_starting_locs)
    # print("trg_ending_locs",trg_ending_locs)



    # print("valid",valid)
    # print("---")
    for new_x0 in src_starting_locs:
      for new_x1 in src_ending_locs:
        if new_x1-new_x0>max_size: continue
        new_src_span=(new_x0,new_x1)
        for new_y0 in trg_starting_locs:
          for new_y1 in trg_ending_locs:
            if new_y1<new_y0: continue
            new_trg_span=(new_y0,new_y1)
            final_spans.append((new_src_span,new_trg_span))
  all_phrases=[]
  for src_span,trg_span in final_spans:
    #print(src_span, trg_span)
    cur_src_phrase=" ".join(cur_src[src_span[0]:src_span[1]+1])
    cur_trg_phrase=" ".join(cur_trg[trg_span[0]:trg_span[1]+1])
    all_phrases.append((cur_src_phrase,cur_trg_phrase))

    # print("expanded cur_src",cur_src[src_span[0]:src_span[1]+1])
    # print("expanded cur_trg",cur_trg[trg_span[0]:trg_span[1]+1])

  return all_phrases
      



exp_dir="exp01-test"
cur_walign_dir="un-walign"
full_align_dir_path=os.path.join(cur_walign_dir,exp_dir)
files=os.listdir(full_align_dir_path)
files=[os.path.join(full_align_dir_path,v) for v in files if v.endswith(".txt")]

matching_dict={}
src_counter_dict,trg_counter_dict={},{}
#print(files)
cur_i=0
cur_n=200000

min_src_count=20
min_trg_count=5

cur_fpath=files[0]
for cur_fpath in files:
  print(cur_fpath)
  fopen=open(cur_fpath)
  for line_i,line0 in enumerate(fopen):
    if line_i%2000==0: print("processing:",line_i)
    if line_i<cur_i: continue
    if line_i>cur_i+cur_n: break
    cur_obj=json.loads(line0.strip())
    cur_src,cur_trg,cur_align=cur_obj["src"],cur_obj["trg"],cur_obj.get("align",[])
    if cur_align==[]: continue
    all_phrases0=extract_phrases(cur_src,cur_trg,cur_align)
    for phrase_pair0 in all_phrases0:
      #print(phrase_pair0)
      src0,trg0=phrase_pair0
      src0=src0.lower()
      trg0=trg0.lower()
      src_counter_dict[src0]=src_counter_dict.get(src0,0)+1
      trg_counter_dict[trg0]=trg_counter_dict.get(trg0,0)+1
      tmp_dict=matching_dict.get(src0,{})
      tmp_dict[trg0]=tmp_dict.get(trg0,0)+1
      matching_dict[src0]=tmp_dict
    #print("=======")
  fopen.close()

new_ratio_dict={}
final_phrase_pair_list=[]
for src_phrase,b_dict in matching_dict.items():
  src_instances_n=sum(b_dict.values())
  if max(b_dict.values())<min_trg_count: continue
  if src_instances_n<min_src_count: continue
  #print(src_phrase)
  tmp_trg_ratio_dict={}
  for trg_phrase,b0 in b_dict.items():
    if b0<min_trg_count: continue
    overall_trg_phrase_count=trg_counter_dict[trg_phrase]
    ratio=b0/(src_instances_n+overall_trg_phrase_count-b0)
    final_phrase_pair_list.append((src_phrase,trg_phrase,b0,ratio))
    tmp_trg_ratio_dict[trg_phrase]=(ratio,b0)
  new_ratio_dict[src_phrase]=tmp_trg_ratio_dict
  #   print(src_phrase,trg_phrase, round(ratio,4))
  # print("-----")

  #print(a,src_instances_n)
final_phrase_pair_list.sort(key=lambda x:-x[-1])
# for a in final_phrase_pair_list[:50]:
#   print(a)
print("final_phrase_pair_list", len(final_phrase_pair_list))

un-walign/exp01-test/100000.txt
processing: 0
processing: 2000
processing: 4000
processing: 6000
processing: 8000
processing: 10000
processing: 12000
processing: 14000
processing: 16000
processing: 18000
processing: 20000
processing: 22000
processing: 24000
processing: 26000
processing: 28000
processing: 30000
processing: 32000
processing: 34000
processing: 36000
processing: 38000
processing: 40000
processing: 42000
processing: 44000
processing: 46000
processing: 48000
processing: 50000
processing: 52000
processing: 54000
processing: 56000
processing: 58000
processing: 60000
processing: 62000
processing: 64000
processing: 66000
processing: 68000
processing: 70000
processing: 72000
processing: 74000
processing: 76000
processing: 78000
processing: 80000
processing: 82000
processing: 84000
processing: 86000
processing: 88000
processing: 90000
processing: 92000
processing: 94000
processing: 96000
processing: 98000
un-walign/exp01-test/200000.txt
processing: 0
processing: 2000
processing: 4

In [ ]:
src_phrase="other countries"
src_phrase=src_phrase.strip()
overall_src_count=src_counter_dict[src_phrase]
tmp_dict=matching_dict[src_phrase]

final_list=[]
for cur_trg_phrase,trg_phrase_val in tmp_dict.items():
  if trg_phrase_val<2: continue
  overall_trg_count=trg_counter_dict[cur_trg_phrase]
  cur_ratio=trg_phrase_val/(overall_src_count+overall_trg_count-trg_phrase_val)
  final_list.append((src_phrase,cur_trg_phrase,trg_phrase_val, round(cur_ratio,4)))
  #print(cur_trg_phrase,trg_phrase_val, round(cur_ratio,4))
final_list.sort(key=lambda x:-x[-1])
for a in final_list[:10]:
  print(a)

('other countries', 'بلدان أخرى', 67, 0.1569)
('other countries', 'ال_بلدان ال_أخرى', 49, 0.1222)
('other countries', 'وـ ال_بلدان ال_أخرى', 13, 0.0458)
('other countries', 'إلى بلدان أخرى', 8, 0.0304)
('other countries', 'وـ بلدان أخرى', 4, 0.016)
('other countries', 'لـ بلدان أخرى', 4, 0.0154)
('other countries', 'بـ ال_بلدان ال_أخرى', 3, 0.0126)
('other countries', 'لـ ال_بلدان ال_أخرى', 3, 0.0122)
('other countries', 'وـ غير ـها من ال_بلدان', 3, 0.0119)
('other countries', 'غير ـها من ال_بلدان', 3, 0.0117)


In [ ]:
span1=(5,15)
span2=(18,19)
y_dist=get_span_dist(span1,span2)
print(y_dist)

3


In [ ]:
ar_corpus_fname="UNv1.0.ar-en-clean2.ar"
en_corpus_fname="UNv1.0.ar-en.en"

n_sents_max=200000
ar_fopen=open(ar_corpus_fname)
en_fopen=open(en_corpus_fname)

src_sents,trg_sents=[],[]
for i,pair in enumerate(zip(en_fopen,ar_fopen)):
  if i>=n_sents_max: break
  if i%20000==0: print(i)
  en_line,ar_line=pair
  en_line,ar_line=en_line.strip("\n\r\t "),ar_line.strip("\n\r\t ")
  src_sents.append(en_line)
  trg_sents.append(ar_line)

ar_fopen.close()
en_fopen.close()
print(len(src_sents),len(src_sents))
print("Now adding another bitext in a Google sheet")
import pandas as pd
#Job Bitexts
#xls_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vSqipSUAaMWJrizvZtg1WIpds2pIiXtcZC6wjOLeVYie9p5O0lqiPnVdd8ambGKH8B0qJ4kmlVeEs6f/pub?output=xlsx'
#Ref bitexts
xls_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vSVy7hY4fV0LHqTCypOjZAM9OrBevDDnpIcEKEAPKDsYRoxAz9TUBcDIgy8PvHkw5IDAZ6eRmKdZuRw/pub?output=xlsx'
cur_xls = pd.ExcelFile(xls_path)
for cur_sheet_name in cur_xls.sheet_names:
  print(cur_sheet_name)
  #cur_sheet_name="2"
  cur_sheet_obj=pd.read_excel(cur_xls, cur_sheet_name,keep_default_na=False)
  cur_sheet_obj['en']=cur_sheet_obj['en'].apply(str)
  cur_sheet_obj['ar']=cur_sheet_obj['ar'].apply(str)
  # print(cur_sheet_obj)
  # continue

  sent_pair_list=[]
  for i,row in enumerate(cur_sheet_obj.iterrows()):
    row_dict=row[1].to_dict()
    en0,ar0=row_dict["en"],row_dict["ar"]
    ar0=clean_ar(ar0)
    sent_pair_list.append((en0,ar0))
    src_sents.append(en0)
    trg_sents.append(ar0)

#Now indexing
print("Now indexing all sentences")
src_indexing_obj=indexing(src_sents,tok,stop_words=["the","of","and","its","his","her","it","is","are", "their"],ignore_punc=True)
print("finihsed indexing source sentences")
trg_indexing_obj=indexing(trg_sents,cur_ar_tok_fn,ignore_ar_pre_suf=True,ignore_punc=True)
print("finihsed indexing target sentences")

0
20000
40000
60000
80000
100000
120000
140000
160000
180000
200000 200000
Now adding another bitext in a Google sheet
A75760
A76562
A76564
A76572
A76529
A76547
A74594
A76549
A76552
A74597
A75785
Now indexing all sentences
0
5000
10000
15000
20000
25000
30000
35000
40000
45000
50000
55000
60000
65000
70000
75000
80000
85000
90000
95000
100000
105000
110000
115000
120000
125000
130000
135000
140000
145000
150000
155000
160000
165000
170000
175000
180000
185000
190000
195000
200000
205000
210000
215000
220000
225000
230000
finihsed indexing source sentences
0
5000
10000
15000
20000
25000
30000
35000
40000
45000
50000
55000
60000
65000
70000
75000
80000
85000
90000
95000
100000
105000
110000
115000
120000
125000
130000
135000
140000
145000
150000
155000
160000
165000
170000
175000
180000
185000
190000
195000
200000
205000
210000
215000
220000
225000
230000
finihsed indexing target sentences


#Starting Alignmenet

In [ ]:
import math

def overlaps(span1,span2):
  span1_i0,span1_i1=span1
  span2_i0,span2_i1=span2
  if span1_i0>=span2_i0 and span1_i0<=span2_i1: return True
  if span1_i1>=span2_i0 and span1_i1<=span2_i1: return True
  if span2_i0>=span1_i0 and span2_i0<=span1_i1: return True
  if span2_i1>=span1_i0 and span2_i1<=span1_i1: return True
  return False

def get_inner_dist(span1,span2):
  combined_xs=[]
  combined_xs.extend(span1)
  combined_xs.extend(span2)  
  combined_xs.sort()
  return combined_xs[2]-combined_xs[1]

def get_rec_el_children(el0,el_child_dict0,el_list0=[]):
  cur_children0=el_child_dict0.get(el0,[])
  for ch0 in cur_children0:
    el_list0.append(ch0)
    el_list0=get_rec_el_children(ch0,el_child_dict0,el_list0)
  return el_list0

def get_min_max(range1,range2):
  range1_x0,range1_x1=range1
  range2_x0,range2_x1=range2
  min_x=min(range1_x0,range1_x1,range2_x0,range2_x1)
  max_x=max(range1_x0,range1_x1,range2_x0,range2_x1)
  return (min_x,max_x)

def get_area_factor(x_range1,y_range1):
  x_dist=x_range1[1]-x_range1[0]+1
  y_dist=y_range1[1]-y_range1[0]+1
  cur_factor=(x_dist+y_dist)/2
  return cur_factor #math.log(cur_factor)


def get_tok_loc(tok_list):
  tok_locs_list=[]
  for i_,cur_tok in enumerate(tok_list):
    tok_locs_list.append(((cur_tok,),(i_,i_))) #to get unigrams and their locations
    if i_<len(tok_list)-1: tok_locs_list.append(((cur_tok,tok_list[i_+1]), (i_,i_+1))) #to get bigrams and their locations
  tok_locs_list.sort(key=lambda x:x[0])
  grouped=[(key,[v[1] for v in list(group)]) for key,group in groupby(tok_locs_list,lambda x:x[0])]
  return grouped


class walign:
  def __init__(self,src0,trg0,src_inv_dict0,trg_inv_dict0,max_n_elms=10,min_ratio=0.05):
    span_el_dict={} #which element corresponds to this span
    span_wt_dict={} #wight of each span
    span_child_dict={} #which subspans this span consists of
    
    span_top_elms_dict={} #show the top elements for each span
    el_wt_dict={} #show the weight of each element
    start_span_dict={} #show all the spans corresponding to a src location
    el_child_dict={} #show which elements are children of which
    all_phrase_pairs=[]

    src0=['<s>']+src0+['</s>']
    trg0=['<s>']+trg0+['</s>']
    self.src0=src0
    self.trg0=trg0
    src_grouped=get_tok_loc(src0) #group all the locations for a list of consecutive tokens (src then trg)
    trg_grouped=get_tok_loc(trg0)
    src_side,trg_side=[],[]

    for s_toks,s_locs_grp in src_grouped: #retrive the indexes for each token sequence, map them to the locations
      src_indexes0= rtrv_idx(s_toks,src_inv_dict0)
      src_side.append((s_toks,s_locs_grp,src_indexes0))
    for t_toks,t_locs_grp in trg_grouped:
      trg_indexes0= rtrv_idx(t_toks,trg_inv_dict0)
      trg_side.append((t_toks,t_locs_grp,trg_indexes0))

    #now starting the match the indexes of both src and trg token locations and get the corresponding rations/weights
    matching_list=[]
    all_elements=[] #to create elements (pairs of src-trg spans)
    tmp_ratio_dict={}
    for s_toks,s_locs_grp,src_indexes0 in src_side:
      s_toks_str=" ".join(s_toks)
      for t_toks,t_locs_grp,trg_indexes0 in trg_side:
        cur_ratio=0
        t_toks_str=" ".join(t_toks)
        if s_toks==t_toks: cur_ratio=1
        else: 
          if len(src_indexes0)==0 or len(trg_indexes0)==0: continue #cur_ratio= 0
          cur_ratio=idx_match(src_indexes0,trg_indexes0,5)
        if cur_ratio==0: continue
        for sl0 in s_locs_grp:
          for tl0 in t_locs_grp:
            cur_el=(sl0,tl0) #an element is a tuple containing the span of src indexes and span of trg indexes
            tmp_ratio_dict[cur_el]=cur_ratio
            #all_elements.append((cur_el,s_toks_str,t_toks_str,cur_ratio))
            all_elements.append((cur_el,cur_ratio))
            found_wt=span_wt_dict.get(sl0,0)
            if found_wt<cur_ratio:
              span_wt_dict[sl0]=cur_ratio
              span_el_dict[sl0]=cur_el
              span_child_dict[sl0]=[]
    #####
    #and now let's group all the elements by the starting location of the src tokenized sentence
    all_elements.sort(key=lambda x:(x[0][0],-x[-1]))
    all_elements_grouped=[(key,list(group)) for key,group in groupby(all_elements,lambda x:x[0][0])]

    #initially populating the start/span/element/weight dictionaries
    for k0,grp0 in all_elements_grouped:
      for el0,el_wt0 in grp0[:max_n_elms]:
        if el_wt0<min_ratio: continue
        el_wt_dict[el0]=el_wt0

    all_elements.sort(key=lambda x:-x[-1])
    used_src,used_trg=[],[]
    new_el_wt_list=[]
    for ae in all_elements: #get the elements below the top by iteratively discarding the top used elements
      el0,wt0=ae
      src_span,trg_span=el0    
      if any([v in used_src for v in src_span]): continue
      if any([v in used_trg for v in trg_span]): continue
      used_src.extend(src_span)
      used_trg.extend(trg_span)
      new_el_wt_list.append(ae)
      el_wt_dict[el0]=wt0#+0.2
    
    #all_elements.sort(key=lambda x:(x[0][0][0],-x[-1]))

    el_wt_list=list(el_wt_dict.items())
    el_wt_list.sort(key=lambda x:(x[0][0],-x[-1]))
    for el0,wt0 in el_wt_list:
      #print(el0,wt0)
      src_span0,trg_span0=el0
      start_i=src_span0[0]
      found_spans=start_span_dict.get(start_i,[])
      if not src_span0 in found_spans: start_span_dict[start_i]=found_spans+[src_span0]
      found_elements=span_top_elms_dict.get(src_span0,[])
      if not el0 in found_elements: span_top_elms_dict[src_span0]=found_elements+[el0]


    used_el_dict={}
    full_src_span=(0,len(src0)-1)
    full_trg_span=(0,len(trg0)-1)
    src_trg_span=(full_src_span,full_trg_span)
    #cur_full_span_wt=span_wt_dict.get(full_src_span,0)
    cur_el_full_span_wt=el_wt_dict.get(src_trg_span,0) #check if there is an element that covers the full src/trg span
    

    for inc0 in range(15): #increments to cover slices of src location indexes
      
      test_el_wt=sorted(list(el_wt_dict.items()),key=lambda x:-x[-1])
      tmp_el_full_span_wt=el_wt_dict.get(src_trg_span,0)
      print(inc0,test_el_wt[0], tmp_el_full_span_wt) #Checking the situation with the convergence of the full src/trg span element
      if tmp_el_full_span_wt>0:
        if tmp_el_full_span_wt>cur_el_full_span_wt: cur_el_full_span_wt=tmp_el_full_span_wt
        else: 
          print("alignment solved")
          break


      for i0 in range(len(src0)):
        first_spans=start_span_dict.get(i0,[])
        first_elements=[]
        for sp0 in first_spans:
          first_elements.extend(span_top_elms_dict.get(sp0,[]))
        valid_next_items_counter=0
        for el0 in first_elements:
          el0_wt=el_wt_dict.get(el0,0)
          el0_src_span,el0_trg_span=el0
          el0_src_span_i0,el0_src_span_i1=el0_src_span
          el0_trg_span_i0,el0_trg_span_i1=el0_trg_span

          second_spans=[]
          second_elements=[]
          for i1 in range(el0_src_span_i1,el0_src_span_i1+5):
            second_spans.extend(start_span_dict.get(i1,[]))
          for sp1 in second_spans: second_elements.extend(span_top_elms_dict.get(sp1,[]))
          for el1 in second_elements:
            if el1==el0: continue #we should clean up all the skipping conditions to make sure everything is organized and accounted for, and we're not skipping something that should be kept
            el1_wt=el_wt_dict.get(el1,0)
            el1_src_span,el1_trg_span=el1
            el1_src_span_i0,el1_src_span_i1=el1_src_span
            el1_trg_span_i0,el1_trg_span_i1=el1_trg_span
            trg_spans_overlap=overlaps(el0_trg_span,el1_trg_span)
            src_spans_overlap=overlaps(el0_src_span,el1_src_span)
            
            if el0_src_span==el1_src_span and el0_src_span_i0!=el0_src_span_i1: continue #if [(1,2),(4,5)] [(1,2),(7,6)]
            if trg_spans_overlap: continue #skip if target spans overlap
            if src_spans_overlap and el0_src_span!=el1_src_span: continue

            trg_span_inner_dist=get_inner_dist(el0_trg_span,el1_trg_span)
            if trg_span_inner_dist>10: continue #skip if there is much distance between target spans

            src_span_inner_dist=get_inner_dist(el0_src_span,el1_src_span)
            
            delta_x=el0_src_span_i1-el0_src_span_i0
            excluded=False
            trg_outer_dist=max(el1_trg_span) - min(el0_trg_span)
            if el0_src_span==el1_src_span:
              if el1_trg_span_i1<el0_trg_span_i0: excluded=True
              elif trg_outer_dist>6: excluded=True
              elif trg_span_inner_dist>1: excluded=True
            
            combined_src_span=get_min_max(el0_src_span,el1_src_span)
            combined_trg_span=get_min_max(el0_trg_span,el1_trg_span) 
            if combined_src_span[1]-combined_src_span[0]<2:
              if combined_trg_span[1]-combined_trg_span[0]>8: excluded=True
            if combined_src_span[1]-combined_src_span[0]<3:
              if combined_trg_span[1]-combined_trg_span[0]>10: excluded=True
            

            el_pair=(el0,el1)
            if used_el_dict.get(el_pair,False)==True: excluded=True
            used_el_dict[el_pair]=True

            if excluded: continue

            
            combined_wt=el0_wt+el1_wt
            

            area_factor=get_area_factor(combined_src_span,combined_trg_span)
            #combined_wt=combined_wt-0.02*area_factor
            combined_wt=combined_wt-trg_span_inner_dist*0.05

            combined_el=(combined_src_span,combined_trg_span)
            found_wt=el_wt_dict.get(combined_el,0)
            if found_wt>0 and (combined_src_span[0]==combined_src_span[1]): continue #very sketechy solution to avoid situations where a bigram is replaced by a less likely combination of two consecutive unigrams
            if found_wt>0 and (combined_trg_span[0]==combined_trg_span[1]): continue
            if combined_wt>found_wt:
              el_wt_dict[combined_el]=combined_wt
              el_child_dict[combined_el]=(el0,el1)
              tmp_elements_in_span=span_top_elms_dict.get(combined_src_span,[])
              if not combined_el in tmp_elements_in_span:
                tmp_elements_in_span.append(combined_el)
                tmp_elements_in_span.sort(key=lambda x:-el_wt_dict.get(x,0))
                span_top_elms_dict[combined_src_span]=tmp_elements_in_span[:max_n_elms]
              tmp_spans_starting_with_i0=start_span_dict.get(i0,[])
              if not combined_src_span in tmp_spans_starting_with_i0:
                start_span_dict[i0]=tmp_spans_starting_with_i0+[combined_src_span]
            #if found_wt>0:
            # if el0_src_span==el1_src_span and False:
            #   print(inc0,"excluded",excluded,trg_outer_dist)
            #   print(el0,el0_wt)
            #   print(el1,el1_wt)
            #   print("combined:",combined_el,combined_wt)
            #   print("found:",found_wt)
            #   print("-----")

            valid_next_items_counter+=1

    all_elements2=get_rec_el_children(src_trg_span,el_child_dict,el_list0=[])
    #all_elements=get_rec_children(list_spans_wts[0][0],span_child_dict,span_el_dict,el_list0=[])
    self.final_el_list=[]
    for ch_el in all_elements2:
      #print(ch_el, el_wt_dict[ch_el])
      self.final_el_list.append((ch_el, el_wt_dict[ch_el]))
      src_span0,trg_span0=ch_el
      cur_src_str=" ".join([src0[i_] for i_ in range(src_span0[0],src_span0[1]+1)])
      cur_trg_str=" ".join([trg0[i_] for i_ in range(trg_span0[0],trg_span0[1]+1)])  
      cur_pair=(cur_src_str,cur_trg_str)
      # print(cur_src_str)   
      # print(cur_trg_str) 
      # print("--") 
      # all_phrase_pairs.append((cur_pair))
      #all_phrase_pairs.append((cur_pair,sent_counter))
    # for a in all_phrase_pairs:
    #   print(a)

src_list=src_indexing_obj.all_tok_sentences
trg_list=trg_indexing_obj.all_tok_sentences
src_list_orig=src_indexing_obj.all_tok_original_sentences
trg_list_orig=trg_indexing_obj.all_tok_original_sentences
src_mappings_list=src_indexing_obj.all_mappings
trg_mappings_list=trg_indexing_obj.all_mappings


src_inv_dict=src_indexing_obj.inv_index
trg_inv_dict=trg_indexing_obj.inv_index

phrase_fpath="phrase_list_test.txt"
fopen=open(phrase_fpath,"w")

test_i=7104
n_sents=1
sent_counter=0
all_phrase_pairs=[]
for test_i in range(0,1000):
  print(test_i)
  src_tokens,trg_tokens=src_list[test_i],trg_list[test_i]
  src_mappings,trg_mappings=src_mappings_list[test_i],trg_mappings_list[test_i]
  src_original_tokens,trg_original_tokens=src_list_orig[test_i],trg_list_orig[test_i]
  # print("src_mappings",src_mappings)
  # print("trg_mappings",trg_mappings)
  src_original_tokens=["<s>"]+src_original_tokens+["</s>"]
  trg_original_tokens=["<s>"]+trg_original_tokens+["</s>"]

  new_src_mappings=[0]+[v+1 for v in src_mappings]+[len(src_original_tokens)-1]
  new_trg_mappings=[0]+[v+1 for v in trg_mappings]+[len(trg_original_tokens)-1]
  # print("new_src_mappings",new_src_mappings)
  # print("new_trg_mappings",new_trg_mappings)
  align_obj=walign(src_tokens,trg_tokens,src_inv_dict,trg_inv_dict,max_n_elms=10)
  # print(src_tokens)
  # print(trg_tokens)

  # print("Original SRC: >>>",src_original_tokens)
  # print("Original TRG: >>>",trg_original_tokens)
  # print("orig src:",len(src_original_tokens), "orig trg:",len(trg_original_tokens))
  # print("filtered src:",len(src_tokens), "filtered trg:",len(trg_tokens))
  # print("aligned src:",len(align_obj.src0), "aligned trg:",len(align_obj.trg0))
  for el0,wt0 in align_obj.final_el_list:
    # print(el0,wt0)
    src_span0,trg_span0=el0
    src_i0,src_i1=src_span0
    trg_i0,trg_i1=trg_span0
    new_src_i0,new_src_i1=new_src_mappings[src_i0],new_src_mappings[src_i1]
    new_trg_i0,new_trg_i1=new_trg_mappings[trg_i0],new_trg_mappings[trg_i1]
    src_phrase_tokens=src_original_tokens[new_src_i0:new_src_i1+1]
    trg_phrase_tokens=trg_original_tokens[new_trg_i0:new_trg_i1+1]
    src_phrase_str=" ".join(src_phrase_tokens)
    trg_phrase_str=" ".join(trg_phrase_tokens)
    # print(src_phrase_str)
    # print(trg_phrase_str)
    line='%s\t%s\t%s\n'%(src_phrase_str,trg_phrase_str,round(wt0,4))
    fopen.write(line)
    # #src_span0,trg_span0=ch_el
    # cur_src_str=" ".join([src_tokens[i_] for i_ in range(src_span0[0],src_span0[1]+1)])
    # cur_trg_str=" ".join([trg_tokens[i_] for i_ in range(trg_span0[0],trg_span0[1]+1)])  
    # print("Filtered - SRC: >>>",cur_src_str)
    # print("Filtered - TRG: >>>",cur_trg_str)

  # print("----")

fopen.close()
# for src_tokens,trg_tokens in zip(src_list[test_i:test_i+n_sents],trg_list[test_i:test_i+n_sents]):
#   print(sent_counter)
#   print(src_tokens)
#   print(trg_tokens)
  

Streaming output truncated to the last 5000 lines.
1 (((12, 14), (10, 14)), 2.021784913973186) 0
2 (((0, 13), (0, 11)), 3.0805376007702883) 0
3 (((0, 14), (0, 14)), 5.522061867548715) 5.522061867548715
4 (((0, 14), (0, 14)), 5.522061867548715) 5.522061867548715
alignment solved
337
0 (((0, 0), (0, 0)), 1) 0
1 (((0, 4), (0, 6)), 1.613978494623656) 0
2 (((0, 7), (0, 6)), 1.6272819883449043) 0
3 (((0, 21), (0, 18)), 2.581283214889811) 0
4 (((0, 22), (0, 18)), 2.816168752231888) 0
5 (((0, 22), (0, 18)), 2.816168752231888) 0
6 (((0, 22), (0, 18)), 2.816168752231888) 0
7 (((0, 22), (0, 18)), 2.816168752231888) 0
8 (((0, 22), (0, 18)), 2.816168752231888) 0
9 (((0, 22), (0, 18)), 2.816168752231888) 0
10 (((0, 22), (0, 18)), 2.816168752231888) 0
11 (((0, 22), (0, 18)), 2.816168752231888) 0
12 (((0, 22), (0, 18)), 2.816168752231888) 0
13 (((0, 22), (0, 18)), 2.816168752231888) 0
14 (((0, 22), (0, 18)), 2.816168752231888) 0
338
0 (((0, 0), (0, 0)), 1) 0
1 (((44, 46), (40, 42)), 2.2500868325172014

#Processing Phrase Table

In [ ]:
phrase_fpath="phrase_list_test.txt"
phrase_fopen=open(phrase_fpath)
phrase_corr_dict={}
for i0,line0 in enumerate(phrase_fopen):
  #continue
  #if i0>5000: break
  line_split=line0.strip().split("\t")
  if len(line_split)<3: continue
  src0,trg0,wt0=line_split[:3]
  wt0=float(wt0)
  if src0==trg0: continue
  src0_lower=src0.lower()
  tmp_dict=phrase_corr_dict.get(src0_lower,{})
  found_total_count,found_total_wt=tmp_dict.get(trg0,(0,0))
  found_total_count,found_total_wt=found_total_count+1,found_total_wt+wt0
  tmp_dict[trg0]=(found_total_count,found_total_wt)
  phrase_corr_dict[src0_lower]=tmp_dict




  #print([src0,trg0,wt0])

phrase_fopen.close()
for a,b in phrase_corr_dict.items():
  for a1,b1 in b.items():
    if b1[0]<5: continue
    print(a)
    print(a1)
    print(b1)
    print("-----")


international law commission
لجنة ال_قانون ال_دولي
(5, 6.6690000000000005)
-----
international law
ال_قانون ال_دولي
(10, 11.372)
-----
international
ال_دولي
(31, 14.904800000000007)
-----
international
دولي
(21, 10.096800000000004)
-----
international
دولية
(34, 13.739399999999993)
-----
international
ال_دولية
(35, 14.143499999999992)
-----
law
ال_قانون
(43, 30.375199999999978)
-----
law
قانون
(5, 3.532)
-----
commission
لجنة
(9, 2.2184999999999997)
-----
commission
ال_لجنة
(20, 4.9300000000000015)
-----
forty
ال_أربعين
(13, 7.695999999999998)
-----
session
ال_دورة
(10, 5.198999999999999)
-----
session
دورتها
(9, 3.1032)
-----
may
أيار / مايو
(10, 3.5210000000000004)
-----
may
قد
(11, 0.8162000000000001)
-----
july
تموز / يوليه
(10, 9.006)
-----
comments
تعليقات
(11, 8.3897)
-----
comments
ال_تعليقات
(7, 5.3389)
-----
governments
ال_حكومات
(22, 17.48119999999999)
-----
on
على
(41, 9.753899999999993)
-----
on
بشأن
(13, 2.1476)
-----
on
في
(18, 4.433400000000001)
-----
on
من
(11, 2.02840

In [ ]:
import math
src_list=src_indexing_obj.all_tok_sentences
trg_list=trg_indexing_obj.all_tok_sentences
src_inv_dict=src_indexing_obj.inv_index
trg_inv_dict=trg_indexing_obj.inv_index

def overlaps(span1,span2):
  span1_i0,span1_i1=span1
  span2_i0,span2_i1=span2
  if span1_i0>=span2_i0 and span1_i0<=span2_i1: return True
  if span1_i1>=span2_i0 and span1_i1<=span2_i1: return True
  if span2_i0>=span1_i0 and span2_i0<=span1_i1: return True
  if span2_i1>=span1_i0 and span2_i1<=span1_i1: return True
  return False

def get_inner_dist(span1,span2):
  combined_xs=[]
  combined_xs.extend(span1)
  combined_xs.extend(span2)  
  combined_xs.sort()
  return combined_xs[2]-combined_xs[1]

# def get_rec_children(span0,span_child_dict0,span_el_dict0,el_list0=[]):
#   cur_children0=span_child_dict0.get(span0,[])
#   for ch0 in cur_children0:
#     el_list0.append(span_el_dict0[ch0])
#     el_list0=get_rec_children(ch0,span_child_dict0,span_el_dict0,el_list0)
#   return el_list0

def get_rec_el_children(el0,el_child_dict0,el_list0=[]):
  cur_children0=el_child_dict0.get(el0,[])
  for ch0 in cur_children0:
    el_list0.append(ch0)
    el_list0=get_rec_el_children(ch0,el_child_dict0,el_list0)
  return el_list0

def get_min_max(range1,range2):
  range1_x0,range1_x1=range1
  range2_x0,range2_x1=range2
  min_x=min(range1_x0,range1_x1,range2_x0,range2_x1)
  max_x=max(range1_x0,range1_x1,range2_x0,range2_x1)
  return (min_x,max_x)

def get_dist_factor(el1,el2): #[(5,6),(9,9)] - [(7,7),(12,13)] #get inner distance between two elements, 1 if adjacent
  el1_xrange,el1_yrange=el1
  el2_xrange,el2_yrange=el2
  combined_xs=[]
  combined_xs.extend(el1_xrange)
  combined_xs.extend(el2_xrange)
  combined_ys=[]
  combined_ys.extend(el1_yrange)
  combined_ys.extend(el2_yrange)
  combined_xs.sort()
  combined_ys.sort()
  inner_xdist=combined_xs[2]-combined_xs[1]
  inner_ydist=combined_ys[2]-combined_ys[1]
  return (inner_xdist+inner_ydist)/2

def get_area_factor(x_range1,y_range1):
  x_dist=x_range1[1]-x_range1[0]+1
  y_dist=y_range1[1]-y_range1[0]+1
  cur_factor=(x_dist+y_dist)/2
  return cur_factor #math.log(cur_factor)


def get_tok_loc(tok_list):
  tok_locs_list=[]
  for i_,cur_tok in enumerate(tok_list):
    tok_locs_list.append(((cur_tok,),(i_,i_)))
    if i_<len(tok_list)-1: tok_locs_list.append(((cur_tok,tok_list[i_+1]), (i_,i_+1)))
  tok_locs_list.sort(key=lambda x:x[0])
  grouped=[(key,[v[1] for v in list(group)]) for key,group in groupby(tok_locs_list,lambda x:x[0])]
  return grouped


test_i=-len(sent_pair_list)
n_sents=len(sent_pair_list)-2

max_n_elms=10 #max number of elements per span

test_i=4001
test_i=100
#test_i=12005
n_sents=1
sent_counter=0
all_phrase_pairs=[]
for src0,trg0 in zip(src_list[test_i:test_i+n_sents],trg_list[test_i:test_i+n_sents]):
  print(sent_counter)
  print(src0)
  print(trg0)
  span_el_dict={} #which element corresponds to this span
  span_wt_dict={} #wight of each span
  span_child_dict={} #which subspans this span consists of
  
  span_top_elms_dict={} #show the top elements for each span
  el_wt_dict={} #show the weight of each element
  start_span_dict={} #show all the spans corresponding to a src location
  el_child_dict={} #show which elements are children of which

  src0=['<s>']+src0+['</s>']
  trg0=['<s>']+trg0+['</s>']
  src_grouped=get_tok_loc(src0) #group all the locations for a list of consecutive tokens (src then trg)
  trg_grouped=get_tok_loc(trg0)
  src_side,trg_side=[],[]

  for s_toks,s_locs_grp in src_grouped: #retrive the indexes for each token sequence, map them to the locations
    src_indexes0= rtrv_idx(s_toks,src_inv_dict)
    src_side.append((s_toks,s_locs_grp,src_indexes0))
  for t_toks,t_locs_grp in trg_grouped:
    trg_indexes0= rtrv_idx(t_toks,trg_inv_dict)
    trg_side.append((t_toks,t_locs_grp,trg_indexes0))

  #now starting the match the indexes of both src and trg token locations
  matching_list=[]
  all_elements=[] #to create elements (pairs of src-trg spans)
  tmp_ratio_dict={}
  for s_toks,s_locs_grp,src_indexes0 in src_side:
    s_toks_str=" ".join(s_toks)
    #continue
    #print(s_toks,s_locs_grp,len(src_indexes0))
    for t_toks,t_locs_grp,trg_indexes0 in trg_side:
      cur_ratio=0
      t_toks_str=" ".join(t_toks)
      if s_toks==t_toks: cur_ratio=1
      else: 
        #cur_ratio=idx_match(src_indexes0,trg_indexes0)
        if len(src_indexes0)==0 or len(trg_indexes0)==0: continue #cur_ratio= 0
        cur_ratio=idx_match(src_indexes0,trg_indexes0,5)
      if cur_ratio==0: continue
      for sl0 in s_locs_grp:
        for tl0 in t_locs_grp:
          cur_el=(sl0,tl0) #an element is a tuple containing the span of src indexes and span of trg indexes
          tmp_ratio_dict[cur_el]=cur_ratio
          #all_elements.append((cur_el,s_toks_str,t_toks_str,cur_ratio))
          all_elements.append((cur_el,cur_ratio))
          found_wt=span_wt_dict.get(sl0,0)
          if found_wt<cur_ratio:
            span_wt_dict[sl0]=cur_ratio
            span_el_dict[sl0]=cur_el
            span_child_dict[sl0]=[]
  


      #matching_list.append((s_toks,t_toks,cur_ratio))
  #and now let's group all the elements by the starting location of the src tokenized sentence
  all_elements.sort(key=lambda x:(x[0][0],-x[-1]))
  all_elements_grouped=[(key,list(group)) for key,group in groupby(all_elements,lambda x:x[0][0])]

  #initially populating the start/span/element/weight dictionaries
  for k0,grp0 in all_elements_grouped:
    start_i=k0[0]
    #start_span_dict[start_i]=start_span_dict.get(start_i,[])+[k0]
    #span_top_elms_dict[k0]=[v[0] for v in grp0[:max_n_elms]]
    for el0,el_wt0 in grp0[:max_n_elms]:
      if el_wt0<0.01: continue
      el_wt_dict[el0]=el_wt0
      #print(g0)
  #   print("---")
  # for a,b in start_span_dict.items():
  #   print(a,b)
  all_elements.sort(key=lambda x:-x[-1])
  used_src,used_trg=[],[]
  new_el_wt_list=[]
  for ae in all_elements: #get the elements below the top by iteratively discarding the top used elements
    el0,wt0=ae
    src_span,trg_span=el0    
    if any([v in used_src for v in src_span]): continue
    if any([v in used_trg for v in trg_span]): continue
    used_src.extend(src_span)
    used_trg.extend(trg_span)
    new_el_wt_list.append(ae)
    el_wt_dict[el0]=wt0#+0.2
    #print(ae)

  
  all_elements.sort(key=lambda x:(x[0][0][0],-x[-1]))
  # all_elements=new_el_wt_list+all_elements
  # for ae0 in all_elements[:30]:
  #   print(">>", ae0)
  el_wt_list=list(el_wt_dict.items())
  el_wt_list.sort(key=lambda x:(x[0][0],-x[-1]))
  for el0,wt0 in el_wt_list:
    #print(el0,wt0)
    src_span0,trg_span0=el0
    start_i=src_span0[0]
    found_spans=start_span_dict.get(start_i,[])
    if not src_span0 in found_spans: start_span_dict[start_i]=found_spans+[src_span0]
    found_elements=span_top_elms_dict.get(src_span0,[])
    if not el0 in found_elements: span_top_elms_dict[src_span0]=found_elements+[el0]

    
  # for a,b in start_span_dict.items():
  #   print("start span >>>",a,b)
  # for a,b in span_top_elms_dict.items():
  #   print("top elements +++",a,b)

  # break
  # all_elements_grouped=[(key,list(group)) for key,group in groupby(all_elements,lambda x:x[0][0][0])]
  # el_start_dict={}
  # for k0,el_grp in all_elements_grouped:
  #   #el_start_dict[k0]=el_grp[:10] 
  #   el_start_dict[k0]=dict(iter(el_grp[:10])) #for each starting src index , we identify the top 10 elements that start with it
  used_el_dict={}
  full_src_span=(0,len(src0)-1)
  full_trg_span=(0,len(trg0)-1)
  src_trg_span=(full_src_span,full_trg_span)
  cur_full_span_wt=span_wt_dict.get(full_src_span,0)
  cur_el_full_span_wt=el_wt_dict.get(src_trg_span,0)
  
  #continue  
  for inc0 in range(15): #increments to cover slices of src location indexes
    
    # test_wt=sorted(list(span_wt_dict.items()),key=lambda x:-x[-1])
    # tmp_full_span_wt=span_wt_dict.get(full_src_span,0)
    # test_wt1=[v for v in test_wt if v[0][0]==0]
    #print(inc0,test_wt[0],test_wt1[0],full_src_span, tmp_full_span_wt)
    test_el_wt=sorted(list(el_wt_dict.items()),key=lambda x:-x[-1])
    #test_el_wt1=[v for v in test_el_wt if v[0][0]==0]
    tmp_el_full_span_wt=el_wt_dict.get(src_trg_span,0)
    print(inc0,test_el_wt[0], tmp_el_full_span_wt)
    if tmp_el_full_span_wt>0:
      if tmp_el_full_span_wt>cur_el_full_span_wt: cur_el_full_span_wt=tmp_el_full_span_wt
      else: 
        print("alignment solved")
        break

    


    for i0 in range(len(src0)):
      i1=i0+inc0
      if i1>len(src0)-1: continue
      #if inc0>15: continue
      #first_items=el_start_dict.get(i0,[])
      #first_items=el_start_dict.get(i0,{})

      #New approach
      first_spans=start_span_dict.get(i0,[])
      first_elements=[]
      for sp0 in first_spans:
        first_elements.extend(span_top_elms_dict.get(sp0,[]))
      # print(i0)
      # print("first_spans",len(first_spans),first_spans[:5])
      # print("first_elements",len(first_elements),first_elements[:5])
      valid_next_items_counter=0
      for el0 in first_elements:
        el0_wt=el_wt_dict.get(el0,0)
        el0_src_span,el0_trg_span=el0
        el0_src_span_i0,el0_src_span_i1=el0_src_span
        el0_trg_span_i0,el0_trg_span_i1=el0_trg_span

        second_spans=[]
        second_elements=[]
        for i1 in range(el0_src_span_i1,el0_src_span_i1+5):
          second_spans.extend(start_span_dict.get(i1,[]))
        for sp1 in second_spans: second_elements.extend(span_top_elms_dict.get(sp1,[]))
        for el1 in second_elements:
          if el1==el0: continue
          el1_wt=el_wt_dict.get(el1,0)
          el1_src_span,el1_trg_span=el1
          el1_src_span_i0,el1_src_span_i1=el1_src_span
          el1_trg_span_i0,el1_trg_span_i1=el1_trg_span
          trg_spans_overlap=overlaps(el0_trg_span,el1_trg_span)
          src_spans_overlap=overlaps(el0_src_span,el1_src_span)
          if el0_src_span==el1_src_span and el0_src_span_i0!=el0_src_span_i1: continue #if [(1,2),(4,5)] [(1,2),(7,6)]
          #
          if trg_spans_overlap: continue #skip if target spans overlap
          if src_spans_overlap and el0_src_span!=el1_src_span: continue

          trg_span_inner_dist=get_inner_dist(el0_trg_span,el1_trg_span)
          if trg_span_inner_dist>10: continue #skip if there is much distance between target spans

          src_span_inner_dist=get_inner_dist(el0_src_span,el1_src_span)
          
          #if el0_src_span_i0==el0_src_span_i1==el1_src_span_i0 and el0_src_span_i1!=el1_src_span_i0: continue #vertical element with non-vertical element
          #if el0_src_span_i0==el0_src_span_i1==el1_src_span_i1 and el0_src_span_i1!=el1_src_span_i0: continue #vertical element with non-vertical element
          #print(el0,el1)
          delta_x=el0_src_span_i1-el0_src_span_i0
          excluded=False
          trg_outer_dist=max(el1_trg_span) - min(el0_trg_span)
          if el0_src_span==el1_src_span:
            if el1_trg_span_i1<el0_trg_span_i0: excluded=True
            elif trg_outer_dist>6: excluded=True
            elif trg_span_inner_dist>1: excluded=True
          #if delta_x<2 and trg_outer_dist>8: excluded=True
          
          combined_src_span=get_min_max(el0_src_span,el1_src_span)
          combined_trg_span=get_min_max(el0_trg_span,el1_trg_span) 
          if combined_src_span[1]-combined_src_span[0]<2:
            if combined_trg_span[1]-combined_trg_span[0]>8: excluded=True
          if combined_src_span[1]-combined_src_span[0]<3:
            if combined_trg_span[1]-combined_trg_span[0]>10: excluded=True
          

          el_pair=(el0,el1)
          if used_el_dict.get(el_pair,False)==True: excluded=True
          used_el_dict[el_pair]=True

          if excluded: continue

          
          combined_wt=el0_wt+el1_wt
          

          area_factor=get_area_factor(combined_src_span,combined_trg_span)
          #combined_wt=combined_wt-0.02*area_factor
          combined_wt=combined_wt-trg_span_inner_dist*0.05

          combined_el=(combined_src_span,combined_trg_span)
          found_wt=el_wt_dict.get(combined_el,0)
          if found_wt>0 and (combined_src_span[0]==combined_src_span[1]): continue
          if found_wt>0 and (combined_trg_span[0]==combined_trg_span[1]): continue
          if combined_wt>found_wt:
            el_wt_dict[combined_el]=combined_wt
            el_child_dict[combined_el]=(el0,el1)
            tmp_elements_in_span=span_top_elms_dict.get(combined_src_span,[])
            if not combined_el in tmp_elements_in_span:
              tmp_elements_in_span.append(combined_el)
              tmp_elements_in_span.sort(key=lambda x:-el_wt_dict.get(x,0))
              span_top_elms_dict[combined_src_span]=tmp_elements_in_span[:max_n_elms]
            tmp_spans_starting_with_i0=start_span_dict.get(i0,[])
            if not combined_src_span in tmp_spans_starting_with_i0:
              start_span_dict[i0]=tmp_spans_starting_with_i0+[combined_src_span]
          #if found_wt>0:
          if el0_src_span==el1_src_span and False:
            print(inc0,"excluded",excluded,trg_outer_dist)
            print(el0,el0_wt)
            print(el1,el1_wt)
            print("combined:",combined_el,combined_wt)
            print("found:",found_wt)
            print("-----")

          valid_next_items_counter+=1
          #if valid_next_items_counter>10: continue

        #print("second_elements",len(second_elements),second_elements[:5])
          

      
      continue

  all_elements2=get_rec_el_children(src_trg_span,el_child_dict,el_list0=[])
  #all_elements=get_rec_children(list_spans_wts[0][0],span_child_dict,span_el_dict,el_list0=[])
  for ch_el in all_elements2:
    print(ch_el)
    src_span0,trg_span0=ch_el
    cur_src_str=" ".join([src0[i_] for i_ in range(src_span0[0],src_span0[1]+1)])
    cur_trg_str=" ".join([trg0[i_] for i_ in range(trg_span0[0],trg_span0[1]+1)])  
    cur_pair=(cur_src_str,cur_trg_str)
    print(cur_src_str)   
    print(cur_trg_str) 
    print("--") 
    all_phrase_pairs.append((cur_pair,sent_counter))
  sent_counter+=1
  # print("\t".join(src0))
  # for t0 in trg0: print(t0)

# for a in all_phrase_pairs:
#   print(a)




0
['this', 'a', 'further', 'aspect', 'broader', 'task', 'settling', 'relationship', 'between', 'statute', 'existing', 'treaties']
['هذا', 'جانب', 'آخر', 'من', 'مهمة', 'أعم', 'متمثلة', 'في', 'تسوية', 'علاقة', 'بين', 'نظام', 'أساسي', 'معاهدات', 'قائمة']
0 (((0, 0), (0, 0)), 1) 0
1 (((11, 13), (14, 16)), 1.8009590917987863) 0
2 (((6, 13), (5, 16)), 3.6476920594577056) 2.66096910074624
3 (((0, 13), (0, 16)), 5.257242927554253) 5.257242927554253
4 (((0, 13), (0, 16)), 5.257242927554253) 5.257242927554253
alignment solved
((0, 9), (0, 11))
<s> this a further aspect broader task settling relationship between
<s> هذا جانب آخر من مهمة أعم متمثلة في تسوية علاقة بين
--
((0, 6), (0, 6))
<s> this a further aspect broader task
<s> هذا جانب آخر من مهمة أعم
--
((0, 1), (0, 1))
<s> this
<s> هذا
--
((0, 0), (0, 0))
<s>
<s>
--
((1, 1), (1, 1))
this
هذا
--
((2, 6), (2, 6))
a further aspect broader task
جانب آخر من مهمة أعم
--
((2, 4), (2, 4))
a further aspect
جانب آخر من
--
((2, 3), (3, 4))
a further
آخر 

In [ ]:
cur_span=(47, 47)
cur_span=(21, 22)
cur_span=(21, 21)
#cur_span=(22, 22)
#cur_span=(4, 5)
#cur_span=(34, 35)
#cur_span=(31, 31)
#cur_span=(28, 30)
#cur_span=(29, 29)
#cur_span=(29, 31)
#cur_span=(35, 35)
#cur_span=(21, 22)
cur_span=(23, 23)
test=span_top_elms_dict.get(cur_span,[]) 
for a in test:
  print(a, el_wt_dict.get(a,0))
  src_str=" ".join(src0[a[0][0]:a[0][1]+1])
  trg_str=" ".join(trg0[a[1][0]:a[1][1]+1])
  print(src_str)
  print(trg_str)
  print("----")  
# ((21, 22), (21, 22)) 0.9872094270568594
# secretary general
# أمين عام
# ((21, 21), (21, 21)) 0.911346964257843
# secretary
# أمين
# ----
# ((21, 21), (21, 22)) 1.4313109930348213
# secretary
# أمين عام

((23, 23), (11, 11)) 0.447362499598187
to
في
----
((23, 23), (14, 14)) 0.447362499598187
to
في
----
((23, 23), (32, 32)) 0.447362499598187
to
في
----
((23, 23), (20, 20)) 0.3907348358576708
to
من
----
((23, 23), (4, 4)) 0.3719612262313735
to
إلى
----


In [ ]:
el_child_dict[((21, 23), (20, 21))]

(((21, 21), (21, 21)), ((23, 23), (20, 20)))

In [ ]:
for a,b in el_wt_dict.items():
  if a[0][1]>a[0][0]+3: continue
  print(a,b)
  src_str=" ".join(src0[a[0][0]:a[0][1]+1])
  trg_str=" ".join(trg0[a[1][0]:a[1][1]+1])
  print(src_str, trg_str)
  print("----")
  #print(trg0[a[1][0]:a[1][1]+1])

Streaming output truncated to the last 5000 lines.
not be used نظام لا يجوز استخدام ـها كـ ذريعة لقمع حريات أساسية وـ
----
((6, 9), (4, 14)) 0.5698722927490186
not be used as نظام لا يجوز استخدام ـها كـ ذريعة لقمع حريات أساسية وـ
----
((6, 7), (9, 14)) 0.19729898966059234
not be كـ ذريعة لقمع حريات أساسية وـ
----
((6, 7), (14, 15)) 0.18138297549981997
not be وـ حقوق
----
((6, 7), (7, 14)) 0.17561852475700077
not be استخدام ـها كـ ذريعة لقمع حريات أساسية وـ
----
((6, 7), (13, 14)) 0.17270720657494257
not be أساسية وـ
----
((6, 8), (7, 14)) 0.12807995997190613
not be used استخدام ـها كـ ذريعة لقمع حريات أساسية وـ
----
((6, 8), (10, 14)) 0.0807053147495788
not be used ذريعة لقمع حريات أساسية وـ
----
((6, 8), (9, 14)) 0.07230965281988545
not be used كـ ذريعة لقمع حريات أساسية وـ
----
((6, 8), (13, 14)) 0.06553552029024011
not be used أساسية وـ
----
((6, 9), (10, 14)) 0.16873566921923983
not be used as ذريعة لقمع حريات أساسية وـ
----
((6, 9), (7, 14)) 0.17509057404612044
not be used as استخ

In [ ]:
test_ch=((17, 18), (3, 16))
children0=el_child_dict.get(test_ch,[])
#children0=get_rec_el_children(test_ch,el_child_dict,[])
for ch0 in children0:
  print(ch0)
# print(span_top_elms_dict[(57,57)])
# print(start_span_dict[56])

((17, 17), (3, 3))
((17, 18), (8, 16))


In [ ]:
cur_items=list(span_child_dict.items())
for a in cur_items[:100]:
  print(a)

((1, 1), [])
((47, 47), [])
((47, 48), [(47, 48), (47, 47)])
((45, 45), [])
((45, 46), [(45, 45), (46, 46)])
((51, 51), [])
((51, 52), [(51, 52), (51, 51)])
((57, 57), [])
((57, 58), [(57, 57), (58, 58)])
((43, 43), [(43, 43), (43, 43)])
((49, 49), [(49, 49), (49, 49)])
((43, 44), [(43, 44), (43, 43)])
((49, 50), [(49, 50), (49, 49)])
((42, 42), [])
((42, 43), [(42, 43), (42, 42)])
((54, 54), [])
((54, 55), [(54, 54), (55, 55)])
((55, 55), [])
((55, 56), [(55, 55), (56, 56)])
((41, 41), [])
((41, 42), [(41, 41), (42, 42)])
((46, 46), [])
((46, 47), [(46, 46), (47, 47)])
((53, 53), [])
((53, 54), [(53, 53), (54, 54)])
((58, 58), [])
((0, 0), [])
((0, 1), [(0, 0), (1, 1)])
((48, 48), [])
((48, 49), [])
((21, 21), [(21, 21), (21, 21)])
((21, 22), [(21, 22), (21, 21)])
((31, 31), [])
((31, 32), [])
((27, 27), [])
((27, 28), [])
((2, 2), [])
((15, 15), [(15, 15), (15, 15)])
((19, 19), [(19, 19), (19, 19)])
((52, 52), [])
((52, 53), [])
((15, 16), [(15, 15), (16, 16)])
((19, 20), [(19, 19), 

In [ ]:
fopen=open("test-out-align.txt","w")
for a in all_phrase_pairs:
  line=" ".join([str(v) for v in a])+"\n"
  fopen.write(line)
fopen.close()
  #print(a)

In [ ]:
from collections import Counter
just_pairs=[]
for a in all_phrase_pairs:
  pair,sent_i=a
  src0,trg0=pair
  just_pairs.append(pair)
just_pairs.sort()
grouped=[(key,[v[1] for v in list(group)]) for key,group in groupby(just_pairs,lambda x:x[0])]
grouped.sort(key=lambda x:len(x[1]))
for k0,grp0 in grouped:
  print(k0)
  #print(grp0)
  print(Counter(grp0))
  print("----")

Streaming output truncated to the last 5000 lines.
Counter({'لـ قياس قدرة': 1})
----
mechanism
Counter({'آلية': 1})
----
mechanisms were
Counter({'كانت آليات': 1})
----
meeting
Counter({'اجتماع': 1})
----
meetings
Counter({'اجتماعات': 1})
----
member delegation concerned
Counter({'أعضاء وفد معني': 1})
----
member states at
Counter({'دول أعضاء في': 1})
----
member states at current meeting
Counter({'دول أعضاء في اجتماع حالي': 1})
----
member states but
Counter({'دول أعضاء ولكن': 1})
----
member states but was nevertheless
Counter({'دول أعضاء ولكن ـها مع ذلك': 1})
----
member states but was nevertheless essential to ensuring smooth operation organization </s>
Counter({'دول أعضاء ولكن ـها مع ذلك ضرورية لـ ضمان سلاسة عمل منظمة </s>': 1})
----
member states capacity
Counter({'قدرة دول أعضاء': 1})
----
member states capacity to
Counter({'إلى قدرة دول أعضاء': 1})
----
member states capacity to pay and on
Counter({'إلى قدرة دول أعضاء على دفع وـ': 1})
----
member states capacity to pay and on m

In [ ]:
def get_dist_factor(el1,el2): #[(5,6),(9,9)] - [(7,7),(12,13)] #get inner distance between two elements, 1 if adjacent
  el1_xrange,el1_yrange=el1
  el2_xrange,el2_yrange=el2
  combined_xs=[]
  combined_xs.extend(el1_xrange)
  combined_xs.extend(el2_xrange)
  combined_ys=[]
  combined_ys.extend(el1_yrange)
  combined_ys.extend(el2_yrange)
  combined_xs.sort()
  combined_ys.sort()
  inner_xdist=combined_xs[2]-combined_xs[1]
  inner_ydist=combined_ys[2]-combined_ys[1]
  return (inner_xdist+inner_ydist)/2
test_el1=[(5,6),(9,9)]
test_el2=[(6,6),(10,11)]
print(get_dist_factor(test_el1,test_el2))

0.5


In [ ]:
def overlaps(span1,span2):
  span1_i0,span1_i1=span1
  span2_i0,span2_i1=span2
  if span1_i0>=span2_i0 and span1_i0<=span2_i1: return True
  if span1_i1>=span2_i0 and span1_i1<=span2_i1: return True
  if span2_i0>=span1_i0 and span2_i0<=span1_i1: return True
  if span2_i1>=span1_i0 and span2_i1<=span1_i1: return True
  return False
sp1=(2,3)
sp2=(4,4)
print(overlaps(sp1,sp2))

False


In [ ]:
def get_inner_dist(span1,span2):
  combined_xs=[]
  combined_xs.extend(span1)
  combined_xs.extend(span2)  
  combined_xs.sort()
  return combined_xs[2]-combined_xs[1]
sp1=(22,30)
sp2=(14,16)
print(get_inner_dist(sp1,sp2))

6


In [ ]:
for ix in range(1,10):
  print(ix,math.log(ix))

1 0.0
2 0.6931471805599453
3 1.0986122886681098
4 1.3862943611198906
5 1.6094379124341003
6 1.791759469228055
7 1.9459101490553132
8 2.0794415416798357
9 2.1972245773362196


In [ ]:
import pandas as pd
xls_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vSqipSUAaMWJrizvZtg1WIpds2pIiXtcZC6wjOLeVYie9p5O0lqiPnVdd8ambGKH8B0qJ4kmlVeEs6f/pub?output=xlsx'
cur_xls = pd.ExcelFile(xls_path)
cur_sheet_name="2"
cur_sheet_obj=pd.read_excel(cur_xls, cur_sheet_name,keep_default_na=False)
sent_pair_list=[]
for i,row in enumerate(cur_sheet_obj.iterrows()):
  row_dict=row[1].to_dict()
  sent_pair_list.append((row_dict["en"],row_dict["ar"]))

for a in sent_pair_list:
  print(a)
# print(cur_sheet_obj.keys())

('A/C.5/76/SR.2', 'A/C.5/76/SR.2')
('A/C.5/76/SR.2', 'A/C.5/76/SR.2')
('United Nations', 'الأمم المتحدة')
('A/C.5/76/SR.2', 'A/C.5/76/SR.2')
('General Assembly', 'الجمعية العامة')
('Seventy-sixth session', 'الدورة السادسة والسبعون')
('Official Records', 'وثيقة رسمية')
('Distr.: General', 'Distr.: General')
('24 January 2022', '24 January 2022')
('Original: English', 'Arabic Original: English')
('21-14241', '21-14241')
('This record is subject to correction.', 'هذا المحضر قابل للتصويب.')
('Corrections should be sent as soon as possible, under the signature of a member of the delegation concerned, to the Chief of the Documents Management Section (dms@un.org), and incorporated in a copy of the record.', 'وينبغي إدراج التصويبات في نسخة من المحضر مذيلة بتوقيع أحد أعضاء الوفد المعني وإرسالها في أقرب وقت ممكن إلى: Chief of the Documents Management Section (dms@un.org).')
('Corrected records will be reissued electronically on the Official Document System of the United Nations (http://documents

In [ ]:
def idx_match(idx1,idx2,min_common=5): #This function is to give a ratio of matching between the inverted indexes for two words
    if len(idx1)==0 or len(idx2)==0: return 0
    intersection=len(list(set(idx1).intersection(set(idx2))))
    union=len(idx1)+len(idx2)-intersection
    if union==0: return 0
    if intersection<min_common: return 0    
    return float(intersection)/union

test_idx1=[1,2,4,5,6,9]
test_idx2=[5,6,9,12,25]
idx_match(test_idx1,test_idx2,min_common=2)

0.375

In [ ]:
def filter_tokens(token_list0, lang="en",stop_words=[], ignore_punc=False,ignore_ar_pre_suf=False,remove_al=True,index_words=True,lower=True,stemming=False):
  tokens_original=list(token_list0)
  tokens_copy_enum=[(i,v) for i,v in enumerate(tokens_original)]   
  #if lang=="ar": tokens=tok_ar(tokens,count_dict) #tok_ar(tokens)
  if ignore_punc: tokens_copy_enum=[(i,v) for i,v in tokens_copy_enum if not is_punct(v)]
  if ignore_ar_pre_suf: tokens_copy_enum=[(i,v) for i,v in tokens_copy_enum if not v.startswith("ـ") and not v.endswith("ـ")]
  if stop_words: tokens_copy_enum=[(i,v) for i,v in tokens_copy_enum if not v.lower() in stop_words]
  if remove_al: tokens_copy_enum=[(i,v.replace("ال_","")) for i,v in tokens_copy_enum if not v.lower() in stop_words]
  tokens_out=[v[1] for v in tokens_copy_enum]
  if lower: tokens_out=[v.lower() for v in tokens_out]
  cur_mapping=[v[0] for v in tokens_copy_enum]
  return tokens_out,cur_mapping

sent='As only one country had benefited from that ceiling historically, it should be reviewed in accordance with General Assembly resolution 55/5 C.'
tokens0=tok(sent)
a,b=filter_tokens(tokens0, ignore_punc=True)
print(a)
print(b)

['as', 'only', 'one', 'country', 'had', 'benefited', 'from', 'that', 'ceiling', 'historically', 'it', 'should', 'be', 'reviewed', 'in', 'accordance', 'with', 'general', 'assembly', 'resolution', '55', '5', 'c']
[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 23, 24]


In [ ]:
#DUMP


  #     #print(first_items)
  #     #print(first_items[:3])
  #     #next_items=[]
  #     # next_items=list(first_items)
  #     # for tmp_i in range(i0+1,i1+1):
  #     #   next_items+=el_start_dict.get(tmp_i,[]) 
  #     #tmp_final_list=list(first_items)
  #     tmp_final_list=[] #the list of combined items with the first and next items
  #     #first_items.sort(key=lambda x:-x[-1])
  #     #next_items.sort(key=lambda x:-x[-1])
  #     #print(i0,i1)
  #     # print("first_items",len(first_items),"next_items",len(next_items))
  #     # print("first_items",first_items[:5],"next_items",next_items[:5])
      
  #     # for ni in next_items[-50:]:
  #     #   ni_element,ni_cur_ratio=ni
  #     #   print("NI",ni)
  #     # print("========")
  #     #for fi in first_items:
  #     cur_first_items=list(first_items.items())
  #     for fi in cur_first_items:
  #       fi_element,fi_cur_ratio=fi
  #       fi_src_range,fi_trg_range=fi_element
  #       fi_src_i0,fi_src_i1=fi_src_range
  #       fi_trg_i0,fi_trg_i1=fi_trg_range
  #       valid_next_items_counter=0
  #       next_items=list(cur_first_items)
  #       for i_plus in range(fi_src_i1+1,fi_src_i1+5):
  #         #next_items+=el_start_dict.get(i_plus,[]) 
  #         test_next=el_start_dict.get(i_plus,{})
  #         for nx in test_next.items(): next_items.append(nx)

  #         #print("test_next",test_next)
        

  #       # print(fi, len(next_items))
  #       # print(next_items[:3])
  #       # print("-------")
  #       # continue

  #       for ni in next_items:
  #         ni_element,ni_cur_ratio=ni
  #         if fi_element==ni_element: continue
  #         ni_src_range,ni_trg_range=ni_element
  #         ni_src_i0,ni_src_i1=ni_src_range
  #         ni_trg_i0,ni_trg_i1=ni_trg_range   
  #         if ni_src_i0>fi_src_i1+10: continue

  #         trg_spans_overlap=overlaps(fi_trg_range,ni_trg_range)
  #         if trg_spans_overlap: continue #skip if target spans overlap

  #         trg_span_inner_dist=get_inner_dist(fi_trg_range,ni_trg_range)
  #         if trg_span_inner_dist>10: continue #skip if there is much distance between target spans

  #         src_span_inner_dist=get_inner_dist(fi_src_range,ni_src_range)
          
          
          
  #         if fi_src_i0==fi_src_i1==ni_src_i0 and ni_src_i0!=ni_src_i1: continue #vertical element with non-vertical element
  #         #if ni_src_i0<=fi_src_i1: continue #skip if src spans overlap
          
          
  #         #if src_span_inner_dist>10: continue #skip if there is much distance between source spans
  #         if fi_src_range==ni_src_range: 
  #           if fi_src_i0!=fi_src_i1: continue
  #           if ni_trg_i0<fi_trg_i0: continue
  #           #print(">>>>> Vertical element",fi_element,ni_element)

  #         el_pair=(fi_element,ni_element)
  #         if used_el_dict.get(el_pair,False)==True: continue
  #         used_el_dict[el_pair]=True

  #         valid_next_items_counter+=1

  #         new_src_range=get_min_max(fi_src_range,ni_src_range)
  #         new_trg_range=get_min_max(fi_trg_range,ni_trg_range)
  #         combined_ratio=fi_cur_ratio+ni_cur_ratio
  #         cur_area_factor=get_area_factor(new_src_range,new_trg_range)

  #         if cur_area_factor<1: continue
  #         #adj_ratio=combined_ratio/cur_area_factor
  #         #adj_ratio=combined_ratio-trg_span_inner_dist*0.05-src_span_inner_dist*0.05-cur_area_factor*0.005
  #         adj_ratio=combined_ratio
  #         adj_wt=combined_ratio
  #         cur_el=(new_src_range,new_trg_range)
  #         found_span_wt=span_wt_dict.get(new_src_range,0)
  #         if adj_wt>found_span_wt:


  #           el_start_dict[i0][cur_el]=adj_wt
  #           span_wt_dict[new_src_range]=adj_wt
  #           span_el_dict[new_src_range]=cur_el
  #           # print("fi_element,fi_cur_ratio",fi)
  #           # print("ni_element,ni_cur_ratio",ni)
  #           # print("cur_el,adj_wt",cur_el,adj_wt)
  #           # print("el_start_dict[i0][cur_el]",el_start_dict[i0].get(cur_el,0))
  #           # print("UPDATED el_start_dict[i0][cur_el]",el_start_dict[i0].get(cur_el,0))
  #           # print("------------------")

  #           if new_src_range!=fi_src_range and new_src_range!=ni_src_range:  
  #             span_child_dict[new_src_range]=[fi_src_range,ni_src_range]
  #         found_ratio=tmp_ratio_dict.get(cur_el,0)
  #         if adj_ratio>found_ratio:
  #           tmp_final_list.append((cur_el,adj_ratio))
      
  #     # print("first_items",len(first_items),"next_items",len(next_items),"valid",valid_next_items_counter)
  #     # print("used_el_dict", len(used_el_dict.keys()))
  #     # if valid_next_items_counter==0:
  #     #   for fi in first_items:
  #     #     print(fi)
      
  #     tmp_final_list.sort(key=lambda x:-x[-1])
  #     used_els=[]
  #     final_items=[]
  #     for tp in tmp_final_list:
  #       el0,ratio0=tp
  #       if el0 in used_els: continue
  #       used_els.append(el0)
  #       final_items.append(tp)
  #       src_range0,trg_range0=tp[0]        
  #       cur_src_str=" ".join([src0[i_] for i_ in range(src_range0[0],src_range0[1]+1)])
  #       cur_trg_str=" ".join([trg0[i_] for i_ in range(trg_range0[0],trg_range0[1]+1)])

  #     final_items.sort(key=lambda x:-x[-1])
  #     #el_start_dict[i0]=first_items+final_items[:5] ##### CHECK

  # # list_spans_wts=[]
  # # for a,b in span_wt_dict.items():
  # #   list_spans_wts.append((a,b))
  
  # # list_spans_wts.sort(key=lambda x:-x[-1])

  # # #get_rec_children(span0,span_child_dict0,span_el_dict0,el_list0=[])
  # # print(list_spans_wts[0])
  # tmp_full_span_wt=span_wt_dict.get(full_src_span,0)
  #all_elements=get_rec_children(full_src_span,span_child_dict,span_el_dict,el_list0=[])

#Translation/QA from reference bitexts

In [ ]:
#Preparing references
import pandas as pd
import re
def get_bitext(xls_path0,sheet_name0="",src_col="en",trg_col="ar",filter_non_alpha=False, filter_numbers=False):
  #xls_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vSVy7hY4fV0LHqTCypOjZAM9OrBevDDnpIcEKEAPKDsYRoxAz9TUBcDIgy8PvHkw5IDAZ6eRmKdZuRw/pub?output=xlsx'
  cur_xls = pd.ExcelFile(xls_path0)
  bitext_list=[]
  if sheet_name0!="": cur_sheet_list=[sheet_name0]
  else: cur_sheet_list=cur_xls.sheet_names
  for cur_sheet_name in cur_sheet_list:
    print(cur_sheet_name)
    cur_sheet_obj=pd.read_excel(cur_xls, cur_sheet_name,keep_default_na=False)
    cur_sheet_obj[src_col]=cur_sheet_obj[src_col].apply(str)
    cur_sheet_obj[trg_col]=cur_sheet_obj[trg_col].apply(str)
    for i,row in enumerate(cur_sheet_obj.iterrows()):
      row_dict=row[1].to_dict()
      en0,ar0=row_dict["en"],row_dict["ar"]
      test_alpha=re.sub("\W+","",en0)
      if filter_non_alpha and test_alpha=="": continue
      if filter_numbers and test_alpha.isdigit(): continue
      if trg_col=="ar": ar0=clean_ar(ar0)
      bitext_list.append((en0,ar0))
  return bitext_list


def get_key(txt):
  txt=re.sub("\W+","_",txt)
  txt=txt.strip("_")
  return txt.lower()
#Ref bitexts
xls_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vSVy7hY4fV0LHqTCypOjZAM9OrBevDDnpIcEKEAPKDsYRoxAz9TUBcDIgy8PvHkw5IDAZ6eRmKdZuRw/pub?output=xlsx'
cur_xls = pd.ExcelFile(xls_path)
translation_dict={}
for cur_sheet_name in cur_xls.sheet_names:
  print(cur_sheet_name)
  cur_sheet_obj=pd.read_excel(cur_xls, cur_sheet_name,keep_default_na=False)
  cur_sheet_obj['en']=cur_sheet_obj['en'].apply(str)
  cur_sheet_obj['ar']=cur_sheet_obj['ar'].apply(str)

  sent_pair_list=[]
  key_str_pairs=[]
  for i,row in enumerate(cur_sheet_obj.iterrows()):
    row_dict=row[1].to_dict()
    en0,ar0=row_dict["en"],row_dict["ar"]
    en_key=get_key(en0)
    test_alpha=re.sub("\W+","",en0)
    if test_alpha=="": continue
    if test_alpha.isdigit(): continue

    key_str_pairs.append((en_key,en_key))
    #if en0.replace(".","").replace("-","").replace("/","").isdigit(): continue
    ar0=clean_ar(ar0)
    tmp_translation_dict=translation_dict.get(en_key,{})
    tmp_translation_dict[ar0]=tmp_translation_dict.get(ar0,0)+1
    translation_dict[en_key]=tmp_translation_dict
    sent_pair_list.append((en0,ar0))
    src_sents.append(en0)
    trg_sents.append(ar0)
  #for a in sent_pair_list[:20]: print(a)
test_items=list(translation_dict.items())
test_items.sort(key=lambda x:-sum(x[1].values()))
for a,b in test_items[:200]:
  b_items=list(b.items())
  b_items.sort(key=lambda x:-x[1])
  for a1,b1 in b_items:
    print(a,a1,b1)
  print("-----")

A75760


NameError: ignored

In [ ]:
from itertools import groupby
all_ref_keys=list(translation_dict.keys())
first_word_list=[(v.split("_")[0],v) for v in all_ref_keys]
first_word_list.sort()
first_word_list_grouped=[(key,[v[1] for v in list(group)]) for key,group in groupby(first_word_list,lambda x:x[0])]
first_word_dict=dict(iter(first_word_list_grouped))
first_word_dict_items=list(first_word_dict.items())
print(len(first_word_dict_items))
for a,b in first_word_dict_items[1000:1020]:
  print(a,b)
#print(all_ref_keys[:20])

1377
ptsd ['ptsd', 'ptsd_claims_are_assessed_and_processed_within_90_days_of_receipt_of_required_documentation_percentage', 'ptsd_claims_reviewed_and_processed_within_90_days_after_receipt_of_required_documentation_percentage']
public ['public_awareness_raising_activity_on_the_protection_monitoring_and_reporting_mechanism_on_grave_violations_against_children_in_situations_of_armed_conflicts_for_2_594_participants_including_552_women', 'public_events', 'public_events_were_conducted_pending_the_publication_of_the_report_on_human_rights_trends', 'public_health', 'public_information_and_publication_services', 'public_information_and_publication_services_including_subscriptions', 'public_information_and_publication_services_translation', 'public_information_campaigns_on_the_electoral_cycle_process_based_on_the_scope_of_the_mission_s_mandate_aimed_at_informing_malian_citizens_and_voters_about_the_electoral_procedures_to_prevent_conflicts_triggered_by_the_electoral_process_through_60_radio_pr

In [ ]:
from code_utils.general import * 
import code_utils.general as utils

job_xls_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vSqipSUAaMWJrizvZtg1WIpds2pIiXtcZC6wjOLeVYie9p5O0lqiPnVdd8ambGKH8B0qJ4kmlVeEs6f/pub?output=xlsx'
cur_sheet_name="current"
cur_job_bitext=get_bitext(job_xls_path,sheet_name0=cur_sheet_name,src_col="en",trg_col="ar",filter_non_alpha=True, filter_numbers=True)
cur_terminology_bitext=get_bitext(job_xls_path,sheet_name0="terminology",src_col="en",trg_col="ar",filter_non_alpha=True, filter_numbers=True)
src_only=[v[0] for v in cur_job_bitext]
xl8_list=[]
for en0 in src_only:
  match_type="" #exact - terminology - template - linear - MT ... ??
  en_key0=get_key(en0) #first check the exact match
  eq=translation_dict.get(en_key0,{})
  eq_items=list(eq.items())
  eq_items.sort(key=lambda x:-x[1])  
  selected_eq=""
  if eq_items: 
    selected_eq=eq_items[0][0]
    match_type="exact"
  if match_type!="": continue
  print(en0)
  
  
  en_key0_split=en_key0.split("_")
  words=list(set(en_key0_split))
  valid_keys_tokens=[]
  for w in words:
    corr_keys=first_word_dict.get(w,[])
    for k0 in corr_keys:
      k0_split=k0.split("_")
      if list_in_list(k0_split,en_key0_split): valid_keys_tokens.append(k0)
  valid_keys_tokens.sort(key=lambda x:-len(x[0]))
  print(valid_keys_tokens)
  tmp_linear_str=" ".join(en_key0_split)
  for vk in valid_keys_tokens:
    key_str=vk.replace("_"," ")
    corr=translation_dict.get(vk,{})
    corr_items=sorted(list(corr.items()),key=lambda x:-x[1])
    top_corr_str=corr_items[0][0]
    tmp_linear_str=re.sub(r'\b%s\b'%key_str,top_corr_str,tmp_linear_str)
    #print(vk, corr_items[0])
  print(tmp_linear_str)

  
  xl8_list.append((en0,selected_eq,match_type))




test_out_fopen=open("xl8_out.txt","w")
for item in xl8_list:
  test_out_fopen.write("\t".join(item)+"\n")
test_out_fopen.close()  


current
terminology
A/76/xxx
['a']
(أ) 76 xxx
A/76/XXX
['a']
(أ) 76 xxx
MINUSCA will seek to strengthen its interregional cooperation and economies of scale with missions in the region, including the United Nations Regional Office for Central Africa (UNOCA), to enhance collaboration, information-sharing and analysis, and facilitation, as appropriate.
['united_nations', 'office', 'minusca']
بعثة الأمم المتحدة المتكاملة المتعددة الأبعاد لتحقيق الاستقرار في جمهورية أفريقيا الوسطى will seek to strengthen its interregional cooperation and economies of scale with missions in the region including the الأمم المتحدة regional المكتب for central africa unoca to enhance collaboration information sharing and analysis and facilitation as appropriate
MINUSCA will seek to leverage existing assets of other missions following their downsizing and withdrawal to meet its operational requirements, if any.
['other', 'minusca']
بعثة الأمم المتحدة المتكاملة المتعددة الأبعاد لتحقيق الاستقرار في جمهورية أفريقيا

#OLD

In [ ]:

#Job Bitexts
xls_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vSqipSUAaMWJrizvZtg1WIpds2pIiXtcZC6wjOLeVYie9p5O0lqiPnVdd8ambGKH8B0qJ4kmlVeEs6f/pub?output=xlsx'
cur_xls = pd.ExcelFile(xls_path)
cur_sheet_name="current"
cur_job_bitext=get_bitext(xls_path,sheet_name0=cur_sheet_name,src_col="en",trg_col="ar",filter_non_alpha=True, filter_numbers=True)

cur_sheet_obj=pd.read_excel(cur_xls, cur_sheet_name,keep_default_na=False)
cur_sheet_obj['en']=cur_sheet_obj['en'].apply(str)
cur_sheet_obj['ar']=cur_sheet_obj['ar'].apply(str)

job_pair_list=[]
for i,row in enumerate(cur_sheet_obj.iterrows()):
  row_dict=row[1].to_dict()
  en0,ar0=row_dict["en"],row_dict["ar"]
  en_key=get_key(en0)

  
  if en_key.replace("_","")=="": continue
  if en_key.replace("_","").isdigit(): continue

  # print(en_key)
  # print(en0)
  # print("------")

  ar0=clean_ar(ar0)
  job_pair_list.append((en_key,en0,ar0))
translated_list=[]
used_en=[]
for en_key0,en0,ar0 in job_pair_list:
  #continue
  
  # if en_key0 in used_en: continue
  # used_en.append(en_key0)
  #print(en0)
  eq=translation_dict.get(en_key0,{})
  eq_items=list(eq.items())
  eq_items.sort(key=lambda x:-x[1])  
  selected_eq=""
  if eq_items: selected_eq=eq_items[0][0]
  translated_list.append((en0,selected_eq))
  # for eq_ar0 in eq_items:
  #   print(eq_ar0)
  # print("----")

test_out_fopen=open("xl8_out.txt","w")
for item in translated_list:
  test_out_fopen.write("\t".join(item)+"\n")
test_out_fopen.close()  


#Classification/embedding with gensim

In [ ]:
#Create a model
import time, os, re
#from code_utils.general import *
from gensim.models import Word2Vec

def tok(txt):
  return re.findall("\w+",txt)


en_corpus_fname="UNv1.0.ar-en.en"

n_sents_max=500000
en_fopen=open(en_corpus_fname)

src_sents=[]
for i,en_line in enumerate(en_fopen):
  if i>=n_sents_max: break
  if i%50000==0: print(i)
  en_line=en_line.strip("\n\r\t ")
  toks=tok(en_line.lower())
  if len(toks)<3: continue
  src_sents.append(toks)

#ar_fopen.close()
en_fopen.close()


# def get_sentences(fpath):
#   fopen=open(fpath)
#   tmp_sentences=[]
#   sent_counter=0
#   completed=False
#   for i,site_content in enumerate(fopen):
#     if completed: break
#     content_split=site_content.split("<br>")
#     #print(len(content_split), content_split[0])
#     if len(content_split)<4: continue
#     for line in content_split:
#       line=line.strip("\n\r\t ")
#       toks=tok(line.lower())
#       if len(toks)<3: continue
#       sent_counter+=1
#       if sent_counter%10000==0: print(sent_counter)
#       if sent_counter>2000000: 
#         completed=True
#         break
#       tmp_sentences.append(toks)
#       #yield toks
#   fopen.close()
#   return tmp_sentences

model_fname="un_en.wv"

# t0=time.time()
# data_fpath="crawl/oct21_au/cached_all.txt"
t0=time.time()
#sentences=get_sentences(data_fpath)
print("collected %s sentences"%len(src_sents))
print("Now creating the WV model")
un_model = Word2Vec(src_sents, size=100, min_count=5) #small model
t1=time.time()
print("collected sentences in %s seconds"%(t1-t0))
#fopen.close()

un_model.save(model_fname)
print("saved model as: ",model_fname)

0
50000
100000
150000
200000
250000
300000
350000
400000
450000
collected 474505 sentences
Now creating the WV model
collected sentences in 90.76132202148438 seconds
saved model as:  un_en.wv


In [ ]:
import gensim
from collections import Counter
from scipy import spatial

def get_words_vector(words,wv_model,excluded_words=[]):
  wd_counter=Counter(words)
  flag=False
  total_count0=0
  wd_vector_dict={}
  for wd0,wd0_n in wd_counter.items():
    if wd0 in excluded_words: continue
    try: cur_vec0=wv_model[wd0]
    except: continue
    wd_vector_dict[wd0]=cur_vec0
    weighted_vec0=cur_vec0*wd0_n
    if flag==False: total_vec0=weighted_vec0
    else: total_vec0+=weighted_vec0
    flag=True
    total_count0+=wd0_n
  if total_count0==0: return [],{}
  avg_vec=total_vec0/total_count0
  return avg_vec,wd_vector_dict

#cosine similarity between word vectors
def cos_sim(vector1,vector2):
  result = 1 - spatial.distance.cosine(vector1, vector2)
  return result

un_model = gensim.models.Word2Vec.load("un_en.wv")
#un_model["about"]
un_model.most_similar("agriculture")

cur_sent='To reduce transnational threats and enhance stabilization efforts, the Mission will continue to work closely with regional actors for the full operationalization of joint mixed commissions and fully functional cross-border mechanisms, in close cooperation with UNOCA.'
cur_tokens=tok(cur_sent)
sent_vec,_=get_words_vector(cur_tokens,un_model)
term1='United Nations Regional Office for Central Africa'
term2='United Nations Operations Centre in Afghanistan'

terms=['United Nations Regional Office for Central Africa','United Nations Operations Centre in Afghanistan',"Peace and Security","Human Rights","Environment","Spain","General Assembly","International Law"]
for tr in terms:
  term_tokens=tok(tr.lower())
  term_vec,_=get_words_vector(term_tokens,un_model)
  sim0=cos_sim(sent_vec,term_vec)
  print(tr,sim0)

# term1='Security'
# term2='Environment'
# term1_tokens=tok(term1.lower())
# term2_tokens=tok(term2.lower())
# term1_vec,_=get_words_vector(term1_tokens,un_model)
# term2_vec,_=get_words_vector(term2_tokens,un_model)
# print(cos_sim(sent_vec,term1_vec))
# print(cos_sim(sent_vec,term2_vec))



# term1_tokens=tok(term1.lower())
# term2_tokens=tok(term2.lower())
# term1_vec,_=get_words_vector(term1_tokens,un_model)
# term2_vec,_=get_words_vector(term2_tokens,un_model)
# print(cos_sim(sent_vec,term1_vec))
# print(cos_sim(sent_vec,term2_vec))


United Nations Regional Office for Central Africa 0.6001240015029907
United Nations Operations Centre in Afghanistan 0.538229763507843
Peace and Security 0.45091143250465393
Human Rights 0.27792084217071533
Environment 0.26981398463249207
Spain -0.17120014131069183
General Assembly -0.005136891268193722
International Law 0.3549458980560303


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:31: DeprecationWarning: Call to deprecated `most_similar` (Method will be removed in 4.0.0, use self.wv.most_similar() instead).
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:12: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  if sys.path[0] == '':


#Parsing and Segmentation Experiments

In [ ]:
from code_utils.parsing_lib import *
from code_utils.dep_lib import *


In [ ]:
sent1="""
At the same time, in line with the Secretary-General call for operating as ‘One UN’ and as part of DOS/OSCM, the Centre is responding to demands to achieve system-wide efficiencies and to deliver solutions to a broader client base that includes the wider United Nations system.
"""
conll0=get_conll(sent1.strip())
for c_line in conll0:
  print("\t".join([str(v) for v in c_line]))

1	At	at	IN	ADP	_	0	ROOT	_	_
2	the	the	DT	DET	_	4	det	_	_
3	same	same	JJ	ADJ	_	4	amod	_	_
4	time	time	NN	NOUN	_	1	pobj	_	_
5	,	,	,	PUNCT	_	1	punct	_	_
6	in	in	IN	ADP	_	5	intj	_	_
7	line	line	NN	NOUN	_	6	pobj	_	_
8	with	with	IN	ADP	_	7	prep	_	_
9	the	the	DT	DET	_	13	det	_	_
10	Secretary	Secretary	NNP	PROPN	_	12	compound	_	_
11	-	-	HYPH	PUNCT	_	12	punct	_	_
12	General	General	NNP	PROPN	_	13	compound	_	_
13	call	call	NN	NOUN	_	8	pobj	_	_
14	for	for	IN	ADP	_	13	prep	_	_
15	operating	operate	VBG	VERB	_	14	pcomp	_	_
16	as	as	IN	SCONJ	_	15	prep	_	_
17	‘	'	``	PUNCT	_	19	punct	_	_
18	One	one	CD	NUM	_	19	nummod	_	_
19	UN	UN	NNP	PROPN	_	16	pobj	_	_
20	’	'	''	PUNCT	_	19	punct	_	_
21	and	and	CC	CCONJ	_	32	cc	_	_
22	as	as	IN	SCONJ	_	32	prep	_	_
23	part	part	NN	NOUN	_	22	pobj	_	_
24	of	of	IN	ADP	_	23	prep	_	_
25	DOS	DOS	NNP	PROPN	_	27	nmod	_	_
26	/	/	SYM	SYM	_	27	punct	_	_
27	OSCM	OSCM	NNP	PROPN	_	24	pobj	_	_
28	,	,	,	PUNCT	_	32	punct	_	_
29	the	the	DT	DET	_	30	det	_	_
30	Centre	Centre	NNP	PROPN	_	32	

In [ ]:
# for c_line in conll0:
#   print("\t".join([str(v) for v in c_line])+"\n")
link_count_dict={}
side_dict={}
tok_dict={}
left_emanating_dict={}
right_emanating_dict={}

token_list=[v[1] for v in conll0]
for c_i,c_line in enumerate(conll0):
  cur_token=c_line[1]
  cur_tag=c_line[4]
  cur_i=int(c_line[0])
  cur_parent_i=int(c_line[6]) 
  tok_dict[cur_i]=cur_token
  
  if cur_parent_i==0: cur_side="0"
  elif cur_parent_i>cur_i: cur_side="R"
  elif cur_parent_i<cur_i: cur_side="L"
  side_dict[cur_i]=cur_side
  if cur_side=="R": left_emanating_dict[cur_parent_i]=left_emanating_dict.get(cur_parent_i,0)+1
  if cur_side=="L": right_emanating_dict[cur_parent_i]=right_emanating_dict.get(cur_parent_i,0)+1
  #let's process links - count how many links between two consecutive words
  if cur_tag=='PUNCT' and c_i==len(conll0)-1: continue #ignore last token from counting links if it is punctuation 
  if cur_parent_i==0: continue 
  min_i,max_i=min(cur_i,cur_parent_i),max(cur_i,cur_parent_i)
  for tmp_i in range(min_i,max_i):
    link_count_dict[tmp_i]=link_count_dict.get(tmp_i,0)+1

boundary_i_list=[0]
for i0 in range(1,len(conll0)-1):
  i1=i0+1
  cur_link_count=link_count_dict.get(i0,0)
  #print(tok_dict[i0],tok_dict[i1], ">> n links:",cur_link_count)
  side1,side2=side_dict[i0],side_dict[i1]
  #print("sides:",side1,side2)
  #if (side1,side2)==("L","R") or cur_link_count==1: boundary_i_list.append(i0)
  if (side1,side2)!=("L","R"): continue
  if left_emanating_dict.get(i1,0)>0: continue
  if right_emanating_dict.get(i0,0)>0: continue
  boundary_i_list.append(i0)
  #if (side1,side2)==("L","R"): 
    
boundary_i_list.append(len(conll0))
for i0,i1 in zip(boundary_i_list,boundary_i_list[1:]):
  cur_slice=" ".join(token_list[i0:i1])
  print(i0,i1, cur_slice)
  #print(i0,i1)
  #print()
  #print(side_dict[i0],side_dict[i1])
  
  print("----")
# for c_i,c_line in conll0:
#   #print(a, side_dict[cur_i])
#   cur_i0=int(c_line[0])


0 20 At the same time , in line with the Secretary - General call for operating as ‘ One UN ’
----
20 27 and as part of DOS / OSCM
----
27 41 , the Centre is responding to demands to achieve system - wide efficiencies and
----
41 57 to deliver solutions to a broader client base that includes the wider United Nations system .
----


In [ ]:
from code_utils.parsing_lib import *
from code_utils.dep_lib import *

def conll2seg(conll0_input):
  link_count_dict={}
  side_dict={}
  tok_dict={}
  left_emanating_dict={}
  right_emanating_dict={}

  token_list=[v[1] for v in conll0_input]
  for c_i,c_line in enumerate(conll0_input):
    cur_token=c_line[1]
    cur_tag=c_line[4]
    cur_i=int(c_line[0])
    cur_parent_i=int(c_line[6]) 
    tok_dict[cur_i]=cur_token
    
    if cur_parent_i==0: cur_side="0"
    elif cur_parent_i>cur_i: cur_side="R"
    elif cur_parent_i<cur_i: cur_side="L"
    side_dict[cur_i]=cur_side
    if cur_side=="R": left_emanating_dict[cur_parent_i]=left_emanating_dict.get(cur_parent_i,0)+1
    if cur_side=="L": right_emanating_dict[cur_parent_i]=right_emanating_dict.get(cur_parent_i,0)+1
    #let's process links - count how many links between two consecutive words
    if cur_tag=='PUNCT' and c_i==len(conll0_input)-1: continue #ignore last token from counting links if it is punctuation 
    if cur_parent_i==0: continue 
    min_i,max_i=min(cur_i,cur_parent_i),max(cur_i,cur_parent_i)
    for tmp_i in range(min_i,max_i):
      link_count_dict[tmp_i]=link_count_dict.get(tmp_i,0)+1

  boundary_i_list=[0]
  for i0 in range(1,len(conll0_input)-1):
    i1=i0+1
    cur_link_count=link_count_dict.get(i0,0)
    #print(tok_dict[i0],tok_dict[i1], ">> n links:",cur_link_count)
    side1,side2=side_dict[i0],side_dict[i1]
    #print("sides:",side1,side2)
    #if (side1,side2)==("L","R") or cur_link_count==1: boundary_i_list.append(i0)
    if (side1,side2)!=("L","R"): continue
    if left_emanating_dict.get(i1,0)>0: continue
    if right_emanating_dict.get(i0,0)>0: continue
    boundary_i_list.append(i0)
    #if (side1,side2)==("L","R"): 
      
  boundary_i_list.append(len(conll0_input))
  all_slices=[]
  for i0,i1 in zip(boundary_i_list,boundary_i_list[1:]):
    cur_slice=" ".join(token_list[i0:i1])
    all_slices.append(cur_slice)
    #print(i0,i1, cur_slice)  
  return all_slices
sent1="""
This proposal is based on the vision of supply chain management that guides OSCM operations and the strengthening of core digital technology capacities to increase the Organization’s resilience and effectiveness and to contribute to the Secretary-General’s Data and New Technologies Strategies.
"""

conll0=get_conll(sent1.strip())
for c_line in conll0:
  print("\t".join([str(v) for v in c_line]))

segs=conll2seg(conll0)
for s0 in segs:
  print(s0) 

1	This	this	DT	DET	_	2	det	_	_
2	proposal	proposal	NN	NOUN	_	4	nsubjpass	_	_
3	is	be	VBZ	AUX	_	4	auxpass	_	_
4	based	base	VBN	VERB	_	0	ROOT	_	_
5	on	on	IN	ADP	_	4	prep	_	_
6	the	the	DT	DET	_	7	det	_	_
7	vision	vision	NN	NOUN	_	5	pobj	_	_
8	of	of	IN	ADP	_	7	prep	_	_
9	supply	supply	NN	NOUN	_	10	compound	_	_
10	chain	chain	NN	NOUN	_	11	compound	_	_
11	management	management	NN	NOUN	_	8	pobj	_	_
12	that	that	WDT	DET	_	13	nsubj	_	_
13	guides	guide	VBZ	VERB	_	11	relcl	_	_
14	OSCM	OSCM	NNP	PROPN	_	15	compound	_	_
15	operations	operation	NNS	NOUN	_	13	dobj	_	_
16	and	and	CC	CCONJ	_	7	cc	_	_
17	the	the	DT	DET	_	18	det	_	_
18	strengthening	strengthening	NN	NOUN	_	7	conj	_	_
19	of	of	IN	ADP	_	18	prep	_	_
20	core	core	JJ	ADJ	_	23	amod	_	_
21	digital	digital	JJ	ADJ	_	22	amod	_	_
22	technology	technology	NN	NOUN	_	23	compound	_	_
23	capacities	capacitie	VBZ	VERB	_	19	pobj	_	_
24	to	to	TO	PART	_	25	aux	_	_
25	increase	increase	VB	VERB	_	18	acl	_	_
26	the	the	DT	DET	_	27	det	_	_
27	Organization	Organi

In [ ]:
xls_path0='https://docs.google.com/spreadsheets/d/e/2PACX-1vSqipSUAaMWJrizvZtg1WIpds2pIiXtcZC6wjOLeVYie9p5O0lqiPnVdd8ambGKH8B0qJ4kmlVeEs6f/pub?output=xlsx'
cur_bitext=get_bitext(xls_path0,sheet_name0="current")
src_list=[v[0] for v in cur_bitext]
for s_i, sent0 in enumerate(src_list):
  print(s_i, "::",sent0)
  cur_conll0=get_conll(sent0)
  segs0=conll2seg(cur_conll0)
  for s_ in segs0:
    print(">",s_)
  print("---")


current
0 :: A/75/769xxx
> A/75/769xxx
---
1 :: A/76/xxx
> A/76 / xxx
---
2 :: United Nations
> United Nations
---
3 :: A/76/730
> A/76/730
---
4 :: General Assembly
> General Assembly
---
5 :: Distr.: General
> Distr .
> : General
---
6 :: 2022-03-01 00:00:00
> 2022 - 03 - 01 00:00:00
---
7 :: Original: English
> Original : English
---
8 :: f
> f
---
9 :: Seventy-sixth session
> Seventy - sixth session
---
10 :: Agenda item 150
> Agenda item 150
---
11 :: Administrative and budgetary aspects of the financing of the United Nations peacekeeping operations
> Administrative and budgetary aspects of the financing of the United Nations peacekeeping operations
---
12 :: Budget for the United Nations Logistics Base at Brindisi, Italy, for the period from 1 July 2022 to 30 June 2023
> Budget for the United Nations Logistics Base at Brindisi , Italy , for the period from 1 July 2022 to 30 June 2023
---
13 :: Report of the Secretary-General
> Report of the Secretary - General
---
14 :: Contents


#Testing New approach for hashing matching

In [ ]:
ar_corpus_fname="UNv1.0.ar-en-clean2.ar"
en_corpus_fname="UNv1.0.ar-en.en"

n_sents_max=200000
ar_fopen=open(ar_corpus_fname)
en_fopen=open(en_corpus_fname)

src_counter,trg_counter={},{}
src_sents,trg_sents=[],[]
for i,pair in enumerate(zip(en_fopen,ar_fopen)):
  if i>=n_sents_max: break
  if i%20000==0: print(i)
  en_line,ar_line=pair
  en_line,ar_line=en_line.strip("\n\r\t "),ar_line.strip("\n\r\t ")
  # src_sents.append(en_line)
  # trg_sents.append(ar_line)
  src_tokens=tok(en_line)
  trg_tokens=cur_ar_tok_fn(ar_line)
  src_sents.append(src_tokens)
  trg_sents.append(trg_tokens)
  for a in src_tokens:src_counter[a]=src_counter.get(a,0)+1
  for a in trg_tokens:trg_counter[a]=trg_counter.get(a,0)+1
  # print(en_tokens)
  # print(ar_tokens)
  # print("---")
print("len src tokens=",len(src_counter.keys()))
print("len trg tokens=",len(trg_counter.keys()))

0
20000
40000
60000
80000
100000
120000
140000
160000
180000
len src tokens= 48972
len trg tokens= 64447


In [ ]:
import gensim
print("working on src")
en_model=gensim.models.Word2Vec(
        src_sents,
        size=100,
        window=10,
        min_count=2,
        workers=10,
        iter=10)
print("working on trg")
ar_model=gensim.models.Word2Vec(
        trg_sents,
        size=100,
        window=10,
        min_count=2,
        workers=10,
        iter=10)

en_model.save("un_en_model_200k.wv")
ar_model.save("un_ar_model_200k.wv")

working on src
working on trg


In [ ]:
en_model.similar_by_word("court")

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `similar_by_word` (Method will be removed in 4.0.0, use self.wv.similar_by_word() instead).
  """Entry point for launching an IPython kernel.


[('tribunal', 0.8088857531547546),
 ('commission', 0.7441569566726685),
 ('jurisdiction', 0.7220062613487244),
 ('prosecutor', 0.7023400664329529),
 ('courts', 0.6946955919265747),
 ('judgement', 0.6882531642913818),
 ('Court', 0.6809461116790771),
 ('offender', 0.6621584892272949),
 ('accused', 0.658098578453064),
 ('offence', 0.6564067006111145)]

In [ ]:
ar_corpus_fname="UNv1.0.ar-en-clean2.ar"
en_corpus_fname="UNv1.0.ar-en.en"

n_sents_max=100000
ar_fopen=open(ar_corpus_fname)
en_fopen=open(en_corpus_fname)

src_counter,trg_counter={},{}
src_sents,trg_sents=[],[]
src_fwd_index,trg_fwd_index=[],[]
for i,pair in enumerate(zip(en_fopen,ar_fopen)):
  if i>=n_sents_max: break
  if i%20000==0: print(i)
  en_line,ar_line=pair
  en_line,ar_line=en_line.strip("\n\r\t "),ar_line.strip("\n\r\t ")
  #src_tokens=tok(en_line)
  #trg_tokens=cur_ar_tok_fn(ar_line)
  src_sents.append(en_line)
  trg_sents.append(ar_line)


src_index_obj=indexing(src_sents,tok)
trg_index_obj=indexing(trg_sents,cur_ar_tok_fn)

0
20000
40000
60000
80000


In [ ]:
en_inv_dict=src_index_obj.inv_index
en_tok_sents=src_index_obj.all_tok_sentences
ar_inv_dict=trg_index_obj.inv_index
ar_tok_sents=trg_index_obj.all_tok_sentences


def get_ngrams(sent_tokens0,max_ngram_size0=3):
  all_sent_ngrams=[]
  for s_i in range(len(sent_tokens0)):
    for ngram_size in range(1,max_ngram_size0+1):
      if s_i+ngram_size>len(sent_tokens0): continue
      all_sent_ngrams.append(tuple(sent_tokens0[s_i:s_i+ngram_size]))
  return all_sent_ngrams
      #print(sent_tokens0[s_i:s_i+ngram_size])

#test_indexes=rtrv_idx(["of","the"],en_inv_dict)
all_data=[]
used_dict={}
sent_i=100
for sent_i in range(200):
  print("sentence:",sent_i)
  en_sent=en_tok_sents[sent_i]
  ar_sent=ar_tok_sents[sent_i]

  print("en_sent",en_sent)
  print("ar_sent",ar_sent)
  mini_en_wv_model={}
  mini_ar_wv_model={}
  for en_word in list(set(en_sent)):
    try: mini_en_wv_model[en_word]= en_model[en_word]
    except: pass
  for ar_word in list(set(ar_sent)):
    try: mini_ar_wv_model[ar_word]= ar_model[ar_word]
    except: pass



  src_ngrams=list(set(get_ngrams(en_sent)))
  trg_ngrams=list(set(get_ngrams(ar_sent)))
  src_ngrams_indexes_list=[]
  trg_ngrams_indexes_list=[]
  for sn in src_ngrams:
    cur_src_indexes=rtrv_idx(sn,en_inv_dict)
    cur_src_vec,_=get_words_vector(sn,mini_en_wv_model)
    src_ngrams_indexes_list.append((sn,cur_src_vec,cur_src_indexes))
  for tn in trg_ngrams:
    cur_trg_indexes=rtrv_idx(tn,ar_inv_dict)
    cur_trg_vec,_=get_words_vector(tn,mini_ar_wv_model)
    trg_ngrams_indexes_list.append((tn,cur_trg_vec,cur_trg_indexes))

  matching_list=[]
  for sn,sn_vec,sn_indexes in src_ngrams_indexes_list:
    for tn,tn_vec,tn_indexes in trg_ngrams_indexes_list:
      match_ratio=idx_match(sn_indexes,tn_indexes)
      #print(sn,tn,match_ratio)
      #combined_vec=sn_vec+tn_vec
      
      combined_vec=np.concatenate((sn_vec, tn_vec), axis=0)
      matching_list.append((sn,tn,combined_vec,match_ratio))
    
  matching_list.sort(key=lambda x:-x[-1])
  for ml in matching_list[:100]:
    sn,tn,combined_vec,match_ratio=ml
    if match_ratio==0: continue
    sn_tn_key=(sn,tn)
    if used_dict.get(sn_tn_key,False): continue
    used_dict[sn_tn_key]=True
    #print(sn,tn,match_ratio,combined_vec.shape)
    all_data.append((sn,tn,combined_vec,match_ratio))
  if len(all_data)>10000: break
  print("all_data", len(all_data))


# max_ngram=3
# for s_i in range(len(en_sent)):
#   for ngram_size in range(1,max_ngram+1):
#     if s_i+ngram_size>len(en_sent): continue
#     print(en_sent[s_i:s_i+ngram_size])
#print(en_tok_sents[100])

sentence: 0
en_sent ['ORIGINAL', ':', 'ENGLISH', '/', 'SPANISH']
ar_sent ['ORIGINAL', ':', 'ENGLISH', '/', 'SPANISH']


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:30: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:33: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).


all_data 100
sentence: 1
en_sent ['INTERNATIONAL', 'LAW', 'COMMISSION']
ar_sent ['لجنة', 'ال_قانون', 'ال_دولي']
all_data 111
sentence: 2
en_sent ['Forty', '-', 'fifth', 'session']
ar_sent ['ال_دورة', 'ال_خامسة', 'وـ', 'ال_أربعون']
all_data 185
sentence: 3
en_sent ['3', 'May', '-', '23', 'July', '1993']
ar_sent ['3', 'أيار', '/', 'مايو', '-', '23', 'تموز', '/', 'يوليه', '1993']
all_data 285
sentence: 4
en_sent ['COMMENTS', 'OF', 'GOVERNMENTS', 'ON', 'THE', 'REPORT', 'OF', 'THE', 'WORKING', 'GROUP']
ar_sent ['تعليقات', 'ال_حكومات', 'على', 'تقرير', 'ال_فريق', 'ال_عامل', 'ال_معني']
all_data 307
sentence: 5
en_sent ['ON', 'THE', 'QUESTION', 'OF', 'AN', 'INTERNATIONAL', 'CRIMINAL', 'JURISDICTION']
ar_sent ['بـ', 'مسألة', 'إنشاء', 'قضاء', 'جنائي', 'دولي']
all_data 323
sentence: 6
en_sent ['CONTENTS']
ar_sent ['ال_محتويات']
all_data 324
sentence: 7
en_sent ['Page']
ar_sent ['ال_صفحة']
all_data 325
sentence: 8
en_sent ['INTRODUCTION', '.', '2']
ar_sent ['مقدمة', '.', '2']
all_data 345
sentence:

In [ ]:
all_data[0]
len(all_data)

361

In [ ]:
from random import shuffle
n_layers=2
n_hidden=128 #256 #64#64
LR=0.0000001
n_epochs=100
n_output=1
cur_matching_in_out=False

torch.manual_seed(1)
random.seed(1)

cur_data_item=all_data[0]
sn,tn,combined_vec,match_ratio=cur_data_item
n_input=combined_vec.shape[0]
rnn=RNN(n_input,n_hidden,n_output,n_layers,cur_matching_in_out)
loss_func = nn.MSELoss()
rnn = RNN(n_input, n_hidden, n_output,n_layers,matching_in_out=cur_matching_in_out).to(device)
optimizer = torch.optim.Adam(rnn.parameters(), lr=LR) 

shuffle(all_data)
train_data,test_data=split_train_test(all_data)
# def split_train_test(all_data0,train_ratio=0.8):
#   train_size=int(len(all_data0)*train_ratio)
#   train_set0,tes_set0=all_data0[:train_size],all_data0[train_size:]
#   return train_set0,tes_set0

for epoch_i in range(n_epochs):
  train_loss_items=[]
  test_loss_items=[]
  for cur_data_item in train_data:
    sn,tn,combined_vec,match_ratio=cur_data_item
    actual_out=[match_ratio]
    actual_out_tensor=torch.tensor(actual_out,dtype=torch.float32)
    input_tensor=torch.tensor(combined_vec,dtype=torch.float32)
    input_tensor=input_tensor.reshape(1,n_input)
    rnn_out=rnn(input_tensor)
    rnn_out_flat=rnn_out.ravel()
    rnn_out_val=rnn_out_flat.item()
    
    loss=loss_func(actual_out_tensor,rnn_out_flat)
    loss_val=loss.item()
    loss.backward()
    optimizer.step()  
    train_loss_items.append(loss.item())
  for data_i,cur_data_item in enumerate(test_data):
    sn,tn,combined_vec,match_ratio=cur_data_item
    actual_out=[match_ratio]
    actual_out_tensor=torch.tensor(actual_out,dtype=torch.float32)
    input_tensor=torch.tensor(combined_vec,dtype=torch.float32)
    input_tensor=input_tensor.reshape(1,n_input)
    rnn_out=rnn(input_tensor)
    rnn_out_flat=rnn_out.ravel()
    rnn_out_val=rnn_out_flat.item()
    
    loss=loss_func(actual_out_tensor,rnn_out_flat)
    loss_val=loss.item()
    test_loss_items.append(loss.item())
    #print("epoch_i", epoch_i, "rnn output:", round(rnn_out_val,4),"actual:",round(match_ratio,4),"loss value:",round(loss_val,4))
    if epoch_i>20 and data_i<20:
      print("epoch_i", epoch_i, "rnn output:", round(rnn_out_val,4),"actual:",round(match_ratio,4),sn,tn)
  train_loss_avg=sum(train_loss_items)/len(train_loss_items)
  test_loss_avg=sum(test_loss_items)/len(test_loss_items)
  print("epoch_i", epoch_i,"train_loss_avg",round(train_loss_avg,4),"test_loss_avg",round(test_loss_avg,4))
  print("==========")


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:45: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).


epoch_i 0 train_loss_avg 0.1154 test_loss_avg 0.0845
epoch_i 1 train_loss_avg 0.0752 test_loss_avg 0.0621
epoch_i 2 train_loss_avg 0.0634 test_loss_avg 0.0629
epoch_i 3 train_loss_avg 0.0718 test_loss_avg 0.0785
epoch_i 4 train_loss_avg 0.0889 test_loss_avg 0.0935
epoch_i 5 train_loss_avg 0.0876 test_loss_avg 0.0758
epoch_i 6 train_loss_avg 0.0661 test_loss_avg 0.0568
epoch_i 7 train_loss_avg 0.0554 test_loss_avg 0.0537
epoch_i 8 train_loss_avg 0.0575 test_loss_avg 0.0595
epoch_i 9 train_loss_avg 0.0662 test_loss_avg 0.0659
epoch_i 10 train_loss_avg 0.0686 test_loss_avg 0.0616
epoch_i 11 train_loss_avg 0.0593 test_loss_avg 0.0524
epoch_i 12 train_loss_avg 0.0518 test_loss_avg 0.0488
epoch_i 13 train_loss_avg 0.0498 test_loss_avg 0.0502
epoch_i 14 train_loss_avg 0.0513 test_loss_avg 0.0531
epoch_i 15 train_loss_avg 0.0538 test_loss_avg 0.0553
epoch_i 16 train_loss_avg 0.0539 test_loss_avg 0.0549
epoch_i 17 train_loss_avg 0.0517 test_loss_avg 0.0504
epoch_i 18 train_loss_avg 0.0477 test_

KeyboardInterrupt: ignored

In [ ]:

start_i=300
n_sents=20
for sent_i in range(start_i,start_i+n_sents):
  print("sentence:",sent_i)
  en_sent=en_tok_sents[sent_i]
  ar_sent=ar_tok_sents[sent_i]

  print("en_sent",en_sent)
  print("ar_sent",ar_sent)
  mini_en_wv_model={}
  mini_ar_wv_model={}
  for en_word in list(set(en_sent)):
    try: mini_en_wv_model[en_word]= en_model[en_word]
    except: pass
  for ar_word in list(set(ar_sent)):
    try: mini_ar_wv_model[ar_word]= ar_model[ar_word]
    except: pass



  src_ngrams=list(set(get_ngrams(en_sent)))
  trg_ngrams=list(set(get_ngrams(ar_sent)))
  src_ngrams_indexes_list=[]
  trg_ngrams_indexes_list=[]
  for sn in src_ngrams:
    cur_src_indexes=rtrv_idx(sn,en_inv_dict)
    cur_src_vec,_=get_words_vector(sn,mini_en_wv_model)
    src_ngrams_indexes_list.append((sn,cur_src_vec,cur_src_indexes))
  for tn in trg_ngrams:
    cur_trg_indexes=rtrv_idx(tn,ar_inv_dict)
    cur_trg_vec,_=get_words_vector(tn,mini_ar_wv_model)
    trg_ngrams_indexes_list.append((tn,cur_trg_vec,cur_trg_indexes))

  matching_list=[]
  for sn,sn_vec,sn_indexes in src_ngrams_indexes_list:
    for tn,tn_vec,tn_indexes in trg_ngrams_indexes_list:
      match_ratio=idx_match(sn_indexes,tn_indexes)
      #print(sn,tn,match_ratio)
      #combined_vec=sn_vec+tn_vec
      if sn_vec==[] or tn_vec==[]: continue
      
      combined_vec=np.concatenate((sn_vec, tn_vec), axis=0)
      
      combined_vec_tensor=torch.tensor(combined_vec,dtype=torch.float32)
      combined_vec_tensor=combined_vec_tensor.reshape([1,combined_vec.shape[0]])
      rnn_out=rnn(combined_vec_tensor)
      rnn_out_val=rnn_out.ravel().item()

      matching_list.append((sn,tn,combined_vec,rnn_out_val,match_ratio))
  matching_list.sort(key=lambda x:-x[-2])
  for ml in matching_list[:100]:
    sn,tn,combined_vec,rnn_out_val,match_ratio=ml
    print(sn,tn,"rnn:", rnn_out_val,"match:", match_ratio)
  print("==========")

sentence: 300
en_sent ['3', '.', 'The', 'convention', 'establishing', 'the', 'court', 'should', 'grant', 'all', 'States', '(', 'including', ',', 'as', 'the', 'case', 'may', 'be', ',', 'also', 'non', '-', 'contracting', 'States', ')', 'the', 'right', 'to', 'designate', 'persons', 'having', 'the', 'qualifications', 'of', 'competence', 'and', 'impartiality', 'that', 'are', 'required', 'for', 'the', 'participation', 'in', 'the', 'judgement', 'organs', 'appointed', 'for', 'the', 'various', 'cases', 'to', 'be', 'examined', '.']
ar_sent ['3', '-', 'وـ', 'يجب', 'في', 'ال_اتفاقية', 'التي', 'تقضي', 'بـ', 'إنشاء', 'ال_محكمة', 'أن', 'تمنح', 'جميع', 'ال_دول', ')', 'وـ', 'من', 'ـها', 'أيضا', 'ال_دول', 'ال_متعاقدة', '،', 'حسب', 'طبيعة', 'ال_حالة', '(', 'ال_حق', 'في', 'تسمية', 'أشخاص', 'يملكون', 'مؤهلات', 'ال_اختصاص', 'وـ', 'ال_نزاهة', 'ال_مطلوبة', 'لـ', 'ال_اشتراك', 'في', 'هيئات', 'إصدار', 'ال_حكم', 'ال_معينة', 'من', 'أجل', 'مختلف', 'ال_قضايا', 'ال_منظورة', '.']


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:13: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  del sys.path[0]
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:16: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  app.launch_new_instance()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:40: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:45: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).


('judgement', 'organs', 'appointed') ('ال_حالة', '(', 'ال_حق') rnn: 0.5478397011756897 match: 0
('3',) ('ال_حالة', '(', 'ال_حق') rnn: 0.5252849459648132 match: 0
('organs', 'appointed') ('ال_حالة', '(', 'ال_حق') rnn: 0.5184096693992615 match: 0
('impartiality',) ('(', 'ال_حق') rnn: 0.505550742149353 match: 0
('organs', 'appointed') ('(', 'ال_حق') rnn: 0.5028063654899597 match: 0
('judgement', 'organs', 'appointed') ('(', 'ال_حق') rnn: 0.5015252828598022 match: 0
('appointed',) ('(', 'ال_حق') rnn: 0.4960797131061554 match: 0
('designate',) ('(', 'ال_حق') rnn: 0.4955708682537079 match: 0
('3',) ('(', 'ال_حق', 'في') rnn: 0.4935663044452667 match: 0
('designate',) ('ال_حالة', '(') rnn: 0.4892522096633911 match: 0
('3',) ('ال_حق',) rnn: 0.48894166946411133 match: 0.004741702021462441
('qualifications',) ('ال_حالة', '(', 'ال_حق') rnn: 0.4888571500778198 match: 0
('judgement', 'organs', 'appointed') ('ال_نزاهة',) rnn: 0.48518431186676025 match: 0
('designate',) ('ال_حق',) rnn: 0.4821773767471

In [ ]:
tn_vec

[]

In [ ]:
n_input

200

In [ ]:
src_keys=list(src_counter.keys())
print(src_keys[100:110])
trg_keys=list(trg_counter.keys())
print(trg_keys[100:110])

['Code', 'Crimes', 'against', 'Peace', 'Security', 'Mankind', 'which', 'was', 'devoted', 'to']
['ال_جرائم', 'ال_مخلة', 'سلم', 'ال_إنسانية', 'أمن', 'ـها', 'الذي', 'كرس', 'لـ', 'إمكانية']


In [ ]:
from scipy import spatial
# for a in trg_keys[:10]:
#   vec=ar_model[a]
  # src_sents.append(src_tokens)
  # trg_sents.append(trg_tokens)
for src0,trg0 in zip(src_sents[:20],trg_sents[:20]):
  tmp_src_vec_dict,tmp_trg_vec_dict={},{}
  try: 
    for a in src0: tmp_src_vec_dict[a]=en_model[a]
  except: pass
  try: 
    for a in trg0: tmp_trg_vec_dict[a]=ar_model[a]
  except: pass
  for a0,b0 in tmp_src_vec_dict.items():
    tmp=[]
    print(a0)
    for a1,b1 in tmp_trg_vec_dict.items():
      
      cos_val = abs( 1 - spatial.distance.cosine(b0, b1))
      tmp.append((a1,cos_val))
      #print(a0,a1,cos_val)
    tmp.sort(key=lambda x:-x[1])
    for x in tmp[:5]:
      print(x)
    print("----")



ORIGINAL
('/', 0.1210264042019844)
(':', 0.09776163846254349)
('ENGLISH', 0.09312044829130173)
('SPANISH', 0.07970868051052094)
('ORIGINAL', 0.07445640116930008)
----
:
('/', 0.1281573325395584)
(':', 0.10443489998579025)
('ENGLISH', 0.09897531569004059)
('SPANISH', 0.08429171144962311)
('ORIGINAL', 0.07810582965612411)
----
ENGLISH
('/', 0.12239494174718857)
(':', 0.1018538549542427)
('ENGLISH', 0.09902690351009369)
('SPANISH', 0.08270221203565598)
('ORIGINAL', 0.07603658735752106)
----
/
('/', 0.1405307948589325)
(':', 0.1113162711262703)
('ENGLISH', 0.10568653047084808)
('SPANISH', 0.09063097089529037)
('ORIGINAL', 0.08553128689527512)
----
SPANISH
('/', 0.10009922087192535)
(':', 0.07723880559206009)
('SPANISH', 0.07304131239652634)
('ENGLISH', 0.07231893390417099)
('ORIGINAL', 0.05214103311300278)
----
INTERNATIONAL
('ال_قانون', 0.06248722970485687)
('ال_دولي', 0.05865810811519623)
('لجنة', 0.04715884476900101)
----
LAW
('ال_قانون', 0.059738751500844955)
('ال_دولي', 0.056236479431

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:9: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  if __name__ == '__main__':
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:12: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  if sys.path[0] == '':


In [ ]:
test_en=en_model["general"]
keys=list(test_en.keys())
print(len(keys),keys[:10])
#test_ar=ar_model["العامة"]

In [ ]:
en_model["the"]

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  """Entry point for launching an IPython kernel.


array([ 1.6295501 , -0.3641678 , -0.8005455 , -0.5281693 ,  1.0934305 ,
        0.8150351 ,  1.8593708 , -0.7521438 ,  0.4360393 , -0.5191244 ,
       -0.49931085,  1.0282642 ,  1.3791842 , -0.8435117 ,  0.40540653,
       -1.3977058 ,  0.72926307, -0.88094467, -0.7700975 , -0.29425058,
       -1.2420062 ,  1.053161  ,  0.25826624,  1.2520448 ,  1.8816774 ,
        0.00995926, -0.9422078 , -0.30660504, -1.1771382 ,  0.21316102,
       -1.1989622 ,  1.0406231 ,  1.3392975 , -0.5352807 ,  1.3703241 ,
       -0.0862059 , -0.8194424 , -2.6602635 ,  0.07741913,  1.3939295 ,
        1.1210356 , -0.7005276 , -2.4378896 ,  1.5436195 ,  1.4134588 ,
       -1.7137322 , -0.4230278 ,  1.8795353 , -1.2041483 ,  0.8313264 ,
        0.58736694,  0.07563703, -1.5684607 ,  2.3167934 ,  0.34603527,
        0.10522225,  0.5311361 , -0.02403292, -0.11283378,  2.7475295 ,
       -0.05356972, -0.05729892, -1.7050958 ,  1.0823265 ,  0.12822641,
       -1.9642165 , -0.4824889 , -1.7970736 ,  0.19963118, -0.90

In [ ]:
from itertools import groupby
def hash_tok(token0,vec_size=200):
  hash_val=abs(hash(token0))
  remainder=hash_val%vec_size
  return remainder
cur_vec_size=1000
lr=0.00001
max_val=20000
src_vec_dict={}
trg_vec_dict={}
src_counter,trg_counter={},{}

counter=0
for src0,trg0 in zip(src_sents,trg_sents):
  if counter>max_val: break
  if counter%10==0: print(counter)
  counter+=1  
  src_lower=[v.lower() for v in src0]
  trg_lower=[v.lower() for v in trg0]
  src_hashes=[hash_tok(v,cur_vec_size) for v in src_lower]
  trg_hashes=[hash_tok(v,cur_vec_size) for v in trg_lower]
  for s0 in list(set(src_lower)):
    tmp_vec=src_vec_dict.get(s0,[0]*cur_vec_size)
    new_vec=[]
    for i0,cell0 in enumerate(tmp_vec):
      cur_offset=lr#/len(trg_lower)
      if i0 in trg_hashes: cell0+=cur_offset
      else: cell0-=cur_offset
      new_vec.append(cell0)
    src_vec_dict[s0]=new_vec
  for t0 in list(set(trg_lower)):
    tmp_vec=trg_vec_dict.get(t0,[0]*cur_vec_size)
    new_vec=[]
    for i0,cell0 in enumerate(tmp_vec):
      cur_offset=lr#/len(src_lower)
      if i0 in src_hashes: cell0+=cur_offset
      else: cell0-=cur_offset
      new_vec.append(cell0)
    trg_vec_dict[t0]=new_vec

print("finished training")
counter=0
for src0,trg0 in zip(src_sents,trg_sents):
  if counter>200: break
  counter+=1

  src_lower=[v.lower() for v in src0]
  trg_lower=[v.lower() for v in trg0]
  src_hashes=[(v,hash_tok(v,cur_vec_size)) for v in src_lower]
  trg_hashes=[(v,hash_tok(v,cur_vec_size)) for v in trg_lower]
  for s0,s_hash0 in list(set(src_hashes)):
    tmp_vec=src_vec_dict.get(s0,[0]*cur_vec_size)
    print(s0)
    # print(tmp_vec)
    candidates=[]
    for t_tok0,t_hash0 in list(set(trg_hashes)):
      
      cur_val=tmp_vec[t_hash0]
      other_way_vec=trg_vec_dict[t_tok0]
      other_way_val=other_way_vec[s_hash0]
      combined=cur_val+other_way_val
      #candidates.append((t_tok0,cur_val,other_way_val,combined))
      candidates.append((t_tok0,round(combined,5)))
      #print(t_tok0,t_hash0, tmp_vec[t_hash0])
    candidates.sort(key=lambda x:x[-1],reverse=True)
    for can0 in candidates[:5]:
      print(can0)
    print("---")
  print("====")


  # src_hashes,trg_hashes=[],[]
  # for t0 in trg0:
  #   cur_hash=hash_tok(t0.lower(),cur_vec_size)
  #   trg_hashes.append(cur_hash)
  # for s0 in src0:
  #   cur_hash=hash_tok(s0.lower(),cur_vec_size)
  #   src_hashes.append(cur_hash)    
  # for s0 in src0:
  #   s_tok0=s0.lower()
  #   src_counter[s_tok0]=src_counter.get(s_tok0,0)+1
  #   tmp_vec=src_vec_dict.get(s_tok0,[0]*cur_vec_size)
  #   for th0 in trg_hashes: tmp_vec[th0]+=1/len(trg_hashes)
  #   src_vec_dict[s_tok0]=tmp_vec
  # for t0 in trg0:
  #   t_tok0=t0.lower()
  #   trg_counter[t_tok0]=trg_counter.get(t_tok0,0)+1
  #   tmp_vec=trg_vec_dict.get(t_tok0,[0]*cur_vec_size)
  #   for sh0 in src_hashes: tmp_vec[sh0]+=1/len(src_hashes) #0.0001
  #   trg_vec_dict[t_tok0]=tmp_vec

  #print("------")

# for a,b in src_vec_dict.items():
#   print(a,b)

# counter=0
# for src0,trg0 in zip(src_sents,trg_sents):
#   if counter>50: break
#   counter+=1
#   print(src0)
#   print(trg0)
#   src_hashes,trg_hashes=[],[]
#   tmp_trg_hash_dict={}
#   for t0 in trg0:
#     t_tok0=t0.lower()
#     cur_hash=hash_tok(t_tok0,cur_vec_size)
#     trg_hashes.append((t_tok0,cur_hash))
#     tmp_trg_hash_dict[t_tok0]=trg_vec_dict.get(t_tok0,[0]*cur_vec_size)

#   for s0 in src0:
#     s_tok0=s0.lower()
#     cur_hash=hash_tok(s_tok0,cur_vec_size)
#     src_hashes.append((s_tok0,cur_hash)) 
  
#   for s0 in src0:
#     s_tok0=s0.lower()
#     cur_hash=hash_tok(s_tok0,cur_vec_size)
#     cur_src_vec=src_vec_dict.get(s_tok0,[0]*cur_vec_size)
#     cur_src_vec_sum=sum(cur_src_vec)
#     cur_src_tok_count=src_counter.get(s_tok0,0)
#     print(s0)
#     candidates=[]
#     for t0_,h_hash0_ in trg_hashes:
#       t_val=cur_src_vec[h_hash0_] #round(cur_src_vec[h_hash0_],4)
#       cur_trg_tok_count=trg_counter.get(t0_,0)
#       t_val_norm=round(t_val/cur_src_vec_sum,4)
#       #t_val_norm=round(t_val/cur_trg_tok_count)

#       other_way_vec=trg_vec_dict[t0_]
#       other_way_vec_sum=sum(other_way_vec)
#       other_way_val=other_way_vec[cur_hash]#round(,4)
#       other_way_val_norm=round(other_way_val/other_way_vec_sum,4)
#       #other_way_val_norm=round(other_way_val/cur_src_tok_count)
      
#       t_val_norm=t_val
#       other_way_val_norm=other_way_val
#       #combined=round(t_val+other_way,4)
#       combined=round(t_val_norm+other_way_val_norm,6)
#       #print(t0_,combined)
#       candidates.append((t0_,combined))
#       # print(t_val,other_way)
#       # print("----")
#       #print(t0_,h_hash0_,t_val,other_way)
#     # for th0 in trg_hashes: tmp_vec[th0]+=0.0001
#     # src_vec_dict[s_tok0]=tmp_vec
#     candidates.sort(key=lambda x:-x[1])
#     for can0 in candidates[:5]:
#       print(can0)
#     print("========")
     


# collision_list=[]
# for src_toks in src_sents:
#   for a in src_toks:
#     cur_pair=(a.lower(), hash_tok(a.lower()))
#     if cur_pair in collision_list: continue
#     collision_list.append(cur_pair)
#   #print("--------")
# collision_list.sort(key=lambda x:x[1])
# for cl in collision_list:
#   print(cl)

Streaming output truncated to the last 5000 lines.
a
('.', -0.01105)
('في', -0.01401)
('بـ', -0.01879)
('فـ', -0.03486)
('حكما', -0.03676)
---
will
('سـ', 0.00172)
('ال_اختصاص', -0.00721)
('حكما', -0.00732)
('أحكاما', -0.00738)
('يتطلب', -0.00755)
---
international
('ال_دولية', 0.00138)
('حكما', -0.01019)
('ال_اختصاص', -0.01052)
('أحكاما', -0.01053)
('ال_جرائم', -0.01067)
---
which
('حكما', -0.01033)
('أحكاما', -0.01113)
('ال_اختصاص', -0.0113)
('يتطلب', -0.01192)
('ال_جرائم', -0.01197)
---
or
('أو', 0.01148)
('حكما', -0.00481)
('أحكاما', -0.00627)
('ال_اختصاص', -0.00654)
('إسناد', -0.00665)
---
jurisdiction
('ال_اختصاص', -0.00026)
('ال_جرائم', -0.00099)
('حكما', -0.00117)
('إسناد', -0.00127)
('أحكاما', -0.00141)
---
statute
('ال_أساسي', 0.00128)
('ال_نظام', -0.00069)
('حكما', -0.00088)
('ال_اختصاص', -0.00099)
('إسناد', -0.00108)
---
over
('أحكاما', -0.00154)
('حكما', -0.00156)
('إسناد', -0.00174)
('ال_اختصاص', -0.00181)
('يتطلب', -0.00203)
---
provisions
('أحكاما', -0.00101)
('حكما', -

In [ ]:
counter=0
for src0,trg0 in zip(src_sents,trg_sents):
  if counter>500: break
  counter+=1

  src_lower=[v.lower() for v in src0]
  trg_lower=[v.lower() for v in trg0]
  src_hashes=[(v,hash_tok(v,cur_vec_size)) for v in src_lower]
  trg_hashes=[(v,hash_tok(v,cur_vec_size)) for v in trg_lower]
  for s0,s_hash0 in list(set(src_hashes)):
    tmp_vec=src_vec_dict.get(s0,[0]*cur_vec_size)
    print(s0)
    # print(tmp_vec)
    candidates=[]
    for t_tok0,t_hash0 in list(set(trg_hashes)):
      cur_val=tmp_vec[t_hash0]
      other_way_vec=trg_vec_dict[t_tok0]
      other_way_val=other_way_vec[s_hash0]
      combined=cur_val+other_way_val
      if combined<0: continue
      #candidates.append((t_tok0,cur_val,other_way_val,combined))
      candidates.append((t_tok0,round(combined,5)))
      #print(t_tok0,t_hash0, tmp_vec[t_hash0])
    candidates.sort(key=lambda x:x[-1],reverse=True)
    for can0 in candidates[:5]:
      print(can0)
    print("---")
  print("====")

Streaming output truncated to the last 5000 lines.
go
---
11
---
court
('محكمة', 0.00023)
---
====
jurisidiction
('ال_ضيق', 0.0)
---
,
('.', 0.09434)
('لـ', 0.04235)
('من', 0.01974)
('أن', 0.00747)
---
all
('جميع', 0.00691)
('يوسع', 0.00078)
---
however
('يوسع', 0.00162)
('بيد', 0.00056)
---
to
('.', 0.04704)
('لـ', 0.02905)
('أن', 0.01619)
('من', 0.01318)
('يوسع', 0.00191)
---
"
('"', 0.00924)
('يوسع', 0.00032)
---
crimes
('ال_جرائم', 0.00059)
---
that
('أن', 0.02863)
('يوسع', 0.01893)
---
expands
('ال_ضيق', 0.0)
---
limited
('يوسع', 1e-05)
---
of
('.', 0.12139)
('لـ', 0.06716)
('من', 0.02661)
('أن', 0.00412)
---
an
---
.
('.', 0.18957)
('لـ', 0.06316)
('من', 0.01605)
---
report
---
character
---
the
('.', 0.15209)
('لـ', 0.0811)
('من', 0.03579)
('أن', 0.01704)
---
international
('ال_دولي', 0.00171)
---
====
would
---
such
---
before
---
how
---
trafficking
('ال_اتجار', 0.00042)
---
(
(')', 0.07117)
('(', 0.07093)
('تلك', 0.03194)
---
same
---
the
('.', 0.15209)
('وـ', 0.13902)
('لـ',

In [ ]:
span1,span2=(6, 6),(5, 39)
span1,span2=(6, 6),(7, 2)

def check_span_overlap(span1,span2):
  span1_x1,span1_x2=span1
  span2_x1,span2_x2=span2
  d1=abs(span1_x2-span1_x1)
  d2=abs(span2_x2-span2_x1)
  max_x=max(span1_x1,span1_x2,span2_x1,span2_x2)
  min_x=min(span1_x1,span1_x2,span2_x1,span2_x2)
  d_total=max_x-min_x
  overlapping=False
  if d_total<=d1+d2: overlapping=True
  return overlapping
cur_span1,cur_span2=(3, 5),(8, 12)
cur_span1,cur_span2=(3, 9),(8, 12)
cur_overlapping=check_span_overlap(cur_span1,cur_span2)
# print("d1",d1)
# print("d2",d2)
# print("d_total",d_total)
print("overlapping",cur_overlapping)

overlapping True


#Testing filtering

In [ ]:
params={}
params["lang"]="en"
params["ignore_punc"]=False
params["stop_words"]=[]
params["ignore_ar_pre_suf"]=True
params["remove_al"]=False
params["index_words"]=True
params["lower"]=False
params["stemming"]=False

def filter_tokens(token_list0, params0={}):
#def filter_tokens(token_list0, lang="en",stop_words=[], ignore_punc=False,ignore_ar_pre_suf=False,remove_al=True,index_words=True,lower=True,stemming=False):
  tokens_original=list(token_list0)
  tokens_copy_enum=[(i,v) for i,v in enumerate(token_list0)]   
  ignore_punc=params0.get("ignore_punc",False)
  ignore_ar_pre_suf=params0.get("ignore_ar_pre_suf",False)
  remove_al=params0.get("remove_al",True)
  lower=params0.get("lower",True)
  stemming=params0.get("stemming",False)
  lang=params0.get("lang","en")
  stop_words=params0.get("stop_words",[])
  #if lang=="ar": tokens=tok_ar(tokens,count_dict) #tok_ar(tokens)
  if ignore_punc: tokens_copy_enum=[(i,v) for i,v in tokens_copy_enum if not is_punct(v)]
  if ignore_ar_pre_suf: tokens_copy_enum=[(i,v) for i,v in tokens_copy_enum if not v.startswith("ـ") and not v.endswith("ـ")]
  if stop_words: tokens_copy_enum=[(i,v) for i,v in tokens_copy_enum if not v.lower() in stop_words]
  if remove_al: tokens_copy_enum=[(i,v.replace("ال_","")) for i,v in tokens_copy_enum if not v.lower() in stop_words]
  tokens_out=[v[1] for v in tokens_copy_enum]
  if lower: tokens_out=[v.lower() for v in tokens_out]
  cur_mapping=[v[0] for v in tokens_copy_enum]
  return tokens_out,cur_mapping, tokens_original

#cur_ar_tok_fn(text)  
ar_corpus_fname="UNv1.0.ar-en-clean2.ar"
en_corpus_fname="UNv1.0.ar-en.en"
ar_fopen=open(ar_corpus_fname)
en_fopen=open(en_corpus_fname)
src_sents,trg_sents=[],[]
for pair_i,pair in enumerate(zip(en_fopen,ar_fopen)):
  src_line,trg_line=pair
  src_line,trg_line=src_line.strip("\n\r\t "),trg_line.strip("\n\r\t ")
  src_sents.append(src_line)
  trg_sents.append(trg_line)
  if pair_i>200: break

ar_fopen.close()
en_fopen.close()
sent_i=50
cur_sent=trg_sents[sent_i]
cur_sent=src_sents[sent_i]
cur_tokens=cur_ar_tok_fn(cur_sent)
filtered0,mapping0,original0=filter_tokens(cur_tokens, params)
print(cur_sent)
print(cur_tokens)
print(filtered0)


8. In paragraphs 442 and 443 of the report, the Working Group sets out one possible arrangement for nominating judges to serve on a court and constituting it when required.
['8', '.', 'In', 'paragraphs', '442', 'and', '443', 'of', 'the', 'report', ',', 'the', 'Working', 'Group', 'sets', 'out', 'one', 'possible', 'arrangement', 'for', 'nominating', 'judges', 'to', 'serve', 'on', 'a', 'court', 'and', 'constituting', 'it', 'when', 'required', '.']
['8', '.', 'In', 'paragraphs', '442', 'and', '443', 'of', 'the', 'report', ',', 'the', 'Working', 'Group', 'sets', 'out', 'one', 'possible', 'arrangement', 'for', 'nominating', 'judges', 'to', 'serve', 'on', 'a', 'court', 'and', 'constituting', 'it', 'when', 'required', '.']


In [ ]:
!python align_utils.py

{'lang': 'en', 'ignore_punc': True, 'stop_words': [], 'ignore_ar_pre_suf': True, 'remove_al': True, 'index_words': True, 'lower': True, 'stemming': False}


#Run experiments with pypy

In [ ]:
!chmod 777 run_walign.py
!chmod 777 ./pypy3.9-v7.3.9-linux64/bin/pypy
#!./pypy3.9-v7.3.9-linux64/bin/pypy run_walign.py exp04 250000
!./pypy3.9-v7.3.9-linux64/bin/pypy run_walign.py exp01-test 100000
#!pypy run_walign.py

loaded necessary functions
argv ['run_walign.py', 'exp01-test', '100000']
exp_dir exp01-test batch_size 100000
batch_size 100000
0
10000
20000
30000
40000
50000
60000
70000
80000
90000
batch already processed, moving on to next batch
110000
120000
130000
140000
150000
160000
170000
180000
190000
indexing src sentences
indexing trg sentences
finished indexing, elapsed: 119.3
now aligning - number of sentences: 199999
now aligning 129250 elapsed: 60.9
now aligning 129300 elapsed: 83.8
now aligning 129350 elapsed: 82.9
now aligning 129400 elapsed: 49.7
now aligning 129450 elapsed: 128.8
now aligning 129500 elapsed: 152.7
now aligning 129550 elapsed: 148.0
now aligning 129600 elapsed: 30.8
couldn't find full el: ((0, 10), (0, 17)) used the top el instead ((0, 8), (0, 8))
now aligning 129650 elapsed: 47.6
now aligning 129700 elapsed: 70.6
now aligning 129750 elapsed: 56.1
couldn't find full el: ((0, 22), (0, 32)) used the top el instead ((1, 22), (12, 32))
now aligning 129800 elapsed: 76.2


In [ ]:
!apt-get install pypy

Reading package lists... Done
Building dependency tree       
Reading state information... Done
The following package was automatically installed and is no longer required:
  libnvidia-common-460
Use 'apt autoremove' to remove it.
The following additional packages will be installed:
  pypy-lib
Suggested packages:
  pypy-doc pypy-tk
The following NEW packages will be installed:
  pypy pypy-lib
0 upgraded, 2 newly installed, 0 to remove and 49 not upgraded.
Need to get 13.1 MB of archives.
After this operation, 84.6 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu bionic/universe amd64 pypy-lib amd64 5.10.0+dfsg-3build2 [2,303 kB]
Get:2 http://archive.ubuntu.com/ubuntu bionic/universe amd64 pypy amd64 5.10.0+dfsg-3build2 [10.8 MB]
Fetched 13.1 MB in 3s (4,584 kB/s)
Selecting previously unselected package pypy-lib:amd64.
(Reading database ... 155639 files and directories currently installed.)
Preparing to unpack .../pypy-lib_5.10.0+dfsg-3build2_amd64.deb ..

In [ ]:
!wget https://downloads.python.org/pypy/pypy3.9-v7.3.9-linux64.tar.bz2
!tar xf pypy3.9-v7.3.9-linux64.tar.bz2

--2022-06-30 12:44:04--  https://downloads.python.org/pypy/pypy3.9-v7.3.9-linux64.tar.bz2
Resolving downloads.python.org (downloads.python.org)... 151.101.0.175, 151.101.64.175, 151.101.128.175, ...
Connecting to downloads.python.org (downloads.python.org)|151.101.0.175|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 32841328 (31M) [application/x-tar]
Saving to: ‘pypy3.9-v7.3.9-linux64.tar.bz2.3’

pypy3.9-v7.3.9-linu 100%[===================>]  31.32M  40.2MB/s    in 0.8s    

2022-06-30 12:44:04 (40.2 MB/s) - ‘pypy3.9-v7.3.9-linux64.tar.bz2.3’ saved [32841328/32841328]



In [ ]:
!./pypy3.9-v7.3.9-linux64/bin/pypy align_utils.py

{'lang': 'en', 'ignore_punc': True, 'stop_words': [], 'ignore_ar_pre_suf': True, 'remove_al': True, 'index_words': True, 'lower': True, 'stemming': False}


In [ ]:
!python run_walign.py

loaded necessary functions
0
10000
20000
30000
40000
50000
60000
70000
80000
90000
indexing src sentences
indexing trg sentences
finished indexing, elapsed: 76.7
now aligning - number of sentences: 100000
now aligning 0 elapsed: 0.0
now aligning 10 elapsed: 0.0
now aligning 20 elapsed: 0.0
now aligning 30 elapsed: 0.0
sent_i 36
sent_i 37
sent_i 38
sent_i 39
now aligning 40 elapsed: 2.0
sent_i 40
sent_i 41
sent_i 42
sent_i 43
sent_i 44
sent_i 45
sent_i 46
sent_i 47
sent_i 48
sent_i 49
now aligning 50 elapsed: 39.8
sent_i 50
sent_i 51
sent_i 52
sent_i 53
sent_i 54
sent_i 55
sent_i 56
sent_i 57
sent_i 58
sent_i 59
now aligning 60 elapsed: 5.4
sent_i 60
sent_i 61
sent_i 62
sent_i 63
sent_i 64
sent_i 65
sent_i 66
sent_i 67
sent_i 68
sent_i 69
now aligning 70 elapsed: 7.1
sent_i 70
sent_i 71
sent_i 72
sent_i 73
sent_i 74
sent_i 75
sent_i 76
sent_i 77
sent_i 78
sent_i 79
now aligning 80 elapsed: 11.7
sent_i 80
sent_i 81
sent_i 82
sent_i 83
sent_i 84
sent_i 85
sent_i 86
sent_i 87
sent_i 88
sen

In [ ]:
from collections import Counter

list1=["a","b","a","c"]
c1=Counter(list1)

#Index everything - Sep 2022

In [ ]:
ar_corpus_fname="UNv1.0.ar-en-clean2.ar"
en_corpus_fname="UNv1.0.ar-en.en"

n_sents_max=200000
ar_fopen=open(ar_corpus_fname)
en_fopen=open(en_corpus_fname)

src_counter,trg_counter={},{}
src_sents,trg_sents=[],[]
for i,pair in enumerate(zip(en_fopen,ar_fopen)):
  #if i>=n_sents_max: break
  if i%20000==0: print(i)
  en_line,ar_line=pair
  en_line,ar_line=en_line.strip("\n\r\t "),ar_line.strip("\n\r\t ")
  src_tokens=tok(en_line)
  trg_tokens=cur_ar_tok_fn(ar_line)


0
20000
40000
60000
80000
100000


KeyboardInterrupt: ignored

In [ ]:
!wc UNv1.0.ar-en-clean2.ar

  18539207  397660045 4458094300 UNv1.0.ar-en-clean2.ar


#Combining into bitexts - Sep 2022

In [ ]:

ar_corpus_fname="UNv1.0.ar-en-clean2.ar"
en_corpus_fname="UNv1.0.ar-en.en"
en_ar_corpus_combined_fname="UNv1.0.en-ar-combined3.txt"
en_ar_corpus_combined_fpath=os.path.join(cwd,en_ar_corpus_combined_fname)

ar_fopen=open(ar_corpus_fname)
en_fopen=open(en_corpus_fname)
combined_fopen=open(en_ar_corpus_combined_fname,"w")

n_sents_max=200000

for i,pair in enumerate(zip(en_fopen,ar_fopen)):
  if i>=n_sents_max: break
  if i%20000==0: print(i)
  en_line,ar_line=pair
  en_line,ar_line=en_line.strip("\n\r\t "),ar_line.strip("\n\r\t ")
  en_line,ar_line=en_line.replace("\t"," "),ar_line.replace("\t"," ")
  combined_line="%s\t%s\n"%(en_line,ar_line)
  combined_fopen.write(combined_line)

ar_fopen.close()
en_fopen.close()
combined_fopen.close()

0
20000
40000
60000
80000
100000
120000
140000
160000
180000


#Going full-scale - Sept 2022

In [ ]:
#preparing index shelves
import shelve
en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"


fopen=open(en_ar_corpus_combined_fname)
cur_loc=0
cur_line="-"
counter=0
src_fwd_index0,trg_fwd_index0=[],[]
while cur_line!="":
#for i0,f0 in enumerate(fopen):
#for i0 in range(10):  
  if counter>1000000: break
  if counter%10000==0: print(counter)
  cur_loc=fopen.tell()
  f0=fopen.readline()
  cur_line=f0.strip("\n\r\t")
  line_split=cur_line.split("\t")
  if len(line_split)!=2: continue
  src0,trg0=line_split
  src_tokens0,trg_tokens0=tok(src0),tok(trg0)
  cur_params={}
  cur_params["excluded_words"]=excluded_src_tokens+excluded_trg_tokens
  #print(fopen.tell())
  filtere_src0=filter_toks(src_tokens0,cur_params)
  filtere_trg0=filter_toks(trg_tokens0,cur_params)

  indexed_src0=[(v,cur_loc+0.001*vi) for vi,v in enumerate(filtere_src0) if vi<1000]
  indexed_trg0=[(v,cur_loc+0.001*vi) for vi,v in enumerate(filtere_trg0) if vi<1000]
  src_fwd_index0.extend(indexed_src0)
  trg_fwd_index0.extend(indexed_trg0)
  #indexed_trg0=filter_toks(trg_tokens0,cur_params)

  # print("cur_loc",cur_loc)
  # print(filtere_src0)
  # print(filtere_trg0)
  # print("indexed_src0",indexed_src0)
  # print("indexed_trg0",indexed_trg0)
  counter+=1
  #cur_loc+=len(f0)
fopen.close()
src_fwd_index0.sort()
trg_fwd_index0.sort()
grouped_src=[(key,[v[1] for v in list(group)]) for key,group in groupby(src_fwd_index0,lambda x:x[0])]
grouped_trg=[(key,[v[1] for v in list(group)]) for key,group in groupby(trg_fwd_index0,lambda x:x[0])]

src_shelve_fpath="test-src.shelve"
src_shelve_fopen=shelve.open(src_shelve_fpath)
for k0,grp0 in grouped_src: src_shelve_fopen[k0]=grp0
src_shelve_fopen.close()
trg_shelve_fpath="test-trg.shelve"
trg_shelve_fopen=shelve.open(trg_shelve_fpath)
for k0,grp0 in grouped_trg: trg_shelve_fopen[k0]=grp0
trg_shelve_fopen.close()


print("src_fwd_index0",len(src_fwd_index0))
print("trg_fwd_index0",len(trg_fwd_index0))
print("grouped_src",len(grouped_src))
print("grouped_trg",len(grouped_trg))
# for a in src_fwd_index0[-50:]:
#   print(a)

0
10000
20000
30000
40000
50000
60000
70000
80000
90000
100000
110000
120000
130000
140000
150000
160000
170000
180000
190000
200000
210000
220000
230000
240000
250000
260000
270000
280000
290000
300000
310000
320000
330000
340000
350000
360000
370000
380000
390000
400000
410000
420000
430000
440000
450000
460000
470000
480000
490000
500000
510000
520000
530000
540000
550000
560000
570000
580000
590000
600000
610000
620000
630000
640000
650000
660000
670000
680000
690000
700000
710000
720000
730000
740000
750000
760000
770000
780000
790000
800000
810000
820000
830000
840000
850000
860000
870000
880000
890000
900000
910000
920000
930000
940000
950000
960000
970000
980000
990000
1000000
src_fwd_index0 16415181
trg_fwd_index0 19001975
grouped_src 93832
grouped_trg 255323


In [ ]:
fopen=open(en_ar_corpus_combined_fname)
fopen.seek(592)
print([fopen.readline()])
fopen.close()

['Australia . 3\tاستراليا . 4\n']


#Extract word and phrase pairs - Sept 2022

In [ ]:
import time, shelve
en_ar_corpus_combined_fname="UNv1.0.en-ar-combined.txt"
# excluded_src_tokens=["the","a","an","and","of","its","his","her","to","is","are","am","been", "have","has","had", "in", "on", "at", "with", "from","for","that","he","she","it","would"] #we will need to update this
# excluded_trg_tokens=["من","على","في","مع", "إلى","له","تم","إلى","في"]


t0=time.time()
cur_params={}
cur_params["excluded_words"]=excluded_src_tokens+excluded_trg_tokens
cutoff_ratio=0.01




fopen=open(en_ar_corpus_combined_fname)
src_shelve_fpath="test-src.shelve"
trg_shelve_fpath="test-trg.shelve"
src_shelve_fopen=shelve.open(src_shelve_fpath)
trg_shelve_fopen=shelve.open(trg_shelve_fpath)

test_word="main"
test_out=src_shelve_fopen.get(test_word,[])
all_lines=[]
src_line_ids=[]
for a in test_out[:1000]:
  cur_line_id=int(a)
  fopen.seek(cur_line_id)
  cur_line=fopen.readline()
  all_lines.append(cur_line)
  src_line_ids.append(cur_line_id)
src_line_ids=list(set(src_line_ids))

all_lines.sort(key=lambda x:len(x))
for cur_line in all_lines[:50]:
  line_split=cur_line.split("\t")
  if len(line_split)!=2: continue
  src0,trg0=line_split
  src_tokens0,trg_tokens0=tok(src0),tok(trg0)
  filtere_src0=filter_toks(src_tokens0,cur_params)
  filtere_trg0=filter_toks(trg_tokens0,cur_params)
  print(src0,trg0)
  candidates=[]
  for ft in filtere_trg0:
    cur_trg_line_ids=[int(v) for v in trg_shelve_fopen.get(ft,[])]
    cur_trg_line_ids=list(set(cur_trg_line_ids))
    intersection0=list(set(src_line_ids).intersection(set(cur_trg_line_ids)))
    ratio=len(intersection0)/(len(src_line_ids)+len(cur_trg_line_ids)-len(intersection0))
    if ratio<cutoff_ratio: continue
    candidates.append((ft,len(intersection0), round(ratio,4)))
    #print(ft, ratio) # len(cur_trg_line_ids),cur_trg_line_ids[:5]
  candidates.sort(key=lambda x:-x[-1])
  for c in candidates:
    print(c)
  print("----")

src_shelve_fopen.close()
trg_shelve_fopen.close()

t1=time.time()
elapsed=t1-t0
# for cur_line in all_lines[:50]:
#   print([cur_line])
#   line_split=cur_line.split("\t")
#   if len(line_split)!=2: continue
#   src0,trg0=line_split
#   src_tokens0,trg_tokens0=tok(src0),tok(trg0)
#   cur_params={}
#   cur_params["excluded_words"]=excluded_src_tokens+excluded_trg_tokens
#   #print(fopen.tell())
#   filtere_src0=filter_toks(src_tokens0,cur_params)
#   filtere_trg0=filter_toks(trg_tokens0,cur_params)
#   print("filtere_src0",filtere_src0)
#   print("filtere_trg0",filtere_trg0)
#   print("-----")

print("test_out",len(test_out),test_out[:10],"elapsed",elapsed)
fopen.close()

Main Committee اللجنة الرئيسية

('الرئيسية', 480, 0.0464)
----
Satellite main-hub معدات السواتل

----
Main publications: المنشورات الرئيسية

('الرئيسية', 480, 0.0464)
----
A. Main assumptions ألف - الافتراضات الرئيسية

('الرئيسية', 480, 0.0464)
----
Summary of main findings موجز النتائج الرئيسية

('الرئيسية', 480, 0.0464)
----
Their main functions are: ومهامها الأساسية كما يلي:

----
and by main determining factor والعامل المحدد الرئيسي

('الرئيسي', 207, 0.0566)
('والعامل', 14, 0.0137)
----
Main diplomatic experience الأنشطة الدبلوماسية الرئيسية

('الرئيسية', 480, 0.0464)
----
(b) Main trunking contract - )ب( عقد مقسم الهاتف الرئيسي

('الرئيسي', 207, 0.0566)
----
Main trunking contract - )ب( عقد كابل الاتصالات الرئيسي -

('الرئيسي', 207, 0.0566)
----
(b) Main trunking contract - العقد الرئيسي للخطوط الهاتفية

('الرئيسي', 207, 0.0566)
----
B. Main international treaties باء - المعاهدات الدولية الرئيسية

('الرئيسية', 480, 0.0464)
----
Representation on the Main Committee التمثيل في اللجن

In [ ]:
def get_phrase(phrase_tokens0,index0,max_sent_tokens=1000):
  cur_token_indexes0=index0.get(phrase_tokens0[0],[])
  cur_token_indexes0=[v*max_sent_tokens for v in cur_token_indexes0]
  #print(phrase_tokens0[0], len(cur_token_indexes0))
  for t_i in range(1,len(phrase_tokens0)):
    tmp_token=phrase_tokens0[t_i]
    tmp_indexes=index0.get(tmp_token,[])
    #print(tmp_token, len(tmp_indexes), tmp_indexes[:10])
    tmp_indexes_offset=[v*max_sent_tokens-t_i for vi,v in enumerate(tmp_indexes)]
    #print(tmp_indexes_offset[:10])
    cur_token_indexes0=list(set(tmp_indexes_offset).intersection(cur_token_indexes0))
  return list(set([int(v/max_sent_tokens) for  v in cur_token_indexes0]))

fopen=open(en_ar_corpus_combined_fname)
src_shelve_fpath="test-src.shelve"
trg_shelve_fpath="test-trg.shelve"
src_shelve_fopen=shelve.open(src_shelve_fpath)
trg_shelve_fopen=shelve.open(trg_shelve_fpath)

test_phrase="catastrophic"
test_phrase_tokens=[v.strip() for v in test_phrase.split() if v.strip()]
#test_out=src_shelve_fopen.get(test_word,[])
test_out=get_phrase(test_phrase_tokens,src_shelve_fopen)
all_lines=[]
src_line_ids=[]
for a in test_out[:1000]:
  cur_line_id=int(a)
  fopen.seek(cur_line_id)
  cur_line=fopen.readline()
  all_lines.append(cur_line)
  src_line_ids.append(cur_line_id)
src_line_ids=list(set(src_line_ids))

all_lines.sort(key=lambda x:len(x))
for cur_line in all_lines[:50]:
  line_split=cur_line.split("\t")
  if len(line_split)!=2: continue
  src0,trg0=line_split
  src_tokens0,trg_tokens0=tok(src0),tok(trg0)
  filtere_src0=filter_toks(src_tokens0,cur_params)
  filtere_trg0=filter_toks(trg_tokens0,cur_params)
  print(src0,trg0)
  candidates=[]
  for fi,ft in enumerate(filtere_trg0):
    cur_trg_line_ids=[int(v) for v in trg_shelve_fopen.get(ft,[])]
    cur_trg_line_ids=list(set(cur_trg_line_ids))
    intersection0=list(set(src_line_ids).intersection(set(cur_trg_line_ids)))
    ratio=len(intersection0)/(len(src_line_ids)+len(cur_trg_line_ids)-len(intersection0))
    if ratio>cutoff_ratio: candidates.append((ft,len(intersection0), round(ratio,4)))
    
    if fi==0: continue
    pair=(filtere_trg0[fi-1],ft)
    cur_pair_index_ids=get_phrase(pair,trg_shelve_fopen)
    pair_intersection0=list(set(src_line_ids).intersection(set(cur_pair_index_ids)))
    pair_ratio=len(pair_intersection0)/(len(src_line_ids)+len(cur_pair_index_ids)-len(pair_intersection0))
    if ratio>cutoff_ratio: candidates.append((pair,len(pair_intersection0), round(pair_ratio,4)))


    #print(ft, ratio) # len(cur_trg_line_ids),cur_trg_line_ids[:5]
  candidates.sort(key=lambda x:-x[-1])
  for c in candidates:
    print(c)
  print("----")

src_shelve_fopen.close()
trg_shelve_fopen.close()

t1=time.time()
elapsed=t1-t0
# for cur_line in all_lines[:50]:
#   print([cur_line])
#   line_split=cur_line.split("\t")
#   if len(line_split)!=2: continue
#   src0,trg0=line_split
#   src_tokens0,trg_tokens0=tok(src0),tok(trg0)
#   cur_params={}
#   cur_params["excluded_words"]=excluded_src_tokens+excluded_trg_tokens
#   #print(fopen.tell())
#   filtere_src0=filter_toks(src_tokens0,cur_params)
#   filtere_trg0=filter_toks(trg_tokens0,cur_params)
#   print("filtere_src0",filtere_src0)
#   print("filtere_trg0",filtere_trg0)
#   print("-----")

print("test_out",len(test_out),test_out[:10],"elapsed",elapsed)
fopen.close()

There is destruction of catastrophic proportions in the city. وتعاني المدينة من دمار رهيب.

('دمار', 3, 0.0175)
('رهيب', 2, 0.0165)
(('المدينة', 'دمار'), 1, 0.0088)
(('دمار', 'رهيب'), 1, 0.0088)
----
The humanitarian situation in the city remains catastrophic. ولا تزال الحالة الإنسانية في تلك المدينة مفجعة.

('مفجعة', 6, 0.0395)
(('المدينة', 'مفجعة'), 1, 0.0088)
----
In order to avoid catastrophic consequences, we demand: وتفاديا للكوارث التي ستحدث من جراء ذلك، فإننا نطلب ما يلي:

----
(b) Inhuman conditions prevail, with potentially catastrophic consequences. )ب( تسود ظروف غير انسانية يمكن أن تؤدي إلى عواقب وخيمة؛

('وخيمة', 12, 0.0494)
(('عواقب', 'وخيمة'), 5, 0.0281)
('عواقب', 9, 0.0155)
(('تؤدي', 'عواقب'), 1, 0.0086)
----
The fire business was particularly exposed to insolvency because of catastrophic events. فتعرض نشاط التأمين من الحريق بوجه خاص للإعسار بسبب الكوارث.

----
57. Field studies of catastrophic floods are made by UNESCO scientific missions. 57 - وتقوم البعثات العلمية لل

In [ ]:
def un_rhash(h,modinv0=26087,limit_n=50000):
  return int(h, 16) * modinv0 % limit_n

a='0179'
un_rhash(a)

34799

In [ ]:
#!ls -d */bitexts
!ls bitexts/manual

_0000_ENV_Kyoto_Protocol.tsv
2200731.tsv
A_74_19.tsv
A_74_433.tsv
A_74_603.tsv
A_74_606.tsv
A_74_692.tsv
A_74_737_Add_11.tsv
A_74_821.tsv
A_74_834.tsv
A_74_953_Add_1.tsv
A_74_976_S_2020_773.tsv
A_75_112.tsv
A_75_113.tsv
A_75_116.tsv
A_75_149.tsv
A_75_152.tsv
A_75_164.tsv
A_75_172.tsv
A_75_178.tsv
A_75_182_Part_I_.tsv
A_75_184.tsv
A_75_185.tsv
A_75_186.tsv
A_75_1.tsv
A_75_202.tsv
A_75_208.tsv
A_75_210.tsv
A_75_211.tsv
A_75_212.tsv
A_75_215.tsv
A_75_225.tsv
A_75_226.tsv
A_75_230.tsv
A_75_265.tsv
A_75_273.tsv
A_75_277.tsv
A_75_307.tsv
A_75_395.tsv
A_75_532.tsv
A_75_592_Add_1.tsv
A_75_5_Add_11.tsv
A_75_5_Add_4.tsv
A_75_5_Add_5.tsv
A_75_639.tsv
A_75_67.tsv
A_75_6_Sect_10_.tsv
A_75_6_Sect_23_.tsv
A_75_6_Sect_29B_.tsv
A_75_6_Sect_3_Add_6.tsv
A_75_716.tsv
A_75_785.tsv
A_75_79_E_2020_55.tsv
A_75_80.tsv
A_75_813.tsv
A_75_822_Add_10.tsv
A_75_822_Add_14.tsv
A_75_822_Add_7.tsv
A_75_822_Add_8.tsv
A_75_822.tsv
A_75_82.tsv
A_75_868.tsv
A_75_89.tsv
A_75_905.tsv
A_75_968_S_2021_669.tsv
A_75_96.tsv
A_75_

In [ ]:
import sys
from code_utils.web_lib import *
from code_utils.general import *
from code_utils.align_utils import *
from random import shuffle

bitext_dir="bitexts/manual"
files=get_dir_files(bitext_dir,"tsv")
print(len(files))
combined_bitext=[]
for f1 in files[:250]: 
  cur_bitext=read_tsv(f1)
  for pair0 in cur_bitext:
    if len(pair0)==2: combined_bitext.append(pair0)
  

shuffle(combined_bitext)

print(len(combined_bitext))
for a in combined_bitext[:100]:
  print(a)
#print(len(files),files[:10])

616
169407
['At this time, the international community must reaffirm our collective support for a two-State solution on the basis of the 1967 borders and spare no efforts to achieve a viable solution to the conflict.', 'وفي هذا الوقت، يجب على المجتمع الدولي أن يؤكد من جديد دعمنا الجماعي لحل الدولتين على أساس حدود عام 1967، وألا يدخر جهداً في سبيل التوصل إلى حل للنزاع يكون قابلاً للتطبيق.']
['The notion of incitement as an inchoate crime does not require that the incitement has been acted upon, but in regulating the forms of incitement referred to in article 4, States parties should take into account, as important elements in the incitement offences, in addition to the considerations outlined in paragraph 14 above, the intention of the speaker, and the imminent risk or likelihood that the conduct desired or intended by the speaker will result from the speech in question, considerations which also apply to the other offences listed in paragraph 13.18', '\u202bولا يشترط في مفهوم التحريض ك

In [ ]:
!python code_utils/general.py

Hello!
{'I': {'think': {'': 1}, 'love': {'her': {'': 5}}}, 'where': {'is': {'he': {'': 3}}, 'are': {'we': {'': 2}}}}
0 1 orange orange
1 2 apple apple
2 3 lemons lemons
3 5 grapes grapes


In [ ]:
from code_utils.web_lib import *
from code_utils.general import *
#url0='https://conferences.unite.un.org/eluna/bitext/html/7fb13705-e449-4d42-a7f9-876bfbd3a1cd?Language1=English&Language2=Arabic'
url0='https://conferences.unite.un.org/eluna/bitext/html/de34374c-3605-4171-9e72-04e54a793abf?Language1=English&Language2=Arabic'
page_obj=read_page(url0)
bitext_content0=page_obj.text
bitext_content0=unescape(bitext_content0)
#all_trs=get_html_els(bitext_content0,"tr")

def get_html_els(content,tag_name): #identify pairs of html tags for easy and quick matching - would break if number of closing/open tags mismatch - works maily for tr/td tags 
  all_str_list=[]
  el_open_list=list(re.finditer(r'<%s\b.*?>'%tag_name,content))
  el_close_list=list(re.finditer(r'</%s>'%tag_name,content))
  for a0,b0 in zip(el_open_list,el_close_list):
    str0=content[a0.start():b0.end()]
    all_str_list.append(str0)
  return all_str_list

def remove_html(el_outer_html): #remove html tags
  inner=re.sub('<([^<>]*?)>',"",el_outer_html)
  return inner

def get_bitext(html_content): #get tr/td and extract bitext
  all_trs=get_html_els(html_content,"tr")
  all_pairs0=[]
  for tr0 in all_trs:
    td_list=get_html_els(tr0,"td")
    pair0=[]
    for td0 in td_list:
      pair0.append(remove_html(td0))
    if len(pair0)!=2: continue
    all_pairs0.append(pair0)
  return all_pairs0
  #print(td_list)



cur_pairs=get_bitext(bitext_content0)
for a in cur_pairs[:50]:
  print(a)

['(S) Draft agenda - PSA (blue) 5 Oct. 2114240E.docx (ENGLISH)', '(S) Draft agenda - PSA (blue) 5 Oct. 2114240A.docx (ARABIC)']
['S/Agenda/____', 'S/Agenda/___']
['United Nations', 'الأمــم المتحـدة']
['S/Agenda/____', 'S/Agenda/___']
['Security Council', 'مجلس الأمن']
['Provisional', 'Provisional']
['___ October 2021', '__ October 2021 Arabic']
['Original: English', 'Original: English']
['S/Agenda/____', 'S/Agenda/___ 21-14240']
['/3', '/3']
['21-14240 (E)', '21-14240 (A)']
['/4', '/4']
['Provisional agenda for the _____ meeting of the Security Council', '21-14240 جدول الأعمال المؤقت لجلسة مجلس الأمن']
['To be held on _____________, ___ October 2021, at', 'المقرر عقدها يوم _______، ___ تشرين الأول/أكتوبر 2021، الساعة']
['1.', '1 -']
['Adoption of the agenda.', 'إقرار جدول الأعمال.']
['2.', '2 -']
['Peace and security in Africa.', 'السلام والأمن في أفريقيا.']
['', '']


In [ ]:
final_list[:10]

[(['WHC operational guidelines'],
  '/eluna/bitext/html/593f20df-e256-26c0-933f-fb81181ceb01?Language1=English&amp;Language2=Arabic',
  True),
 (['UNW/2022/L.4'],
  '/eluna/bitext/html/7fa6b292-40fb-42b2-b7c1-36d039f9a92e?Language1=English&amp;Language2=Arabic',
  True),
 (['UNW/2022/L.3'],
  '/eluna/bitext/html/0ae5f5bc-6ba9-4fe4-ba7f-53ad4ded5341?Language1=English&amp;Language2=Arabic',
  True),
 (['UNW/2022/L.2'],
  '/eluna/bitext/html/bbbb541b-7b4f-4012-9c27-16a0df59521e?Language1=English&amp;Language2=Arabic',
  True),
 (['UNW/2022/L.1'],
  '/eluna/bitext/html/4451cf2b-2e92-4f4d-904e-3c7054a570c2?Language1=English&amp;Language2=Arabic',
  True),
 (['UNW/2022/8'],
  '/eluna/bitext/html/9c836041-1be0-4505-bfd9-433018aeb7a4?Language1=English&amp;Language2=Arabic',
  True),
 (['UNW/2022/6'],
  '/eluna/bitext/html/212f5e84-1ced-4514-b13a-fe8fc53a6434?Language1=English&amp;Language2=Arabic',
  True),
 (['UNW/2022/5'],
  '/eluna/bitext/html/967396f2-5271-4e44-94aa-f9f560c84423?Language1=

#Experimenting fast walign - 16 Dec 2022

In [ ]:
#Preparing references
import re, time
from code_utils.general import *
from code_utils.align_utils import *
from code_utils.arabic_lib import *
from code_utils.pandas_utils import *

from itertools import groupby
from collections import Counter

ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})
def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)


#Now processing references
# npt_ref_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vTUXpDvvhBcrRBWqrz-CfoANQ9Hu7kKJ_i_cyyGC7hvBhjiyHtWFhDl7V2AZwULZ86dxZiF-lQ7nTUD/pub?output=xlsx'
# cedaw_wb_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vRFH-hHy3lm7pIHpYrYwfWP4GA6GbX6l7uHwnczP6NKOcvXvdw0avrCqMJjxXA9R9LlbB85003FgYAF/pub?output=xlsx'
# stat_wb_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vTuvjp20eZcXigBgrVvwJg0pzQzC7B4EjN6yVSC7VKGFqRg4AUFW33El56W3xiftrzismUHTb4yfJ_S/pub?output=xlsx'
# ref_path_list=[npt_ref_path,cedaw_wb_path,stat_wb_path]
# cols=["en","ar"]
# ref_data=[]
# for ref_wb_path in ref_path_list:
#   ref_wb_obj=get_workbook_obj(ref_wb_path)
#   ref_sheets=list(ref_wb_obj.keys())
#   print("ref_sheets",ref_sheets)
#   cur_ref_data=get_sheets_cols(ref_wb_obj,ref_sheets,cols)
#   ref_data.extend(cur_ref_data)


bitext_dir="bitexts/manual"
files=get_dir_files(bitext_dir,"tsv")
print(len(files))
ref_data=[]
for f1 in files[:100]: 
  cur_bitext=read_tsv(f1)
  for pair0 in cur_bitext:
    if len(pair0)!=2: continue
    if pair0[0]==pair0[1]: continue
    ref_data.append(pair0)


print("ref_data",len(ref_data))
params={}
params["lang2_tok_fn"]=cur_ar_tok_fn

job_wb_path='https://docs.google.com/spreadsheets/d/e/2PACX-1vS8-zn0nwjU9U_NMnUkBG6PsdsnN78izRte1BLZjGzJhryDrkDzY7OVds3Szm91r1Vqh8gv4PoAtkkO/pub?output=xlsx'
job_wb_obj=get_workbook_obj(job_wb_path)
cols=["en","ar"]
job_data=get_sheets_cols(job_wb_obj,["doc"],cols)

print("job_data",len(job_data))
ref_job_data=ref_data+job_data
src_index0,trg_index0=index_bitext_list(ref_job_data,params)
print("finished indexing")



616
ref_data 43738
job_data 979
finished indexing


In [ ]:
params={}
params["lang2_tok_fn"]=cur_ar_tok_fn
params["excluded_words"]=['the', 'a', 'an', 'and', 'of', 'its', 'his', 'her', 'their', 'them', 'to', 'is', 'are', 'am', 'been', 'was', 'were', 'be', 'have', 'has', 'had', 'in', 'on', 'at', 'with', 'from', 'for', 'that', 'he', 'she', 'it', 'would', 'من', 'على', 'في', 'مع', 'إلى', 'له', 'تم', 'إلى', 'في']
#["the","of","a","and"]


src_sent='Protect, restore and promote sustainable use of terrestrial ecosystems, sustainably manage forests, combat desertification, and halt and reverse land degradation and halt biodiversity loss'
trg_sent='حماية النظم الإيكولوجية البرّية وترميمها وتعزيز استخدامها على نحو مستدام، وإدارة الغابات على نحو مستدام، ومكافحة التصحر، ووقف تدهور الأراضي وعكس مساره، ووقف فقدان التنوع البيولوجي'

table_cell_list=[]
sent_i=50#51
for sent_i in range(len(job_data)):
#for sent_i in range(50):  
  if sent_i%10==0: print(sent_i)
  #src_sent,trg_sent=ref_data[sent_i]
  src_sent,trg_sent=job_data[sent_i]
  # src_tokens=[v.lower() for v in tok(src_sent)]
  # trg_tokens=[v.lower() for v in cur_ar_tok_fn(trg_sent)]

  src_tokens=tok(src_sent)#[v.lower() for v in tok(src_sent)]
  trg_tokens=cur_ar_tok_fn(trg_sent)#[v.lower() for v in cur_ar_tok_fn(trg_sent)]
  src_tokens=add_padding(src_tokens)
  trg_tokens=add_padding(trg_tokens)


  filtered_src0=filter_toks(src_tokens,params)
  filtered_trg0=filter_toks(trg_tokens,params)



  # src_phrase_index_loc_dict=retr_sent_phrase_indexes(filtered_src0,src_index0,min_index_size=0)
  # for a,b in src_phrase_index_loc_dict.items():
  #   print(a,b)
  # print("src_tokens",len(src_tokens))
  # print("trg_tokens",len(trg_tokens))

  mlist1=get_index_matching_list(filtered_src0,filtered_trg0,src_index0,trg_index0,max_phrase_length=6)

  align_path0=get_aligned_path(src_tokens,trg_tokens,mlist1,n_epochs=5)

  src_outcome,trg_outcome=align_words_phrases_classes(src_tokens,trg_tokens,align_path0,sent_class0="sent0")

  src_cell=" ".join([v[0] for v in src_outcome])
  trg_cell=" ".join([v[0] for v in trg_outcome])
  table_cell_list.append((src_cell,trg_cell))

content1=create_align_html_content(table_cell_list)
fopen=open("qa-test8.html","w")
fopen.write(content1)
fopen.close()
#print("outcome",outcome)
# for a in align_path0:
#   print(a)

print("src_tokens",src_tokens)
print("trg_tokens",trg_tokens)

# test=present_aligned(src_tokens,trg_tokens,align_path0)
# for ts in test:
#   print(ts)


0
10
20
30
40
50
60
70
80
90
100
110
120
130
140
150
160
170
180
190
200
210
220
230
240
250
260
270
280
290
300
310
320
330
340
350
360
370
380
390
400
410
420
430
440
450
460
470
480
490
500
510
520
530
540
550
560
570
580
590
600
610
620
630
640
650
660
670
680
690
700
710
720
730
740
750
760
770
780
790
800
810
820
830
840
850
860
870
880
890
900
910
920
930
940
950
960
970
src_tokens ['<s>', 'UNOPS', 'is', 'committed', 'to', 'addressing', 'the', 'areas', 'of', 'improvement', 'identified', 'in', 'the', 'report', ',', 'and', 'will', 'continue', 'to', 'strengthen', 'and', 'widen', 'the', 'scope', 'of', 'these', 'initiatives', '.', '</s>']
trg_tokens ['<s>', '#', 'وـ', 'يلتزم', 'مكتب', 'ال_أمم', 'ال_متحدة', 'لـ', 'خدمات', 'ال_مشاريع', 'بـ', 'ال_نظر', 'في', 'مجالات', 'ال_تحسين', 'ال_واردة', 'في', 'ال_تقرير', '،', 'وـ', 'سـ', 'يواصل', 'تعزيز', 'هذه', 'ال_مبادرات', 'وـ', 'توسيع', 'نطاق', 'ـها', '.', '</s>']


#Phonetic matching/Transliteration - 22 Dec 2022

In [ ]:
#Preparing references
import re, time
from code_utils.general import *
from code_utils.align_utils import *
from code_utils.arabic_lib import *
from code_utils.pandas_utils import *

transliteration_link='https://docs.google.com/spreadsheets/d/e/2PACX-1vTeFLaZRLK3v2b65mxY7fiqvk4a8IRdmkPOHFStk15DEVhU8LuBsaqBalHhgY3G7T51beZYzyzbTtEN/pub?output=xlsx'
t8_wb_obj=get_workbook_obj(transliteration_link)
cols=["en","ar-any","ar-start","ar-end"]
t8_data=get_sheets_cols(t8_wb_obj,["Sheet1"],cols,exclude_empty=False)
t8_dict={}
for item0 in t8_data:
  en0,ar_any0,ar_start0,ar_end0=item0
  if ar_any0.strip()=="": continue
  tmp_dict={}
  tmp_dict["any"]=[v if v!="-" else "" for v in ar_any0.split()]
  tmp_dict["start"]=[v if v!="-" else "" for v in ar_start0.split()]
  tmp_dict["end"]=[v if v!="-" else "" for v in ar_end0.split()]
  #ar_split=[v if v!="-" else "" for v in ar0.split()]
  t8_dict[en0]=tmp_dict
  # print(en0)
  # print(ar0.split())

for a,b in t8_dict.items():
  print(a,b)
print(t8_dict)

a {'any': ['ا', ''], 'start': ['أ', 'ع', 'عا'], 'end': ['ى', 'ة']}
b {'any': ['ب'], 'start': [], 'end': []}
c {'any': ['س', 'ك', 'تش', 'ث'], 'start': [], 'end': []}
d {'any': ['د', 'ض'], 'start': [], 'end': []}
e {'any': ['ي', 'ا', ''], 'start': ['إ', 'ا'], 'end': ['ه', '']}
f {'any': ['ف'], 'start': [], 'end': []}
g {'any': ['ج', 'غ'], 'start': [], 'end': []}
h {'any': ['ه', 'ح', ''], 'start': [], 'end': ['ة']}
i {'any': ['ي', 'اي', ''], 'start': ['إ', 'ا', 'إي', 'ع'], 'end': []}
j {'any': ['ج', 'خ', 'ي', 'ه'], 'start': [], 'end': []}
k {'any': ['ك', 'ق'], 'start': [], 'end': []}
l {'any': ['ل', ''], 'start': [], 'end': []}
m {'any': ['م'], 'start': [], 'end': []}
n {'any': ['ن'], 'start': [], 'end': []}
o {'any': ['و', ''], 'start': ['أ', 'أو'], 'end': []}
p {'any': ['ب'], 'start': [], 'end': []}
q {'any': ['ك', 'ق', 'تش'], 'start': [], 'end': []}
r {'any': ['ر'], 'start': [], 'end': []}
s {'any': ['س', 'ش', 'ز', 'ص'], 'start': [], 'end': []}
t {'any': ['ت', 'ط'], 'start': [], 'end':

In [ ]:
t8_dict={'a': {'any': ['ا', ''], 'start': ['أ', 'ع', 'عا'], 'end': ['ى', 'ة']}, 'b': {'any': ['ب'], 'start': [], 'end': []}, 'c': {'any': ['س', 'ك', 'تش', 'ث'], 'start': [], 'end': []}, 'd': {'any': ['د', 'ض'], 'start': [], 'end': []}, 'e': {'any': ['ي', 'ا', ''], 'start': ['إ', 'ا'], 'end': ['ه', '']}, 'f': {'any': ['ف'], 'start': [], 'end': []}, 'g': {'any': ['ج', 'غ'], 'start': [], 'end': []}, 'h': {'any': ['ه', 'ح', ''], 'start': [], 'end': ['ة']}, 'i': {'any': ['ي', 'اي', ''], 'start': ['إ', 'ا', 'إي', 'ع'], 'end': []}, 'j': {'any': ['ج', 'خ', 'ي', 'ه'], 'start': [], 'end': []}, 'k': {'any': ['ك', 'ق'], 'start': [], 'end': []}, 'l': {'any': ['ل', ''], 'start': [], 'end': []}, 'm': {'any': ['م'], 'start': [], 'end': []}, 'n': {'any': ['ن'], 'start': [], 'end': []}, 'o': {'any': ['و', ''], 'start': ['أ', 'أو'], 'end': []}, 'p': {'any': ['ب'], 'start': [], 'end': []}, 'q': {'any': ['ك', 'ق', 'تش'], 'start': [], 'end': []}, 'r': {'any': ['ر'], 'start': [], 'end': []}, 's': {'any': ['س', 'ش', 'ز', 'ص'], 'start': [], 'end': []}, 't': {'any': ['ت', 'ط'], 'start': [], 'end': []}, 'u': {'any': ['و', 'ا', ''], 'start': ['أ', 'أو'], 'end': []}, 'v': {'any': ['ف'], 'start': [], 'end': []}, 'w': {'any': ['و', 'ف'], 'start': [], 'end': []}, 'x': {'any': ['كس', 'ز', 'ه'], 'start': [], 'end': []}, 'y': {'any': ['ي', 'اي'], 'start': [], 'end': ['يا']}, 'z': {'any': ['ز', 'س', 'تس', 'ث', 'ش'], 'start': [], 'end': []}, 'sh': {'any': ['ش'], 'start': [], 'end': []}, 'ch': {'any': ['تش', 'ش', 'خ', 'ك'], 'start': [], 'end': []}, 'th': {'any': ['ث', 'ذ', 'ت', 'تح'], 'start': [], 'end': []}, 'dh': {'any': ['ذ', 'ظ'], 'start': [], 'end': []}, 'gh': {'any': ['غ', 'ج', ''], 'start': [], 'end': []}, 'kh': {'any': ['خ', 'ك'], 'start': [], 'end': []}, 'sch': {'any': ['ش', 'سك'], 'start': [], 'end': []}, 'zh': {'any': ['ج'], 'start': [], 'end': []}, 'ck': {'any': ['ك'], 'start': [], 'end': []}, 'ae': {'any': ['اي', 'ائ', 'ي', ''], 'start': [], 'end': []}, 'oi': {'any': ['وا'], 'start': [], 'end': []}, 'll': {'any': ['ل', 'ج', 'ي', 'لل'], 'start': [], 'end': []}, 'é': {'any': ['ي', ''], 'start': [], 'end': ['يه']}, 'et': {'any': ['ت', 'يت'], 'start': [], 'end': ['يه']}, 'que': {'any': ['ك'], 'start': [], 'end': []}, 'ph': {'any': ['ف'], 'start': [], 'end': []}, 'aa': {'any': ['ا'], 'start': [], 'end': ['اء']}, 'el': {'any': ['ل', 'يل'], 'start': ['ال'], 'end': []}, 'al': {'any': ['ل', 'ال'], 'start': ['ال'], 'end': []}, 'ç': {'any': ['س'], 'start': [], 'end': []}, 'ce': {'any': ['سي', 'س', 'ثي', 'ث', 'تشي', 'تش'], 'start': [], 'end': []}, 'ci': {'any': ['سي', 'س', 'ثي', 'ث', 'تشي', 'تش'], 'start': [], 'end': []}, 'ñ': {'any': ['ني'], 'start': [], 'end': []}}


def gen_ts8(name):
  found_items=[]
  for a,equiv_dict in t8_dict.items():
    locs=is_in(a,name)
    if locs==[]: continue
    for span0 in locs:
      cur_equiv=[]
      equiv_any,equiv_start,equiv_end=equiv_dict.get("any",[]),equiv_dict.get("start",[]),equiv_dict.get("end",[])
      if span0[0]==0 and equiv_start!=[]: cur_equiv=equiv_start
      elif span0[-1]==len(name)-1 and equiv_end!=[]: cur_equiv=list(set(equiv_any+equiv_end))
      else: cur_equiv=equiv_any
      found_items.append((a,cur_equiv, span0))
  for i0 in range(len(name)-1):
    if name[i0]==name[i0+1]:
      equiv_dict=t8_dict.get(name[i0],{})
      equiv=equiv_dict.get("any",[])
      if i0==0: equiv=equiv_dict.get("start",[])
      #double_equiv=[v+v for v in equiv]
      double_equiv=[]
      full_equiv=list(set(equiv+double_equiv))
      span0=(i0,i0+1)#[]
      found_items.append((name[i0:i0+2],full_equiv,span0))
  found_items.sort(key=lambda x:-len(x[0]))
  used_locs=[]
  final=[]
  for fi in found_items:
    src0,equiv0,span0=fi
    span_range=list(range(span0[0],span0[1]+1))
    if any([v in used_locs for v in span_range]): continue
    used_locs.extend(span_range)
    final.append((span0,equiv0))
  final.sort()
  candidates=[""]
  for f_locs,f_equivs in final:
    print(f_locs,f_equivs)
    new_candidates=[]
    for cd0 in candidates:
      for eq0 in f_equivs: new_candidates.append(cd0+eq0)
    candidates=new_candidates
  return list(set(candidates))

name0="kazakhstan"
candidates0=gen_ts8(name0)
candidates0.sort()
print("candidates0",len(candidates0))
for cd in candidates0:
  print(cd)

(0, 0) ['ك', 'ق']
(1, 1) ['ا', '']
(2, 2) ['ز', 'س', 'تس', 'ث', 'ش']
(3, 3) ['ا', '']
(4, 5) ['خ', 'ك']
(6, 6) ['س', 'ش', 'ز', 'ص']
(7, 7) ['ت', 'ط']
(8, 8) ['ا', '']
(9, 9) ['ن']
candidates0 1280
قاتساخزتان
قاتساخزتن
قاتساخزطان
قاتساخزطن
قاتساخستان
قاتساخستن
قاتساخسطان
قاتساخسطن
قاتساخشتان
قاتساخشتن
قاتساخشطان
قاتساخشطن
قاتساخصتان
قاتساخصتن
قاتساخصطان
قاتساخصطن
قاتساكزتان
قاتساكزتن
قاتساكزطان
قاتساكزطن
قاتساكستان
قاتساكستن
قاتساكسطان
قاتساكسطن
قاتساكشتان
قاتساكشتن
قاتساكشطان
قاتساكشطن
قاتساكصتان
قاتساكصتن
قاتساكصطان
قاتساكصطن
قاتسخزتان
قاتسخزتن
قاتسخزطان
قاتسخزطن
قاتسخستان
قاتسخستن
قاتسخسطان
قاتسخسطن
قاتسخشتان
قاتسخشتن
قاتسخشطان
قاتسخشطن
قاتسخصتان
قاتسخصتن
قاتسخصطان
قاتسخصطن
قاتسكزتان
قاتسكزتن
قاتسكزطان
قاتسكزطن
قاتسكستان
قاتسكستن
قاتسكسطان
قاتسكسطن
قاتسكشتان
قاتسكشتن
قاتسكشطان
قاتسكشطن
قاتسكصتان
قاتسكصتن
قاتسكصطان
قاتسكصطن
قاثاخزتان
قاثاخزتن
قاثاخزطان
قاثاخزطن
قاثاخستان
قاثاخستن
قاثاخسطان
قاثاخسطن
قاثاخشتان
قاثاخشتن
قاثاخشطان
قاثاخشطن
قاثاخصتان
قاثاخصتن
قاثاخصطان
قاثاخصطن
قاثاكزتان
ق

In [ ]:
import time
def gen_t8_equivs(name): #get transliteration equivalents
  end_dict={}
  for let_i,let0 in enumerate(name):
    cur_vals=end_dict.get(let_i,[""])
    if let_i>0 and cur_vals==[""]:
      for start_i in range(let_i,-1,-1):
        cur_vals=end_dict.get(start_i,[""])
        print("start_i",start_i,"cur_vals",cur_vals)
        if cur_vals!=[""]: break

    found_items=[]
    for i2 in range(4,0,-1):
    #print(let_i,let0,t8_dict.get(let0,""))
      end_i=let_i+i2
      cur_str="".join(name[let_i:let_i+i2])
      str_eq=t8_dict.get(cur_str)
      print("end_i",end_i, "let_i",let_i,"cur_str",cur_str,str_eq)
      if str_eq!=None: 
        new_vals=[]
        for cv in cur_vals:
          if cv and cv[-1] in str_eq and not "" in str_eq: str_eq=[""]+str_eq
          for str0 in str_eq:
            new_str=cv+str0
            new_vals.append(new_str)
        updated_vals=list(set(end_dict.get(end_i,[])+new_vals))
        end_dict[end_i]=updated_vals
        break
  for a,b in end_dict.items():
    print(a,b)
  return end_dict.get(len(name),[])

name="fathy"
t0=time.time()
equivs=gen_t8_equivs(name)
elapsed=time.time()-t0
print(len(equivs),elapsed)
print(equivs[:100])
# for a in equivs:
#   print(a)
#print("final",final)
# for a,b in end_dict.items():
#   print(a,b)

end_i 4 let_i 0 cur_str fath None
end_i 3 let_i 0 cur_str fat None
end_i 2 let_i 0 cur_str fa None
end_i 1 let_i 0 cur_str f ['ف']
end_i 5 let_i 1 cur_str athy None
end_i 4 let_i 1 cur_str ath None
end_i 3 let_i 1 cur_str at None
end_i 2 let_i 1 cur_str a ['ا', '']
end_i 6 let_i 2 cur_str thy None
end_i 5 let_i 2 cur_str thy None
end_i 4 let_i 2 cur_str th ['ث', 'ذ', 'ت', 'تح']
start_i 3 cur_vals ['']
start_i 2 cur_vals ['ف', 'فا']
end_i 7 let_i 3 cur_str hy None
end_i 6 let_i 3 cur_str hy None
end_i 5 let_i 3 cur_str hy None
end_i 4 let_i 3 cur_str h ['ه', 'ح', '']
end_i 8 let_i 4 cur_str y ['ي', 'اي']
1 ['ف']
2 ['ف', 'فا']
4 ['فتح', 'فاذ', 'فا', 'فاث', 'فاه', 'فذ', 'فح', 'فه', 'فاح', 'فات', 'فث', 'ف', 'فاتح', 'فت']
8 ['فتاي', 'فاذي', 'فتحاي', 'فحي', 'فاتي', 'فذاي', 'فاهي', 'فاي', 'في', 'فثي', 'فاتحي', 'فاثاي', 'فاحاي', 'فهي', 'فاتاي', 'فتحي', 'فذي', 'فااي', 'فاثي', 'فاذاي', 'فثاي', 'فاتحاي', 'فحاي', 'فاحي', 'فهاي', 'فاهاي', 'فتي']
0 0.0069942474365234375
[]


#Web templating

In [ ]:
from code_utils.web_lib import *
url='http://kmatters.com/itrade360-ui/template.html'
page_content=get_page_content(url)
dom_obj=DOM(page_content)
repl_dict={}
repl_dict["#main-content"]=("testing",{}) #content and attributes

out_content=dom_obj.replace(repl_dict)
fopen=open("test-templating.html","w")
fopen.write(out_content)
fopen.close()
#print(out_content[:2000])

In [ ]:
test=src_index0["undp"]
print(len(test))

3150


In [ ]:
import unicodedata

def strip_accents(s):
   return ''.join(c for c in unicodedata.normalize('NFD', s)
                  if unicodedata.category(c) != 'Mn')


def get_chars(start_i,end_i,include_diacritics=False): #generate list of chars depending on the range - ar 1568,1646 
  char_list=[]
  for i in range(start_i,end_i):
    ch0=chr(i)
    ch_type=unicodedata.category(ch0)
    if include_diacritics==False and not (ch_type.startswith("Ll") or ch_type.startswith("Lo")): continue
    char_list.append(ch0)
  return char_list

# def is_punct(token):
#     if len(token)==0: return True
#     unicode_check=unicodedata.category(token[0])
# if len(unicode_check)>0: return unicode_check[0]=="P" 
start_i=1568
#n=200
end_i=1646
ar_chars=get_ar_chars(start_i=1560,end_i=1646,include_diacritics=True)
ascii_chars=get_ar_chars(start_i=0,end_i=500,include_diacritics=False)
print(ar_chars)
print(ascii_chars)

# for i in range(start_i,end_i):
#   ch0=chr(i)

#   ch_type=unicodedata.category(ch0)
#   #print(i, ch0,ch_type)
#   #normalized0=unicodedata.normalize('NFKD', ch0)
#   normalized0=strip_accents(ch0)
#   if not (ch_type.startswith("Ll") or ch_type.startswith("Lo")): continue
#   print(i, chr(i),[chr(i)], unicodedata.category(chr(i)), normalized0)   

['ؘ', 'ؙ', 'ؚ', '؛', '\u061c', '\u061d', '؞', '؟', 'ؠ', 'ء', 'آ', 'أ', 'ؤ', 'إ', 'ئ', 'ا', 'ب', 'ة', 'ت', 'ث', 'ج', 'ح', 'خ', 'د', 'ذ', 'ر', 'ز', 'س', 'ش', 'ص', 'ض', 'ط', 'ظ', 'ع', 'غ', 'ػ', 'ؼ', 'ؽ', 'ؾ', 'ؿ', 'ـ', 'ف', 'ق', 'ك', 'ل', 'م', 'ن', 'ه', 'و', 'ى', 'ي', 'ً', 'ٌ', 'ٍ', 'َ', 'ُ', 'ِ', 'ّ', 'ْ', 'ٓ', 'ٔ', 'ٕ', 'ٖ', 'ٗ', '٘', 'ٙ', 'ٚ', 'ٛ', 'ٜ', 'ٝ', 'ٞ', 'ٟ', '٠', '١', '٢', '٣', '٤', '٥', '٦', '٧', '٨', '٩', '٪', '٫', '٬', '٭']
['a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z', 'ª', 'µ', 'º', 'ß', 'à', 'á', 'â', 'ã', 'ä', 'å', 'æ', 'ç', 'è', 'é', 'ê', 'ë', 'ì', 'í', 'î', 'ï', 'ð', 'ñ', 'ò', 'ó', 'ô', 'õ', 'ö', 'ø', 'ù', 'ú', 'û', 'ü', 'ý', 'þ', 'ÿ', 'ā', 'ă', 'ą', 'ć', 'ĉ', 'ċ', 'č', 'ď', 'đ', 'ē', 'ĕ', 'ė', 'ę', 'ě', 'ĝ', 'ğ', 'ġ', 'ģ', 'ĥ', 'ħ', 'ĩ', 'ī', 'ĭ', 'į', 'ı', 'ĳ', 'ĵ', 'ķ', 'ĸ', 'ĺ', 'ļ', 'ľ', 'ŀ', 'ł', 'ń', 'ņ', 'ň', 'ŉ', 'ŋ', 'ō', 'ŏ', 'ő', 'œ', 'ŕ', 'ŗ', 'ř', 'ś', 'ŝ', 'ş', 'š', 'ţ'

In [ ]:
for a in ascii_chars:
  print(a)

a
b
c
d
e
f
g
h
i
j
k
l
m
n
o
p
q
r
s
t
u
v
w
x
y
z
ª
µ
º
ß
à
á
â
ã
ä
å
æ
ç
è
é
ê
ë
ì
í
î
ï
ð
ñ
ò
ó
ô
õ
ö
ø
ù
ú
û
ü
ý
þ
ÿ
ā
ă
ą
ć
ĉ
ċ
č
ď
đ
ē
ĕ
ė
ę
ě
ĝ
ğ
ġ
ģ
ĥ
ħ
ĩ
ī
ĭ
į
ı
ĳ
ĵ
ķ
ĸ
ĺ
ļ
ľ
ŀ
ł
ń
ņ
ň
ŉ
ŋ
ō
ŏ
ő
œ
ŕ
ŗ
ř
ś
ŝ
ş
š
ţ
ť
ŧ
ũ
ū
ŭ
ů
ű
ų
ŵ
ŷ
ź
ż
ž
ſ
ƀ
ƃ
ƅ
ƈ
ƌ
ƍ
ƒ
ƕ
ƙ
ƚ
ƛ
ƞ
ơ
ƣ
ƥ
ƨ
ƪ
ƫ
ƭ
ư
ƴ
ƶ
ƹ
ƺ
ƻ
ƽ
ƾ
ƿ
ǀ
ǁ
ǂ
ǃ
ǆ
ǉ
ǌ
ǎ
ǐ
ǒ
ǔ
ǖ
ǘ
ǚ
ǜ
ǝ
ǟ
ǡ
ǣ
ǥ
ǧ
ǩ
ǫ
ǭ
ǯ
ǰ
ǳ


In [ ]:
src_outcome,trg_outcome=outcome

In [ ]:
" ".join([v[0] for v in src_outcome]) 

'<span class="aligned sent0 walign-16"><span class="aligned sent0 walign-15">updated</span> the tier <span class="aligned sent0 walign-17">classification</span></span> <span class="aligned sent0 walign-11">on</span> the <span class="aligned sent0 walign-7"><span class="aligned sent0 walign-3">basis</span> of the <span class="aligned sent0 walign-5"><span class="aligned sent0 walign-4">annual</span> <span class="aligned sent0 walign-6">review</span></span></span> of the <span class="aligned sent0 walign-9"><span class="aligned sent0 walign-8">data</span> <span class="aligned sent0 walign-10">availability</span></span> and reviewed <span class="aligned sent0 walign-13"><span class="aligned sent0 walign-12">data</span> <span class="aligned sent0 walign-14">gaps</span></span> ;'

In [ ]:
import re, time
from code_utils.general import *
from code_utils.align_utils import *
from code_utils.arabic_lib import *

from itertools import groupby
from collections import Counter

ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})
def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)

# index_dir="indexes/un/exp4"
# params_fpath=os.path.join(index_dir,"params.json") #
# params_dict=read_json(params_fpath)
# params_dict["ar_counter_dict"]=ar_counter_dict

# def get_aligned_path_NEW(src_toks0,trg_toks0,match_list,n_epochs=10,allow_ortho=True,max_dist=5,min_freq_without_penalty=10,penalty=0.25,reward_combined_phrases=True,only_without_children=False): #we apply penalty for less frequent pairs
#   match_list=sorted(list(set(match_list)))
#   #Now we have the matching list - let's align
#   el_dict={} #weight of each element
#   el_child_dict={} #children of each element
#   for a in match_list:
#     src_span0,trg_span0,ratio0,freq0=a
#     #if freq0<min_freq_without_penalty: ratio0=ratio0*penalty
#     el0=(src_span0,trg_span0)
#     found_ratio=el_dict.get(el0,0)
#     if ratio0>found_ratio: el_dict[el0]=ratio0
#   all_elements=list(el_dict.items()) #let's get horizontal and vertical spans
  
#   elements_list1,elements_list2=all_elements,all_elements
#   #epoch
#   for i in range(n_epochs):
#     #print("epoch",i)
#     new_elements=[]
#     for cur_el0,cur_el_wt0 in elements_list1:
#       src_span0,trg_span0=cur_el0
#       for cur_el1,cur_el_wt1 in elements_list2:
#         valid_el_pair=check_el_pair(cur_el0,cur_el1,allow_ortho=allow_ortho,max_dist=max_dist)
#         if not valid_el_pair: continue
#         #print("cur_el0",cur_el0,"cur_el1",cur_el1,"valid_el_pair",valid_el_pair )
#         combined_el01=combine_els(cur_el0,cur_el1)
#         combined_wt=cur_el_wt0+cur_el_wt1
#         found_wt=el_dict.get(combined_el01,0)
        
#         if combined_wt>found_wt:
#           el_dict[combined_el01]= combined_wt
#           el_child_dict[combined_el01]=(cur_el0,cur_el1)
#           new_elements.append((combined_el01,combined_wt))
#           # print("cur_el0",cur_el0,"cur_el1",cur_el1)
#           # print("combined_el01",combined_el01,"combined_wt",combined_wt,"found_wt",found_wt)
          
#           # print("----")
#     if new_elements==[]: break
#     elements_list1=new_elements
#     elements_list2=list(el_dict.items())
  
#   all_elements=list(el_dict.items())
#   all_elements.sort(key=lambda x:-x[-1])
#   final_elements=[]
#   used_xs,used_ys=[],[]
#   for cur_el0,el_wt0 in all_elements:
#     src_span0,trg_span0=cur_el0
#     src_range0=list(range(src_span0[0],src_span0[1]+1))
#     trg_range0=list(range(trg_span0[0],trg_span0[1]+1))
#     if any([v in used_xs for v in src_range0]): continue
#     if any([v in used_ys for v in trg_range0]): continue
#     used_xs.extend(src_range0)
#     used_ys.extend(trg_range0)
#     cur_children=get_rec_el_children(cur_el0,el_child_dict,el_list0=[])
#     for ch0 in cur_children:
#       child_check=el_child_dict.get(ch0)
#       ch0_wt=el_dict.get(ch0,0)
#       if child_check!=None: continue
#       final_elements.append((ch0,ch0_wt))
#   return final_elements

#   # first_src_span,first_trg_span=(0,0),(0,0)
#   # last_src_span=(len(src_toks0)-1,len(src_toks0)-1)
#   # last_trg_span=(len(trg_toks0)-1,len(trg_toks0)-1)
#   # ne_el=(last_src_span,first_trg_span) #north eastern element - uppermost rightmost, so we go diagonally up to the right
#   # se_el=(last_src_span,last_trg_span)
#   # el_dict[ne_el]=0
#   # top_wt=0
#   # full_src_span0=(0,len(src_toks0)-1)
#   # full_trg_span0=(0,len(trg_toks0)-1)
#   # full_el=(full_src_span0,full_trg_span0)

#   return 

src_sent='Protect, restore and promote sustainable use of terrestrial ecosystems, sustainably manage forests, combat desertification, and halt and reverse land degradation and halt biodiversity loss'
trg_sent='حماية النظم الإيكولوجية البرّية وترميمها وتعزيز استخدامها على نحو مستدام، وإدارة الغابات على نحو مستدام، ومكافحة التصحر، ووقف تدهور الأراضي وعكس مساره، ووقف فقدان التنوع البيولوجي'
src_tokens=[v.lower() for v in tok(src_sent)]
trg_tokens=[v.lower() for v in cur_ar_tok_fn(trg_sent)]
test_dict={}
test_dict["loss"]=["فقدان"]
test_dict["use"]=["استخدام"]
test_dict["manage"]=["إدارة"]
test_dict["promote"]=["تعزيز"]
test_dict["protect"]=["حماية"]
test_dict["reverse"]=["عكس مسار"]
test_dict["sustainable"]=["مستدام","مستدامة"]
matching_list=[]
for a,b_list in test_dict.items():
  a_split=a.split()
  src_locs=is_in(a_split,src_tokens)
  print(a, src_locs)
  for b in b_list:
    b_split=b.split()
    trg_locs=is_in(b_split,trg_tokens)
    for s1 in src_locs:
      for t1 in trg_locs: matching_list.append((s1,t1,0.5,20))
    # if trg_locs:
    #   print(b, trg_locs)
# for ml in matching_list:
#   print(ml) 
t0=time.time()
for i in range(100):
  test=get_aligned_path(src_tokens,trg_tokens,matching_list,max_dist=10)
elapsed=time.time()-t0
for ts in test:
  print(ts)
print("elapsed",elapsed)
# print("src_tokens",src_tokens)
# print("trg_tokens",trg_tokens)

loss [(27, 27)]
use [(6, 6)]
manage [(12, 12)]
promote [(4, 4)]
protect [(0, 0)]
reverse [(21, 21)]
sustainable [(5, 5)]
(((0, 12), (0, 16)), 2.5, True)
(((0, 6), (0, 13)), 2.0, True)
(((0, 4), (0, 8)), 1.0, True)
(((0, 0), (0, 0)), 0.5, False)
(((4, 4), (8, 8)), 0.5, False)
(((5, 6), (9, 13)), 1.0, True)
(((5, 5), (13, 13)), 0.5, False)
(((6, 6), (9, 9)), 0.5, False)
(((12, 12), (16, 16)), 0.5, False)
(((21, 27), (31, 37)), 1.0, True)
(((21, 21), (31, 32)), 0.5, False)
(((27, 27), (37, 37)), 0.5, False)
elapsed 0.3924684524536133


In [ ]:
def get_aligned_path_NEW(src_toks0,trg_toks0,match_list,n_epochs=10,allow_ortho=False,min_freq_without_penalty=10,penalty=0.25,reward_combined_phrases=True,only_without_children=False): #we apply penalty for less frequent pairs
  match_list=sorted(list(set(match_list)))
  #Now we have the matching list - let's align
  el_dict={} #weight of each element
  el_child_dict={} #children of each element
  for a in match_list:
    src_span0,trg_span0,ratio0,freq0=a
    if freq0<min_freq_without_penalty: ratio0=ratio0*penalty
    el0=(src_span0,trg_span0)
    found_ratio=el_dict.get(el0,0)
    if ratio0>found_ratio: el_dict[el0]=ratio0
  all_elements=list(el_dict.items()) #let's get horizontal and vertical spans
  for cur_el0,cur_el_wt0 in all_elements:
    src_span0,trg_span0=cur_el0
    for cur_el1,cur_el_wt1 in all_elements:
        if cur_el0==cur_el1: continue
        src_span1,trg_span1=cur_el1
        if src_span1[0]<src_span0[0]: continue
        src_span_dist=get_span_dist(src_span0,src_span1)
        trg_span_dist=get_span_dist(trg_span0,trg_span1)
        if src_span_dist>3 or trg_span_dist>3: continue
        if src_span1==src_span0 and trg_span_dist<1: continue
        if trg_span1==trg_span0 and src_span_dist<1: continue
        if trg_span_dist<1 and trg_span1!=trg_span0: continue
        if src_span_dist<1 and src_span1!=src_span0: continue
        combined_el01=combine_els(cur_el0,cur_el1)
        combined_wt=cur_el_wt0+cur_el_wt1
        found_wt=el_dict.get(combined_el01,0)
        if combined_wt>found_wt:
          el_dict[combined_el01]= combined_wt
          el_child_dict[combined_el01]=(cur_el0,cur_el1)

  first_src_span,first_trg_span=(0,0),(0,0)
  last_src_span=(len(src_toks0)-1,len(src_toks0)-1)
  last_trg_span=(len(trg_toks0)-1,len(trg_toks0)-1)
  ne_el=(last_src_span,first_trg_span) #north eastern element - uppermost rightmost, so we go diagonally up to the right
  se_el=(last_src_span,last_trg_span)
  el_dict[ne_el]=0
  top_wt=0
  full_src_span0=(0,len(src_toks0)-1)
  full_trg_span0=(0,len(trg_toks0)-1)
  full_el=(full_src_span0,full_trg_span0)

  # #start iteration here
  
  # for epoch0 in range(n_epochs):
  #   #print("epoch0",epoch0)
  #   all_elements=list(el_dict.items())
  #   all_elements.sort()
  #   se_transition_dict,ne_transition_dict=get_ne_se_dict(all_elements,allow_ortho)
  #   new_el_counter=0
  #   for cur_el,b in ne_transition_dict.items():
  #     next_els=list(b.keys())
  #     if len(next_els)<2: continue
  #     cur_pts=[cur_el]+next_els
  #     cur_path,cur_path_wt=general.djk(cur_el,ne_el,ne_transition_dict,cur_pts)
  #     path_el_wts=[(v, el_dict.get(v,0)) for v in cur_path]
  #     path_el_wts_chunks=split_path_chunks(path_el_wts)
  #     for chunk in path_el_wts_chunks:
  #       chunk_wt=sum([v[1] for v in chunk])
  #       chunk_els=[v[0] for v in chunk]
  #       combined_el=combine_els(chunk_els[0],chunk_els[-1])
  #       found_wt=el_dict.get(combined_el,0)
  #       found_children=el_child_dict.get(combined_el,[])
  #       if chunk_wt>found_wt:
  #         if reward_combined_phrases: chunk_wt+=0.00000001 #give advantage to combined phrases
  #         el_dict[combined_el]=chunk_wt#+0.00000001
  #         el_child_dict[combined_el]=chunk_els
  #         new_el_counter+=1

  #   all_elements=list(el_dict.items())
  #   all_elements.sort()
  #   se_transition_dict,ne_transition_dict=get_ne_se_dict(all_elements,allow_ortho)

  #   for cur_el,b in se_transition_dict.items():
  #     next_els=list(b.keys())
  #     #print("se_transition_dict", "cur_el", cur_el,"next_els",next_els)
  #     if len(next_els)<2: continue
  #     cur_pts=[cur_el]+next_els
  #     cur_path,cur_path_wt=general.djk(cur_el,se_el,se_transition_dict,cur_pts)
  #     path_el_wts=[(v, el_dict.get(v,0)) for v in cur_path]
  #     path_el_wts_chunks=split_path_chunks(path_el_wts)
  #     for chunk in path_el_wts_chunks:
  #       chunk_wt=sum([v[1] for v in chunk])
  #       chunk_els=[v[0] for v in chunk]
  #       combined_el=combine_els(chunk_els[0],chunk_els[-1])
  #       found_wt=el_dict.get(combined_el,0)
  #       found_children=el_child_dict.get(combined_el,[])
  #       if chunk_wt>found_wt:
  #         if reward_combined_phrases: chunk_wt+=0.00000001
  #         el_dict[combined_el]=chunk_wt
  #         el_child_dict[combined_el]=chunk_els
  #         new_el_counter+=1
  #   cur_full_wt=el_dict.get(full_el,0)
  #   if cur_full_wt>0 and cur_full_wt==top_wt: break
  #   top_wt=cur_full_wt
  # align_list=get_rec_el_children(full_el,el_child_dict,el_list0=[],only_without_children=only_without_children)
  # #Now filling the unaligned parts
  # used_xs,used_ys=[],[]
  # src_span_dict,trg_span_dict={},{}
  # new_align_list=[]
  # for el0 in align_list:
  #   src_span0,trg_span0=el0
  #   el_children=el_child_dict.get(el0)
  #   src_span_dict[src_span0]=el0
  #   trg_span_dict[trg_span0]=el0
  #   if el_children!=None: continue
  #   new_align_list.append(el0)
  #   used_xs.extend(list(range(src_span0[0],src_span0[1]+1)))
  #   used_ys.extend(list(range(trg_span0[0],trg_span0[1]+1)))
  #   #print(el0, el_children)

  # all_elements=list(el_dict.items())
  # all_elements.sort(key=lambda x:-x[-1])
  # for el1,el_wt1 in all_elements:
  #   src_span0,trg_span0=el1
  #   skip=False
  #   for x0 in range(src_span0[0],src_span0[1]+1):
  #       if x0 in used_xs: 
  #           skip=True
  #           break
  #   for y0 in range(trg_span0[0],trg_span0[1]+1):
  #       if y0 in used_ys: 
  #           skip=True
  #           break
  #   if skip: continue
  #   #print("not used:", el1, el_wt1)
  #   used_xs.extend(list(range(src_span0[0],src_span0[1]+1)))
  #   used_ys.extend(list(range(trg_span0[0],trg_span0[1]+1)))
  #   new_align_list.append(el1)

       

  # align_list_wt=[(v,el_dict.get(v,0)) for v in new_align_list]  
  #print("used_xs",used_xs)
  #print("used_ys",used_ys)
  return align_list_wt

In [ ]:
import re, time
from code_utils.general import *
from code_utils.align_utils import *
from code_utils.arabic_lib import *

from itertools import groupby
from collections import Counter

def check_el_pair(el0,el1,allow_ortho=True,max_dist=None, max_ortho_span=2): #check if two elements can be combined -if they do not overlap, with ortho and dist requirements
  if el0==el1: return False
  src_span0,trg_span0=el0
  src_span1,trg_span1=el1
  cur_src_dist=get_span_dist(src_span0,src_span1)
  cur_trg_dist=get_span_dist(trg_span0,trg_span1)    
  if not allow_ortho: #check ortho cases -vertical/horizontal co-inciding spans
    if src_span0==src_span1 or trg_span0==trg_span1: return False
  else:
    if src_span0==src_span1:
      if src_span0[1]-src_span0[0]>max_ortho_span: return False #if els have same src span, but it is large e.g. (5,10),(5,10)
      elif cur_trg_dist<1: return False #if overlap
      elif max_dist!=None and cur_trg_dist>max_dist: return False #if further than max distance
      else: return True
    elif trg_span0==trg_span1:
      if trg_span0[1]-trg_span0[0]>max_ortho_span: return False
      elif cur_src_dist<1: return False
      elif max_dist!=None and cur_src_dist>max_dist: return False
      else: return True
  if cur_src_dist<1: return False
  if max_dist!=None and cur_src_dist>max_dist: return False
  if cur_trg_dist<1: return False
  if max_dist!=None and cur_trg_dist>max_dist: return False  
  return True


def add_padding(token_list):
  return ["<s>"]+token_list+["</s>"]




# ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})

# def cur_ar_tok_fn(text):
#   cur_toks=tok(text)
#   return tok_ar(cur_toks,ar_counter_dict)

src_span0=(10,10)
trg_span0=(13,13)

src_span1=(7,7)
trg_span1=(7,10)
el0=(src_span0,trg_span0)
el1=(src_span1,trg_span1)

t0=time.time()
for i in range(10000):
  check0=check_el_pair(el0,el1,allow_ortho=True,max_dist=3)
elapsed=time.time()-t0
print(check0,elapsed)
# print(get_span_dist(src_span0,src_span1)) 
# print(get_span_dist(src_span1,src_span0)) 

True 0.04288911819458008


In [ ]:
ar_counter_dict=load_counts("ar_count.txt", tmp_count_dict={})

def cur_ar_tok_fn(text):
  cur_toks=tok(text)
  return tok_ar(cur_toks,ar_counter_dict)

In [ ]:
#Clone the github codebase
# import os, subprocess
# clone_command='git clone https://github.com/hmghaly/word_align.git code_utils'
# if not os.path.exists("code_utils"): 
#   proc0=subprocess.Popen(clone_command,shell=True)
#   proc0.wait()  
#   print("cloned/created")
# else:
#   pull_command="git pull"
#   proc0=subprocess.Popen(pull_command,shell=True,cwd="code_utils")
#   proc0.wait()
#   print("updated")

#Dump

In [ ]:
from code_utils.general import *
# import re
# def tok(txt):
#   new_str=""
#   txt_split=txt.split()
#   punc_exists_dict={}
#   for char0 in set(txt):
#      if char_is_punct(char0):punc_exists_dict[char0]=True 
#   #cur_punct_items=[v for v in list(set(txt)) if char_is_punct(v)]
#   for item0 in txt_split:
#     if punc_exists_dict.get(item0,False):
#        new_str+=" %s "%item0
#        continue
#     begin_punc_chars,end_punc_chars="",""
#     for char0 in item0: 
#       if punc_exists_dict.get(char0,False): begin_punc_chars+=char0
#       else: break
#     for char0 in reversed(item0): 
#       if punc_exists_dict.get(char0,False): end_punc_chars=char0+end_punc_chars
#       else: break
#     bare_token=item0[len(begin_punc_chars):len(item0)-len(end_punc_chars)]
#     splitting_hyphen_slash=True
#     if bare_token.lower().startswith("http") or bare_token.lower().startswith("www.") or "@" in bare_token: splitting_hyphen_slash=False
#     if bare_token and bare_token[0].isupper() and bare_token[-1].isdigit() and "/" in bare_token: splitting_hyphen_slash=False
#     if splitting_hyphen_slash: bare_token=bare_token.replace("-"," _-_ ") #" _-_ ".join(bare_token.split("-")) 
#     if splitting_hyphen_slash: bare_token=bare_token.replace("/"," _/_ ")
#     if bare_token.endswith("'s"): bare_token=bare_token[:-2]+" _'s"
#     print([item0,begin_punc_chars,end_punc_chars, bare_token])
#     for i0,char0 in enumerate(begin_punc_chars):
#       if i0==0: new_str+=char0+"_ "
#       else: new_str+=" _"+char0+"_ "
#     new_str+=bare_token
#     if begin_punc_chars!=end_punc_chars:
#       for i0,char0 in enumerate(end_punc_chars):
#         if i0==len(end_punc_chars)-1: new_str+=" _"+char0
#         else: new_str+=" _"+char0+"_ "
#     new_str+=" "    
#   return [v for v in new_str.split(" ") if v]

text="""Taking note of the report of the Secretary-General on Guinea-Bissau, dated 18 August 2014 (S/2014/603) and his letter dated 11 November 2014 (S/2014/805) and the recommendations contained therein, and commending the engagement of the Special Representative of the Secretary-General and head of the United Nations Integrated Peacebuilding Office in Guinea-Bissau (UNIOGBIS),	"""
text="""وإذ يحيط علما بـتقرير الأمين العام و500 عن غينيا - بيساو المؤرخ 18 آب/أغسطس 2014 (S/2014/603) وـرسالتـه المؤرخة 11 تشرين الثاني/نوفمبر 2014 (S/2014/805) وـبـما ورد فيـهما من توصيات، وإذ يشيد بـمساعي الممثل الخاص لـلأمين العام وـرئيس مكتب الأمم المتحدة المتكامل لـبناء السلام في غينيا - بيساو،"""
tok(text)

['وإذ',
 'يحيط',
 'علما',
 'بـتقرير',
 'الأمين',
 'العام',
 'و',
 '500',
 'عن',
 'غينيا',
 '-',
 'بيساو',
 'المؤرخ',
 '18',
 'آب',
 '_/_',
 'أغسطس',
 '2014',
 '(_',
 'S/2014/603',
 '_)',
 'وـرسالتـه',
 'المؤرخة',
 '11',
 'تشرين',
 'الثاني',
 '_/_',
 'نوفمبر',
 '2014',
 '(_',
 'S/2014/805',
 '_)',
 'وـبـما',
 'ورد',
 'فيـهما',
 'من',
 'توصيات',
 '_،',
 'وإذ',
 'يشيد',
 'بـمساعي',
 'الممثل',
 'الخاص',
 'لـلأمين',
 'العام',
 'وـرئيس',
 'مكتب',
 'الأمم',
 'المتحدة',
 'المتكامل',
 'لـبناء',
 'السلام',
 'في',
 'غينيا',
 '-',
 'بيساو',
 '_،']

#Experiments

##Wikipedia extraction

In [ ]:
!pip3 install wikipedia-api

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
import wikipediaapi

In [ ]:
import wikipediaapi
wiki_wiki = wikipediaapi.Wikipedia('en')
#page_py = wiki_wiki.page('Python_(programming_language)')
page_py = wiki_wiki.page('Ash Shāriqah')
print(page_py.summary)
#print(page_py.sections)
page_langs = page_py.langlinks
for a,b in page_langs.items():
  print(a,b)

cat_list=page_py.categories
for a in cat_list:
  print(a)
# print(page_py_cs)
# page_py.exists()

Sharjah (; Arabic: ٱلشَّارقَة aš-Šāriqah, Gulf Arabic: aš-Šārja) is the third-most populous city in the United Arab Emirates, after Dubai and Abu Dhabi, forming part of the Dubai-Sharjah-Ajman metropolitan area.
Sharjah is the capital of the eponymous emirate. The emirate shares legal, political, military and economic functions with the other emirates of the UAE within a federal framework, although each emirate has jurisdiction over some functions such as civil law enforcement and provision and upkeep of local facilities. Sharjah has been ruled by the Al Qasimi dynasty since the 18th century.

The city is a centre for culture and industry, and alone contributes 7.4% of the GDP of the United Arab Emirates. The city covers an approximate area of 235 km2 and has a population of over 800,000 (2008). The sale or consumption of alcoholic beverages is prohibited in the emirate of Sharjah without possession of an alcohol licence and alcohol is not served in hotels, restaurants or other outlets